## Instalação do Pandera

In [1]:
pip install pandera

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     |████████████████████████████████| 197 kB 2.6 MB/s 


## Instalação do PySpark


In [2]:
!pip install pyspark

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     |████████████████████████████████| 281.3 MB 44 kB/s 
     |████████████████████████████████| 199 kB 49.4 MB/s 
  Created wheel for pyspark: filename=pyspark-3.3.0-py2.py3-none-any.whl size=281764026 sha256=7a28f003ee61a5ff9c24d4fe1fc96a556b71b7bc6a30a0c684adc73db80f2a53
  Stored in directory: /root/.cache/pip/wheels/7a/8e/1b/f73a52650d2e5f337708d9f6a1750d451a7349a867f928b885
Successfully built pyspark


###Importação das Bibliotecas Pandas, Pandera e PySpark e ferramentas

In [3]:
import pandas as pd
import pandera as pa

from pyspark.sql import SparkSession
from pyspark import SparkConf
import pyspark.sql.functions as F

from pyspark.sql.types import*

In [5]:
# Configurando a quantidade de linhas máximas mostradas em tela

pd.set_option('display.max_columns',1000)
pd.set_option('display.max_rows',1000)

##ACRE

In [713]:
# Conector

dfac = pd.read_csv('/content/acre.csv',sep=';')

In [714]:
# Backup

dfac_backup = dfac.copy()

In [715]:
# Visualização da Tabela

dfac.head(13)

Mês     2000  2001  2002  2003  2004  2005  2006  2007  2008  \
0     Janeiro  501.000   431   310   250   297   303   344   448   687   
1   Fevereiro  454.000   387   306   316   296   265   318   346   571   
2       Março  676.000   428   395   350   282   260   293   404   647   
3       Abril  678.000   401   447   255   254   301   243   436   697   
4        Maio    1.467   427   411   253   337   312   286   474   763   
5       Junho  351.000   446   362   227   257   342   304   454   808   
6       Julho  451.000   402   379   376   338   311   357   596   880   
7      Agosto  603.000   476   407   293   356   367   380   620   858   
8    Setembro  531.000   427   458   373   332   361   378   620   835   
9     Outubro  573.000   304   450   319   327   381   362   655   930   
10   Novembro  305.000   365   288   294   318   342   407   683   858   
11   Dezembro  566.000   277   215   347   359   454   463   638   975   

       2009     2010     2011  2012  2013  2014     2015  2016  2017    2018  \
0   907.000  802.000    1.011   453   448   575  408.000   799   672  618.00   
1   845.000  406.000  894.000   413   475   467  339.000   674   610  574.00   
2   957.000  517.000  881.000   493   477    43  496.000   621   625  651.00   
3   960.000  527.000  769.000   477   496   100  480.000   590   610  501.00   
4   968.000  503.000  967.000   514   523   353  458.000   473   625  544.00   
5     1.043  843.000  502.000   430   491   254  430.000   470   400  748.00   
6     1.056  776.000    1.026   448   521   318  475.000   463   315  690.00   
7     1.089  553.000  543.000   582   490   288  444.000   572   477  803.00   
8     1.095    1.201  479.000   520   469   295  575.000   710   502  912.00   
9     1.148    1.012  513.000   437   511   308    1.022   917   568    1.09   
10  963.000    1.093  470.000   468   505   335    1.062   640   619  787.00   
11  921.000    1.261  532.000   512   620   363    1.196   677   728  615.00   

    2019  2020  2021   2022  
0    545   663   682  375.0  
1    470   604   689  395.0  
2    558   525   784  556.0  
3    592   285   662  588.0  
4    730   210   663  593.0  
5    728   362   578  621.0  
6    742   485   504    NaN  
7    638   599   537    NaN  
8    658   791   477    NaN  
9    770   649   510    NaN  
10   676   610   460    NaN  
11   798   760   425    NaN

In [716]:
# Replace do Mês para numérico

dfac["Mês"].replace("Janeiro", "01", inplace=True)
dfac["Mês"].replace("Fevereiro", "02", inplace=True)
dfac["Mês"].replace("Março", "03", inplace=True)
dfac["Mês"].replace("Abril", "04", inplace=True)
dfac["Mês"].replace("Maio", "05", inplace=True)
dfac["Mês"].replace("Junho", "06", inplace=True)
dfac["Mês"].replace("Julho", "07", inplace=True)
dfac["Mês"].replace("Agosto", "08", inplace=True)
dfac["Mês"].replace("Setembro", "09", inplace=True)
dfac["Mês"].replace("Outubro", "10", inplace=True)
dfac["Mês"].replace("Novembro", "11", inplace=True)
dfac["Mês"].replace("Dezembro", "12", inplace=True)

In [717]:
# Criação das colunas uf, produto, unid, criado_em

dfac['uf']='AC'
dfac['produto']='Etanol Hidratado'
dfac['unid']='m3'
dfac['criado_em'] ='2022-09-10'

In [718]:
# Despivotar a tabela em ano e volume 

dfac.reset_index(inplace=True)

In [719]:
dfac=dfac.melt(id_vars = ['Mês', 'uf', 'produto', 'unid', 'criado_em'], value_vars = ['2000', '2001', '2002', '2003', '2004', '2005', '2006', '2007', '2008', '2009', '2010', '2011', '2012', '2013', '2014', '2015', '2016', '2017', '2018', '2019', '2020', '2021', '2022'], var_name='ano', value_name='venda')

In [720]:
# Visão geral da tabela

dfac

Mês  uf           produto unid   criado_em   ano    venda
0    01  AC  Etanol Hidratado   m3  2022-09-10  2000  501.000
1    02  AC  Etanol Hidratado   m3  2022-09-10  2000  454.000
2    03  AC  Etanol Hidratado   m3  2022-09-10  2000  676.000
3    04  AC  Etanol Hidratado   m3  2022-09-10  2000  678.000
4    05  AC  Etanol Hidratado   m3  2022-09-10  2000    1.467
5    06  AC  Etanol Hidratado   m3  2022-09-10  2000  351.000
6    07  AC  Etanol Hidratado   m3  2022-09-10  2000  451.000
7    08  AC  Etanol Hidratado   m3  2022-09-10  2000  603.000
8    09  AC  Etanol Hidratado   m3  2022-09-10  2000  531.000
9    10  AC  Etanol Hidratado   m3  2022-09-10  2000  573.000
10   11  AC  Etanol Hidratado   m3  2022-09-10  2000  305.000
11   12  AC  Etanol Hidratado   m3  2022-09-10  2000  566.000
12   01  AC  Etanol Hidratado   m3  2022-09-10  2001  431.000
13   02  AC  Etanol Hidratado   m3  2022-09-10  2001  387.000
14   03  AC  Etanol Hidratado   m3  2022-09-10  2001  428.000
15   04  AC  Etanol Hidratado   m3  2022-09-10  2001  401.000
16   05  AC  Etanol Hidratado   m3  2022-09-10  2001  427.000
17   06  AC  Etanol Hidratado   m3  2022-09-10  2001  446.000
18   07  AC  Etanol Hidratado   m3  2022-09-10  2001  402.000
19   08  AC  Etanol Hidratado   m3  2022-09-10  2001  476.000
20   09  AC  Etanol Hidratado   m3  2022-09-10  2001  427.000
21   10  AC  Etanol Hidratado   m3  2022-09-10  2001  304.000
22   11  AC  Etanol Hidratado   m3  2022-09-10  2001  365.000
23   12  AC  Etanol Hidratado   m3  2022-09-10  2001  277.000
24   01  AC  Etanol Hidratado   m3  2022-09-10  2002  310.000
25   02  AC  Etanol Hidratado   m3  2022-09-10  2002  306.000
26   03  AC  Etanol Hidratado   m3  2022-09-10  2002  395.000
27   04  AC  Etanol Hidratado   m3  2022-09-10  2002  447.000
28   05  AC  Etanol Hidratado   m3  2022-09-10  2002  411.000
29   06  AC  Etanol Hidratado   m3  2022-09-10  2002  362.000
30   07  AC  Etanol Hidratado   m3  2022-09-10  2002  379.000
31   08  AC  Etanol Hidratado   m3  2022-09-10  2002  407.000
32   09  AC  Etanol Hidratado   m3  2022-09-10  2002  458.000
33   10  AC  Etanol Hidratado   m3  2022-09-10  2002  450.000
34   11  AC  Etanol Hidratado   m3  2022-09-10  2002  288.000
35   12  AC  Etanol Hidratado   m3  2022-09-10  2002  215.000
36   01  AC  Etanol Hidratado   m3  2022-09-10  2003  250.000
37   02  AC  Etanol Hidratado   m3  2022-09-10  2003  316.000
38   03  AC  Etanol Hidratado   m3  2022-09-10  2003  350.000
39   04  AC  Etanol Hidratado   m3  2022-09-10  2003  255.000
40   05  AC  Etanol Hidratado   m3  2022-09-10  2003  253.000
41   06  AC  Etanol Hidratado   m3  2022-09-10  2003  227.000
42   07  AC  Etanol Hidratado   m3  2022-09-10  2003  376.000
43   08  AC  Etanol Hidratado   m3  2022-09-10  2003  293.000
44   09  AC  Etanol Hidratado   m3  2022-09-10  2003  373.000
45   10  AC  Etanol Hidratado   m3  2022-09-10  2003  319.000
46   11  AC  Etanol Hidratado   m3  2022-09-10  2003  294.000
47   12  AC  Etanol Hidratado   m3  2022-09-10  2003  347.000
48   01  AC  Etanol Hidratado   m3  2022-09-10  2004  297.000
49   02  AC  Etanol Hidratado   m3  2022-09-10  2004  296.000
50   03  AC  Etanol Hidratado   m3  2022-09-10  2004  282.000
51   04  AC  Etanol Hidratado   m3  2022-09-10  2004  254.000
52   05  AC  Etanol Hidratado   m3  2022-09-10  2004  337.000
53   06  AC  Etanol Hidratado   m3  2022-09-10  2004  257.000
54   07  AC  Etanol Hidratado   m3  2022-09-10  2004  338.000
55   08  AC  Etanol Hidratado   m3  2022-09-10  2004  356.000
56   09  AC  Etanol Hidratado   m3  2022-09-10  2004  332.000
57   10  AC  Etanol Hidratado   m3  2022-09-10  2004  327.000
58   11  AC  Etanol Hidratado   m3  2022-09-10  2004  318.000
59   12  AC  Etanol Hidratado   m3  2022-09-10  2004  359.000
60   01  AC  Etanol Hidratado   m3  2022-09-10  2005  303.000
61   02  AC  Etanol Hidratado   m3  2022-09-10  2005  265.000
62   03  AC  Etanol Hidratado   m3  2022-09-10  2005  260.000
63   04  AC  Etanol Hidratado   m3  

In [721]:
# Concatenando as colunas ano e Mês

dfac['ano_mês'] = dfac[['ano', 'Mês']].agg('-'.join, axis=1)

In [722]:
# Eliminando as colunas Mês e ano

dfac.drop(["Mês"], axis=1, inplace=True)
dfac.drop(["ano"], axis=1, inplace=True)

In [723]:
# Organização da ordem das colunas

dfac =dfac[['ano_mês', 'uf', 'produto', 'unid', 'venda', 'criado_em']]

In [724]:
#Levantamento de possíveis inconsistências

dfac.isna().sum()

ano_mês      0
uf           0
produto      0
unid         0
venda        6
criado_em    0
dtype: int64

In [725]:
# Tratamento das inconsistências

dfac.replace(['Na', 'nA', 'na','NA', 'NaN', 'NAN', 'nan', '', ' '],pd.NA,inplace=True)

In [726]:
# Visão geral da tabela

dfac

ano_mês  uf           produto unid    venda   criado_em
0    2000-01  AC  Etanol Hidratado   m3  501.000  2022-09-10
1    2000-02  AC  Etanol Hidratado   m3  454.000  2022-09-10
2    2000-03  AC  Etanol Hidratado   m3  676.000  2022-09-10
3    2000-04  AC  Etanol Hidratado   m3  678.000  2022-09-10
4    2000-05  AC  Etanol Hidratado   m3    1.467  2022-09-10
5    2000-06  AC  Etanol Hidratado   m3  351.000  2022-09-10
6    2000-07  AC  Etanol Hidratado   m3  451.000  2022-09-10
7    2000-08  AC  Etanol Hidratado   m3  603.000  2022-09-10
8    2000-09  AC  Etanol Hidratado   m3  531.000  2022-09-10
9    2000-10  AC  Etanol Hidratado   m3  573.000  2022-09-10
10   2000-11  AC  Etanol Hidratado   m3  305.000  2022-09-10
11   2000-12  AC  Etanol Hidratado   m3  566.000  2022-09-10
12   2001-01  AC  Etanol Hidratado   m3  431.000  2022-09-10
13   2001-02  AC  Etanol Hidratado   m3  387.000  2022-09-10
14   2001-03  AC  Etanol Hidratado   m3  428.000  2022-09-10
15   2001-04  AC  Etanol Hidratado   m3  401.000  2022-09-10
16   2001-05  AC  Etanol Hidratado   m3  427.000  2022-09-10
17   2001-06  AC  Etanol Hidratado   m3  446.000  2022-09-10
18   2001-07  AC  Etanol Hidratado   m3  402.000  2022-09-10
19   2001-08  AC  Etanol Hidratado   m3  476.000  2022-09-10
20   2001-09  AC  Etanol Hidratado   m3  427.000  2022-09-10
21   2001-10  AC  Etanol Hidratado   m3  304.000  2022-09-10
22   2001-11  AC  Etanol Hidratado   m3  365.000  2022-09-10
23   2001-12  AC  Etanol Hidratado   m3  277.000  2022-09-10
24   2002-01  AC  Etanol Hidratado   m3  310.000  2022-09-10
25   2002-02  AC  Etanol Hidratado   m3  306.000  2022-09-10
26   2002-03  AC  Etanol Hidratado   m3  395.000  2022-09-10
27   2002-04  AC  Etanol Hidratado   m3  447.000  2022-09-10
28   2002-05  AC  Etanol Hidratado   m3  411.000  2022-09-10
29   2002-06  AC  Etanol Hidratado   m3  362.000  2022-09-10
30   2002-07  AC  Etanol Hidratado   m3  379.000  2022-09-10
31   2002-08  AC  Etanol Hidratado   m3  407.000  2022-09-10
32   2002-09  AC  Etanol Hidratado   m3  458.000  2022-09-10
33   2002-10  AC  Etanol Hidratado   m3  450.000  2022-09-10
34   2002-11  AC  Etanol Hidratado   m3  288.000  2022-09-10
35   2002-12  AC  Etanol Hidratado   m3  215.000  2022-09-10
36   2003-01  AC  Etanol Hidratado   m3  250.000  2022-09-10
37   2003-02  AC  Etanol Hidratado   m3  316.000  2022-09-10
38   2003-03  AC  Etanol Hidratado   m3  350.000  2022-09-10
39   2003-04  AC  Etanol Hidratado   m3  255.000  2022-09-10
40   2003-05  AC  Etanol Hidratado   m3  253.000  2022-09-10
41   2003-06  AC  Etanol Hidratado   m3  227.000  2022-09-10
42   2003-07  AC  Etanol Hidratado   m3  376.000  2022-09-10
43   2003-08  AC  Etanol Hidratado   m3  293.000  2022-09-10
44   2003-09  AC  Etanol Hidratado   m3  373.000  2022-09-10
45   2003-10  AC  Etanol Hidratado   m3  319.000  2022-09-10
46   2003-11  AC  Etanol Hidratado   m3  294.000  2022-09-10
47   2003-12  AC  Etanol Hidratado   m3  347.000  2022-09-10
48   2004-01  AC  Etanol Hidratado   m3  297.000  2022-09-10
49   2004-02  AC  Etanol Hidratado   m3  296.000  2022-09-10
50   2004-03  AC  Etanol Hidratado   m3  282.000  2022-09-10
51   2004-04  AC  Etanol Hidratado   m3  254.000  2022-09-10
52   2004-05  AC  Etanol Hidratado   m3  337.000  2022-09-10
53   2004-06  AC  Etanol Hidratado   m3  257.000  2022-09-10
54   2004-07  AC  Etanol Hidratado   m3  338.000  2022-09-10
55   2004-08  AC  Etanol Hidratado   m3  356.000  2022-09-10
56   2004-09  AC  Etanol Hidratado   m3  332.000  2022-09-10
57   2004-10  AC  Etanol Hidratado   m3  327.000  2022-09-10
58   2004-11  AC  Etanol Hidratado   m3  318.000  2022-09-10
59   2004-12  AC  Etanol Hidratado   m3  359.000  2022-09-10
60   2005-01  AC  Etanol Hidratado   m3  303.000  2022-09-10
61   2005-02  AC  Etanol Hidratado   m3  265.000  2022-09-10
62   2005-03  AC  Etanol Hidratado   m3  260.000  2022-09-10
63   2005-04  AC  Etanol Hidratado   m3  301.000  2022-09-10
64   2005-05  AC  Etanol Hidratado   m3 

In [727]:
# Verificando os tipos

dfac.dtypes

ano_mês       object
uf            object
produto       object
unid          object
venda        float64
criado_em     object
dtype: object

In [728]:
# Validação

schema = pa.DataFrameSchema(
    columns = {
        'ano_mês': pa.Column(pa.String, nullable=True),
        'uf': pa.Column(pa.String, nullable = True),
        'produto': pa.Column(pa.String, nullable = True),
        'unid': pa.Column(pa.String, nullable = True),
        'venda': pa.Column(pa.Float, nullable = True),
        'criado_em': pa.Column(pa.String, nullable = True),
                
    }
)
schema.validate(dfac)

ano_mês  uf           produto unid    venda   criado_em
0    2000-01  AC  Etanol Hidratado   m3  501.000  2022-09-10
1    2000-02  AC  Etanol Hidratado   m3  454.000  2022-09-10
2    2000-03  AC  Etanol Hidratado   m3  676.000  2022-09-10
3    2000-04  AC  Etanol Hidratado   m3  678.000  2022-09-10
4    2000-05  AC  Etanol Hidratado   m3    1.467  2022-09-10
5    2000-06  AC  Etanol Hidratado   m3  351.000  2022-09-10
6    2000-07  AC  Etanol Hidratado   m3  451.000  2022-09-10
7    2000-08  AC  Etanol Hidratado   m3  603.000  2022-09-10
8    2000-09  AC  Etanol Hidratado   m3  531.000  2022-09-10
9    2000-10  AC  Etanol Hidratado   m3  573.000  2022-09-10
10   2000-11  AC  Etanol Hidratado   m3  305.000  2022-09-10
11   2000-12  AC  Etanol Hidratado   m3  566.000  2022-09-10
12   2001-01  AC  Etanol Hidratado   m3  431.000  2022-09-10
13   2001-02  AC  Etanol Hidratado   m3  387.000  2022-09-10
14   2001-03  AC  Etanol Hidratado   m3  428.000  2022-09-10
15   2001-04  AC  Etanol Hidratado   m3  401.000  2022-09-10
16   2001-05  AC  Etanol Hidratado   m3  427.000  2022-09-10
17   2001-06  AC  Etanol Hidratado   m3  446.000  2022-09-10
18   2001-07  AC  Etanol Hidratado   m3  402.000  2022-09-10
19   2001-08  AC  Etanol Hidratado   m3  476.000  2022-09-10
20   2001-09  AC  Etanol Hidratado   m3  427.000  2022-09-10
21   2001-10  AC  Etanol Hidratado   m3  304.000  2022-09-10
22   2001-11  AC  Etanol Hidratado   m3  365.000  2022-09-10
23   2001-12  AC  Etanol Hidratado   m3  277.000  2022-09-10
24   2002-01  AC  Etanol Hidratado   m3  310.000  2022-09-10
25   2002-02  AC  Etanol Hidratado   m3  306.000  2022-09-10
26   2002-03  AC  Etanol Hidratado   m3  395.000  2022-09-10
27   2002-04  AC  Etanol Hidratado   m3  447.000  2022-09-10
28   2002-05  AC  Etanol Hidratado   m3  411.000  2022-09-10
29   2002-06  AC  Etanol Hidratado   m3  362.000  2022-09-10
30   2002-07  AC  Etanol Hidratado   m3  379.000  2022-09-10
31   2002-08  AC  Etanol Hidratado   m3  407.000  2022-09-10
32   2002-09  AC  Etanol Hidratado   m3  458.000  2022-09-10
33   2002-10  AC  Etanol Hidratado   m3  450.000  2022-09-10
34   2002-11  AC  Etanol Hidratado   m3  288.000  2022-09-10
35   2002-12  AC  Etanol Hidratado   m3  215.000  2022-09-10
36   2003-01  AC  Etanol Hidratado   m3  250.000  2022-09-10
37   2003-02  AC  Etanol Hidratado   m3  316.000  2022-09-10
38   2003-03  AC  Etanol Hidratado   m3  350.000  2022-09-10
39   2003-04  AC  Etanol Hidratado   m3  255.000  2022-09-10
40   2003-05  AC  Etanol Hidratado   m3  253.000  2022-09-10
41   2003-06  AC  Etanol Hidratado   m3  227.000  2022-09-10
42   2003-07  AC  Etanol Hidratado   m3  376.000  2022-09-10
43   2003-08  AC  Etanol Hidratado   m3  293.000  2022-09-10
44   2003-09  AC  Etanol Hidratado   m3  373.000  2022-09-10
45   2003-10  AC  Etanol Hidratado   m3  319.000  2022-09-10
46   2003-11  AC  Etanol Hidratado   m3  294.000  2022-09-10
47   2003-12  AC  Etanol Hidratado   m3  347.000  2022-09-10
48   2004-01  AC  Etanol Hidratado   m3  297.000  2022-09-10
49   2004-02  AC  Etanol Hidratado   m3  296.000  2022-09-10
50   2004-03  AC  Etanol Hidratado   m3  282.000  2022-09-10
51   2004-04  AC  Etanol Hidratado   m3  254.000  2022-09-10
52   2004-05  AC  Etanol Hidratado   m3  337.000  2022-09-10
53   2004-06  AC  Etanol Hidratado   m3  257.000  2022-09-10
54   2004-07  AC  Etanol Hidratado   m3  338.000  2022-09-10
55   2004-08  AC  Etanol Hidratado   m3  356.000  2022-09-10
56   2004-09  AC  Etanol Hidratado   m3  332.000  2022-09-10
57   2004-10  AC  Etanol Hidratado   m3  327.000  2022-09-10
58   2004-11  AC  Etanol Hidratado   m3  318.000  2022-09-10
59   2004-12  AC  Etanol Hidratado   m3  359.000  2022-09-10
60   2005-01  AC  Etanol Hidratado   m3  303.000  2022-09-10
61   2005-02  AC  Etanol Hidratado   m3  265.000  2022-09-10
62   2005-03  AC  Etanol Hidratado   m3  260.000  2022-09-10
63   2005-04  AC  Etanol Hidratado   m3  301.000  2022-09-10
64   2005-05  AC  Etanol Hidratado   m3 

In [729]:
dfac_pandas = dfac.copy()

##ALAGOAS

In [730]:
# Conector

dfal = pd.read_csv('/content/alagoas.csv',sep=';')

In [731]:
# Backup

dfal_backup = dfal.copy()

In [732]:
# Configurando a quantidade de linhas máximas mostradas em tela

pd.set_option('display.max_columns',1000)
pd.set_option('display.max_rows',1000)

In [733]:
# Visualização da Tabela

dfal

Mês   2000   2001   2002   2003   2004   2005   2006   2007   2008  \
0     Janeiro  1.763  1.423  1.834  1.653  1.699  1.435  2.900  3.588  6.576   
1   Fevereiro  1.803  1.664  1.332  1.436  1.295  1.370  2.501  2.918  5.878   
2       Março  1.872  1.860  1.413  1.218  1.627  1.383  3.413  3.315  6.179   
3       Abril  2.040  1.588  1.353  1.957  1.563  1.370  2.693  3.329  6.780   
4        Maio  2.313  1.683  1.528  2.185  1.547  1.398  2.684  3.552  7.149   
5       Junho  2.028  1.481  1.313  2.078  2.168  2.063  2.824  4.028  7.183   
6       Julho  3.512  1.552  1.592  1.834  2.877  2.479  2.801  4.134  7.850   
7      Agosto  3.396  1.403  1.895  1.345  2.532  2.913  3.199  4.591  6.343   
8    Setembro  2.692  1.152  1.787  1.694  2.500  3.413  3.115  4.578  6.822   
9     Outubro  1.837  1.360  2.032  1.355  2.146  3.159  2.952  5.260  7.249   
10   Novembro  1.432  1.797  1.502  1.481  1.891  2.779  2.843  5.857  6.776   
11   Dezembro  1.506  1.950  1.460  1.814  1.673  3.136  2.978  6.311  8.318   

     2009   2010   2011   2012   2013   2014   2015   2016   2017    2018  \
0   8.152  7.438  7.283  3.766  3.383  3.775  4.091  4.190  2.281   5.725   
1   7.211  4.408  6.680  3.485  3.481  3.160  4.847  2.518  2.339   5.109   
2   8.100  4.770  6.708  3.844  3.230  2.871  4.949  2.462  2.779   4.518   
3   8.270  5.850  3.678  3.521  2.957  2.785  5.235  2.294  2.355   3.334   
4   8.512  6.041  3.895  3.273  2.825  2.761  4.515  2.773  2.600   2.986   
5   8.752  6.092  3.922  3.074  2.620  2.480  4.526  2.780  2.263   4.900   
6   9.841  6.397  3.440  2.875  2.625  2.449  5.247  2.221  2.027   4.882   
7   8.797  6.596  3.433  3.073  2.489  2.934  4.767  2.543  2.780   5.504   
8   9.364  6.651  3.323  2.929  2.592  2.649  4.261  2.443  3.751   7.629   
9   9.764  6.691  3.276  3.203  2.769  2.767  6.239  2.566  2.857  10.538   
10  8.365  6.667  3.411  3.231  2.759  3.137  4.916  2.408  4.148  10.681   
11  9.388  8.502  4.189  3.282  3.238  3.892  5.116  2.567  4.880  11.769   

     2019   2020   2021    2022  
0   9.792  8.744  7.484   5.891  
1   7.616  6.712  8.409   5.354  
2   7.213  4.805  8.559  11.820  
3   6.378  2.707  7.681   8.227  
4   4.685  2.591  5.697   7.837  
5   3.895  3.449  4.351   6.014  
6   4.281  4.545  4.510     NaN  
7   3.945  5.077  4.180     NaN  
8   4.455  5.853  3.577     NaN  
9   5.162  6.220  4.453     NaN  
10  6.423  6.499  5.910     NaN  
11  9.763  7.723  6.775     NaN

In [734]:
# Replace do Mês para numérico

dfal["Mês"].replace("Janeiro", "01", inplace=True)
dfal["Mês"].replace("Fevereiro", "02", inplace=True)
dfal["Mês"].replace("Março", "03", inplace=True)
dfal["Mês"].replace("Abril", "04", inplace=True)
dfal["Mês"].replace("Maio", "05", inplace=True)
dfal["Mês"].replace("Junho", "06", inplace=True)
dfal["Mês"].replace("Julho", "07", inplace=True)
dfal["Mês"].replace("Agosto", "08", inplace=True)
dfal["Mês"].replace("Setembro", "09", inplace=True)
dfal["Mês"].replace("Outubro", "10", inplace=True)
dfal["Mês"].replace("Novembro", "11", inplace=True)
dfal["Mês"].replace("Dezembro", "12", inplace=True)

In [735]:
# Criação das colunas uf, produto, unid, criado_em

dfal['uf']='AL'
dfal['produto']='Etanol Hidratado'
dfal['unid']='m3'
dfal['criado_em'] ='2022-09-10'

In [736]:
# Despivotar a tabela em ano e volume 

dfal.reset_index(inplace=True)

In [737]:
dfal=dfal.melt(id_vars = ['Mês', 'uf', 'produto', 'unid', 'criado_em'], value_vars = ['2000', '2001', '2002', '2003', '2004', '2005', '2006', '2007', '2008', '2009', '2010', '2011', '2012', '2013', '2014', '2015', '2016', '2017', '2018', '2019', '2020', '2021', '2022'], var_name='ano', value_name='venda')

In [738]:
# Visão geral da tabela

dfal

Mês  uf           produto unid   criado_em   ano   venda
0    01  AL  Etanol Hidratado   m3  2022-09-10  2000   1.763
1    02  AL  Etanol Hidratado   m3  2022-09-10  2000   1.803
2    03  AL  Etanol Hidratado   m3  2022-09-10  2000   1.872
3    04  AL  Etanol Hidratado   m3  2022-09-10  2000   2.040
4    05  AL  Etanol Hidratado   m3  2022-09-10  2000   2.313
5    06  AL  Etanol Hidratado   m3  2022-09-10  2000   2.028
6    07  AL  Etanol Hidratado   m3  2022-09-10  2000   3.512
7    08  AL  Etanol Hidratado   m3  2022-09-10  2000   3.396
8    09  AL  Etanol Hidratado   m3  2022-09-10  2000   2.692
9    10  AL  Etanol Hidratado   m3  2022-09-10  2000   1.837
10   11  AL  Etanol Hidratado   m3  2022-09-10  2000   1.432
11   12  AL  Etanol Hidratado   m3  2022-09-10  2000   1.506
12   01  AL  Etanol Hidratado   m3  2022-09-10  2001   1.423
13   02  AL  Etanol Hidratado   m3  2022-09-10  2001   1.664
14   03  AL  Etanol Hidratado   m3  2022-09-10  2001   1.860
15   04  AL  Etanol Hidratado   m3  2022-09-10  2001   1.588
16   05  AL  Etanol Hidratado   m3  2022-09-10  2001   1.683
17   06  AL  Etanol Hidratado   m3  2022-09-10  2001   1.481
18   07  AL  Etanol Hidratado   m3  2022-09-10  2001   1.552
19   08  AL  Etanol Hidratado   m3  2022-09-10  2001   1.403
20   09  AL  Etanol Hidratado   m3  2022-09-10  2001   1.152
21   10  AL  Etanol Hidratado   m3  2022-09-10  2001   1.360
22   11  AL  Etanol Hidratado   m3  2022-09-10  2001   1.797
23   12  AL  Etanol Hidratado   m3  2022-09-10  2001   1.950
24   01  AL  Etanol Hidratado   m3  2022-09-10  2002   1.834
25   02  AL  Etanol Hidratado   m3  2022-09-10  2002   1.332
26   03  AL  Etanol Hidratado   m3  2022-09-10  2002   1.413
27   04  AL  Etanol Hidratado   m3  2022-09-10  2002   1.353
28   05  AL  Etanol Hidratado   m3  2022-09-10  2002   1.528
29   06  AL  Etanol Hidratado   m3  2022-09-10  2002   1.313
30   07  AL  Etanol Hidratado   m3  2022-09-10  2002   1.592
31   08  AL  Etanol Hidratado   m3  2022-09-10  2002   1.895
32   09  AL  Etanol Hidratado   m3  2022-09-10  2002   1.787
33   10  AL  Etanol Hidratado   m3  2022-09-10  2002   2.032
34   11  AL  Etanol Hidratado   m3  2022-09-10  2002   1.502
35   12  AL  Etanol Hidratado   m3  2022-09-10  2002   1.460
36   01  AL  Etanol Hidratado   m3  2022-09-10  2003   1.653
37   02  AL  Etanol Hidratado   m3  2022-09-10  2003   1.436
38   03  AL  Etanol Hidratado   m3  2022-09-10  2003   1.218
39   04  AL  Etanol Hidratado   m3  2022-09-10  2003   1.957
40   05  AL  Etanol Hidratado   m3  2022-09-10  2003   2.185
41   06  AL  Etanol Hidratado   m3  2022-09-10  2003   2.078
42   07  AL  Etanol Hidratado   m3  2022-09-10  2003   1.834
43   08  AL  Etanol Hidratado   m3  2022-09-10  2003   1.345
44   09  AL  Etanol Hidratado   m3  2022-09-10  2003   1.694
45   10  AL  Etanol Hidratado   m3  2022-09-10  2003   1.355
46   11  AL  Etanol Hidratado   m3  2022-09-10  2003   1.481
47   12  AL  Etanol Hidratado   m3  2022-09-10  2003   1.814
48   01  AL  Etanol Hidratado   m3  2022-09-10  2004   1.699
49   02  AL  Etanol Hidratado   m3  2022-09-10  2004   1.295
50   03  AL  Etanol Hidratado   m3  2022-09-10  2004   1.627
51   04  AL  Etanol Hidratado   m3  2022-09-10  2004   1.563
52   05  AL  Etanol Hidratado   m3  2022-09-10  2004   1.547
53   06  AL  Etanol Hidratado   m3  2022-09-10  2004   2.168
54   07  AL  Etanol Hidratado   m3  2022-09-10  2004   2.877
55   08  AL  Etanol Hidratado   m3  2022-09-10  2004   2.532
56   09  AL  Etanol Hidratado   m3  2022-09-10  2004   2.500
57   10  AL  Etanol Hidratado   m3  2022-09-10  2004   2.146
58   11  AL  Etanol Hidratado   m3  2022-09-10  2004   1.891
59   12  AL  Etanol Hidratado   m3  2022-09-10  2004   1.673
60   01  AL  Etanol Hidratado   m3  2022-09-10  2005   1.435
61   02  AL  Etanol Hidratado   m3  2022-09-10  2005   1.370
62   03  AL  Etanol Hidratado   m3  2022-09-10  2005   1.383
63   04  AL  Etanol Hidratado   m3  2022-09-10  2005   1.370
64   05  AL  Etanol Hidratado   m3  202

In [739]:
# Concatenando as colunas ano e Mês
dfal['ano_mês'] = dfal[['ano', 'Mês']].agg('-'.join, axis=1)

In [740]:
# Eliminando as colunas Mês e ano

dfal.drop(["Mês"], axis=1, inplace=True)
dfal.drop(["ano"], axis=1, inplace=True)

In [741]:
# Organização da ordem das colunas

dfal =dfal[['ano_mês', 'uf', 'produto', 'unid', 'venda', 'criado_em']]

In [742]:
# Levantamento de possíveis inconsistências

dfal.isna().sum()

ano_mês      0
uf           0
produto      0
unid         0
venda        6
criado_em    0
dtype: int64

In [743]:
# Tratamento das inconsistências

dfal.replace(['Na', 'nA', 'na','NA', 'NaN', 'NAN', 'nan', '', ' '],pd.NA,inplace=True)


In [744]:
# Visão geral da tabela

dfal

ano_mês  uf           produto unid   venda   criado_em
0    2000-01  AL  Etanol Hidratado   m3   1.763  2022-09-10
1    2000-02  AL  Etanol Hidratado   m3   1.803  2022-09-10
2    2000-03  AL  Etanol Hidratado   m3   1.872  2022-09-10
3    2000-04  AL  Etanol Hidratado   m3   2.040  2022-09-10
4    2000-05  AL  Etanol Hidratado   m3   2.313  2022-09-10
5    2000-06  AL  Etanol Hidratado   m3   2.028  2022-09-10
6    2000-07  AL  Etanol Hidratado   m3   3.512  2022-09-10
7    2000-08  AL  Etanol Hidratado   m3   3.396  2022-09-10
8    2000-09  AL  Etanol Hidratado   m3   2.692  2022-09-10
9    2000-10  AL  Etanol Hidratado   m3   1.837  2022-09-10
10   2000-11  AL  Etanol Hidratado   m3   1.432  2022-09-10
11   2000-12  AL  Etanol Hidratado   m3   1.506  2022-09-10
12   2001-01  AL  Etanol Hidratado   m3   1.423  2022-09-10
13   2001-02  AL  Etanol Hidratado   m3   1.664  2022-09-10
14   2001-03  AL  Etanol Hidratado   m3   1.860  2022-09-10
15   2001-04  AL  Etanol Hidratado   m3   1.588  2022-09-10
16   2001-05  AL  Etanol Hidratado   m3   1.683  2022-09-10
17   2001-06  AL  Etanol Hidratado   m3   1.481  2022-09-10
18   2001-07  AL  Etanol Hidratado   m3   1.552  2022-09-10
19   2001-08  AL  Etanol Hidratado   m3   1.403  2022-09-10
20   2001-09  AL  Etanol Hidratado   m3   1.152  2022-09-10
21   2001-10  AL  Etanol Hidratado   m3   1.360  2022-09-10
22   2001-11  AL  Etanol Hidratado   m3   1.797  2022-09-10
23   2001-12  AL  Etanol Hidratado   m3   1.950  2022-09-10
24   2002-01  AL  Etanol Hidratado   m3   1.834  2022-09-10
25   2002-02  AL  Etanol Hidratado   m3   1.332  2022-09-10
26   2002-03  AL  Etanol Hidratado   m3   1.413  2022-09-10
27   2002-04  AL  Etanol Hidratado   m3   1.353  2022-09-10
28   2002-05  AL  Etanol Hidratado   m3   1.528  2022-09-10
29   2002-06  AL  Etanol Hidratado   m3   1.313  2022-09-10
30   2002-07  AL  Etanol Hidratado   m3   1.592  2022-09-10
31   2002-08  AL  Etanol Hidratado   m3   1.895  2022-09-10
32   2002-09  AL  Etanol Hidratado   m3   1.787  2022-09-10
33   2002-10  AL  Etanol Hidratado   m3   2.032  2022-09-10
34   2002-11  AL  Etanol Hidratado   m3   1.502  2022-09-10
35   2002-12  AL  Etanol Hidratado   m3   1.460  2022-09-10
36   2003-01  AL  Etanol Hidratado   m3   1.653  2022-09-10
37   2003-02  AL  Etanol Hidratado   m3   1.436  2022-09-10
38   2003-03  AL  Etanol Hidratado   m3   1.218  2022-09-10
39   2003-04  AL  Etanol Hidratado   m3   1.957  2022-09-10
40   2003-05  AL  Etanol Hidratado   m3   2.185  2022-09-10
41   2003-06  AL  Etanol Hidratado   m3   2.078  2022-09-10
42   2003-07  AL  Etanol Hidratado   m3   1.834  2022-09-10
43   2003-08  AL  Etanol Hidratado   m3   1.345  2022-09-10
44   2003-09  AL  Etanol Hidratado   m3   1.694  2022-09-10
45   2003-10  AL  Etanol Hidratado   m3   1.355  2022-09-10
46   2003-11  AL  Etanol Hidratado   m3   1.481  2022-09-10
47   2003-12  AL  Etanol Hidratado   m3   1.814  2022-09-10
48   2004-01  AL  Etanol Hidratado   m3   1.699  2022-09-10
49   2004-02  AL  Etanol Hidratado   m3   1.295  2022-09-10
50   2004-03  AL  Etanol Hidratado   m3   1.627  2022-09-10
51   2004-04  AL  Etanol Hidratado   m3   1.563  2022-09-10
52   2004-05  AL  Etanol Hidratado   m3   1.547  2022-09-10
53   2004-06  AL  Etanol Hidratado   m3   2.168  2022-09-10
54   2004-07  AL  Etanol Hidratado   m3   2.877  2022-09-10
55   2004-08  AL  Etanol Hidratado   m3   2.532  2022-09-10
56   2004-09  AL  Etanol Hidratado   m3   2.500  2022-09-10
57   2004-10  AL  Etanol Hidratado   m3   2.146  2022-09-10
58   2004-11  AL  Etanol Hidratado   m3   1.891  2022-09-10
59   2004-12  AL  Etanol Hidratado   m3   1.673  2022-09-10
60   2005-01  AL  Etanol Hidratado   m3   1.435  2022-09-10
61   2005-02  AL  Etanol Hidratado   m3   1.370  2022-09-10
62   2005-03  AL  Etanol Hidratado   m3   1.383  2022-09-10
63   2005-04  AL  Etanol Hidratado   m3   1.370  2022-09-10
64   2005-05  AL  Etanol Hidratado   m3   1.398  2022-09-10
65   2005-06  AL  Etanol Hidratado   m3   2.0

In [745]:
# Verificando os tipos

dfal.dtypes

ano_mês       object
uf            object
produto       object
unid          object
venda        float64
criado_em     object
dtype: object

In [746]:
# Validação

schema = pa.DataFrameSchema(
    columns = {
        'ano_mês': pa.Column(pa.String, nullable=True),
        'uf': pa.Column(pa.String, nullable = True),
        'produto': pa.Column(pa.String, nullable = True),
        'unid': pa.Column(pa.String, nullable = True),
        'venda': pa.Column(pa.Float, nullable = True),
        'criado_em': pa.Column(pa.String, nullable = True),
                
    }
)
schema.validate(dfal)

ano_mês  uf           produto unid   venda   criado_em
0    2000-01  AL  Etanol Hidratado   m3   1.763  2022-09-10
1    2000-02  AL  Etanol Hidratado   m3   1.803  2022-09-10
2    2000-03  AL  Etanol Hidratado   m3   1.872  2022-09-10
3    2000-04  AL  Etanol Hidratado   m3   2.040  2022-09-10
4    2000-05  AL  Etanol Hidratado   m3   2.313  2022-09-10
5    2000-06  AL  Etanol Hidratado   m3   2.028  2022-09-10
6    2000-07  AL  Etanol Hidratado   m3   3.512  2022-09-10
7    2000-08  AL  Etanol Hidratado   m3   3.396  2022-09-10
8    2000-09  AL  Etanol Hidratado   m3   2.692  2022-09-10
9    2000-10  AL  Etanol Hidratado   m3   1.837  2022-09-10
10   2000-11  AL  Etanol Hidratado   m3   1.432  2022-09-10
11   2000-12  AL  Etanol Hidratado   m3   1.506  2022-09-10
12   2001-01  AL  Etanol Hidratado   m3   1.423  2022-09-10
13   2001-02  AL  Etanol Hidratado   m3   1.664  2022-09-10
14   2001-03  AL  Etanol Hidratado   m3   1.860  2022-09-10
15   2001-04  AL  Etanol Hidratado   m3   1.588  2022-09-10
16   2001-05  AL  Etanol Hidratado   m3   1.683  2022-09-10
17   2001-06  AL  Etanol Hidratado   m3   1.481  2022-09-10
18   2001-07  AL  Etanol Hidratado   m3   1.552  2022-09-10
19   2001-08  AL  Etanol Hidratado   m3   1.403  2022-09-10
20   2001-09  AL  Etanol Hidratado   m3   1.152  2022-09-10
21   2001-10  AL  Etanol Hidratado   m3   1.360  2022-09-10
22   2001-11  AL  Etanol Hidratado   m3   1.797  2022-09-10
23   2001-12  AL  Etanol Hidratado   m3   1.950  2022-09-10
24   2002-01  AL  Etanol Hidratado   m3   1.834  2022-09-10
25   2002-02  AL  Etanol Hidratado   m3   1.332  2022-09-10
26   2002-03  AL  Etanol Hidratado   m3   1.413  2022-09-10
27   2002-04  AL  Etanol Hidratado   m3   1.353  2022-09-10
28   2002-05  AL  Etanol Hidratado   m3   1.528  2022-09-10
29   2002-06  AL  Etanol Hidratado   m3   1.313  2022-09-10
30   2002-07  AL  Etanol Hidratado   m3   1.592  2022-09-10
31   2002-08  AL  Etanol Hidratado   m3   1.895  2022-09-10
32   2002-09  AL  Etanol Hidratado   m3   1.787  2022-09-10
33   2002-10  AL  Etanol Hidratado   m3   2.032  2022-09-10
34   2002-11  AL  Etanol Hidratado   m3   1.502  2022-09-10
35   2002-12  AL  Etanol Hidratado   m3   1.460  2022-09-10
36   2003-01  AL  Etanol Hidratado   m3   1.653  2022-09-10
37   2003-02  AL  Etanol Hidratado   m3   1.436  2022-09-10
38   2003-03  AL  Etanol Hidratado   m3   1.218  2022-09-10
39   2003-04  AL  Etanol Hidratado   m3   1.957  2022-09-10
40   2003-05  AL  Etanol Hidratado   m3   2.185  2022-09-10
41   2003-06  AL  Etanol Hidratado   m3   2.078  2022-09-10
42   2003-07  AL  Etanol Hidratado   m3   1.834  2022-09-10
43   2003-08  AL  Etanol Hidratado   m3   1.345  2022-09-10
44   2003-09  AL  Etanol Hidratado   m3   1.694  2022-09-10
45   2003-10  AL  Etanol Hidratado   m3   1.355  2022-09-10
46   2003-11  AL  Etanol Hidratado   m3   1.481  2022-09-10
47   2003-12  AL  Etanol Hidratado   m3   1.814  2022-09-10
48   2004-01  AL  Etanol Hidratado   m3   1.699  2022-09-10
49   2004-02  AL  Etanol Hidratado   m3   1.295  2022-09-10
50   2004-03  AL  Etanol Hidratado   m3   1.627  2022-09-10
51   2004-04  AL  Etanol Hidratado   m3   1.563  2022-09-10
52   2004-05  AL  Etanol Hidratado   m3   1.547  2022-09-10
53   2004-06  AL  Etanol Hidratado   m3   2.168  2022-09-10
54   2004-07  AL  Etanol Hidratado   m3   2.877  2022-09-10
55   2004-08  AL  Etanol Hidratado   m3   2.532  2022-09-10
56   2004-09  AL  Etanol Hidratado   m3   2.500  2022-09-10
57   2004-10  AL  Etanol Hidratado   m3   2.146  2022-09-10
58   2004-11  AL  Etanol Hidratado   m3   1.891  2022-09-10
59   2004-12  AL  Etanol Hidratado   m3   1.673  2022-09-10
60   2005-01  AL  Etanol Hidratado   m3   1.435  2022-09-10
61   2005-02  AL  Etanol Hidratado   m3   1.370  2022-09-10
62   2005-03  AL  Etanol Hidratado   m3   1.383  2022-09-10
63   2005-04  AL  Etanol Hidratado   m3   1.370  2022-09-10
64   2005-05  AL  Etanol Hidratado   m3   1.398  2022-09-10
65   2005-06  AL  Etanol Hidratado   m3   2.0

In [747]:
dfal_pandas = dfal.copy()

##AMAZONAS

In [748]:
# Conector

dfam = pd.read_csv('/content/amazonas.csv',sep=';')

In [749]:
# Backup

dfam_backup = dfam.copy()

In [750]:
# Configurando a quantidade de linhas máximas mostradas em tela

pd.set_option('display.max_columns',1000)
pd.set_option('display.max_rows',1000)

In [751]:
# Visualização da Tabela

dfam

Mês   2000     2001     2002     2003     2004   2005     2006  \
0     Janeiro  1.439    1.162  789.000    1.664  870.000  1.103    1.676   
1   Fevereiro  1.465    1.068  782.000  926.000  819.000  1.052    1.421   
2       Março  1.408    1.353  751.000  956.000    1.137  1.149    1.353   
3       Abril  1.422    1.133    1.025    1.086  998.000  1.199  845.000   
4        Maio  1.498    1.197  879.000    1.082    1.054  1.371    1.119   
5       Junho  1.059    1.112    1.042  998.000    1.151  1.585    1.015   
6       Julho  1.510    1.091    1.139  928.000    1.170  1.465    1.142   
7      Agosto  1.515    1.172    1.297    1.076    1.235  1.840    1.358   
8    Setembro  1.344    1.054    1.206  912.000    1.138  1.756    1.373   
9     Outubro  1.404    1.253    1.358  952.000    1.239  1.933    1.517   
10   Novembro  1.378  976.000    1.147  925.000    1.226  2.200    1.679   
11   Dezembro  1.302  960.000  851.000    1.052    1.497  2.363    1.767   

     2007   2008   2009   2010   2011   2012   2013   2014   2015   2016  \
0   1.486  3.728  5.416  4.844  3.975  2.913  3.591  4.036  4.480  3.196   
1   1.667  3.694  5.146  3.630  4.005  2.925  3.703  4.077  5.945  3.864   
2   1.776  4.102  5.873  3.247  3.899  3.392  4.060  3.726  7.268  3.753   
3   1.788  4.278  6.105  4.255  2.640  3.159  3.886  3.771  6.776  2.741   
4   1.806  4.362  6.003  4.670  3.048  3.425  3.879  4.189  6.758  2.197   
5   2.105  4.121  6.889  4.494  2.771  3.172  3.638  3.669  6.708  2.029   
6   2.627  4.617  6.948  4.716  2.738  3.081  3.853  4.180  6.833  3.200   
7   3.230  4.647  7.481  5.218  3.307  3.499  4.041  4.282  6.955  4.530   
8   3.461  5.012  8.129  5.246  3.459  3.291  3.772  4.308  7.002  3.995   
9   4.220  5.224  7.351  4.660  3.571  3.797  4.107  4.378  7.894  2.905   
10  4.211  4.999  6.900  4.188  3.520  3.611  3.902  4.409  6.378  1.909   
11  4.126  5.920  7.361  5.707  3.585  3.804  4.580  5.414  5.603  4.052   

     2017    2018    2019    2020    2021    2022  
0   2.331   6.489   3.525   9.372   7.700   8.599  
1   2.260   5.984   4.227  12.854   9.317   9.045  
2   2.214   6.590   7.027  10.490  12.515  12.415  
3   3.614   6.676   8.031   6.705  12.571  13.622  
4   2.010   6.946   6.805   7.260  10.507  13.400  
5   2.060   6.390  11.296   9.124   9.305  12.130  
6   2.325   5.376  11.363   7.994  11.686     NaN  
7   3.026   8.530   7.848   9.090  11.346     NaN  
8   5.219   9.513   9.506  10.623  11.094     NaN  
9   5.156  11.085  10.673   9.918  12.261     NaN  
10  4.526  11.363  12.212   8.509  11.336     NaN  
11  4.117   5.589   9.532  10.958  11.174     NaN

In [752]:
# Replace do Mês para numérico

dfam["Mês"].replace("Janeiro", "01", inplace=True)
dfam["Mês"].replace("Fevereiro", "02", inplace=True)
dfam["Mês"].replace("Março", "03", inplace=True)
dfam["Mês"].replace("Abril", "04", inplace=True)
dfam["Mês"].replace("Maio", "05", inplace=True)
dfam["Mês"].replace("Junho", "06", inplace=True)
dfam["Mês"].replace("Julho", "07", inplace=True)
dfam["Mês"].replace("Agosto", "08", inplace=True)
dfam["Mês"].replace("Setembro", "09", inplace=True)
dfam["Mês"].replace("Outubro", "10", inplace=True)
dfam["Mês"].replace("Novembro", "11", inplace=True)
dfam["Mês"].replace("Dezembro", "12", inplace=True)

In [753]:
# Criação das colunas uf, produto, unid, criado_em

dfam['uf']='AM'
dfam['produto']='Etanol Hidratado'
dfam['unid']='m3'
dfam['criado_em'] ='2022-09-10'

In [754]:
# Despivotar a tabela em ano e volume 

dfam.reset_index(inplace=True)

In [755]:
dfam=dfam.melt(id_vars = ['Mês', 'uf', 'produto', 'unid', 'criado_em'], value_vars = ['2000', '2001', '2002', '2003', '2004', '2005', '2006', '2007', '2008', '2009', '2010', '2011', '2012', '2013', '2014', '2015', '2016', '2017', '2018', '2019', '2020', '2021', '2022'], var_name='ano', value_name='venda')

In [756]:
# Visão geral da tabela

dfam

Mês  uf           produto unid   criado_em   ano    venda
0    01  AM  Etanol Hidratado   m3  2022-09-10  2000    1.439
1    02  AM  Etanol Hidratado   m3  2022-09-10  2000    1.465
2    03  AM  Etanol Hidratado   m3  2022-09-10  2000    1.408
3    04  AM  Etanol Hidratado   m3  2022-09-10  2000    1.422
4    05  AM  Etanol Hidratado   m3  2022-09-10  2000    1.498
5    06  AM  Etanol Hidratado   m3  2022-09-10  2000    1.059
6    07  AM  Etanol Hidratado   m3  2022-09-10  2000    1.510
7    08  AM  Etanol Hidratado   m3  2022-09-10  2000    1.515
8    09  AM  Etanol Hidratado   m3  2022-09-10  2000    1.344
9    10  AM  Etanol Hidratado   m3  2022-09-10  2000    1.404
10   11  AM  Etanol Hidratado   m3  2022-09-10  2000    1.378
11   12  AM  Etanol Hidratado   m3  2022-09-10  2000    1.302
12   01  AM  Etanol Hidratado   m3  2022-09-10  2001    1.162
13   02  AM  Etanol Hidratado   m3  2022-09-10  2001    1.068
14   03  AM  Etanol Hidratado   m3  2022-09-10  2001    1.353
15   04  AM  Etanol Hidratado   m3  2022-09-10  2001    1.133
16   05  AM  Etanol Hidratado   m3  2022-09-10  2001    1.197
17   06  AM  Etanol Hidratado   m3  2022-09-10  2001    1.112
18   07  AM  Etanol Hidratado   m3  2022-09-10  2001    1.091
19   08  AM  Etanol Hidratado   m3  2022-09-10  2001    1.172
20   09  AM  Etanol Hidratado   m3  2022-09-10  2001    1.054
21   10  AM  Etanol Hidratado   m3  2022-09-10  2001    1.253
22   11  AM  Etanol Hidratado   m3  2022-09-10  2001  976.000
23   12  AM  Etanol Hidratado   m3  2022-09-10  2001  960.000
24   01  AM  Etanol Hidratado   m3  2022-09-10  2002  789.000
25   02  AM  Etanol Hidratado   m3  2022-09-10  2002  782.000
26   03  AM  Etanol Hidratado   m3  2022-09-10  2002  751.000
27   04  AM  Etanol Hidratado   m3  2022-09-10  2002    1.025
28   05  AM  Etanol Hidratado   m3  2022-09-10  2002  879.000
29   06  AM  Etanol Hidratado   m3  2022-09-10  2002    1.042
30   07  AM  Etanol Hidratado   m3  2022-09-10  2002    1.139
31   08  AM  Etanol Hidratado   m3  2022-09-10  2002    1.297
32   09  AM  Etanol Hidratado   m3  2022-09-10  2002    1.206
33   10  AM  Etanol Hidratado   m3  2022-09-10  2002    1.358
34   11  AM  Etanol Hidratado   m3  2022-09-10  2002    1.147
35   12  AM  Etanol Hidratado   m3  2022-09-10  2002  851.000
36   01  AM  Etanol Hidratado   m3  2022-09-10  2003    1.664
37   02  AM  Etanol Hidratado   m3  2022-09-10  2003  926.000
38   03  AM  Etanol Hidratado   m3  2022-09-10  2003  956.000
39   04  AM  Etanol Hidratado   m3  2022-09-10  2003    1.086
40   05  AM  Etanol Hidratado   m3  2022-09-10  2003    1.082
41   06  AM  Etanol Hidratado   m3  2022-09-10  2003  998.000
42   07  AM  Etanol Hidratado   m3  2022-09-10  2003  928.000
43   08  AM  Etanol Hidratado   m3  2022-09-10  2003    1.076
44   09  AM  Etanol Hidratado   m3  2022-09-10  2003  912.000
45   10  AM  Etanol Hidratado   m3  2022-09-10  2003  952.000
46   11  AM  Etanol Hidratado   m3  2022-09-10  2003  925.000
47   12  AM  Etanol Hidratado   m3  2022-09-10  2003    1.052
48   01  AM  Etanol Hidratado   m3  2022-09-10  2004  870.000
49   02  AM  Etanol Hidratado   m3  2022-09-10  2004  819.000
50   03  AM  Etanol Hidratado   m3  2022-09-10  2004    1.137
51   04  AM  Etanol Hidratado   m3  2022-09-10  2004  998.000
52   05  AM  Etanol Hidratado   m3  2022-09-10  2004    1.054
53   06  AM  Etanol Hidratado   m3  2022-09-10  2004    1.151
54   07  AM  Etanol Hidratado   m3  2022-09-10  2004    1.170
55   08  AM  Etanol Hidratado   m3  2022-09-10  2004    1.235
56   09  AM  Etanol Hidratado   m3  2022-09-10  2004    1.138
57   10  AM  Etanol Hidratado   m3  2022-09-10  2004    1.239
58   11  AM  Etanol Hidratado   m3  2022-09-10  2004    1.226
59   12  AM  Etanol Hidratado   m3  2022-09-10  2004    1.497
60   01  AM  Etanol Hidratado   m3  2022-09-10  2005    1.103
61   02  AM  Etanol Hidratado   m3  2022-09-10  2005    1.052
62   03  AM  Etanol Hidratado   m3  2022-09-10  2005    1.149
63   04  AM  Etanol Hidratado   m3  

In [757]:
# Concatenando as colunas ano e Mês
dfam['ano_mês'] = dfam[['ano', 'Mês']].agg('-'.join, axis=1)

In [758]:
# Eliminando as colunas Mês e ano

dfam.drop(["Mês"], axis=1, inplace=True)
dfam.drop(["ano"], axis=1, inplace=True)

In [759]:
# Organização da ordem das colunas

dfam =dfam[['ano_mês', 'uf', 'produto', 'unid', 'venda', 'criado_em']]

In [760]:
# Levantamento de possíveis inconsistências

dfam.isna().sum()

ano_mês      0
uf           0
produto      0
unid         0
venda        6
criado_em    0
dtype: int64

In [761]:
# Tratamento das inconsistências

dfam.replace(['Na', 'nA', 'na','NA', 'NaN', 'NAN', 'nan', '', ' '],pd.NA,inplace=True)


In [762]:
# Visão geral da tabela

dfam

ano_mês  uf           produto unid    venda   criado_em
0    2000-01  AM  Etanol Hidratado   m3    1.439  2022-09-10
1    2000-02  AM  Etanol Hidratado   m3    1.465  2022-09-10
2    2000-03  AM  Etanol Hidratado   m3    1.408  2022-09-10
3    2000-04  AM  Etanol Hidratado   m3    1.422  2022-09-10
4    2000-05  AM  Etanol Hidratado   m3    1.498  2022-09-10
5    2000-06  AM  Etanol Hidratado   m3    1.059  2022-09-10
6    2000-07  AM  Etanol Hidratado   m3    1.510  2022-09-10
7    2000-08  AM  Etanol Hidratado   m3    1.515  2022-09-10
8    2000-09  AM  Etanol Hidratado   m3    1.344  2022-09-10
9    2000-10  AM  Etanol Hidratado   m3    1.404  2022-09-10
10   2000-11  AM  Etanol Hidratado   m3    1.378  2022-09-10
11   2000-12  AM  Etanol Hidratado   m3    1.302  2022-09-10
12   2001-01  AM  Etanol Hidratado   m3    1.162  2022-09-10
13   2001-02  AM  Etanol Hidratado   m3    1.068  2022-09-10
14   2001-03  AM  Etanol Hidratado   m3    1.353  2022-09-10
15   2001-04  AM  Etanol Hidratado   m3    1.133  2022-09-10
16   2001-05  AM  Etanol Hidratado   m3    1.197  2022-09-10
17   2001-06  AM  Etanol Hidratado   m3    1.112  2022-09-10
18   2001-07  AM  Etanol Hidratado   m3    1.091  2022-09-10
19   2001-08  AM  Etanol Hidratado   m3    1.172  2022-09-10
20   2001-09  AM  Etanol Hidratado   m3    1.054  2022-09-10
21   2001-10  AM  Etanol Hidratado   m3    1.253  2022-09-10
22   2001-11  AM  Etanol Hidratado   m3  976.000  2022-09-10
23   2001-12  AM  Etanol Hidratado   m3  960.000  2022-09-10
24   2002-01  AM  Etanol Hidratado   m3  789.000  2022-09-10
25   2002-02  AM  Etanol Hidratado   m3  782.000  2022-09-10
26   2002-03  AM  Etanol Hidratado   m3  751.000  2022-09-10
27   2002-04  AM  Etanol Hidratado   m3    1.025  2022-09-10
28   2002-05  AM  Etanol Hidratado   m3  879.000  2022-09-10
29   2002-06  AM  Etanol Hidratado   m3    1.042  2022-09-10
30   2002-07  AM  Etanol Hidratado   m3    1.139  2022-09-10
31   2002-08  AM  Etanol Hidratado   m3    1.297  2022-09-10
32   2002-09  AM  Etanol Hidratado   m3    1.206  2022-09-10
33   2002-10  AM  Etanol Hidratado   m3    1.358  2022-09-10
34   2002-11  AM  Etanol Hidratado   m3    1.147  2022-09-10
35   2002-12  AM  Etanol Hidratado   m3  851.000  2022-09-10
36   2003-01  AM  Etanol Hidratado   m3    1.664  2022-09-10
37   2003-02  AM  Etanol Hidratado   m3  926.000  2022-09-10
38   2003-03  AM  Etanol Hidratado   m3  956.000  2022-09-10
39   2003-04  AM  Etanol Hidratado   m3    1.086  2022-09-10
40   2003-05  AM  Etanol Hidratado   m3    1.082  2022-09-10
41   2003-06  AM  Etanol Hidratado   m3  998.000  2022-09-10
42   2003-07  AM  Etanol Hidratado   m3  928.000  2022-09-10
43   2003-08  AM  Etanol Hidratado   m3    1.076  2022-09-10
44   2003-09  AM  Etanol Hidratado   m3  912.000  2022-09-10
45   2003-10  AM  Etanol Hidratado   m3  952.000  2022-09-10
46   2003-11  AM  Etanol Hidratado   m3  925.000  2022-09-10
47   2003-12  AM  Etanol Hidratado   m3    1.052  2022-09-10
48   2004-01  AM  Etanol Hidratado   m3  870.000  2022-09-10
49   2004-02  AM  Etanol Hidratado   m3  819.000  2022-09-10
50   2004-03  AM  Etanol Hidratado   m3    1.137  2022-09-10
51   2004-04  AM  Etanol Hidratado   m3  998.000  2022-09-10
52   2004-05  AM  Etanol Hidratado   m3    1.054  2022-09-10
53   2004-06  AM  Etanol Hidratado   m3    1.151  2022-09-10
54   2004-07  AM  Etanol Hidratado   m3    1.170  2022-09-10
55   2004-08  AM  Etanol Hidratado   m3    1.235  2022-09-10
56   2004-09  AM  Etanol Hidratado   m3    1.138  2022-09-10
57   2004-10  AM  Etanol Hidratado   m3    1.239  2022-09-10
58   2004-11  AM  Etanol Hidratado   m3    1.226  2022-09-10
59   2004-12  AM  Etanol Hidratado   m3    1.497  2022-09-10
60   2005-01  AM  Etanol Hidratado   m3    1.103  2022-09-10
61   2005-02  AM  Etanol Hidratado   m3    1.052  2022-09-10
62   2005-03  AM  Etanol Hidratado   m3    1.149  2022-09-10
63   2005-04  AM  Etanol Hidratado   m3    1.199  2022-09-10
64   2005-05  AM  Etanol Hidratado   m3 

In [763]:
# Verificando os tipos

dfam.dtypes

ano_mês       object
uf            object
produto       object
unid          object
venda        float64
criado_em     object
dtype: object

In [764]:
# Validação

schema = pa.DataFrameSchema(
    columns = {
        'ano_mês': pa.Column(pa.String, nullable=True),
        'uf': pa.Column(pa.String, nullable = True),
        'produto': pa.Column(pa.String, nullable = True),
        'unid': pa.Column(pa.String, nullable = True),
        'venda': pa.Column(pa.Float, nullable = True),
        'criado_em': pa.Column(pa.String, nullable = True),
                
    }
)
schema.validate(dfam)

ano_mês  uf           produto unid    venda   criado_em
0    2000-01  AM  Etanol Hidratado   m3    1.439  2022-09-10
1    2000-02  AM  Etanol Hidratado   m3    1.465  2022-09-10
2    2000-03  AM  Etanol Hidratado   m3    1.408  2022-09-10
3    2000-04  AM  Etanol Hidratado   m3    1.422  2022-09-10
4    2000-05  AM  Etanol Hidratado   m3    1.498  2022-09-10
5    2000-06  AM  Etanol Hidratado   m3    1.059  2022-09-10
6    2000-07  AM  Etanol Hidratado   m3    1.510  2022-09-10
7    2000-08  AM  Etanol Hidratado   m3    1.515  2022-09-10
8    2000-09  AM  Etanol Hidratado   m3    1.344  2022-09-10
9    2000-10  AM  Etanol Hidratado   m3    1.404  2022-09-10
10   2000-11  AM  Etanol Hidratado   m3    1.378  2022-09-10
11   2000-12  AM  Etanol Hidratado   m3    1.302  2022-09-10
12   2001-01  AM  Etanol Hidratado   m3    1.162  2022-09-10
13   2001-02  AM  Etanol Hidratado   m3    1.068  2022-09-10
14   2001-03  AM  Etanol Hidratado   m3    1.353  2022-09-10
15   2001-04  AM  Etanol Hidratado   m3    1.133  2022-09-10
16   2001-05  AM  Etanol Hidratado   m3    1.197  2022-09-10
17   2001-06  AM  Etanol Hidratado   m3    1.112  2022-09-10
18   2001-07  AM  Etanol Hidratado   m3    1.091  2022-09-10
19   2001-08  AM  Etanol Hidratado   m3    1.172  2022-09-10
20   2001-09  AM  Etanol Hidratado   m3    1.054  2022-09-10
21   2001-10  AM  Etanol Hidratado   m3    1.253  2022-09-10
22   2001-11  AM  Etanol Hidratado   m3  976.000  2022-09-10
23   2001-12  AM  Etanol Hidratado   m3  960.000  2022-09-10
24   2002-01  AM  Etanol Hidratado   m3  789.000  2022-09-10
25   2002-02  AM  Etanol Hidratado   m3  782.000  2022-09-10
26   2002-03  AM  Etanol Hidratado   m3  751.000  2022-09-10
27   2002-04  AM  Etanol Hidratado   m3    1.025  2022-09-10
28   2002-05  AM  Etanol Hidratado   m3  879.000  2022-09-10
29   2002-06  AM  Etanol Hidratado   m3    1.042  2022-09-10
30   2002-07  AM  Etanol Hidratado   m3    1.139  2022-09-10
31   2002-08  AM  Etanol Hidratado   m3    1.297  2022-09-10
32   2002-09  AM  Etanol Hidratado   m3    1.206  2022-09-10
33   2002-10  AM  Etanol Hidratado   m3    1.358  2022-09-10
34   2002-11  AM  Etanol Hidratado   m3    1.147  2022-09-10
35   2002-12  AM  Etanol Hidratado   m3  851.000  2022-09-10
36   2003-01  AM  Etanol Hidratado   m3    1.664  2022-09-10
37   2003-02  AM  Etanol Hidratado   m3  926.000  2022-09-10
38   2003-03  AM  Etanol Hidratado   m3  956.000  2022-09-10
39   2003-04  AM  Etanol Hidratado   m3    1.086  2022-09-10
40   2003-05  AM  Etanol Hidratado   m3    1.082  2022-09-10
41   2003-06  AM  Etanol Hidratado   m3  998.000  2022-09-10
42   2003-07  AM  Etanol Hidratado   m3  928.000  2022-09-10
43   2003-08  AM  Etanol Hidratado   m3    1.076  2022-09-10
44   2003-09  AM  Etanol Hidratado   m3  912.000  2022-09-10
45   2003-10  AM  Etanol Hidratado   m3  952.000  2022-09-10
46   2003-11  AM  Etanol Hidratado   m3  925.000  2022-09-10
47   2003-12  AM  Etanol Hidratado   m3    1.052  2022-09-10
48   2004-01  AM  Etanol Hidratado   m3  870.000  2022-09-10
49   2004-02  AM  Etanol Hidratado   m3  819.000  2022-09-10
50   2004-03  AM  Etanol Hidratado   m3    1.137  2022-09-10
51   2004-04  AM  Etanol Hidratado   m3  998.000  2022-09-10
52   2004-05  AM  Etanol Hidratado   m3    1.054  2022-09-10
53   2004-06  AM  Etanol Hidratado   m3    1.151  2022-09-10
54   2004-07  AM  Etanol Hidratado   m3    1.170  2022-09-10
55   2004-08  AM  Etanol Hidratado   m3    1.235  2022-09-10
56   2004-09  AM  Etanol Hidratado   m3    1.138  2022-09-10
57   2004-10  AM  Etanol Hidratado   m3    1.239  2022-09-10
58   2004-11  AM  Etanol Hidratado   m3    1.226  2022-09-10
59   2004-12  AM  Etanol Hidratado   m3    1.497  2022-09-10
60   2005-01  AM  Etanol Hidratado   m3    1.103  2022-09-10
61   2005-02  AM  Etanol Hidratado   m3    1.052  2022-09-10
62   2005-03  AM  Etanol Hidratado   m3    1.149  2022-09-10
63   2005-04  AM  Etanol Hidratado   m3    1.199  2022-09-10
64   2005-05  AM  Etanol Hidratado   m3 

In [765]:
dfam_pandas = dfam.copy()

##AMAPÁ

In [766]:
# Conector

dfap = pd.read_csv('/content/amapa.csv',sep=';')

In [767]:
# Backup

dfap_backup = dfap.copy()

In [768]:
# Configurando a quantidade de linhas máximas mostradas em tela

pd.set_option('display.max_columns',1000)
pd.set_option('display.max_rows',1000)

In [769]:
# Visualização da Tabela

dfap

Mês  2000  2001  2002  2003  2004  2005  2006  2007  2008  2009  \
0     Janeiro   119   101    94   102    82    44   120    94   192   399   
1   Fevereiro   164   106    98    94    25    84    68    79   204   509   
2       Março   108   119    80    69   107    54    54   114   298   533   
3       Abril   124    91   114    79    60    67    65   112   284   612   
4        Maio   124   112    81    69    61    58    82   158   289   581   
5       Junho    98    83   134    50    50    63    62   117   266   756   
6       Julho   122    99    92   109    60    82    68    84   215   825   
7      Agosto   147   100    84    53    59    83    92   111   170   940   
8    Setembro   148    87   135    80    81    83    68    83   176   908   
9     Outubro   114   119   155    63    64    82    69   128   145   799   
10   Novembro   140   102    96    56    58   106    90   165   201   626   
11   Dezembro   115   111   140    56    63    86    88   208   332   808   

    2010  2011  2012  2013  2014  2015  2016  2017  2018  2019  2020  2021  \
0    469   466   302    75   182   121    90    20    65    60    77    30   
1    320   488   305    50   172   114    80    10    65    40    25    35   
2    461   408   307    80   110   113    40    10    70    35    45    60   
3    467   316   326   100    69   118    25    20    60    60     5    25   
4    557   448   291   167    86   209    25    10    90    85    25    40   
5    479   436   280    76    50   212    20    20    60    81    13    20   
6    721   422   296   177    82   222    90    20    90    57    40    25   
7    641   426   376   113    89   197    65    40    75    85    45    25   
8    826   431   274   161    70   275    44    45    95    87    40    15   
9    648   391   115   173    94   317    20    70   105    95    25    10   
10   494   392   237   125    71   185    15    60   100    84    15    25   
11   639   311   203   162   102   110    25    70    55    94    30    15   

      2022  
0   20.000  
1   15.000  
2   35.000  
3   40.000  
4    2.638  
5    3.679  
6      NaN  
7      NaN  
8      NaN  
9      NaN  
10     NaN  
11     NaN

In [770]:
# Replace do Mês para numérico

dfap["Mês"].replace("Janeiro", "01", inplace=True)
dfap["Mês"].replace("Fevereiro", "02", inplace=True)
dfap["Mês"].replace("Março", "03", inplace=True)
dfap["Mês"].replace("Abril", "04", inplace=True)
dfap["Mês"].replace("Maio", "05", inplace=True)
dfap["Mês"].replace("Junho", "06", inplace=True)
dfap["Mês"].replace("Julho", "07", inplace=True)
dfap["Mês"].replace("Agosto", "08", inplace=True)
dfap["Mês"].replace("Setembro", "09", inplace=True)
dfap["Mês"].replace("Outubro", "10", inplace=True)
dfap["Mês"].replace("Novembro", "11", inplace=True)
dfap["Mês"].replace("Dezembro", "12", inplace=True)

In [771]:
# Criação das colunas uf, produto, unid, criado_em

dfap['uf']='AP'
dfap['produto']='Etanol Hidratado'
dfap['unid']='m3'
dfap['criado_em'] ='2022-09-10'

In [772]:
# Despivotar a tabela em ano e volume 

dfap.reset_index(inplace=True)

In [773]:
dfap=dfap.melt(id_vars = ['Mês', 'uf', 'produto', 'unid', 'criado_em'], value_vars = ['2000', '2001', '2002', '2003', '2004', '2005', '2006', '2007', '2008', '2009', '2010', '2011', '2012', '2013', '2014', '2015', '2016', '2017', '2018', '2019', '2020', '2021', '2022'], var_name='ano', value_name='venda')

In [774]:
# Visão geral da tabela

dfap

Mês  uf           produto unid   criado_em   ano    venda
0    01  AP  Etanol Hidratado   m3  2022-09-10  2000  119.000
1    02  AP  Etanol Hidratado   m3  2022-09-10  2000  164.000
2    03  AP  Etanol Hidratado   m3  2022-09-10  2000  108.000
3    04  AP  Etanol Hidratado   m3  2022-09-10  2000  124.000
4    05  AP  Etanol Hidratado   m3  2022-09-10  2000  124.000
5    06  AP  Etanol Hidratado   m3  2022-09-10  2000   98.000
6    07  AP  Etanol Hidratado   m3  2022-09-10  2000  122.000
7    08  AP  Etanol Hidratado   m3  2022-09-10  2000  147.000
8    09  AP  Etanol Hidratado   m3  2022-09-10  2000  148.000
9    10  AP  Etanol Hidratado   m3  2022-09-10  2000  114.000
10   11  AP  Etanol Hidratado   m3  2022-09-10  2000  140.000
11   12  AP  Etanol Hidratado   m3  2022-09-10  2000  115.000
12   01  AP  Etanol Hidratado   m3  2022-09-10  2001  101.000
13   02  AP  Etanol Hidratado   m3  2022-09-10  2001  106.000
14   03  AP  Etanol Hidratado   m3  2022-09-10  2001  119.000
15   04  AP  Etanol Hidratado   m3  2022-09-10  2001   91.000
16   05  AP  Etanol Hidratado   m3  2022-09-10  2001  112.000
17   06  AP  Etanol Hidratado   m3  2022-09-10  2001   83.000
18   07  AP  Etanol Hidratado   m3  2022-09-10  2001   99.000
19   08  AP  Etanol Hidratado   m3  2022-09-10  2001  100.000
20   09  AP  Etanol Hidratado   m3  2022-09-10  2001   87.000
21   10  AP  Etanol Hidratado   m3  2022-09-10  2001  119.000
22   11  AP  Etanol Hidratado   m3  2022-09-10  2001  102.000
23   12  AP  Etanol Hidratado   m3  2022-09-10  2001  111.000
24   01  AP  Etanol Hidratado   m3  2022-09-10  2002   94.000
25   02  AP  Etanol Hidratado   m3  2022-09-10  2002   98.000
26   03  AP  Etanol Hidratado   m3  2022-09-10  2002   80.000
27   04  AP  Etanol Hidratado   m3  2022-09-10  2002  114.000
28   05  AP  Etanol Hidratado   m3  2022-09-10  2002   81.000
29   06  AP  Etanol Hidratado   m3  2022-09-10  2002  134.000
30   07  AP  Etanol Hidratado   m3  2022-09-10  2002   92.000
31   08  AP  Etanol Hidratado   m3  2022-09-10  2002   84.000
32   09  AP  Etanol Hidratado   m3  2022-09-10  2002  135.000
33   10  AP  Etanol Hidratado   m3  2022-09-10  2002  155.000
34   11  AP  Etanol Hidratado   m3  2022-09-10  2002   96.000
35   12  AP  Etanol Hidratado   m3  2022-09-10  2002  140.000
36   01  AP  Etanol Hidratado   m3  2022-09-10  2003  102.000
37   02  AP  Etanol Hidratado   m3  2022-09-10  2003   94.000
38   03  AP  Etanol Hidratado   m3  2022-09-10  2003   69.000
39   04  AP  Etanol Hidratado   m3  2022-09-10  2003   79.000
40   05  AP  Etanol Hidratado   m3  2022-09-10  2003   69.000
41   06  AP  Etanol Hidratado   m3  2022-09-10  2003   50.000
42   07  AP  Etanol Hidratado   m3  2022-09-10  2003  109.000
43   08  AP  Etanol Hidratado   m3  2022-09-10  2003   53.000
44   09  AP  Etanol Hidratado   m3  2022-09-10  2003   80.000
45   10  AP  Etanol Hidratado   m3  2022-09-10  2003   63.000
46   11  AP  Etanol Hidratado   m3  2022-09-10  2003   56.000
47   12  AP  Etanol Hidratado   m3  2022-09-10  2003   56.000
48   01  AP  Etanol Hidratado   m3  2022-09-10  2004   82.000
49   02  AP  Etanol Hidratado   m3  2022-09-10  2004   25.000
50   03  AP  Etanol Hidratado   m3  2022-09-10  2004  107.000
51   04  AP  Etanol Hidratado   m3  2022-09-10  2004   60.000
52   05  AP  Etanol Hidratado   m3  2022-09-10  2004   61.000
53   06  AP  Etanol Hidratado   m3  2022-09-10  2004   50.000
54   07  AP  Etanol Hidratado   m3  2022-09-10  2004   60.000
55   08  AP  Etanol Hidratado   m3  2022-09-10  2004   59.000
56   09  AP  Etanol Hidratado   m3  2022-09-10  2004   81.000
57   10  AP  Etanol Hidratado   m3  2022-09-10  2004   64.000
58   11  AP  Etanol Hidratado   m3  2022-09-10  2004   58.000
59   12  AP  Etanol Hidratado   m3  2022-09-10  2004   63.000
60   01  AP  Etanol Hidratado   m3  2022-09-10  2005   44.000
61   02  AP  Etanol Hidratado   m3  2022-09-10  2005   84.000
62   03  AP  Etanol Hidratado   m3  2022-09-10  2005   54.000
63   04  AP  Etanol Hidratado   m3  

In [775]:
# Concatenando as colunas ano e Mês

dfap['ano_mês'] = dfap[['ano', 'Mês']].agg('-'.join, axis=1)

In [776]:
# Eliminando as colunas Mês e ano

dfap.drop(["Mês"], axis=1, inplace=True)
dfap.drop(["ano"], axis=1, inplace=True)

In [777]:
# Organização da ordem das colunas

dfap =dfap[['ano_mês', 'uf', 'produto', 'unid', 'venda', 'criado_em']]

In [778]:
# Levantamento de possíveis inconsistências

dfap.isna().sum()

ano_mês      0
uf           0
produto      0
unid         0
venda        6
criado_em    0
dtype: int64

In [779]:
# Tratamento das inconsistências

dfap.replace(['Na', 'nA', 'na','NA', 'NaN', 'NAN', 'nan', '', ' '],pd.NA,inplace=True)


In [780]:
# Visão geral da tabela

dfap

ano_mês  uf           produto unid    venda   criado_em
0    2000-01  AP  Etanol Hidratado   m3  119.000  2022-09-10
1    2000-02  AP  Etanol Hidratado   m3  164.000  2022-09-10
2    2000-03  AP  Etanol Hidratado   m3  108.000  2022-09-10
3    2000-04  AP  Etanol Hidratado   m3  124.000  2022-09-10
4    2000-05  AP  Etanol Hidratado   m3  124.000  2022-09-10
5    2000-06  AP  Etanol Hidratado   m3   98.000  2022-09-10
6    2000-07  AP  Etanol Hidratado   m3  122.000  2022-09-10
7    2000-08  AP  Etanol Hidratado   m3  147.000  2022-09-10
8    2000-09  AP  Etanol Hidratado   m3  148.000  2022-09-10
9    2000-10  AP  Etanol Hidratado   m3  114.000  2022-09-10
10   2000-11  AP  Etanol Hidratado   m3  140.000  2022-09-10
11   2000-12  AP  Etanol Hidratado   m3  115.000  2022-09-10
12   2001-01  AP  Etanol Hidratado   m3  101.000  2022-09-10
13   2001-02  AP  Etanol Hidratado   m3  106.000  2022-09-10
14   2001-03  AP  Etanol Hidratado   m3  119.000  2022-09-10
15   2001-04  AP  Etanol Hidratado   m3   91.000  2022-09-10
16   2001-05  AP  Etanol Hidratado   m3  112.000  2022-09-10
17   2001-06  AP  Etanol Hidratado   m3   83.000  2022-09-10
18   2001-07  AP  Etanol Hidratado   m3   99.000  2022-09-10
19   2001-08  AP  Etanol Hidratado   m3  100.000  2022-09-10
20   2001-09  AP  Etanol Hidratado   m3   87.000  2022-09-10
21   2001-10  AP  Etanol Hidratado   m3  119.000  2022-09-10
22   2001-11  AP  Etanol Hidratado   m3  102.000  2022-09-10
23   2001-12  AP  Etanol Hidratado   m3  111.000  2022-09-10
24   2002-01  AP  Etanol Hidratado   m3   94.000  2022-09-10
25   2002-02  AP  Etanol Hidratado   m3   98.000  2022-09-10
26   2002-03  AP  Etanol Hidratado   m3   80.000  2022-09-10
27   2002-04  AP  Etanol Hidratado   m3  114.000  2022-09-10
28   2002-05  AP  Etanol Hidratado   m3   81.000  2022-09-10
29   2002-06  AP  Etanol Hidratado   m3  134.000  2022-09-10
30   2002-07  AP  Etanol Hidratado   m3   92.000  2022-09-10
31   2002-08  AP  Etanol Hidratado   m3   84.000  2022-09-10
32   2002-09  AP  Etanol Hidratado   m3  135.000  2022-09-10
33   2002-10  AP  Etanol Hidratado   m3  155.000  2022-09-10
34   2002-11  AP  Etanol Hidratado   m3   96.000  2022-09-10
35   2002-12  AP  Etanol Hidratado   m3  140.000  2022-09-10
36   2003-01  AP  Etanol Hidratado   m3  102.000  2022-09-10
37   2003-02  AP  Etanol Hidratado   m3   94.000  2022-09-10
38   2003-03  AP  Etanol Hidratado   m3   69.000  2022-09-10
39   2003-04  AP  Etanol Hidratado   m3   79.000  2022-09-10
40   2003-05  AP  Etanol Hidratado   m3   69.000  2022-09-10
41   2003-06  AP  Etanol Hidratado   m3   50.000  2022-09-10
42   2003-07  AP  Etanol Hidratado   m3  109.000  2022-09-10
43   2003-08  AP  Etanol Hidratado   m3   53.000  2022-09-10
44   2003-09  AP  Etanol Hidratado   m3   80.000  2022-09-10
45   2003-10  AP  Etanol Hidratado   m3   63.000  2022-09-10
46   2003-11  AP  Etanol Hidratado   m3   56.000  2022-09-10
47   2003-12  AP  Etanol Hidratado   m3   56.000  2022-09-10
48   2004-01  AP  Etanol Hidratado   m3   82.000  2022-09-10
49   2004-02  AP  Etanol Hidratado   m3   25.000  2022-09-10
50   2004-03  AP  Etanol Hidratado   m3  107.000  2022-09-10
51   2004-04  AP  Etanol Hidratado   m3   60.000  2022-09-10
52   2004-05  AP  Etanol Hidratado   m3   61.000  2022-09-10
53   2004-06  AP  Etanol Hidratado   m3   50.000  2022-09-10
54   2004-07  AP  Etanol Hidratado   m3   60.000  2022-09-10
55   2004-08  AP  Etanol Hidratado   m3   59.000  2022-09-10
56   2004-09  AP  Etanol Hidratado   m3   81.000  2022-09-10
57   2004-10  AP  Etanol Hidratado   m3   64.000  2022-09-10
58   2004-11  AP  Etanol Hidratado   m3   58.000  2022-09-10
59   2004-12  AP  Etanol Hidratado   m3   63.000  2022-09-10
60   2005-01  AP  Etanol Hidratado   m3   44.000  2022-09-10
61   2005-02  AP  Etanol Hidratado   m3   84.000  2022-09-10
62   2005-03  AP  Etanol Hidratado   m3   54.000  2022-09-10
63   2005-04  AP  Etanol Hidratado   m3   67.000  2022-09-10
64   2005-05  AP  Etanol Hidratado   m3 

In [781]:
# Verificando os tipos

dfap.dtypes

ano_mês       object
uf            object
produto       object
unid          object
venda        float64
criado_em     object
dtype: object

In [782]:
# Validação

schema = pa.DataFrameSchema(
    columns = {
        'ano_mês': pa.Column(pa.String, nullable=True),
        'uf': pa.Column(pa.String, nullable = True),
        'produto': pa.Column(pa.String, nullable = True),
        'unid': pa.Column(pa.String, nullable = True),
        'venda': pa.Column(pa.Float, nullable = True),
        'criado_em': pa.Column(pa.String, nullable = True),
                
    }
)
schema.validate(dfap)

ano_mês  uf           produto unid    venda   criado_em
0    2000-01  AP  Etanol Hidratado   m3  119.000  2022-09-10
1    2000-02  AP  Etanol Hidratado   m3  164.000  2022-09-10
2    2000-03  AP  Etanol Hidratado   m3  108.000  2022-09-10
3    2000-04  AP  Etanol Hidratado   m3  124.000  2022-09-10
4    2000-05  AP  Etanol Hidratado   m3  124.000  2022-09-10
5    2000-06  AP  Etanol Hidratado   m3   98.000  2022-09-10
6    2000-07  AP  Etanol Hidratado   m3  122.000  2022-09-10
7    2000-08  AP  Etanol Hidratado   m3  147.000  2022-09-10
8    2000-09  AP  Etanol Hidratado   m3  148.000  2022-09-10
9    2000-10  AP  Etanol Hidratado   m3  114.000  2022-09-10
10   2000-11  AP  Etanol Hidratado   m3  140.000  2022-09-10
11   2000-12  AP  Etanol Hidratado   m3  115.000  2022-09-10
12   2001-01  AP  Etanol Hidratado   m3  101.000  2022-09-10
13   2001-02  AP  Etanol Hidratado   m3  106.000  2022-09-10
14   2001-03  AP  Etanol Hidratado   m3  119.000  2022-09-10
15   2001-04  AP  Etanol Hidratado   m3   91.000  2022-09-10
16   2001-05  AP  Etanol Hidratado   m3  112.000  2022-09-10
17   2001-06  AP  Etanol Hidratado   m3   83.000  2022-09-10
18   2001-07  AP  Etanol Hidratado   m3   99.000  2022-09-10
19   2001-08  AP  Etanol Hidratado   m3  100.000  2022-09-10
20   2001-09  AP  Etanol Hidratado   m3   87.000  2022-09-10
21   2001-10  AP  Etanol Hidratado   m3  119.000  2022-09-10
22   2001-11  AP  Etanol Hidratado   m3  102.000  2022-09-10
23   2001-12  AP  Etanol Hidratado   m3  111.000  2022-09-10
24   2002-01  AP  Etanol Hidratado   m3   94.000  2022-09-10
25   2002-02  AP  Etanol Hidratado   m3   98.000  2022-09-10
26   2002-03  AP  Etanol Hidratado   m3   80.000  2022-09-10
27   2002-04  AP  Etanol Hidratado   m3  114.000  2022-09-10
28   2002-05  AP  Etanol Hidratado   m3   81.000  2022-09-10
29   2002-06  AP  Etanol Hidratado   m3  134.000  2022-09-10
30   2002-07  AP  Etanol Hidratado   m3   92.000  2022-09-10
31   2002-08  AP  Etanol Hidratado   m3   84.000  2022-09-10
32   2002-09  AP  Etanol Hidratado   m3  135.000  2022-09-10
33   2002-10  AP  Etanol Hidratado   m3  155.000  2022-09-10
34   2002-11  AP  Etanol Hidratado   m3   96.000  2022-09-10
35   2002-12  AP  Etanol Hidratado   m3  140.000  2022-09-10
36   2003-01  AP  Etanol Hidratado   m3  102.000  2022-09-10
37   2003-02  AP  Etanol Hidratado   m3   94.000  2022-09-10
38   2003-03  AP  Etanol Hidratado   m3   69.000  2022-09-10
39   2003-04  AP  Etanol Hidratado   m3   79.000  2022-09-10
40   2003-05  AP  Etanol Hidratado   m3   69.000  2022-09-10
41   2003-06  AP  Etanol Hidratado   m3   50.000  2022-09-10
42   2003-07  AP  Etanol Hidratado   m3  109.000  2022-09-10
43   2003-08  AP  Etanol Hidratado   m3   53.000  2022-09-10
44   2003-09  AP  Etanol Hidratado   m3   80.000  2022-09-10
45   2003-10  AP  Etanol Hidratado   m3   63.000  2022-09-10
46   2003-11  AP  Etanol Hidratado   m3   56.000  2022-09-10
47   2003-12  AP  Etanol Hidratado   m3   56.000  2022-09-10
48   2004-01  AP  Etanol Hidratado   m3   82.000  2022-09-10
49   2004-02  AP  Etanol Hidratado   m3   25.000  2022-09-10
50   2004-03  AP  Etanol Hidratado   m3  107.000  2022-09-10
51   2004-04  AP  Etanol Hidratado   m3   60.000  2022-09-10
52   2004-05  AP  Etanol Hidratado   m3   61.000  2022-09-10
53   2004-06  AP  Etanol Hidratado   m3   50.000  2022-09-10
54   2004-07  AP  Etanol Hidratado   m3   60.000  2022-09-10
55   2004-08  AP  Etanol Hidratado   m3   59.000  2022-09-10
56   2004-09  AP  Etanol Hidratado   m3   81.000  2022-09-10
57   2004-10  AP  Etanol Hidratado   m3   64.000  2022-09-10
58   2004-11  AP  Etanol Hidratado   m3   58.000  2022-09-10
59   2004-12  AP  Etanol Hidratado   m3   63.000  2022-09-10
60   2005-01  AP  Etanol Hidratado   m3   44.000  2022-09-10
61   2005-02  AP  Etanol Hidratado   m3   84.000  2022-09-10
62   2005-03  AP  Etanol Hidratado   m3   54.000  2022-09-10
63   2005-04  AP  Etanol Hidratado   m3   67.000  2022-09-10
64   2005-05  AP  Etanol Hidratado   m3 

In [783]:
dfap_pandas = dfap.copy()

##BAHIA

In [784]:
# Conector

dfba = pd.read_csv('/content/bahia.csv',sep=';')

In [785]:
# Backup

dfba_backup = dfba.copy()

In [786]:
# Configurando a quantidade de linhas máximas mostradas em tela

pd.set_option('display.max_columns',1000)
pd.set_option('display.max_rows',1000)

In [787]:
# Visualização da Tabela

dfba

Mês    2000    2001   2002   2003   2004    2005    2006    2007  \
0     Janeiro  10.367  10.500  5.265  4.603  5.202   4.684   9.955  11.745   
1   Fevereiro   9.105   7.977  4.030  4.168  4.444   3.980   8.918   9.585   
2       Março   8.536   7.376  3.804  2.776  5.643   4.340   8.236  11.786   
3       Abril   8.058   5.508  4.331  3.278  5.076   4.296   6.305  10.887   
4        Maio   8.013   5.237  4.388  2.941  4.501   4.671   6.548  11.795   
5       Junho   6.527   5.547  4.135  4.136  4.863   4.893   7.439  12.296   
6       Julho   8.602   4.818  4.330  4.714  5.174   5.218   7.112  13.556   
7      Agosto   8.059   4.758  2.975  3.864  4.963   5.255   7.993  15.102   
8    Setembro   7.359   4.289  4.414  4.473  5.203   5.998   7.145  15.020   
9     Outubro   7.063   4.457  5.194  4.671  5.373   6.605   7.324  19.500   
10   Novembro   8.173   4.252  3.742  4.493  4.242   7.025   8.057  20.369   
11   Dezembro  11.660   4.814  3.743  5.754  4.868  10.148  10.494  22.312   

      2008    2009    2010    2011    2012    2013    2014    2015    2016  \
0   24.714  42.482  43.030  42.964  19.580  21.318  28.842  28.212  37.708   
1   20.837  37.917  27.927  29.037  16.766  22.181  24.272  36.680  27.281   
2   24.981  39.653  34.120  27.655  18.253  20.035  23.569  42.798  22.438   
3   27.391  46.346  39.478  14.482  17.198  18.350  21.791  42.688  21.339   
4   29.631  43.832  42.308  14.929  16.832  16.546  20.231  38.598  26.126   
5   30.292  46.108  43.787  17.712  17.334  17.815  18.330  42.758  25.870   
6   32.855  49.333  46.529  18.442  13.318  20.711  18.950  43.468  25.733   
7   32.495  45.231  49.752  17.717  14.032  19.709  18.717  42.325  26.493   
8   34.315  49.893  52.187  17.482  12.528  19.079  19.475  44.587  22.439   
9   37.362  49.513  48.564  15.897  15.748  20.933  22.642  51.934  23.988   
10  34.520  39.459  31.619  16.297  15.147  19.695  23.615  44.584  21.531   
11  40.113  51.404  39.060  21.616  20.877  29.167  30.753  49.488  25.101   

      2017    2018    2019    2020    2021    2022  
0   20.475  37.492  55.258  57.160  50.219  35.584  
1   17.795  32.664  46.131  46.914  45.317  37.360  
2   18.557  32.231  45.466  37.687  46.747  55.883  
3   16.472  27.380  46.183  27.316  43.390  44.177  
4   18.582  27.844  47.188  26.722  40.735  42.494  
5   18.105  38.993  47.229  32.283  35.983  43.863  
6   20.341  37.309  50.026  36.590  36.723     NaN  
7   25.926  42.873  46.626  43.710  33.590     NaN  
8   27.784  49.054  45.658  43.485  32.922     NaN  
9   28.419  59.709  52.375  45.690  33.721     NaN  
10  29.952  59.323  51.791  43.046  32.018     NaN  
11  34.950  56.405  61.068  53.672  37.779     NaN

In [788]:
# Replace do Mês para numérico

dfba["Mês"].replace("Janeiro", "01", inplace=True)
dfba["Mês"].replace("Fevereiro", "02", inplace=True)
dfba["Mês"].replace("Março", "03", inplace=True)
dfba["Mês"].replace("Abril", "04", inplace=True)
dfba["Mês"].replace("Maio", "05", inplace=True)
dfba["Mês"].replace("Junho", "06", inplace=True)
dfba["Mês"].replace("Julho", "07", inplace=True)
dfba["Mês"].replace("Agosto", "08", inplace=True)
dfba["Mês"].replace("Setembro", "09", inplace=True)
dfba["Mês"].replace("Outubro", "10", inplace=True)
dfba["Mês"].replace("Novembro", "11", inplace=True)
dfba["Mês"].replace("Dezembro", "12", inplace=True)

In [789]:
# Criação das colunas uf, produto, unid, criado_em

dfba['uf']='BA'
dfba['produto']='Etanol Hidratado'
dfba['unid']='m3'
dfba['criado_em'] ='2022-09-10'

In [790]:
# Despivotar a tabela em ano e volume 

dfba.reset_index(inplace=True)

In [791]:
dfba=dfba.melt(id_vars = ['Mês', 'uf', 'produto', 'unid', 'criado_em'], value_vars = ['2000', '2001', '2002', '2003', '2004', '2005', '2006', '2007', '2008', '2009', '2010', '2011', '2012', '2013', '2014', '2015', '2016', '2017', '2018', '2019', '2020', '2021', '2022'], var_name='ano', value_name='venda')

In [792]:
# Visão geral da tabela

dfba

Mês  uf           produto unid   criado_em   ano   venda
0    01  BA  Etanol Hidratado   m3  2022-09-10  2000  10.367
1    02  BA  Etanol Hidratado   m3  2022-09-10  2000   9.105
2    03  BA  Etanol Hidratado   m3  2022-09-10  2000   8.536
3    04  BA  Etanol Hidratado   m3  2022-09-10  2000   8.058
4    05  BA  Etanol Hidratado   m3  2022-09-10  2000   8.013
5    06  BA  Etanol Hidratado   m3  2022-09-10  2000   6.527
6    07  BA  Etanol Hidratado   m3  2022-09-10  2000   8.602
7    08  BA  Etanol Hidratado   m3  2022-09-10  2000   8.059
8    09  BA  Etanol Hidratado   m3  2022-09-10  2000   7.359
9    10  BA  Etanol Hidratado   m3  2022-09-10  2000   7.063
10   11  BA  Etanol Hidratado   m3  2022-09-10  2000   8.173
11   12  BA  Etanol Hidratado   m3  2022-09-10  2000  11.660
12   01  BA  Etanol Hidratado   m3  2022-09-10  2001  10.500
13   02  BA  Etanol Hidratado   m3  2022-09-10  2001   7.977
14   03  BA  Etanol Hidratado   m3  2022-09-10  2001   7.376
15   04  BA  Etanol Hidratado   m3  2022-09-10  2001   5.508
16   05  BA  Etanol Hidratado   m3  2022-09-10  2001   5.237
17   06  BA  Etanol Hidratado   m3  2022-09-10  2001   5.547
18   07  BA  Etanol Hidratado   m3  2022-09-10  2001   4.818
19   08  BA  Etanol Hidratado   m3  2022-09-10  2001   4.758
20   09  BA  Etanol Hidratado   m3  2022-09-10  2001   4.289
21   10  BA  Etanol Hidratado   m3  2022-09-10  2001   4.457
22   11  BA  Etanol Hidratado   m3  2022-09-10  2001   4.252
23   12  BA  Etanol Hidratado   m3  2022-09-10  2001   4.814
24   01  BA  Etanol Hidratado   m3  2022-09-10  2002   5.265
25   02  BA  Etanol Hidratado   m3  2022-09-10  2002   4.030
26   03  BA  Etanol Hidratado   m3  2022-09-10  2002   3.804
27   04  BA  Etanol Hidratado   m3  2022-09-10  2002   4.331
28   05  BA  Etanol Hidratado   m3  2022-09-10  2002   4.388
29   06  BA  Etanol Hidratado   m3  2022-09-10  2002   4.135
30   07  BA  Etanol Hidratado   m3  2022-09-10  2002   4.330
31   08  BA  Etanol Hidratado   m3  2022-09-10  2002   2.975
32   09  BA  Etanol Hidratado   m3  2022-09-10  2002   4.414
33   10  BA  Etanol Hidratado   m3  2022-09-10  2002   5.194
34   11  BA  Etanol Hidratado   m3  2022-09-10  2002   3.742
35   12  BA  Etanol Hidratado   m3  2022-09-10  2002   3.743
36   01  BA  Etanol Hidratado   m3  2022-09-10  2003   4.603
37   02  BA  Etanol Hidratado   m3  2022-09-10  2003   4.168
38   03  BA  Etanol Hidratado   m3  2022-09-10  2003   2.776
39   04  BA  Etanol Hidratado   m3  2022-09-10  2003   3.278
40   05  BA  Etanol Hidratado   m3  2022-09-10  2003   2.941
41   06  BA  Etanol Hidratado   m3  2022-09-10  2003   4.136
42   07  BA  Etanol Hidratado   m3  2022-09-10  2003   4.714
43   08  BA  Etanol Hidratado   m3  2022-09-10  2003   3.864
44   09  BA  Etanol Hidratado   m3  2022-09-10  2003   4.473
45   10  BA  Etanol Hidratado   m3  2022-09-10  2003   4.671
46   11  BA  Etanol Hidratado   m3  2022-09-10  2003   4.493
47   12  BA  Etanol Hidratado   m3  2022-09-10  2003   5.754
48   01  BA  Etanol Hidratado   m3  2022-09-10  2004   5.202
49   02  BA  Etanol Hidratado   m3  2022-09-10  2004   4.444
50   03  BA  Etanol Hidratado   m3  2022-09-10  2004   5.643
51   04  BA  Etanol Hidratado   m3  2022-09-10  2004   5.076
52   05  BA  Etanol Hidratado   m3  2022-09-10  2004   4.501
53   06  BA  Etanol Hidratado   m3  2022-09-10  2004   4.863
54   07  BA  Etanol Hidratado   m3  2022-09-10  2004   5.174
55   08  BA  Etanol Hidratado   m3  2022-09-10  2004   4.963
56   09  BA  Etanol Hidratado   m3  2022-09-10  2004   5.203
57   10  BA  Etanol Hidratado   m3  2022-09-10  2004   5.373
58   11  BA  Etanol Hidratado   m3  2022-09-10  2004   4.242
59   12  BA  Etanol Hidratado   m3  2022-09-10  2004   4.868
60   01  BA  Etanol Hidratado   m3  2022-09-10  2005   4.684
61   02  BA  Etanol Hidratado   m3  2022-09-10  2005   3.980
62   03  BA  Etanol Hidratado   m3  2022-09-10  2005   4.340
63   04  BA  Etanol Hidratado   m3  2022-09-10  2005   4.296
64   05  BA  Etanol Hidratado   m3  202

In [793]:
# Concatenando as colunas ano e Mês

dfba['ano_mês'] = dfba[['ano', 'Mês']].agg('-'.join, axis=1)

In [794]:
# Eliminando as colunas Mês e ano

dfba.drop(["Mês"], axis=1, inplace=True)
dfba.drop(["ano"], axis=1, inplace=True)

In [795]:
# Organização da ordem das colunas

dfba =dfba[['ano_mês', 'uf', 'produto', 'unid', 'venda', 'criado_em']]

In [796]:
# Levantamento de possíveis inconsistências

dfba.isna().sum()

ano_mês      0
uf           0
produto      0
unid         0
venda        6
criado_em    0
dtype: int64

In [797]:
# Tratamento das inconsistências

dfba.replace(['Na', 'nA', 'na','NA', 'NaN', 'NAN', 'nan', '', ' '],pd.NA,inplace=True)


In [798]:
# Visão geral da tabela

dfba

ano_mês  uf           produto unid   venda   criado_em
0    2000-01  BA  Etanol Hidratado   m3  10.367  2022-09-10
1    2000-02  BA  Etanol Hidratado   m3   9.105  2022-09-10
2    2000-03  BA  Etanol Hidratado   m3   8.536  2022-09-10
3    2000-04  BA  Etanol Hidratado   m3   8.058  2022-09-10
4    2000-05  BA  Etanol Hidratado   m3   8.013  2022-09-10
5    2000-06  BA  Etanol Hidratado   m3   6.527  2022-09-10
6    2000-07  BA  Etanol Hidratado   m3   8.602  2022-09-10
7    2000-08  BA  Etanol Hidratado   m3   8.059  2022-09-10
8    2000-09  BA  Etanol Hidratado   m3   7.359  2022-09-10
9    2000-10  BA  Etanol Hidratado   m3   7.063  2022-09-10
10   2000-11  BA  Etanol Hidratado   m3   8.173  2022-09-10
11   2000-12  BA  Etanol Hidratado   m3  11.660  2022-09-10
12   2001-01  BA  Etanol Hidratado   m3  10.500  2022-09-10
13   2001-02  BA  Etanol Hidratado   m3   7.977  2022-09-10
14   2001-03  BA  Etanol Hidratado   m3   7.376  2022-09-10
15   2001-04  BA  Etanol Hidratado   m3   5.508  2022-09-10
16   2001-05  BA  Etanol Hidratado   m3   5.237  2022-09-10
17   2001-06  BA  Etanol Hidratado   m3   5.547  2022-09-10
18   2001-07  BA  Etanol Hidratado   m3   4.818  2022-09-10
19   2001-08  BA  Etanol Hidratado   m3   4.758  2022-09-10
20   2001-09  BA  Etanol Hidratado   m3   4.289  2022-09-10
21   2001-10  BA  Etanol Hidratado   m3   4.457  2022-09-10
22   2001-11  BA  Etanol Hidratado   m3   4.252  2022-09-10
23   2001-12  BA  Etanol Hidratado   m3   4.814  2022-09-10
24   2002-01  BA  Etanol Hidratado   m3   5.265  2022-09-10
25   2002-02  BA  Etanol Hidratado   m3   4.030  2022-09-10
26   2002-03  BA  Etanol Hidratado   m3   3.804  2022-09-10
27   2002-04  BA  Etanol Hidratado   m3   4.331  2022-09-10
28   2002-05  BA  Etanol Hidratado   m3   4.388  2022-09-10
29   2002-06  BA  Etanol Hidratado   m3   4.135  2022-09-10
30   2002-07  BA  Etanol Hidratado   m3   4.330  2022-09-10
31   2002-08  BA  Etanol Hidratado   m3   2.975  2022-09-10
32   2002-09  BA  Etanol Hidratado   m3   4.414  2022-09-10
33   2002-10  BA  Etanol Hidratado   m3   5.194  2022-09-10
34   2002-11  BA  Etanol Hidratado   m3   3.742  2022-09-10
35   2002-12  BA  Etanol Hidratado   m3   3.743  2022-09-10
36   2003-01  BA  Etanol Hidratado   m3   4.603  2022-09-10
37   2003-02  BA  Etanol Hidratado   m3   4.168  2022-09-10
38   2003-03  BA  Etanol Hidratado   m3   2.776  2022-09-10
39   2003-04  BA  Etanol Hidratado   m3   3.278  2022-09-10
40   2003-05  BA  Etanol Hidratado   m3   2.941  2022-09-10
41   2003-06  BA  Etanol Hidratado   m3   4.136  2022-09-10
42   2003-07  BA  Etanol Hidratado   m3   4.714  2022-09-10
43   2003-08  BA  Etanol Hidratado   m3   3.864  2022-09-10
44   2003-09  BA  Etanol Hidratado   m3   4.473  2022-09-10
45   2003-10  BA  Etanol Hidratado   m3   4.671  2022-09-10
46   2003-11  BA  Etanol Hidratado   m3   4.493  2022-09-10
47   2003-12  BA  Etanol Hidratado   m3   5.754  2022-09-10
48   2004-01  BA  Etanol Hidratado   m3   5.202  2022-09-10
49   2004-02  BA  Etanol Hidratado   m3   4.444  2022-09-10
50   2004-03  BA  Etanol Hidratado   m3   5.643  2022-09-10
51   2004-04  BA  Etanol Hidratado   m3   5.076  2022-09-10
52   2004-05  BA  Etanol Hidratado   m3   4.501  2022-09-10
53   2004-06  BA  Etanol Hidratado   m3   4.863  2022-09-10
54   2004-07  BA  Etanol Hidratado   m3   5.174  2022-09-10
55   2004-08  BA  Etanol Hidratado   m3   4.963  2022-09-10
56   2004-09  BA  Etanol Hidratado   m3   5.203  2022-09-10
57   2004-10  BA  Etanol Hidratado   m3   5.373  2022-09-10
58   2004-11  BA  Etanol Hidratado   m3   4.242  2022-09-10
59   2004-12  BA  Etanol Hidratado   m3   4.868  2022-09-10
60   2005-01  BA  Etanol Hidratado   m3   4.684  2022-09-10
61   2005-02  BA  Etanol Hidratado   m3   3.980  2022-09-10
62   2005-03  BA  Etanol Hidratado   m3   4.340  2022-09-10
63   2005-04  BA  Etanol Hidratado   m3   4.296  2022-09-10
64   2005-05  BA  Etanol Hidratado   m3   4.671  2022-09-10
65   2005-06  BA  Etanol Hidratado   m3   4.8

In [799]:
# Verificando os tipos

dfba.dtypes

ano_mês       object
uf            object
produto       object
unid          object
venda        float64
criado_em     object
dtype: object

In [800]:
# Validação

schema = pa.DataFrameSchema(
    columns = {
        'ano_mês': pa.Column(pa.String, nullable=True),
        'uf': pa.Column(pa.String, nullable = True),
        'produto': pa.Column(pa.String, nullable = True),
        'unid': pa.Column(pa.String, nullable = True),
        'venda': pa.Column(pa.Float, nullable = True),
        'criado_em': pa.Column(pa.String, nullable = True),
                
    }
)
schema.validate(dfba)

ano_mês  uf           produto unid   venda   criado_em
0    2000-01  BA  Etanol Hidratado   m3  10.367  2022-09-10
1    2000-02  BA  Etanol Hidratado   m3   9.105  2022-09-10
2    2000-03  BA  Etanol Hidratado   m3   8.536  2022-09-10
3    2000-04  BA  Etanol Hidratado   m3   8.058  2022-09-10
4    2000-05  BA  Etanol Hidratado   m3   8.013  2022-09-10
5    2000-06  BA  Etanol Hidratado   m3   6.527  2022-09-10
6    2000-07  BA  Etanol Hidratado   m3   8.602  2022-09-10
7    2000-08  BA  Etanol Hidratado   m3   8.059  2022-09-10
8    2000-09  BA  Etanol Hidratado   m3   7.359  2022-09-10
9    2000-10  BA  Etanol Hidratado   m3   7.063  2022-09-10
10   2000-11  BA  Etanol Hidratado   m3   8.173  2022-09-10
11   2000-12  BA  Etanol Hidratado   m3  11.660  2022-09-10
12   2001-01  BA  Etanol Hidratado   m3  10.500  2022-09-10
13   2001-02  BA  Etanol Hidratado   m3   7.977  2022-09-10
14   2001-03  BA  Etanol Hidratado   m3   7.376  2022-09-10
15   2001-04  BA  Etanol Hidratado   m3   5.508  2022-09-10
16   2001-05  BA  Etanol Hidratado   m3   5.237  2022-09-10
17   2001-06  BA  Etanol Hidratado   m3   5.547  2022-09-10
18   2001-07  BA  Etanol Hidratado   m3   4.818  2022-09-10
19   2001-08  BA  Etanol Hidratado   m3   4.758  2022-09-10
20   2001-09  BA  Etanol Hidratado   m3   4.289  2022-09-10
21   2001-10  BA  Etanol Hidratado   m3   4.457  2022-09-10
22   2001-11  BA  Etanol Hidratado   m3   4.252  2022-09-10
23   2001-12  BA  Etanol Hidratado   m3   4.814  2022-09-10
24   2002-01  BA  Etanol Hidratado   m3   5.265  2022-09-10
25   2002-02  BA  Etanol Hidratado   m3   4.030  2022-09-10
26   2002-03  BA  Etanol Hidratado   m3   3.804  2022-09-10
27   2002-04  BA  Etanol Hidratado   m3   4.331  2022-09-10
28   2002-05  BA  Etanol Hidratado   m3   4.388  2022-09-10
29   2002-06  BA  Etanol Hidratado   m3   4.135  2022-09-10
30   2002-07  BA  Etanol Hidratado   m3   4.330  2022-09-10
31   2002-08  BA  Etanol Hidratado   m3   2.975  2022-09-10
32   2002-09  BA  Etanol Hidratado   m3   4.414  2022-09-10
33   2002-10  BA  Etanol Hidratado   m3   5.194  2022-09-10
34   2002-11  BA  Etanol Hidratado   m3   3.742  2022-09-10
35   2002-12  BA  Etanol Hidratado   m3   3.743  2022-09-10
36   2003-01  BA  Etanol Hidratado   m3   4.603  2022-09-10
37   2003-02  BA  Etanol Hidratado   m3   4.168  2022-09-10
38   2003-03  BA  Etanol Hidratado   m3   2.776  2022-09-10
39   2003-04  BA  Etanol Hidratado   m3   3.278  2022-09-10
40   2003-05  BA  Etanol Hidratado   m3   2.941  2022-09-10
41   2003-06  BA  Etanol Hidratado   m3   4.136  2022-09-10
42   2003-07  BA  Etanol Hidratado   m3   4.714  2022-09-10
43   2003-08  BA  Etanol Hidratado   m3   3.864  2022-09-10
44   2003-09  BA  Etanol Hidratado   m3   4.473  2022-09-10
45   2003-10  BA  Etanol Hidratado   m3   4.671  2022-09-10
46   2003-11  BA  Etanol Hidratado   m3   4.493  2022-09-10
47   2003-12  BA  Etanol Hidratado   m3   5.754  2022-09-10
48   2004-01  BA  Etanol Hidratado   m3   5.202  2022-09-10
49   2004-02  BA  Etanol Hidratado   m3   4.444  2022-09-10
50   2004-03  BA  Etanol Hidratado   m3   5.643  2022-09-10
51   2004-04  BA  Etanol Hidratado   m3   5.076  2022-09-10
52   2004-05  BA  Etanol Hidratado   m3   4.501  2022-09-10
53   2004-06  BA  Etanol Hidratado   m3   4.863  2022-09-10
54   2004-07  BA  Etanol Hidratado   m3   5.174  2022-09-10
55   2004-08  BA  Etanol Hidratado   m3   4.963  2022-09-10
56   2004-09  BA  Etanol Hidratado   m3   5.203  2022-09-10
57   2004-10  BA  Etanol Hidratado   m3   5.373  2022-09-10
58   2004-11  BA  Etanol Hidratado   m3   4.242  2022-09-10
59   2004-12  BA  Etanol Hidratado   m3   4.868  2022-09-10
60   2005-01  BA  Etanol Hidratado   m3   4.684  2022-09-10
61   2005-02  BA  Etanol Hidratado   m3   3.980  2022-09-10
62   2005-03  BA  Etanol Hidratado   m3   4.340  2022-09-10
63   2005-04  BA  Etanol Hidratado   m3   4.296  2022-09-10
64   2005-05  BA  Etanol Hidratado   m3   4.671  2022-09-10
65   2005-06  BA  Etanol Hidratado   m3   4.8

In [801]:
dfba_pandas = dfba.copy()

##CEARÁ

In [802]:
# Conector

dfce = pd.read_csv('/content/ceara.csv',sep=';')

In [803]:
# Backup

dfce_backup = dfce.copy()

In [804]:
# Configurando a quantidade de linhas máximas mostradas em tela

pd.set_option('display.max_columns',1000)
pd.set_option('display.max_rows',1000)

In [805]:
# Visualização da Tabela

dfce

Mês   2000   2001   2002   2003   2004   2005   2006    2007  \
0     Janeiro  6.138  4.940  3.884  3.703  2.683  2.571  6.360   7.483   
1   Fevereiro  5.303  4.244  3.256  3.204  2.386  2.411  5.668   6.796   
2       Março  5.266  4.636  3.487  2.312  2.480  2.897  5.336   7.799   
3       Abril  5.369  4.347  3.665  2.544  2.782  3.559  4.731   7.283   
4        Maio  6.685  4.682  3.780  2.616  3.139  3.430  4.813   7.785   
5       Junho  5.700  4.433  3.742  2.802  3.469  2.886  4.675   7.840   
6       Julho  7.204  4.675  3.708  3.270  3.845  3.656  5.033   8.459   
7      Agosto  6.242  4.065  3.931  2.528  3.118  3.317  5.150   9.726   
8    Setembro  6.821  3.987  3.450  2.880  2.937  3.543  5.299   9.917   
9     Outubro  5.751  3.573  4.091  2.761  3.037  3.322  5.608  11.623   
10   Novembro  5.483  3.722  3.630  2.680  2.701  3.537  6.095  11.586   
11   Dezembro  5.671  4.005  3.633  2.937  3.047  5.373  7.332  11.580   

      2008    2009    2010    2011   2012    2013    2014    2015    2016  \
0   12.259  15.325  11.660  14.922  7.356   8.923  10.214  11.745  14.213   
1   10.978  12.883   7.807  11.839  7.448   7.842   9.093  12.777  11.975   
2   11.996  13.761   7.743  12.620  8.816   8.044   8.259  14.565  12.235   
3   11.940  13.981   9.610   7.147  7.847   8.010   8.105  14.713  11.427   
4   12.850  12.706  12.000   8.459  7.498   7.092   8.217  13.913  11.529   
5   12.407  13.773  13.510   9.712  6.449   7.941   8.235  14.046  12.505   
6   13.976  16.665  14.995   8.466  7.125   8.221   9.150  14.619  12.144   
7   11.813  16.030  15.812   8.261  8.155   8.008   8.623  13.838  12.545   
8   12.441  16.437  16.419   7.606  7.701   7.526   8.685  14.096  11.540   
9   13.655  16.161  15.523   7.968  8.359   8.060   9.414  17.209  10.760   
10  12.934  12.568  15.155   8.156  8.632   8.037  10.024  14.519   9.971   
11  15.692  14.303  17.271   8.450  8.034  10.162  11.916  16.550  12.457   

      2017    2018    2019    2020    2021    2022  
0   10.623  13.437  13.931  18.413  14.257   9.434  
1    9.449  10.208  12.099  15.773  14.100   9.500  
2    9.964  12.299  13.728  11.699  15.227  13.121  
3    7.927  11.041  14.439   7.128  10.876  12.712  
4    9.578  12.595  14.130   5.556  11.949  11.627  
5    9.219  16.813  12.072   8.017   9.819  10.943  
6    9.155  13.696  12.383  10.237  10.249     NaN  
7   11.096  13.356  13.515  12.315   8.300     NaN  
8   11.211  14.826  13.169  13.403   8.343     NaN  
9   10.599  18.024  14.630  13.941  10.059     NaN  
10  11.232  16.846  13.764  12.829  11.935     NaN  
11  12.796  16.570  18.649  15.638  12.471     NaN

In [806]:
# Replace do Mês para numérico

dfce["Mês"].replace("Janeiro", "01", inplace=True)
dfce["Mês"].replace("Fevereiro", "02", inplace=True)
dfce["Mês"].replace("Março", "03", inplace=True)
dfce["Mês"].replace("Abril", "04", inplace=True)
dfce["Mês"].replace("Maio", "05", inplace=True)
dfce["Mês"].replace("Junho", "06", inplace=True)
dfce["Mês"].replace("Julho", "07", inplace=True)
dfce["Mês"].replace("Agosto", "08", inplace=True)
dfce["Mês"].replace("Setembro", "09", inplace=True)
dfce["Mês"].replace("Outubro", "10", inplace=True)
dfce["Mês"].replace("Novembro", "11", inplace=True)
dfce["Mês"].replace("Dezembro", "12", inplace=True)

In [807]:
# Criação das colunas uf, produto, unid, criado_em

dfce['uf']='CE'
dfce['produto']='Eanol Hidratado'
dfce['unid']='m3'
dfce['criado_em'] ='2022-09-10'

In [808]:
# Despivotar a tabela em ano e volume
 
dfce.reset_index(inplace=True)

In [809]:
dfce=dfce.melt(id_vars = ['Mês', 'uf', 'produto', 'unid', 'criado_em'], value_vars = ['2000', '2001', '2002', '2003', '2004', '2005', '2006', '2007', '2008', '2009', '2010', '2011', '2012', '2013', '2014', '2015', '2016', '2017', '2018', '2019', '2020', '2021', '2022'], var_name='ano', value_name='venda')

In [810]:
# Visão geral da tabela

dfce

Mês  uf          produto unid   criado_em   ano   venda
0    01  CE  Eanol Hidratado   m3  2022-09-10  2000   6.138
1    02  CE  Eanol Hidratado   m3  2022-09-10  2000   5.303
2    03  CE  Eanol Hidratado   m3  2022-09-10  2000   5.266
3    04  CE  Eanol Hidratado   m3  2022-09-10  2000   5.369
4    05  CE  Eanol Hidratado   m3  2022-09-10  2000   6.685
5    06  CE  Eanol Hidratado   m3  2022-09-10  2000   5.700
6    07  CE  Eanol Hidratado   m3  2022-09-10  2000   7.204
7    08  CE  Eanol Hidratado   m3  2022-09-10  2000   6.242
8    09  CE  Eanol Hidratado   m3  2022-09-10  2000   6.821
9    10  CE  Eanol Hidratado   m3  2022-09-10  2000   5.751
10   11  CE  Eanol Hidratado   m3  2022-09-10  2000   5.483
11   12  CE  Eanol Hidratado   m3  2022-09-10  2000   5.671
12   01  CE  Eanol Hidratado   m3  2022-09-10  2001   4.940
13   02  CE  Eanol Hidratado   m3  2022-09-10  2001   4.244
14   03  CE  Eanol Hidratado   m3  2022-09-10  2001   4.636
15   04  CE  Eanol Hidratado   m3  2022-09-10  2001   4.347
16   05  CE  Eanol Hidratado   m3  2022-09-10  2001   4.682
17   06  CE  Eanol Hidratado   m3  2022-09-10  2001   4.433
18   07  CE  Eanol Hidratado   m3  2022-09-10  2001   4.675
19   08  CE  Eanol Hidratado   m3  2022-09-10  2001   4.065
20   09  CE  Eanol Hidratado   m3  2022-09-10  2001   3.987
21   10  CE  Eanol Hidratado   m3  2022-09-10  2001   3.573
22   11  CE  Eanol Hidratado   m3  2022-09-10  2001   3.722
23   12  CE  Eanol Hidratado   m3  2022-09-10  2001   4.005
24   01  CE  Eanol Hidratado   m3  2022-09-10  2002   3.884
25   02  CE  Eanol Hidratado   m3  2022-09-10  2002   3.256
26   03  CE  Eanol Hidratado   m3  2022-09-10  2002   3.487
27   04  CE  Eanol Hidratado   m3  2022-09-10  2002   3.665
28   05  CE  Eanol Hidratado   m3  2022-09-10  2002   3.780
29   06  CE  Eanol Hidratado   m3  2022-09-10  2002   3.742
30   07  CE  Eanol Hidratado   m3  2022-09-10  2002   3.708
31   08  CE  Eanol Hidratado   m3  2022-09-10  2002   3.931
32   09  CE  Eanol Hidratado   m3  2022-09-10  2002   3.450
33   10  CE  Eanol Hidratado   m3  2022-09-10  2002   4.091
34   11  CE  Eanol Hidratado   m3  2022-09-10  2002   3.630
35   12  CE  Eanol Hidratado   m3  2022-09-10  2002   3.633
36   01  CE  Eanol Hidratado   m3  2022-09-10  2003   3.703
37   02  CE  Eanol Hidratado   m3  2022-09-10  2003   3.204
38   03  CE  Eanol Hidratado   m3  2022-09-10  2003   2.312
39   04  CE  Eanol Hidratado   m3  2022-09-10  2003   2.544
40   05  CE  Eanol Hidratado   m3  2022-09-10  2003   2.616
41   06  CE  Eanol Hidratado   m3  2022-09-10  2003   2.802
42   07  CE  Eanol Hidratado   m3  2022-09-10  2003   3.270
43   08  CE  Eanol Hidratado   m3  2022-09-10  2003   2.528
44   09  CE  Eanol Hidratado   m3  2022-09-10  2003   2.880
45   10  CE  Eanol Hidratado   m3  2022-09-10  2003   2.761
46   11  CE  Eanol Hidratado   m3  2022-09-10  2003   2.680
47   12  CE  Eanol Hidratado   m3  2022-09-10  2003   2.937
48   01  CE  Eanol Hidratado   m3  2022-09-10  2004   2.683
49   02  CE  Eanol Hidratado   m3  2022-09-10  2004   2.386
50   03  CE  Eanol Hidratado   m3  2022-09-10  2004   2.480
51   04  CE  Eanol Hidratado   m3  2022-09-10  2004   2.782
52   05  CE  Eanol Hidratado   m3  2022-09-10  2004   3.139
53   06  CE  Eanol Hidratado   m3  2022-09-10  2004   3.469
54   07  CE  Eanol Hidratado   m3  2022-09-10  2004   3.845
55   08  CE  Eanol Hidratado   m3  2022-09-10  2004   3.118
56   09  CE  Eanol Hidratado   m3  2022-09-10  2004   2.937
57   10  CE  Eanol Hidratado   m3  2022-09-10  2004   3.037
58   11  CE  Eanol Hidratado   m3  2022-09-10  2004   2.701
59   12  CE  Eanol Hidratado   m3  2022-09-10  2004   3.047
60   01  CE  Eanol Hidratado   m3  2022-09-10  2005   2.571
61   02  CE  Eanol Hidratado   m3  2022-09-10  2005   2.411
62   03  CE  Eanol Hidratado   m3  2022-09-10  2005   2.897
63   04  CE  Eanol Hidratado   m3  2022-09-10  2005   3.559
64   05  CE  Eanol Hidratado   m3  2022-09-10  2005   3.430
65   06  CE  Eanol Hidratado   m3  2022-09-1

In [811]:
# Concatenando as colunas ano e Mês

dfce['ano_mês'] = dfce[['ano', 'Mês']].agg('-'.join, axis=1)

In [812]:
# Eliminando as colunas Mês e ano

dfce.drop(["Mês"], axis=1, inplace=True)
dfce.drop(["ano"], axis=1, inplace=True)

In [813]:
# Organização da ordem das colunas

dfce =dfce[['ano_mês', 'uf', 'produto', 'unid', 'venda', 'criado_em']]

In [814]:
# Levantamento de possíveis inconsistências

dfce.isna().sum()

ano_mês      0
uf           0
produto      0
unid         0
venda        6
criado_em    0
dtype: int64

In [815]:
# Tratamento das inconsistências

dfce.replace(['Na', 'nA', 'na','NA', 'NaN', 'NAN', 'nan', '', ' '],pd.NA,inplace=True)


In [816]:
# Visão geral da tabela

dfce

ano_mês  uf          produto unid   venda   criado_em
0    2000-01  CE  Eanol Hidratado   m3   6.138  2022-09-10
1    2000-02  CE  Eanol Hidratado   m3   5.303  2022-09-10
2    2000-03  CE  Eanol Hidratado   m3   5.266  2022-09-10
3    2000-04  CE  Eanol Hidratado   m3   5.369  2022-09-10
4    2000-05  CE  Eanol Hidratado   m3   6.685  2022-09-10
5    2000-06  CE  Eanol Hidratado   m3   5.700  2022-09-10
6    2000-07  CE  Eanol Hidratado   m3   7.204  2022-09-10
7    2000-08  CE  Eanol Hidratado   m3   6.242  2022-09-10
8    2000-09  CE  Eanol Hidratado   m3   6.821  2022-09-10
9    2000-10  CE  Eanol Hidratado   m3   5.751  2022-09-10
10   2000-11  CE  Eanol Hidratado   m3   5.483  2022-09-10
11   2000-12  CE  Eanol Hidratado   m3   5.671  2022-09-10
12   2001-01  CE  Eanol Hidratado   m3   4.940  2022-09-10
13   2001-02  CE  Eanol Hidratado   m3   4.244  2022-09-10
14   2001-03  CE  Eanol Hidratado   m3   4.636  2022-09-10
15   2001-04  CE  Eanol Hidratado   m3   4.347  2022-09-10
16   2001-05  CE  Eanol Hidratado   m3   4.682  2022-09-10
17   2001-06  CE  Eanol Hidratado   m3   4.433  2022-09-10
18   2001-07  CE  Eanol Hidratado   m3   4.675  2022-09-10
19   2001-08  CE  Eanol Hidratado   m3   4.065  2022-09-10
20   2001-09  CE  Eanol Hidratado   m3   3.987  2022-09-10
21   2001-10  CE  Eanol Hidratado   m3   3.573  2022-09-10
22   2001-11  CE  Eanol Hidratado   m3   3.722  2022-09-10
23   2001-12  CE  Eanol Hidratado   m3   4.005  2022-09-10
24   2002-01  CE  Eanol Hidratado   m3   3.884  2022-09-10
25   2002-02  CE  Eanol Hidratado   m3   3.256  2022-09-10
26   2002-03  CE  Eanol Hidratado   m3   3.487  2022-09-10
27   2002-04  CE  Eanol Hidratado   m3   3.665  2022-09-10
28   2002-05  CE  Eanol Hidratado   m3   3.780  2022-09-10
29   2002-06  CE  Eanol Hidratado   m3   3.742  2022-09-10
30   2002-07  CE  Eanol Hidratado   m3   3.708  2022-09-10
31   2002-08  CE  Eanol Hidratado   m3   3.931  2022-09-10
32   2002-09  CE  Eanol Hidratado   m3   3.450  2022-09-10
33   2002-10  CE  Eanol Hidratado   m3   4.091  2022-09-10
34   2002-11  CE  Eanol Hidratado   m3   3.630  2022-09-10
35   2002-12  CE  Eanol Hidratado   m3   3.633  2022-09-10
36   2003-01  CE  Eanol Hidratado   m3   3.703  2022-09-10
37   2003-02  CE  Eanol Hidratado   m3   3.204  2022-09-10
38   2003-03  CE  Eanol Hidratado   m3   2.312  2022-09-10
39   2003-04  CE  Eanol Hidratado   m3   2.544  2022-09-10
40   2003-05  CE  Eanol Hidratado   m3   2.616  2022-09-10
41   2003-06  CE  Eanol Hidratado   m3   2.802  2022-09-10
42   2003-07  CE  Eanol Hidratado   m3   3.270  2022-09-10
43   2003-08  CE  Eanol Hidratado   m3   2.528  2022-09-10
44   2003-09  CE  Eanol Hidratado   m3   2.880  2022-09-10
45   2003-10  CE  Eanol Hidratado   m3   2.761  2022-09-10
46   2003-11  CE  Eanol Hidratado   m3   2.680  2022-09-10
47   2003-12  CE  Eanol Hidratado   m3   2.937  2022-09-10
48   2004-01  CE  Eanol Hidratado   m3   2.683  2022-09-10
49   2004-02  CE  Eanol Hidratado   m3   2.386  2022-09-10
50   2004-03  CE  Eanol Hidratado   m3   2.480  2022-09-10
51   2004-04  CE  Eanol Hidratado   m3   2.782  2022-09-10
52   2004-05  CE  Eanol Hidratado   m3   3.139  2022-09-10
53   2004-06  CE  Eanol Hidratado   m3   3.469  2022-09-10
54   2004-07  CE  Eanol Hidratado   m3   3.845  2022-09-10
55   2004-08  CE  Eanol Hidratado   m3   3.118  2022-09-10
56   2004-09  CE  Eanol Hidratado   m3   2.937  2022-09-10
57   2004-10  CE  Eanol Hidratado   m3   3.037  2022-09-10
58   2004-11  CE  Eanol Hidratado   m3   2.701  2022-09-10
59   2004-12  CE  Eanol Hidratado   m3   3.047  2022-09-10
60   2005-01  CE  Eanol Hidratado   m3   2.571  2022-09-10
61   2005-02  CE  Eanol Hidratado   m3   2.411  2022-09-10
62   2005-03  CE  Eanol Hidratado   m3   2.897  2022-09-10
63   2005-04  CE  Eanol Hidratado   m3   3.559  2022-09-10
64   2005-05  CE  Eanol Hidratado   m3   3.430  2022-09-10
65   2005-06  CE  Eanol Hidratado   m3   2.886  2022-09-10
66   2005-07  CE  Eanol Hidratado   m3   3.656  2022

In [817]:
# Verificando os tipos

dfce.dtypes

ano_mês       object
uf            object
produto       object
unid          object
venda        float64
criado_em     object
dtype: object

In [818]:
# Validação

schema = pa.DataFrameSchema(
    columns = {
        'ano_mês': pa.Column(pa.String, nullable=True),
        'uf': pa.Column(pa.String, nullable = True),
        'produto': pa.Column(pa.String, nullable = True),
        'unid': pa.Column(pa.String, nullable = True),
        'venda': pa.Column(pa.Float, nullable = True),
        'criado_em': pa.Column(pa.String, nullable = True),
                
    }
)
schema.validate(dfce)

ano_mês  uf          produto unid   venda   criado_em
0    2000-01  CE  Eanol Hidratado   m3   6.138  2022-09-10
1    2000-02  CE  Eanol Hidratado   m3   5.303  2022-09-10
2    2000-03  CE  Eanol Hidratado   m3   5.266  2022-09-10
3    2000-04  CE  Eanol Hidratado   m3   5.369  2022-09-10
4    2000-05  CE  Eanol Hidratado   m3   6.685  2022-09-10
5    2000-06  CE  Eanol Hidratado   m3   5.700  2022-09-10
6    2000-07  CE  Eanol Hidratado   m3   7.204  2022-09-10
7    2000-08  CE  Eanol Hidratado   m3   6.242  2022-09-10
8    2000-09  CE  Eanol Hidratado   m3   6.821  2022-09-10
9    2000-10  CE  Eanol Hidratado   m3   5.751  2022-09-10
10   2000-11  CE  Eanol Hidratado   m3   5.483  2022-09-10
11   2000-12  CE  Eanol Hidratado   m3   5.671  2022-09-10
12   2001-01  CE  Eanol Hidratado   m3   4.940  2022-09-10
13   2001-02  CE  Eanol Hidratado   m3   4.244  2022-09-10
14   2001-03  CE  Eanol Hidratado   m3   4.636  2022-09-10
15   2001-04  CE  Eanol Hidratado   m3   4.347  2022-09-10
16   2001-05  CE  Eanol Hidratado   m3   4.682  2022-09-10
17   2001-06  CE  Eanol Hidratado   m3   4.433  2022-09-10
18   2001-07  CE  Eanol Hidratado   m3   4.675  2022-09-10
19   2001-08  CE  Eanol Hidratado   m3   4.065  2022-09-10
20   2001-09  CE  Eanol Hidratado   m3   3.987  2022-09-10
21   2001-10  CE  Eanol Hidratado   m3   3.573  2022-09-10
22   2001-11  CE  Eanol Hidratado   m3   3.722  2022-09-10
23   2001-12  CE  Eanol Hidratado   m3   4.005  2022-09-10
24   2002-01  CE  Eanol Hidratado   m3   3.884  2022-09-10
25   2002-02  CE  Eanol Hidratado   m3   3.256  2022-09-10
26   2002-03  CE  Eanol Hidratado   m3   3.487  2022-09-10
27   2002-04  CE  Eanol Hidratado   m3   3.665  2022-09-10
28   2002-05  CE  Eanol Hidratado   m3   3.780  2022-09-10
29   2002-06  CE  Eanol Hidratado   m3   3.742  2022-09-10
30   2002-07  CE  Eanol Hidratado   m3   3.708  2022-09-10
31   2002-08  CE  Eanol Hidratado   m3   3.931  2022-09-10
32   2002-09  CE  Eanol Hidratado   m3   3.450  2022-09-10
33   2002-10  CE  Eanol Hidratado   m3   4.091  2022-09-10
34   2002-11  CE  Eanol Hidratado   m3   3.630  2022-09-10
35   2002-12  CE  Eanol Hidratado   m3   3.633  2022-09-10
36   2003-01  CE  Eanol Hidratado   m3   3.703  2022-09-10
37   2003-02  CE  Eanol Hidratado   m3   3.204  2022-09-10
38   2003-03  CE  Eanol Hidratado   m3   2.312  2022-09-10
39   2003-04  CE  Eanol Hidratado   m3   2.544  2022-09-10
40   2003-05  CE  Eanol Hidratado   m3   2.616  2022-09-10
41   2003-06  CE  Eanol Hidratado   m3   2.802  2022-09-10
42   2003-07  CE  Eanol Hidratado   m3   3.270  2022-09-10
43   2003-08  CE  Eanol Hidratado   m3   2.528  2022-09-10
44   2003-09  CE  Eanol Hidratado   m3   2.880  2022-09-10
45   2003-10  CE  Eanol Hidratado   m3   2.761  2022-09-10
46   2003-11  CE  Eanol Hidratado   m3   2.680  2022-09-10
47   2003-12  CE  Eanol Hidratado   m3   2.937  2022-09-10
48   2004-01  CE  Eanol Hidratado   m3   2.683  2022-09-10
49   2004-02  CE  Eanol Hidratado   m3   2.386  2022-09-10
50   2004-03  CE  Eanol Hidratado   m3   2.480  2022-09-10
51   2004-04  CE  Eanol Hidratado   m3   2.782  2022-09-10
52   2004-05  CE  Eanol Hidratado   m3   3.139  2022-09-10
53   2004-06  CE  Eanol Hidratado   m3   3.469  2022-09-10
54   2004-07  CE  Eanol Hidratado   m3   3.845  2022-09-10
55   2004-08  CE  Eanol Hidratado   m3   3.118  2022-09-10
56   2004-09  CE  Eanol Hidratado   m3   2.937  2022-09-10
57   2004-10  CE  Eanol Hidratado   m3   3.037  2022-09-10
58   2004-11  CE  Eanol Hidratado   m3   2.701  2022-09-10
59   2004-12  CE  Eanol Hidratado   m3   3.047  2022-09-10
60   2005-01  CE  Eanol Hidratado   m3   2.571  2022-09-10
61   2005-02  CE  Eanol Hidratado   m3   2.411  2022-09-10
62   2005-03  CE  Eanol Hidratado   m3   2.897  2022-09-10
63   2005-04  CE  Eanol Hidratado   m3   3.559  2022-09-10
64   2005-05  CE  Eanol Hidratado   m3   3.430  2022-09-10
65   2005-06  CE  Eanol Hidratado   m3   2.886  2022-09-10
66   2005-07  CE  Eanol Hidratado   m3   3.656  2022

In [819]:
dfce_pandas = dfce.copy()

##DISTRITO DEFERAL

In [820]:
# Conector

dfdf = pd.read_csv('/content/distrito_federal.csv',sep=';')

In [821]:
# Backup

dfdf_backup = dfdf.copy()

In [822]:
# Configurando a quantidade de linhas máximas mostradas em tela

pd.set_option('display.max_columns',1000)
pd.set_option('display.max_rows',1000)

In [823]:
# Visualização da Tabela

dfdf

Mês    2000    2001   2002   2003   2004   2005   2006    2007  \
0     Janeiro  11.688   9.752  8.613  8.073  5.808  4.736  6.549   6.704   
1   Fevereiro  13.408   9.235  7.877  6.767  5.494  5.055  6.087   6.618   
2       Março  13.389  10.571  9.191  6.872  6.806  6.775  5.346   9.042   
3       Abril  12.681  10.144  9.057  7.143  7.997  6.140  5.015   6.367   
4        Maio  13.047  10.515  9.425  7.731  6.226  5.563  5.888   7.442   
5       Junho  10.144  10.039  8.334  7.117  5.912  6.200  6.098   9.565   
6       Julho  12.938   9.366  9.394  7.620  6.678  5.609  5.856  13.674   
7      Agosto  12.318  10.331  9.926  7.201  6.507  6.574  7.296  18.021   
8    Setembro  11.603   9.399  9.470  7.492  6.759  7.018  6.798  16.792   
9     Outubro  11.976   9.824  9.830  7.246  6.160  7.003  8.209  20.957   
10   Novembro  11.419   8.931  7.682  7.316  5.637  7.452  8.459  20.590   
11   Dezembro  12.338   9.700  8.606  8.591  6.214  9.433  9.256  14.449   

      2008    2009    2010   2011   2012   2013   2014    2015   2016   2017  \
0   11.935  14.782   7.414  8.659  4.414  4.234  6.547   6.929  5.045  1.815   
1   13.730  15.251   5.172  6.663  5.068  7.106  6.705  10.463  3.828  1.574   
2   14.307  18.558   7.676  6.095  6.319  7.205  5.850  11.875  3.453  1.663   
3   12.986  18.622  10.483  3.041  4.675  6.924  5.643  10.106  2.999  1.438   
4   14.122  18.901  12.329  8.038  4.900  6.390  5.581   9.596  3.927  1.778   
5   13.738  22.446  13.411  9.362  4.686  6.207  5.194   9.275  4.405  1.293   
6   14.114  23.708  13.263  7.531  4.437  6.214  5.646   9.210  4.143  2.063   
7   15.299  22.900  14.508  8.693  4.784  6.593  5.859   9.499  3.905  4.712   
8   15.524  24.183  15.312  8.089  4.686  6.251  6.216   9.936  3.696  8.022   
9   17.141  23.809  12.869  6.846  4.983  7.025  6.588  10.875  2.783  4.869   
10  14.562  17.303  10.329  5.342  4.271  6.655  6.674   7.219  2.180  6.186   
11  17.318  18.892  11.368  5.660  4.912  7.212  7.411   7.395  2.618  5.877   

      2018    2019    2020    2021   2022  
0    4.057   8.890  11.873  12.823  3.985  
1    4.785  11.407   9.766  17.552  5.087  
2    4.042  11.341   6.591  14.109  9.135  
3    4.435  14.403   3.658  10.381  8.696  
4    6.705  16.872   5.841   9.718  7.639  
5    9.283  14.945   8.723   7.890  7.939  
6   14.348  15.244  12.706   8.459    NaN  
7   23.220  16.070  13.177   9.068    NaN  
8   29.567  16.555  14.377   7.189    NaN  
9   32.680  17.827  21.062   7.186    NaN  
10  20.800  15.938  27.472   5.938    NaN  
11  13.709  18.352  14.527   5.228    NaN

In [824]:
# Replace do Mês para numérico

dfdf["Mês"].replace("Janeiro", "01", inplace=True)
dfdf["Mês"].replace("Fevereiro", "02", inplace=True)
dfdf["Mês"].replace("Março", "03", inplace=True)
dfdf["Mês"].replace("Abril", "04", inplace=True)
dfdf["Mês"].replace("Maio", "05", inplace=True)
dfdf["Mês"].replace("Junho", "06", inplace=True)
dfdf["Mês"].replace("Julho", "07", inplace=True)
dfdf["Mês"].replace("Agosto", "08", inplace=True)
dfdf["Mês"].replace("Setembro", "09", inplace=True)
dfdf["Mês"].replace("Outubro", "10", inplace=True)
dfdf["Mês"].replace("Novembro", "11", inplace=True)
dfdf["Mês"].replace("Dezembro", "12", inplace=True)

In [825]:
# Criação das colunas uf, produto, unid, criado_em

dfdf['uf']='DF'
dfdf['produto']='Etanol Hidratado'
dfdf['unid']='m3'
dfdf['criado_em'] ='2022-09-10'

In [826]:
# Despivotar a tabela em ano e volume 

dfdf.reset_index(inplace=True)

In [827]:
dfdf=dfdf.melt(id_vars = ['Mês', 'uf', 'produto', 'unid', 'criado_em'], value_vars = ['2000', '2001', '2002', '2003', '2004', '2005', '2006', '2007', '2008', '2009', '2010', '2011', '2012', '2013', '2014', '2015', '2016', '2017', '2018', '2019', '2020', '2021', '2022'], var_name='ano', value_name='venda')

In [828]:
# Visão geral da tabela

dfdf

Mês  uf           produto unid   criado_em   ano   venda
0    01  DF  Etanol Hidratado   m3  2022-09-10  2000  11.688
1    02  DF  Etanol Hidratado   m3  2022-09-10  2000  13.408
2    03  DF  Etanol Hidratado   m3  2022-09-10  2000  13.389
3    04  DF  Etanol Hidratado   m3  2022-09-10  2000  12.681
4    05  DF  Etanol Hidratado   m3  2022-09-10  2000  13.047
5    06  DF  Etanol Hidratado   m3  2022-09-10  2000  10.144
6    07  DF  Etanol Hidratado   m3  2022-09-10  2000  12.938
7    08  DF  Etanol Hidratado   m3  2022-09-10  2000  12.318
8    09  DF  Etanol Hidratado   m3  2022-09-10  2000  11.603
9    10  DF  Etanol Hidratado   m3  2022-09-10  2000  11.976
10   11  DF  Etanol Hidratado   m3  2022-09-10  2000  11.419
11   12  DF  Etanol Hidratado   m3  2022-09-10  2000  12.338
12   01  DF  Etanol Hidratado   m3  2022-09-10  2001   9.752
13   02  DF  Etanol Hidratado   m3  2022-09-10  2001   9.235
14   03  DF  Etanol Hidratado   m3  2022-09-10  2001  10.571
15   04  DF  Etanol Hidratado   m3  2022-09-10  2001  10.144
16   05  DF  Etanol Hidratado   m3  2022-09-10  2001  10.515
17   06  DF  Etanol Hidratado   m3  2022-09-10  2001  10.039
18   07  DF  Etanol Hidratado   m3  2022-09-10  2001   9.366
19   08  DF  Etanol Hidratado   m3  2022-09-10  2001  10.331
20   09  DF  Etanol Hidratado   m3  2022-09-10  2001   9.399
21   10  DF  Etanol Hidratado   m3  2022-09-10  2001   9.824
22   11  DF  Etanol Hidratado   m3  2022-09-10  2001   8.931
23   12  DF  Etanol Hidratado   m3  2022-09-10  2001   9.700
24   01  DF  Etanol Hidratado   m3  2022-09-10  2002   8.613
25   02  DF  Etanol Hidratado   m3  2022-09-10  2002   7.877
26   03  DF  Etanol Hidratado   m3  2022-09-10  2002   9.191
27   04  DF  Etanol Hidratado   m3  2022-09-10  2002   9.057
28   05  DF  Etanol Hidratado   m3  2022-09-10  2002   9.425
29   06  DF  Etanol Hidratado   m3  2022-09-10  2002   8.334
30   07  DF  Etanol Hidratado   m3  2022-09-10  2002   9.394
31   08  DF  Etanol Hidratado   m3  2022-09-10  2002   9.926
32   09  DF  Etanol Hidratado   m3  2022-09-10  2002   9.470
33   10  DF  Etanol Hidratado   m3  2022-09-10  2002   9.830
34   11  DF  Etanol Hidratado   m3  2022-09-10  2002   7.682
35   12  DF  Etanol Hidratado   m3  2022-09-10  2002   8.606
36   01  DF  Etanol Hidratado   m3  2022-09-10  2003   8.073
37   02  DF  Etanol Hidratado   m3  2022-09-10  2003   6.767
38   03  DF  Etanol Hidratado   m3  2022-09-10  2003   6.872
39   04  DF  Etanol Hidratado   m3  2022-09-10  2003   7.143
40   05  DF  Etanol Hidratado   m3  2022-09-10  2003   7.731
41   06  DF  Etanol Hidratado   m3  2022-09-10  2003   7.117
42   07  DF  Etanol Hidratado   m3  2022-09-10  2003   7.620
43   08  DF  Etanol Hidratado   m3  2022-09-10  2003   7.201
44   09  DF  Etanol Hidratado   m3  2022-09-10  2003   7.492
45   10  DF  Etanol Hidratado   m3  2022-09-10  2003   7.246
46   11  DF  Etanol Hidratado   m3  2022-09-10  2003   7.316
47   12  DF  Etanol Hidratado   m3  2022-09-10  2003   8.591
48   01  DF  Etanol Hidratado   m3  2022-09-10  2004   5.808
49   02  DF  Etanol Hidratado   m3  2022-09-10  2004   5.494
50   03  DF  Etanol Hidratado   m3  2022-09-10  2004   6.806
51   04  DF  Etanol Hidratado   m3  2022-09-10  2004   7.997
52   05  DF  Etanol Hidratado   m3  2022-09-10  2004   6.226
53   06  DF  Etanol Hidratado   m3  2022-09-10  2004   5.912
54   07  DF  Etanol Hidratado   m3  2022-09-10  2004   6.678
55   08  DF  Etanol Hidratado   m3  2022-09-10  2004   6.507
56   09  DF  Etanol Hidratado   m3  2022-09-10  2004   6.759
57   10  DF  Etanol Hidratado   m3  2022-09-10  2004   6.160
58   11  DF  Etanol Hidratado   m3  2022-09-10  2004   5.637
59   12  DF  Etanol Hidratado   m3  2022-09-10  2004   6.214
60   01  DF  Etanol Hidratado   m3  2022-09-10  2005   4.736
61   02  DF  Etanol Hidratado   m3  2022-09-10  2005   5.055
62   03  DF  Etanol Hidratado   m3  2022-09-10  2005   6.775
63   04  DF  Etanol Hidratado   m3  2022-09-10  2005   6.140
64   05  DF  Etanol Hidratado   m3  202

In [829]:
# Concatenando as colunas ano e Mês

dfdf['ano_mês'] = dfdf[['ano', 'Mês']].agg('-'.join, axis=1)

In [830]:
# Eliminando as colunas Mês e ano

dfdf.drop(["Mês"], axis=1, inplace=True)
dfdf.drop(["ano"], axis=1, inplace=True)

In [831]:
# Organização da ordem das colunas

dfdf =dfdf[['ano_mês', 'uf', 'produto', 'unid', 'venda', 'criado_em']]

In [832]:
# Levantamento de possíveis inconsistências

dfdf.isna().sum()

ano_mês      0
uf           0
produto      0
unid         0
venda        6
criado_em    0
dtype: int64

In [833]:
# Tratamento das inconsistências

dfdf.replace(['Na', 'nA', 'na','NA', 'NaN', 'NAN', 'nan', '', ' '],pd.NA,inplace=True)


In [834]:
# Visão geral da tabela

dfdf

ano_mês  uf           produto unid   venda   criado_em
0    2000-01  DF  Etanol Hidratado   m3  11.688  2022-09-10
1    2000-02  DF  Etanol Hidratado   m3  13.408  2022-09-10
2    2000-03  DF  Etanol Hidratado   m3  13.389  2022-09-10
3    2000-04  DF  Etanol Hidratado   m3  12.681  2022-09-10
4    2000-05  DF  Etanol Hidratado   m3  13.047  2022-09-10
5    2000-06  DF  Etanol Hidratado   m3  10.144  2022-09-10
6    2000-07  DF  Etanol Hidratado   m3  12.938  2022-09-10
7    2000-08  DF  Etanol Hidratado   m3  12.318  2022-09-10
8    2000-09  DF  Etanol Hidratado   m3  11.603  2022-09-10
9    2000-10  DF  Etanol Hidratado   m3  11.976  2022-09-10
10   2000-11  DF  Etanol Hidratado   m3  11.419  2022-09-10
11   2000-12  DF  Etanol Hidratado   m3  12.338  2022-09-10
12   2001-01  DF  Etanol Hidratado   m3   9.752  2022-09-10
13   2001-02  DF  Etanol Hidratado   m3   9.235  2022-09-10
14   2001-03  DF  Etanol Hidratado   m3  10.571  2022-09-10
15   2001-04  DF  Etanol Hidratado   m3  10.144  2022-09-10
16   2001-05  DF  Etanol Hidratado   m3  10.515  2022-09-10
17   2001-06  DF  Etanol Hidratado   m3  10.039  2022-09-10
18   2001-07  DF  Etanol Hidratado   m3   9.366  2022-09-10
19   2001-08  DF  Etanol Hidratado   m3  10.331  2022-09-10
20   2001-09  DF  Etanol Hidratado   m3   9.399  2022-09-10
21   2001-10  DF  Etanol Hidratado   m3   9.824  2022-09-10
22   2001-11  DF  Etanol Hidratado   m3   8.931  2022-09-10
23   2001-12  DF  Etanol Hidratado   m3   9.700  2022-09-10
24   2002-01  DF  Etanol Hidratado   m3   8.613  2022-09-10
25   2002-02  DF  Etanol Hidratado   m3   7.877  2022-09-10
26   2002-03  DF  Etanol Hidratado   m3   9.191  2022-09-10
27   2002-04  DF  Etanol Hidratado   m3   9.057  2022-09-10
28   2002-05  DF  Etanol Hidratado   m3   9.425  2022-09-10
29   2002-06  DF  Etanol Hidratado   m3   8.334  2022-09-10
30   2002-07  DF  Etanol Hidratado   m3   9.394  2022-09-10
31   2002-08  DF  Etanol Hidratado   m3   9.926  2022-09-10
32   2002-09  DF  Etanol Hidratado   m3   9.470  2022-09-10
33   2002-10  DF  Etanol Hidratado   m3   9.830  2022-09-10
34   2002-11  DF  Etanol Hidratado   m3   7.682  2022-09-10
35   2002-12  DF  Etanol Hidratado   m3   8.606  2022-09-10
36   2003-01  DF  Etanol Hidratado   m3   8.073  2022-09-10
37   2003-02  DF  Etanol Hidratado   m3   6.767  2022-09-10
38   2003-03  DF  Etanol Hidratado   m3   6.872  2022-09-10
39   2003-04  DF  Etanol Hidratado   m3   7.143  2022-09-10
40   2003-05  DF  Etanol Hidratado   m3   7.731  2022-09-10
41   2003-06  DF  Etanol Hidratado   m3   7.117  2022-09-10
42   2003-07  DF  Etanol Hidratado   m3   7.620  2022-09-10
43   2003-08  DF  Etanol Hidratado   m3   7.201  2022-09-10
44   2003-09  DF  Etanol Hidratado   m3   7.492  2022-09-10
45   2003-10  DF  Etanol Hidratado   m3   7.246  2022-09-10
46   2003-11  DF  Etanol Hidratado   m3   7.316  2022-09-10
47   2003-12  DF  Etanol Hidratado   m3   8.591  2022-09-10
48   2004-01  DF  Etanol Hidratado   m3   5.808  2022-09-10
49   2004-02  DF  Etanol Hidratado   m3   5.494  2022-09-10
50   2004-03  DF  Etanol Hidratado   m3   6.806  2022-09-10
51   2004-04  DF  Etanol Hidratado   m3   7.997  2022-09-10
52   2004-05  DF  Etanol Hidratado   m3   6.226  2022-09-10
53   2004-06  DF  Etanol Hidratado   m3   5.912  2022-09-10
54   2004-07  DF  Etanol Hidratado   m3   6.678  2022-09-10
55   2004-08  DF  Etanol Hidratado   m3   6.507  2022-09-10
56   2004-09  DF  Etanol Hidratado   m3   6.759  2022-09-10
57   2004-10  DF  Etanol Hidratado   m3   6.160  2022-09-10
58   2004-11  DF  Etanol Hidratado   m3   5.637  2022-09-10
59   2004-12  DF  Etanol Hidratado   m3   6.214  2022-09-10
60   2005-01  DF  Etanol Hidratado   m3   4.736  2022-09-10
61   2005-02  DF  Etanol Hidratado   m3   5.055  2022-09-10
62   2005-03  DF  Etanol Hidratado   m3   6.775  2022-09-10
63   2005-04  DF  Etanol Hidratado   m3   6.140  2022-09-10
64   2005-05  DF  Etanol Hidratado   m3   5.563  2022-09-10
65   2005-06  DF  Etanol Hidratado   m3   6.2

In [835]:
# Verificando os tipos

dfdf.dtypes

ano_mês       object
uf            object
produto       object
unid          object
venda        float64
criado_em     object
dtype: object

In [836]:
# Validação

schema = pa.DataFrameSchema(
    columns = {
        'ano_mês': pa.Column(pa.String, nullable=True),
        'uf': pa.Column(pa.String, nullable = True),
        'produto': pa.Column(pa.String, nullable = True),
        'unid': pa.Column(pa.String, nullable = True),
        'venda': pa.Column(pa.Float, nullable = True),
        'criado_em': pa.Column(pa.String, nullable = True),
                
    }
)
schema.validate(dfdf)

ano_mês  uf           produto unid   venda   criado_em
0    2000-01  DF  Etanol Hidratado   m3  11.688  2022-09-10
1    2000-02  DF  Etanol Hidratado   m3  13.408  2022-09-10
2    2000-03  DF  Etanol Hidratado   m3  13.389  2022-09-10
3    2000-04  DF  Etanol Hidratado   m3  12.681  2022-09-10
4    2000-05  DF  Etanol Hidratado   m3  13.047  2022-09-10
5    2000-06  DF  Etanol Hidratado   m3  10.144  2022-09-10
6    2000-07  DF  Etanol Hidratado   m3  12.938  2022-09-10
7    2000-08  DF  Etanol Hidratado   m3  12.318  2022-09-10
8    2000-09  DF  Etanol Hidratado   m3  11.603  2022-09-10
9    2000-10  DF  Etanol Hidratado   m3  11.976  2022-09-10
10   2000-11  DF  Etanol Hidratado   m3  11.419  2022-09-10
11   2000-12  DF  Etanol Hidratado   m3  12.338  2022-09-10
12   2001-01  DF  Etanol Hidratado   m3   9.752  2022-09-10
13   2001-02  DF  Etanol Hidratado   m3   9.235  2022-09-10
14   2001-03  DF  Etanol Hidratado   m3  10.571  2022-09-10
15   2001-04  DF  Etanol Hidratado   m3  10.144  2022-09-10
16   2001-05  DF  Etanol Hidratado   m3  10.515  2022-09-10
17   2001-06  DF  Etanol Hidratado   m3  10.039  2022-09-10
18   2001-07  DF  Etanol Hidratado   m3   9.366  2022-09-10
19   2001-08  DF  Etanol Hidratado   m3  10.331  2022-09-10
20   2001-09  DF  Etanol Hidratado   m3   9.399  2022-09-10
21   2001-10  DF  Etanol Hidratado   m3   9.824  2022-09-10
22   2001-11  DF  Etanol Hidratado   m3   8.931  2022-09-10
23   2001-12  DF  Etanol Hidratado   m3   9.700  2022-09-10
24   2002-01  DF  Etanol Hidratado   m3   8.613  2022-09-10
25   2002-02  DF  Etanol Hidratado   m3   7.877  2022-09-10
26   2002-03  DF  Etanol Hidratado   m3   9.191  2022-09-10
27   2002-04  DF  Etanol Hidratado   m3   9.057  2022-09-10
28   2002-05  DF  Etanol Hidratado   m3   9.425  2022-09-10
29   2002-06  DF  Etanol Hidratado   m3   8.334  2022-09-10
30   2002-07  DF  Etanol Hidratado   m3   9.394  2022-09-10
31   2002-08  DF  Etanol Hidratado   m3   9.926  2022-09-10
32   2002-09  DF  Etanol Hidratado   m3   9.470  2022-09-10
33   2002-10  DF  Etanol Hidratado   m3   9.830  2022-09-10
34   2002-11  DF  Etanol Hidratado   m3   7.682  2022-09-10
35   2002-12  DF  Etanol Hidratado   m3   8.606  2022-09-10
36   2003-01  DF  Etanol Hidratado   m3   8.073  2022-09-10
37   2003-02  DF  Etanol Hidratado   m3   6.767  2022-09-10
38   2003-03  DF  Etanol Hidratado   m3   6.872  2022-09-10
39   2003-04  DF  Etanol Hidratado   m3   7.143  2022-09-10
40   2003-05  DF  Etanol Hidratado   m3   7.731  2022-09-10
41   2003-06  DF  Etanol Hidratado   m3   7.117  2022-09-10
42   2003-07  DF  Etanol Hidratado   m3   7.620  2022-09-10
43   2003-08  DF  Etanol Hidratado   m3   7.201  2022-09-10
44   2003-09  DF  Etanol Hidratado   m3   7.492  2022-09-10
45   2003-10  DF  Etanol Hidratado   m3   7.246  2022-09-10
46   2003-11  DF  Etanol Hidratado   m3   7.316  2022-09-10
47   2003-12  DF  Etanol Hidratado   m3   8.591  2022-09-10
48   2004-01  DF  Etanol Hidratado   m3   5.808  2022-09-10
49   2004-02  DF  Etanol Hidratado   m3   5.494  2022-09-10
50   2004-03  DF  Etanol Hidratado   m3   6.806  2022-09-10
51   2004-04  DF  Etanol Hidratado   m3   7.997  2022-09-10
52   2004-05  DF  Etanol Hidratado   m3   6.226  2022-09-10
53   2004-06  DF  Etanol Hidratado   m3   5.912  2022-09-10
54   2004-07  DF  Etanol Hidratado   m3   6.678  2022-09-10
55   2004-08  DF  Etanol Hidratado   m3   6.507  2022-09-10
56   2004-09  DF  Etanol Hidratado   m3   6.759  2022-09-10
57   2004-10  DF  Etanol Hidratado   m3   6.160  2022-09-10
58   2004-11  DF  Etanol Hidratado   m3   5.637  2022-09-10
59   2004-12  DF  Etanol Hidratado   m3   6.214  2022-09-10
60   2005-01  DF  Etanol Hidratado   m3   4.736  2022-09-10
61   2005-02  DF  Etanol Hidratado   m3   5.055  2022-09-10
62   2005-03  DF  Etanol Hidratado   m3   6.775  2022-09-10
63   2005-04  DF  Etanol Hidratado   m3   6.140  2022-09-10
64   2005-05  DF  Etanol Hidratado   m3   5.563  2022-09-10
65   2005-06  DF  Etanol Hidratado   m3   6.2

In [837]:
dfdf_pandas = dfdf.copy()

##ES

In [838]:
# Conector

dfes = pd.read_csv('/content/espirito_santo.csv',sep=';')

In [839]:
# Backup

dfes_backup = dfes.copy()

In [840]:
# Configurando a quantidade de linhas máximas mostradas em tela

pd.set_option('display.max_columns',1000)
pd.set_option('display.max_rows',1000)

In [841]:
# Visualização da Tabela

dfes

Mês   2000   2001   2002   2003   2004   2005   2006   2007    2008  \
0     Janeiro  7.164  4.184  3.532  4.282  3.245  3.673  4.679  4.734   9.600   
1   Fevereiro  6.550  3.717  3.117  3.233  3.023  3.144  4.070  4.476   8.241   
2       Março  6.211  3.847  3.301  2.411  2.809  3.830  2.973  4.988  10.070   
3       Abril  5.531  3.595  3.350  2.163  3.236  4.212  2.264  4.253  10.996   
4        Maio  5.340  3.634  3.425  2.237  3.040  4.244  2.703  4.349  11.227   
5       Junho  4.897  3.643  3.137  2.023  2.419  3.836  2.915  4.418  10.550   
6       Julho  6.034  3.662  3.609  3.212  2.848  3.795  3.234  5.531  11.788   
7      Agosto  4.491  3.468  3.532  3.339  3.191  4.224  3.519  6.010  11.464   
8    Setembro  5.034  3.055  3.956  2.977  3.271  4.290  3.862  6.043  12.405   
9     Outubro  4.830  3.420  3.786  3.189  3.462  4.333  3.739  8.131  13.406   
10   Novembro  4.296  3.272  2.530  3.310  2.494  4.626  3.799  8.444  12.190   
11   Dezembro  4.549  3.487  4.594  4.163  3.683  6.338  4.670  9.454  15.310   

      2009   2010   2011   2012   2013   2014   2015   2016   2017   2018  \
0   14.771  7.720  5.753  4.072  3.735  3.918  4.790  4.076  2.540  3.169   
1   13.656  4.279  5.590  4.248  3.723  3.526  5.287  3.358  1.553  2.510   
2   14.385  5.575  5.052  4.406  3.572  3.486  5.193  2.895  2.263  2.150   
3   15.098  6.693  3.016  3.785  3.129  3.634  4.849  2.974  1.835  2.053   
4   14.221  7.066  3.785  3.532  3.220  3.247  4.264  2.876  2.211  3.356   
5   15.225  7.282  4.277  3.522  3.081  3.129  4.476  2.908  2.060  4.526   
6   16.431  8.163  4.882  4.152  3.585  3.267  6.165  3.370  2.233  4.394   
7   15.401  8.629  5.585  4.110  3.411  2.867  5.817  3.582  3.242  4.435   
8   16.567  8.646  4.034  3.475  3.071  3.012  5.816  3.457  3.543  6.352   
9   14.605  7.882  4.444  4.056  3.519  3.484  6.883  3.447  3.452  7.519   
10  10.524  6.416  4.565  3.965  3.659  3.507  4.819  3.839  3.004  5.794   
11  11.949  7.407  4.748  4.050  4.245  4.932  5.156  4.513  3.124  6.797   

     2019   2020   2021   2022  
0   6.760  5.526  4.469  2.957  
1   4.863  4.049  4.578  2.844  
2   5.288  2.855  7.323  5.086  
3   4.761  2.371  5.550  5.405  
4   5.079  1.796  3.380  4.003  
5   4.475  2.252  6.743  3.628  
6   4.641  2.940  6.027    NaN  
7   5.002  3.246  4.242    NaN  
8   4.742  3.992  3.245    NaN  
9   5.341  4.531  3.077    NaN  
10  4.845  3.564  3.201    NaN  
11  6.115  4.599  2.927    NaN

In [842]:
# Replace do Mês para numérico

dfes["Mês"].replace("Janeiro", "01", inplace=True)
dfes["Mês"].replace("Fevereiro", "02", inplace=True)
dfes["Mês"].replace("Março", "03", inplace=True)
dfes["Mês"].replace("Abril", "04", inplace=True)
dfes["Mês"].replace("Maio", "05", inplace=True)
dfes["Mês"].replace("Junho", "06", inplace=True)
dfes["Mês"].replace("Julho", "07", inplace=True)
dfes["Mês"].replace("Agosto", "08", inplace=True)
dfes["Mês"].replace("Setembro", "09", inplace=True)
dfes["Mês"].replace("Outubro", "10", inplace=True)
dfes["Mês"].replace("Novembro", "11", inplace=True)
dfes["Mês"].replace("Dezembro", "12", inplace=True)

In [843]:
# Criação das colunas uf, produto, unid, criado_em

dfes['uf']='ES'
dfes['produto']='Etanol Hidratado'
dfes['unid']='m3'
dfes['criado_em'] ='2022-09-10'

In [844]:
# Despivotar a tabela em ano e volume 

dfes.reset_index(inplace=True)

In [845]:
dfes=dfes.melt(id_vars = ['Mês', 'uf', 'produto', 'unid', 'criado_em'], value_vars = ['2000', '2001', '2002', '2003', '2004', '2005', '2006', '2007', '2008', '2009', '2010', '2011', '2012', '2013', '2014', '2015', '2016', '2017', '2018', '2019', '2020', '2021', '2022'], var_name='ano', value_name='venda')

In [846]:
# Visão geral da tabela

dfes

Mês  uf           produto unid   criado_em   ano   venda
0    01  ES  Etanol Hidratado   m3  2022-09-10  2000   7.164
1    02  ES  Etanol Hidratado   m3  2022-09-10  2000   6.550
2    03  ES  Etanol Hidratado   m3  2022-09-10  2000   6.211
3    04  ES  Etanol Hidratado   m3  2022-09-10  2000   5.531
4    05  ES  Etanol Hidratado   m3  2022-09-10  2000   5.340
5    06  ES  Etanol Hidratado   m3  2022-09-10  2000   4.897
6    07  ES  Etanol Hidratado   m3  2022-09-10  2000   6.034
7    08  ES  Etanol Hidratado   m3  2022-09-10  2000   4.491
8    09  ES  Etanol Hidratado   m3  2022-09-10  2000   5.034
9    10  ES  Etanol Hidratado   m3  2022-09-10  2000   4.830
10   11  ES  Etanol Hidratado   m3  2022-09-10  2000   4.296
11   12  ES  Etanol Hidratado   m3  2022-09-10  2000   4.549
12   01  ES  Etanol Hidratado   m3  2022-09-10  2001   4.184
13   02  ES  Etanol Hidratado   m3  2022-09-10  2001   3.717
14   03  ES  Etanol Hidratado   m3  2022-09-10  2001   3.847
15   04  ES  Etanol Hidratado   m3  2022-09-10  2001   3.595
16   05  ES  Etanol Hidratado   m3  2022-09-10  2001   3.634
17   06  ES  Etanol Hidratado   m3  2022-09-10  2001   3.643
18   07  ES  Etanol Hidratado   m3  2022-09-10  2001   3.662
19   08  ES  Etanol Hidratado   m3  2022-09-10  2001   3.468
20   09  ES  Etanol Hidratado   m3  2022-09-10  2001   3.055
21   10  ES  Etanol Hidratado   m3  2022-09-10  2001   3.420
22   11  ES  Etanol Hidratado   m3  2022-09-10  2001   3.272
23   12  ES  Etanol Hidratado   m3  2022-09-10  2001   3.487
24   01  ES  Etanol Hidratado   m3  2022-09-10  2002   3.532
25   02  ES  Etanol Hidratado   m3  2022-09-10  2002   3.117
26   03  ES  Etanol Hidratado   m3  2022-09-10  2002   3.301
27   04  ES  Etanol Hidratado   m3  2022-09-10  2002   3.350
28   05  ES  Etanol Hidratado   m3  2022-09-10  2002   3.425
29   06  ES  Etanol Hidratado   m3  2022-09-10  2002   3.137
30   07  ES  Etanol Hidratado   m3  2022-09-10  2002   3.609
31   08  ES  Etanol Hidratado   m3  2022-09-10  2002   3.532
32   09  ES  Etanol Hidratado   m3  2022-09-10  2002   3.956
33   10  ES  Etanol Hidratado   m3  2022-09-10  2002   3.786
34   11  ES  Etanol Hidratado   m3  2022-09-10  2002   2.530
35   12  ES  Etanol Hidratado   m3  2022-09-10  2002   4.594
36   01  ES  Etanol Hidratado   m3  2022-09-10  2003   4.282
37   02  ES  Etanol Hidratado   m3  2022-09-10  2003   3.233
38   03  ES  Etanol Hidratado   m3  2022-09-10  2003   2.411
39   04  ES  Etanol Hidratado   m3  2022-09-10  2003   2.163
40   05  ES  Etanol Hidratado   m3  2022-09-10  2003   2.237
41   06  ES  Etanol Hidratado   m3  2022-09-10  2003   2.023
42   07  ES  Etanol Hidratado   m3  2022-09-10  2003   3.212
43   08  ES  Etanol Hidratado   m3  2022-09-10  2003   3.339
44   09  ES  Etanol Hidratado   m3  2022-09-10  2003   2.977
45   10  ES  Etanol Hidratado   m3  2022-09-10  2003   3.189
46   11  ES  Etanol Hidratado   m3  2022-09-10  2003   3.310
47   12  ES  Etanol Hidratado   m3  2022-09-10  2003   4.163
48   01  ES  Etanol Hidratado   m3  2022-09-10  2004   3.245
49   02  ES  Etanol Hidratado   m3  2022-09-10  2004   3.023
50   03  ES  Etanol Hidratado   m3  2022-09-10  2004   2.809
51   04  ES  Etanol Hidratado   m3  2022-09-10  2004   3.236
52   05  ES  Etanol Hidratado   m3  2022-09-10  2004   3.040
53   06  ES  Etanol Hidratado   m3  2022-09-10  2004   2.419
54   07  ES  Etanol Hidratado   m3  2022-09-10  2004   2.848
55   08  ES  Etanol Hidratado   m3  2022-09-10  2004   3.191
56   09  ES  Etanol Hidratado   m3  2022-09-10  2004   3.271
57   10  ES  Etanol Hidratado   m3  2022-09-10  2004   3.462
58   11  ES  Etanol Hidratado   m3  2022-09-10  2004   2.494
59   12  ES  Etanol Hidratado   m3  2022-09-10  2004   3.683
60   01  ES  Etanol Hidratado   m3  2022-09-10  2005   3.673
61   02  ES  Etanol Hidratado   m3  2022-09-10  2005   3.144
62   03  ES  Etanol Hidratado   m3  2022-09-10  2005   3.830
63   04  ES  Etanol Hidratado   m3  2022-09-10  2005   4.212
64   05  ES  Etanol Hidratado   m3  202

In [847]:
# Concatenando as colunas ano e Mês

dfes['ano_mês'] = dfes[['ano', 'Mês']].agg('-'.join, axis=1)

In [848]:
# Eliminando as colunas Mês e ano

dfes.drop(["Mês"], axis=1, inplace=True)
dfes.drop(["ano"], axis=1, inplace=True)

In [849]:
# Organização da ordem das colunas

dfes =dfes[['ano_mês', 'uf', 'produto', 'unid', 'venda', 'criado_em']]

In [850]:
# Tratamento de possíveis inconsistências

dfes.isna().sum()

ano_mês      0
uf           0
produto      0
unid         0
venda        6
criado_em    0
dtype: int64

In [851]:
# Tratamento das inconsistências

dfes.replace(['Na', 'nA', 'na','NA', 'NaN', 'NAN', 'nan', '', ' '],pd.NA,inplace=True)


In [852]:
# Visão geral da tabela

dfes

ano_mês  uf           produto unid   venda   criado_em
0    2000-01  ES  Etanol Hidratado   m3   7.164  2022-09-10
1    2000-02  ES  Etanol Hidratado   m3   6.550  2022-09-10
2    2000-03  ES  Etanol Hidratado   m3   6.211  2022-09-10
3    2000-04  ES  Etanol Hidratado   m3   5.531  2022-09-10
4    2000-05  ES  Etanol Hidratado   m3   5.340  2022-09-10
5    2000-06  ES  Etanol Hidratado   m3   4.897  2022-09-10
6    2000-07  ES  Etanol Hidratado   m3   6.034  2022-09-10
7    2000-08  ES  Etanol Hidratado   m3   4.491  2022-09-10
8    2000-09  ES  Etanol Hidratado   m3   5.034  2022-09-10
9    2000-10  ES  Etanol Hidratado   m3   4.830  2022-09-10
10   2000-11  ES  Etanol Hidratado   m3   4.296  2022-09-10
11   2000-12  ES  Etanol Hidratado   m3   4.549  2022-09-10
12   2001-01  ES  Etanol Hidratado   m3   4.184  2022-09-10
13   2001-02  ES  Etanol Hidratado   m3   3.717  2022-09-10
14   2001-03  ES  Etanol Hidratado   m3   3.847  2022-09-10
15   2001-04  ES  Etanol Hidratado   m3   3.595  2022-09-10
16   2001-05  ES  Etanol Hidratado   m3   3.634  2022-09-10
17   2001-06  ES  Etanol Hidratado   m3   3.643  2022-09-10
18   2001-07  ES  Etanol Hidratado   m3   3.662  2022-09-10
19   2001-08  ES  Etanol Hidratado   m3   3.468  2022-09-10
20   2001-09  ES  Etanol Hidratado   m3   3.055  2022-09-10
21   2001-10  ES  Etanol Hidratado   m3   3.420  2022-09-10
22   2001-11  ES  Etanol Hidratado   m3   3.272  2022-09-10
23   2001-12  ES  Etanol Hidratado   m3   3.487  2022-09-10
24   2002-01  ES  Etanol Hidratado   m3   3.532  2022-09-10
25   2002-02  ES  Etanol Hidratado   m3   3.117  2022-09-10
26   2002-03  ES  Etanol Hidratado   m3   3.301  2022-09-10
27   2002-04  ES  Etanol Hidratado   m3   3.350  2022-09-10
28   2002-05  ES  Etanol Hidratado   m3   3.425  2022-09-10
29   2002-06  ES  Etanol Hidratado   m3   3.137  2022-09-10
30   2002-07  ES  Etanol Hidratado   m3   3.609  2022-09-10
31   2002-08  ES  Etanol Hidratado   m3   3.532  2022-09-10
32   2002-09  ES  Etanol Hidratado   m3   3.956  2022-09-10
33   2002-10  ES  Etanol Hidratado   m3   3.786  2022-09-10
34   2002-11  ES  Etanol Hidratado   m3   2.530  2022-09-10
35   2002-12  ES  Etanol Hidratado   m3   4.594  2022-09-10
36   2003-01  ES  Etanol Hidratado   m3   4.282  2022-09-10
37   2003-02  ES  Etanol Hidratado   m3   3.233  2022-09-10
38   2003-03  ES  Etanol Hidratado   m3   2.411  2022-09-10
39   2003-04  ES  Etanol Hidratado   m3   2.163  2022-09-10
40   2003-05  ES  Etanol Hidratado   m3   2.237  2022-09-10
41   2003-06  ES  Etanol Hidratado   m3   2.023  2022-09-10
42   2003-07  ES  Etanol Hidratado   m3   3.212  2022-09-10
43   2003-08  ES  Etanol Hidratado   m3   3.339  2022-09-10
44   2003-09  ES  Etanol Hidratado   m3   2.977  2022-09-10
45   2003-10  ES  Etanol Hidratado   m3   3.189  2022-09-10
46   2003-11  ES  Etanol Hidratado   m3   3.310  2022-09-10
47   2003-12  ES  Etanol Hidratado   m3   4.163  2022-09-10
48   2004-01  ES  Etanol Hidratado   m3   3.245  2022-09-10
49   2004-02  ES  Etanol Hidratado   m3   3.023  2022-09-10
50   2004-03  ES  Etanol Hidratado   m3   2.809  2022-09-10
51   2004-04  ES  Etanol Hidratado   m3   3.236  2022-09-10
52   2004-05  ES  Etanol Hidratado   m3   3.040  2022-09-10
53   2004-06  ES  Etanol Hidratado   m3   2.419  2022-09-10
54   2004-07  ES  Etanol Hidratado   m3   2.848  2022-09-10
55   2004-08  ES  Etanol Hidratado   m3   3.191  2022-09-10
56   2004-09  ES  Etanol Hidratado   m3   3.271  2022-09-10
57   2004-10  ES  Etanol Hidratado   m3   3.462  2022-09-10
58   2004-11  ES  Etanol Hidratado   m3   2.494  2022-09-10
59   2004-12  ES  Etanol Hidratado   m3   3.683  2022-09-10
60   2005-01  ES  Etanol Hidratado   m3   3.673  2022-09-10
61   2005-02  ES  Etanol Hidratado   m3   3.144  2022-09-10
62   2005-03  ES  Etanol Hidratado   m3   3.830  2022-09-10
63   2005-04  ES  Etanol Hidratado   m3   4.212  2022-09-10
64   2005-05  ES  Etanol Hidratado   m3   4.244  2022-09-10
65   2005-06  ES  Etanol Hidratado   m3   3.8

In [853]:
# Verificando os tipos

dfes.dtypes

ano_mês       object
uf            object
produto       object
unid          object
venda        float64
criado_em     object
dtype: object

In [854]:
# Validação

schema = pa.DataFrameSchema(
    columns = {
        'ano_mês': pa.Column(pa.String, nullable=True),
        'uf': pa.Column(pa.String, nullable = True),
        'produto': pa.Column(pa.String, nullable = True),
        'unid': pa.Column(pa.String, nullable = True),
        'venda': pa.Column(pa.Float, nullable = True),
        'criado_em': pa.Column(pa.String, nullable = True),
                
    }
)
schema.validate(dfes)

ano_mês  uf           produto unid   venda   criado_em
0    2000-01  ES  Etanol Hidratado   m3   7.164  2022-09-10
1    2000-02  ES  Etanol Hidratado   m3   6.550  2022-09-10
2    2000-03  ES  Etanol Hidratado   m3   6.211  2022-09-10
3    2000-04  ES  Etanol Hidratado   m3   5.531  2022-09-10
4    2000-05  ES  Etanol Hidratado   m3   5.340  2022-09-10
5    2000-06  ES  Etanol Hidratado   m3   4.897  2022-09-10
6    2000-07  ES  Etanol Hidratado   m3   6.034  2022-09-10
7    2000-08  ES  Etanol Hidratado   m3   4.491  2022-09-10
8    2000-09  ES  Etanol Hidratado   m3   5.034  2022-09-10
9    2000-10  ES  Etanol Hidratado   m3   4.830  2022-09-10
10   2000-11  ES  Etanol Hidratado   m3   4.296  2022-09-10
11   2000-12  ES  Etanol Hidratado   m3   4.549  2022-09-10
12   2001-01  ES  Etanol Hidratado   m3   4.184  2022-09-10
13   2001-02  ES  Etanol Hidratado   m3   3.717  2022-09-10
14   2001-03  ES  Etanol Hidratado   m3   3.847  2022-09-10
15   2001-04  ES  Etanol Hidratado   m3   3.595  2022-09-10
16   2001-05  ES  Etanol Hidratado   m3   3.634  2022-09-10
17   2001-06  ES  Etanol Hidratado   m3   3.643  2022-09-10
18   2001-07  ES  Etanol Hidratado   m3   3.662  2022-09-10
19   2001-08  ES  Etanol Hidratado   m3   3.468  2022-09-10
20   2001-09  ES  Etanol Hidratado   m3   3.055  2022-09-10
21   2001-10  ES  Etanol Hidratado   m3   3.420  2022-09-10
22   2001-11  ES  Etanol Hidratado   m3   3.272  2022-09-10
23   2001-12  ES  Etanol Hidratado   m3   3.487  2022-09-10
24   2002-01  ES  Etanol Hidratado   m3   3.532  2022-09-10
25   2002-02  ES  Etanol Hidratado   m3   3.117  2022-09-10
26   2002-03  ES  Etanol Hidratado   m3   3.301  2022-09-10
27   2002-04  ES  Etanol Hidratado   m3   3.350  2022-09-10
28   2002-05  ES  Etanol Hidratado   m3   3.425  2022-09-10
29   2002-06  ES  Etanol Hidratado   m3   3.137  2022-09-10
30   2002-07  ES  Etanol Hidratado   m3   3.609  2022-09-10
31   2002-08  ES  Etanol Hidratado   m3   3.532  2022-09-10
32   2002-09  ES  Etanol Hidratado   m3   3.956  2022-09-10
33   2002-10  ES  Etanol Hidratado   m3   3.786  2022-09-10
34   2002-11  ES  Etanol Hidratado   m3   2.530  2022-09-10
35   2002-12  ES  Etanol Hidratado   m3   4.594  2022-09-10
36   2003-01  ES  Etanol Hidratado   m3   4.282  2022-09-10
37   2003-02  ES  Etanol Hidratado   m3   3.233  2022-09-10
38   2003-03  ES  Etanol Hidratado   m3   2.411  2022-09-10
39   2003-04  ES  Etanol Hidratado   m3   2.163  2022-09-10
40   2003-05  ES  Etanol Hidratado   m3   2.237  2022-09-10
41   2003-06  ES  Etanol Hidratado   m3   2.023  2022-09-10
42   2003-07  ES  Etanol Hidratado   m3   3.212  2022-09-10
43   2003-08  ES  Etanol Hidratado   m3   3.339  2022-09-10
44   2003-09  ES  Etanol Hidratado   m3   2.977  2022-09-10
45   2003-10  ES  Etanol Hidratado   m3   3.189  2022-09-10
46   2003-11  ES  Etanol Hidratado   m3   3.310  2022-09-10
47   2003-12  ES  Etanol Hidratado   m3   4.163  2022-09-10
48   2004-01  ES  Etanol Hidratado   m3   3.245  2022-09-10
49   2004-02  ES  Etanol Hidratado   m3   3.023  2022-09-10
50   2004-03  ES  Etanol Hidratado   m3   2.809  2022-09-10
51   2004-04  ES  Etanol Hidratado   m3   3.236  2022-09-10
52   2004-05  ES  Etanol Hidratado   m3   3.040  2022-09-10
53   2004-06  ES  Etanol Hidratado   m3   2.419  2022-09-10
54   2004-07  ES  Etanol Hidratado   m3   2.848  2022-09-10
55   2004-08  ES  Etanol Hidratado   m3   3.191  2022-09-10
56   2004-09  ES  Etanol Hidratado   m3   3.271  2022-09-10
57   2004-10  ES  Etanol Hidratado   m3   3.462  2022-09-10
58   2004-11  ES  Etanol Hidratado   m3   2.494  2022-09-10
59   2004-12  ES  Etanol Hidratado   m3   3.683  2022-09-10
60   2005-01  ES  Etanol Hidratado   m3   3.673  2022-09-10
61   2005-02  ES  Etanol Hidratado   m3   3.144  2022-09-10
62   2005-03  ES  Etanol Hidratado   m3   3.830  2022-09-10
63   2005-04  ES  Etanol Hidratado   m3   4.212  2022-09-10
64   2005-05  ES  Etanol Hidratado   m3   4.244  2022-09-10
65   2005-06  ES  Etanol Hidratado   m3   3.8

In [855]:
dfes_pandas = dfes.copy()

##GOIÁS

In [856]:
# Conector

dfgo = pd.read_csv('/content/goias.csv',sep=';')

In [857]:
# Backup
dfgo_backup = dfgo.copy()

In [858]:
# Configurando a quantidade de linhas máximas mostradas em tela

pd.set_option('display.max_columns',1000)
pd.set_option('display.max_rows',1000)

In [859]:
# Visualização da Tabela

dfgo

Mês    2000    2001    2002    2003    2004    2005    2006    2007  \
0     Janeiro  16.683  13.461  13.806  13.793  13.411  12.588  18.409  27.573   
1   Fevereiro  16.256  12.083  11.721  10.407  12.368  11.664  16.227  26.041   
2       Março  15.730  12.802  13.071   9.793  15.253  12.775  11.588  30.913   
3       Abril  16.199  12.326  13.345  10.823  15.030   9.560  10.510  27.408   
4        Maio  16.347  13.204  13.383  10.914  15.017   9.024  16.580  30.106   
5       Junho  16.203  13.380  12.977  10.526  12.399   8.660  17.184  35.791   
6       Julho  17.654  12.853  15.925  13.305  16.897   9.849  18.814  34.312   
7      Agosto  14.287  12.871  14.546  11.766  12.631  10.636  20.525  40.642   
8    Setembro  16.088  12.266  16.075  11.946  14.321  13.449  23.935  39.974   
9     Outubro  14.594  11.636  18.054  13.340  14.135  13.732  25.670  48.332   
10   Novembro  14.365  12.396  14.069  13.827  13.054  15.500  26.346  46.662   
11   Dezembro  16.020  13.766  14.218  14.951  15.580  21.939  32.793  47.552   

      2008    2009    2010    2011    2012    2013    2014     2015    2016  \
0   44.942  53.005  52.108  69.732  49.171  58.406  77.635   88.257  89.178   
1   44.565  50.992  42.348  55.903  53.966  57.099  74.816   85.465  81.883   
2   47.566  56.402  57.383  34.205  55.745  66.202  69.867   96.932  82.638   
3   49.528  60.328  66.898  24.801  50.420  62.150  66.808  100.082  80.909   
4   48.807  57.691  68.788  55.762  50.691  61.641  67.496   98.206  94.882   
5   47.536  61.830  70.665  69.205  53.460  64.682  69.003  103.728  92.999   
6   53.775  71.441  79.906  68.824  56.974  72.868  75.765  110.037  97.507   
7   50.926  67.813  78.664  72.313  61.452  76.886  77.325  107.797  97.658   
8   54.113  71.468  83.208  68.462  61.917  77.478  81.742  113.764  96.921   
9   57.235  75.896  82.835  67.994  68.936  87.275  87.653  122.900  87.802   
10  51.073  67.803  80.279  57.611  64.060  83.373  83.597  100.771  74.410   
11  60.524  79.012  87.996  60.259  61.951  84.486  94.519  112.825  81.716   

       2017     2018     2019     2020     2021     2022  
0    64.808  106.932  133.698  139.384  139.874   95.286  
1    60.210   94.345  124.220  134.413  131.012  107.523  
2    70.408  112.115  138.630  112.856  119.516  124.773  
3    68.474  100.202  143.590   99.707  129.211  126.589  
4    74.054  103.762  148.984  106.822  125.248  129.283  
5    75.892  125.460  138.598  110.632  117.973  129.251  
6    75.532  132.010  150.193  118.256  124.505      NaN  
7    92.945  145.430  151.407  128.344  122.709      NaN  
8   104.781  143.146  149.724  141.479  118.476      NaN  
9   110.556  160.426  159.450  160.560  116.505      NaN  
10  101.125  143.623  154.542  142.270  107.990      NaN  
11  123.190  149.115  159.840  163.024  121.344      NaN

In [860]:
# Replace do Mês para numérico

dfgo["Mês"].replace("Janeiro", "01", inplace=True)
dfgo["Mês"].replace("Fevereiro", "02", inplace=True)
dfgo["Mês"].replace("Março", "03", inplace=True)
dfgo["Mês"].replace("Abril", "04", inplace=True)
dfgo["Mês"].replace("Maio", "05", inplace=True)
dfgo["Mês"].replace("Junho", "06", inplace=True)
dfgo["Mês"].replace("Julho", "07", inplace=True)
dfgo["Mês"].replace("Agosto", "08", inplace=True)
dfgo["Mês"].replace("Setembro", "09", inplace=True)
dfgo["Mês"].replace("Outubro", "10", inplace=True)
dfgo["Mês"].replace("Novembro", "11", inplace=True)
dfgo["Mês"].replace("Dezembro", "12", inplace=True)

In [861]:
# Criação das colunas uf, produto, unid, criado_em
dfgo['uf']='GO'
dfgo['produto']='Etanol Hidratado'
dfgo['unid']='m3'
dfgo['criado_em'] ='2022-09-10'

In [862]:
# Despivotar a tabela em ano e volume 
dfgo.reset_index(inplace=True)

In [863]:
dfgo=dfgo.melt(id_vars = ['Mês', 'uf', 'produto', 'unid', 'criado_em'], value_vars = ['2000', '2001', '2002', '2003', '2004', '2005', '2006', '2007', '2008', '2009', '2010', '2011', '2012', '2013', '2014', '2015', '2016', '2017', '2018', '2019', '2020', '2021', '2022'], var_name='ano', value_name='venda')

In [864]:
# Visão geral da tabela

dfgo

Mês  uf           produto unid   criado_em   ano    venda
0    01  GO  Etanol Hidratado   m3  2022-09-10  2000   16.683
1    02  GO  Etanol Hidratado   m3  2022-09-10  2000   16.256
2    03  GO  Etanol Hidratado   m3  2022-09-10  2000   15.730
3    04  GO  Etanol Hidratado   m3  2022-09-10  2000   16.199
4    05  GO  Etanol Hidratado   m3  2022-09-10  2000   16.347
5    06  GO  Etanol Hidratado   m3  2022-09-10  2000   16.203
6    07  GO  Etanol Hidratado   m3  2022-09-10  2000   17.654
7    08  GO  Etanol Hidratado   m3  2022-09-10  2000   14.287
8    09  GO  Etanol Hidratado   m3  2022-09-10  2000   16.088
9    10  GO  Etanol Hidratado   m3  2022-09-10  2000   14.594
10   11  GO  Etanol Hidratado   m3  2022-09-10  2000   14.365
11   12  GO  Etanol Hidratado   m3  2022-09-10  2000   16.020
12   01  GO  Etanol Hidratado   m3  2022-09-10  2001   13.461
13   02  GO  Etanol Hidratado   m3  2022-09-10  2001   12.083
14   03  GO  Etanol Hidratado   m3  2022-09-10  2001   12.802
15   04  GO  Etanol Hidratado   m3  2022-09-10  2001   12.326
16   05  GO  Etanol Hidratado   m3  2022-09-10  2001   13.204
17   06  GO  Etanol Hidratado   m3  2022-09-10  2001   13.380
18   07  GO  Etanol Hidratado   m3  2022-09-10  2001   12.853
19   08  GO  Etanol Hidratado   m3  2022-09-10  2001   12.871
20   09  GO  Etanol Hidratado   m3  2022-09-10  2001   12.266
21   10  GO  Etanol Hidratado   m3  2022-09-10  2001   11.636
22   11  GO  Etanol Hidratado   m3  2022-09-10  2001   12.396
23   12  GO  Etanol Hidratado   m3  2022-09-10  2001   13.766
24   01  GO  Etanol Hidratado   m3  2022-09-10  2002   13.806
25   02  GO  Etanol Hidratado   m3  2022-09-10  2002   11.721
26   03  GO  Etanol Hidratado   m3  2022-09-10  2002   13.071
27   04  GO  Etanol Hidratado   m3  2022-09-10  2002   13.345
28   05  GO  Etanol Hidratado   m3  2022-09-10  2002   13.383
29   06  GO  Etanol Hidratado   m3  2022-09-10  2002   12.977
30   07  GO  Etanol Hidratado   m3  2022-09-10  2002   15.925
31   08  GO  Etanol Hidratado   m3  2022-09-10  2002   14.546
32   09  GO  Etanol Hidratado   m3  2022-09-10  2002   16.075
33   10  GO  Etanol Hidratado   m3  2022-09-10  2002   18.054
34   11  GO  Etanol Hidratado   m3  2022-09-10  2002   14.069
35   12  GO  Etanol Hidratado   m3  2022-09-10  2002   14.218
36   01  GO  Etanol Hidratado   m3  2022-09-10  2003   13.793
37   02  GO  Etanol Hidratado   m3  2022-09-10  2003   10.407
38   03  GO  Etanol Hidratado   m3  2022-09-10  2003    9.793
39   04  GO  Etanol Hidratado   m3  2022-09-10  2003   10.823
40   05  GO  Etanol Hidratado   m3  2022-09-10  2003   10.914
41   06  GO  Etanol Hidratado   m3  2022-09-10  2003   10.526
42   07  GO  Etanol Hidratado   m3  2022-09-10  2003   13.305
43   08  GO  Etanol Hidratado   m3  2022-09-10  2003   11.766
44   09  GO  Etanol Hidratado   m3  2022-09-10  2003   11.946
45   10  GO  Etanol Hidratado   m3  2022-09-10  2003   13.340
46   11  GO  Etanol Hidratado   m3  2022-09-10  2003   13.827
47   12  GO  Etanol Hidratado   m3  2022-09-10  2003   14.951
48   01  GO  Etanol Hidratado   m3  2022-09-10  2004   13.411
49   02  GO  Etanol Hidratado   m3  2022-09-10  2004   12.368
50   03  GO  Etanol Hidratado   m3  2022-09-10  2004   15.253
51   04  GO  Etanol Hidratado   m3  2022-09-10  2004   15.030
52   05  GO  Etanol Hidratado   m3  2022-09-10  2004   15.017
53   06  GO  Etanol Hidratado   m3  2022-09-10  2004   12.399
54   07  GO  Etanol Hidratado   m3  2022-09-10  2004   16.897
55   08  GO  Etanol Hidratado   m3  2022-09-10  2004   12.631
56   09  GO  Etanol Hidratado   m3  2022-09-10  2004   14.321
57   10  GO  Etanol Hidratado   m3  2022-09-10  2004   14.135
58   11  GO  Etanol Hidratado   m3  2022-09-10  2004   13.054
59   12  GO  Etanol Hidratado   m3  2022-09-10  2004   15.580
60   01  GO  Etanol Hidratado   m3  2022-09-10  2005   12.588
61   02  GO  Etanol Hidratado   m3  2022-09-10  2005   11.664
62   03  GO  Etanol Hidratado   m3  2022-09-10  2005   12.775
63   04  GO  Etanol Hidratado   m3  

In [865]:
# Concatenando as colunas ano e Mês
dfgo['ano_mês'] = dfgo[['ano', 'Mês']].agg('-'.join, axis=1)

In [866]:
# Eliminando as colunas Mês e ano

dfgo.drop(["Mês"], axis=1, inplace=True)
dfgo.drop(["ano"], axis=1, inplace=True)

In [867]:
# Organização da ordem das colunas

dfgo=dfgo[['ano_mês', 'uf', 'produto', 'unid', 'venda', 'criado_em']]

In [868]:
# Levantamento de possíveis inconsistências

dfgo.isna().sum()

ano_mês      0
uf           0
produto      0
unid         0
venda        6
criado_em    0
dtype: int64

In [869]:
# Tratamento das inconsistências

dfgo.replace(['Na', 'nA', 'na','NA', 'NaN', 'NAN', 'nan', '', ' '],pd.NA,inplace=True)


In [870]:
# Visão geral da tabela

dfgo

ano_mês  uf           produto unid    venda   criado_em
0    2000-01  GO  Etanol Hidratado   m3   16.683  2022-09-10
1    2000-02  GO  Etanol Hidratado   m3   16.256  2022-09-10
2    2000-03  GO  Etanol Hidratado   m3   15.730  2022-09-10
3    2000-04  GO  Etanol Hidratado   m3   16.199  2022-09-10
4    2000-05  GO  Etanol Hidratado   m3   16.347  2022-09-10
5    2000-06  GO  Etanol Hidratado   m3   16.203  2022-09-10
6    2000-07  GO  Etanol Hidratado   m3   17.654  2022-09-10
7    2000-08  GO  Etanol Hidratado   m3   14.287  2022-09-10
8    2000-09  GO  Etanol Hidratado   m3   16.088  2022-09-10
9    2000-10  GO  Etanol Hidratado   m3   14.594  2022-09-10
10   2000-11  GO  Etanol Hidratado   m3   14.365  2022-09-10
11   2000-12  GO  Etanol Hidratado   m3   16.020  2022-09-10
12   2001-01  GO  Etanol Hidratado   m3   13.461  2022-09-10
13   2001-02  GO  Etanol Hidratado   m3   12.083  2022-09-10
14   2001-03  GO  Etanol Hidratado   m3   12.802  2022-09-10
15   2001-04  GO  Etanol Hidratado   m3   12.326  2022-09-10
16   2001-05  GO  Etanol Hidratado   m3   13.204  2022-09-10
17   2001-06  GO  Etanol Hidratado   m3   13.380  2022-09-10
18   2001-07  GO  Etanol Hidratado   m3   12.853  2022-09-10
19   2001-08  GO  Etanol Hidratado   m3   12.871  2022-09-10
20   2001-09  GO  Etanol Hidratado   m3   12.266  2022-09-10
21   2001-10  GO  Etanol Hidratado   m3   11.636  2022-09-10
22   2001-11  GO  Etanol Hidratado   m3   12.396  2022-09-10
23   2001-12  GO  Etanol Hidratado   m3   13.766  2022-09-10
24   2002-01  GO  Etanol Hidratado   m3   13.806  2022-09-10
25   2002-02  GO  Etanol Hidratado   m3   11.721  2022-09-10
26   2002-03  GO  Etanol Hidratado   m3   13.071  2022-09-10
27   2002-04  GO  Etanol Hidratado   m3   13.345  2022-09-10
28   2002-05  GO  Etanol Hidratado   m3   13.383  2022-09-10
29   2002-06  GO  Etanol Hidratado   m3   12.977  2022-09-10
30   2002-07  GO  Etanol Hidratado   m3   15.925  2022-09-10
31   2002-08  GO  Etanol Hidratado   m3   14.546  2022-09-10
32   2002-09  GO  Etanol Hidratado   m3   16.075  2022-09-10
33   2002-10  GO  Etanol Hidratado   m3   18.054  2022-09-10
34   2002-11  GO  Etanol Hidratado   m3   14.069  2022-09-10
35   2002-12  GO  Etanol Hidratado   m3   14.218  2022-09-10
36   2003-01  GO  Etanol Hidratado   m3   13.793  2022-09-10
37   2003-02  GO  Etanol Hidratado   m3   10.407  2022-09-10
38   2003-03  GO  Etanol Hidratado   m3    9.793  2022-09-10
39   2003-04  GO  Etanol Hidratado   m3   10.823  2022-09-10
40   2003-05  GO  Etanol Hidratado   m3   10.914  2022-09-10
41   2003-06  GO  Etanol Hidratado   m3   10.526  2022-09-10
42   2003-07  GO  Etanol Hidratado   m3   13.305  2022-09-10
43   2003-08  GO  Etanol Hidratado   m3   11.766  2022-09-10
44   2003-09  GO  Etanol Hidratado   m3   11.946  2022-09-10
45   2003-10  GO  Etanol Hidratado   m3   13.340  2022-09-10
46   2003-11  GO  Etanol Hidratado   m3   13.827  2022-09-10
47   2003-12  GO  Etanol Hidratado   m3   14.951  2022-09-10
48   2004-01  GO  Etanol Hidratado   m3   13.411  2022-09-10
49   2004-02  GO  Etanol Hidratado   m3   12.368  2022-09-10
50   2004-03  GO  Etanol Hidratado   m3   15.253  2022-09-10
51   2004-04  GO  Etanol Hidratado   m3   15.030  2022-09-10
52   2004-05  GO  Etanol Hidratado   m3   15.017  2022-09-10
53   2004-06  GO  Etanol Hidratado   m3   12.399  2022-09-10
54   2004-07  GO  Etanol Hidratado   m3   16.897  2022-09-10
55   2004-08  GO  Etanol Hidratado   m3   12.631  2022-09-10
56   2004-09  GO  Etanol Hidratado   m3   14.321  2022-09-10
57   2004-10  GO  Etanol Hidratado   m3   14.135  2022-09-10
58   2004-11  GO  Etanol Hidratado   m3   13.054  2022-09-10
59   2004-12  GO  Etanol Hidratado   m3   15.580  2022-09-10
60   2005-01  GO  Etanol Hidratado   m3   12.588  2022-09-10
61   2005-02  GO  Etanol Hidratado   m3   11.664  2022-09-10
62   2005-03  GO  Etanol Hidratado   m3   12.775  2022-09-10
63   2005-04  GO  Etanol Hidratado   m3    9.560  2022-09-10
64   2005-05  GO  Etanol Hidratado   m3 

In [871]:
# Verificando os tipos

dfgo.dtypes

ano_mês       object
uf            object
produto       object
unid          object
venda        float64
criado_em     object
dtype: object

In [872]:
# Validação

schema = pa.DataFrameSchema(
    columns = {
        'ano_mês': pa.Column(pa.String, nullable=True),
        'uf': pa.Column(pa.String, nullable = True),
        'produto': pa.Column(pa.String, nullable = True),
        'unid': pa.Column(pa.String, nullable = True),
        'venda': pa.Column(pa.Float, nullable = True),
        'criado_em': pa.Column(pa.String, nullable = True),
                
    }
)
schema.validate(dfgo)

ano_mês  uf           produto unid    venda   criado_em
0    2000-01  GO  Etanol Hidratado   m3   16.683  2022-09-10
1    2000-02  GO  Etanol Hidratado   m3   16.256  2022-09-10
2    2000-03  GO  Etanol Hidratado   m3   15.730  2022-09-10
3    2000-04  GO  Etanol Hidratado   m3   16.199  2022-09-10
4    2000-05  GO  Etanol Hidratado   m3   16.347  2022-09-10
5    2000-06  GO  Etanol Hidratado   m3   16.203  2022-09-10
6    2000-07  GO  Etanol Hidratado   m3   17.654  2022-09-10
7    2000-08  GO  Etanol Hidratado   m3   14.287  2022-09-10
8    2000-09  GO  Etanol Hidratado   m3   16.088  2022-09-10
9    2000-10  GO  Etanol Hidratado   m3   14.594  2022-09-10
10   2000-11  GO  Etanol Hidratado   m3   14.365  2022-09-10
11   2000-12  GO  Etanol Hidratado   m3   16.020  2022-09-10
12   2001-01  GO  Etanol Hidratado   m3   13.461  2022-09-10
13   2001-02  GO  Etanol Hidratado   m3   12.083  2022-09-10
14   2001-03  GO  Etanol Hidratado   m3   12.802  2022-09-10
15   2001-04  GO  Etanol Hidratado   m3   12.326  2022-09-10
16   2001-05  GO  Etanol Hidratado   m3   13.204  2022-09-10
17   2001-06  GO  Etanol Hidratado   m3   13.380  2022-09-10
18   2001-07  GO  Etanol Hidratado   m3   12.853  2022-09-10
19   2001-08  GO  Etanol Hidratado   m3   12.871  2022-09-10
20   2001-09  GO  Etanol Hidratado   m3   12.266  2022-09-10
21   2001-10  GO  Etanol Hidratado   m3   11.636  2022-09-10
22   2001-11  GO  Etanol Hidratado   m3   12.396  2022-09-10
23   2001-12  GO  Etanol Hidratado   m3   13.766  2022-09-10
24   2002-01  GO  Etanol Hidratado   m3   13.806  2022-09-10
25   2002-02  GO  Etanol Hidratado   m3   11.721  2022-09-10
26   2002-03  GO  Etanol Hidratado   m3   13.071  2022-09-10
27   2002-04  GO  Etanol Hidratado   m3   13.345  2022-09-10
28   2002-05  GO  Etanol Hidratado   m3   13.383  2022-09-10
29   2002-06  GO  Etanol Hidratado   m3   12.977  2022-09-10
30   2002-07  GO  Etanol Hidratado   m3   15.925  2022-09-10
31   2002-08  GO  Etanol Hidratado   m3   14.546  2022-09-10
32   2002-09  GO  Etanol Hidratado   m3   16.075  2022-09-10
33   2002-10  GO  Etanol Hidratado   m3   18.054  2022-09-10
34   2002-11  GO  Etanol Hidratado   m3   14.069  2022-09-10
35   2002-12  GO  Etanol Hidratado   m3   14.218  2022-09-10
36   2003-01  GO  Etanol Hidratado   m3   13.793  2022-09-10
37   2003-02  GO  Etanol Hidratado   m3   10.407  2022-09-10
38   2003-03  GO  Etanol Hidratado   m3    9.793  2022-09-10
39   2003-04  GO  Etanol Hidratado   m3   10.823  2022-09-10
40   2003-05  GO  Etanol Hidratado   m3   10.914  2022-09-10
41   2003-06  GO  Etanol Hidratado   m3   10.526  2022-09-10
42   2003-07  GO  Etanol Hidratado   m3   13.305  2022-09-10
43   2003-08  GO  Etanol Hidratado   m3   11.766  2022-09-10
44   2003-09  GO  Etanol Hidratado   m3   11.946  2022-09-10
45   2003-10  GO  Etanol Hidratado   m3   13.340  2022-09-10
46   2003-11  GO  Etanol Hidratado   m3   13.827  2022-09-10
47   2003-12  GO  Etanol Hidratado   m3   14.951  2022-09-10
48   2004-01  GO  Etanol Hidratado   m3   13.411  2022-09-10
49   2004-02  GO  Etanol Hidratado   m3   12.368  2022-09-10
50   2004-03  GO  Etanol Hidratado   m3   15.253  2022-09-10
51   2004-04  GO  Etanol Hidratado   m3   15.030  2022-09-10
52   2004-05  GO  Etanol Hidratado   m3   15.017  2022-09-10
53   2004-06  GO  Etanol Hidratado   m3   12.399  2022-09-10
54   2004-07  GO  Etanol Hidratado   m3   16.897  2022-09-10
55   2004-08  GO  Etanol Hidratado   m3   12.631  2022-09-10
56   2004-09  GO  Etanol Hidratado   m3   14.321  2022-09-10
57   2004-10  GO  Etanol Hidratado   m3   14.135  2022-09-10
58   2004-11  GO  Etanol Hidratado   m3   13.054  2022-09-10
59   2004-12  GO  Etanol Hidratado   m3   15.580  2022-09-10
60   2005-01  GO  Etanol Hidratado   m3   12.588  2022-09-10
61   2005-02  GO  Etanol Hidratado   m3   11.664  2022-09-10
62   2005-03  GO  Etanol Hidratado   m3   12.775  2022-09-10
63   2005-04  GO  Etanol Hidratado   m3    9.560  2022-09-10
64   2005-05  GO  Etanol Hidratado   m3 

In [873]:
dfgo_pandas = dfgo.copy()

##MARANHÃO

In [874]:
# Conector

dfma = pd.read_csv('/content/maranhao.csv',sep=';')

In [875]:
# Backup
dfma_backup = dfma.copy()

In [876]:
# Configurando a quantidade de linhas máximas mostradas em tela

pd.set_option('display.max_columns',1000)
pd.set_option('display.max_rows',1000)

In [877]:
# Visualização da Tabela

dfma

Mês   2000     2001  2002     2003  2004     2005     2006   2007  \
0     Janeiro  1.596    1.182   881    1.065   713    1.066    1.534  2.661   
1   Fevereiro  1.373  988.000   769  679.000   656  655.000    2.131  2.392   
2       Março  1.136    1.017   696  625.000   670  688.000    1.117  2.904   
3       Abril  1.226    1.064   819  509.000   629  661.000  866.000  2.713   
4        Maio  1.306  954.000   715  532.000   714  693.000  984.000  2.807   
5       Junho  1.255  857.000   716  610.000   646  715.000  980.000  3.199   
6       Julho  1.896    1.078   853  704.000   724  783.000    1.049  3.935   
7      Agosto  1.407    1.067   856  793.000   587  854.000    1.168  4.697   
8    Setembro  1.523  856.000   772  759.000   789  996.000    1.134  4.842   
9     Outubro  1.461  851.000   954  787.000   748    1.188    1.491  5.936   
10   Novembro  1.362  702.000   694  675.000   675    1.237    1.735  6.430   
11   Dezembro  1.212  811.000   808  866.000   704    1.737    2.404  6.580   

      2008    2009    2010   2011   2012   2013   2014   2015   2016   2017  \
0    6.754  10.855   7.158  5.665  1.970  2.224  4.044  4.565  3.492  2.172   
1    6.378   9.647   2.613  5.017  1.718  1.932  3.360  4.322  2.853  1.639   
2    6.879  10.989   3.380  4.597  1.940  1.826  3.712  4.903  3.027  1.780   
3    7.388  11.081   5.205  2.214  1.889  1.950  3.626  4.793  2.568  1.658   
4    8.304  11.177   7.366  2.589  1.770  1.663  3.286  4.912  2.759  1.970   
5    8.019  12.259   8.032  2.667  1.613  1.638  3.034  4.497  2.841  1.911   
6    9.291  13.819   9.883  2.355  2.359  2.101  3.472  4.741  4.375  1.781   
7    8.877  13.199  10.371  2.101  2.745  1.910  3.197  4.641  3.772  2.335   
8    9.846  13.765  10.802  1.954  2.305  1.618  2.917  5.069  2.554  2.631   
9    9.200  13.033   8.969  1.891  1.919  2.591  3.450  5.553  2.527  2.430   
10  12.696  10.963   7.875  1.985  1.981  2.950  4.064  4.453  2.214  2.608   
11  13.726  11.862   6.805  2.167  1.630  4.043  4.483  4.765  2.496  2.704   

     2018   2019   2020   2021    2022  
0   2.459  3.386  4.977  4.315   3.489  
1   1.919  2.869  3.236  4.472   5.814  
2   1.958  3.200  2.721  5.479   9.771  
3   1.981  3.694  1.872  3.778  10.273  
4   2.600  4.224  1.730  3.656   7.022  
5   3.270  3.587  2.324  3.456   8.786  
6   3.225  4.077  3.397  4.078     NaN  
7   3.591  3.871  3.442  6.821     NaN  
8   3.864  3.484  3.884  3.778     NaN  
9   4.643  4.286  3.748  6.760     NaN  
10  4.225  4.745  3.305  4.062     NaN  
11  3.564  5.580  4.546  4.264     NaN

In [878]:
# Replace do Mês para numérico

dfma["Mês"].replace("Janeiro", "01", inplace=True)
dfma["Mês"].replace("Fevereiro", "02", inplace=True)
dfma["Mês"].replace("Março", "03", inplace=True)
dfma["Mês"].replace("Abril", "04", inplace=True)
dfma["Mês"].replace("Maio", "05", inplace=True)
dfma["Mês"].replace("Junho", "06", inplace=True)
dfma["Mês"].replace("Julho", "07", inplace=True)
dfma["Mês"].replace("Agosto", "08", inplace=True)
dfma["Mês"].replace("Setembro", "09", inplace=True)
dfma["Mês"].replace("Outubro", "10", inplace=True)
dfma["Mês"].replace("Novembro", "11", inplace=True)
dfma["Mês"].replace("Dezembro", "12", inplace=True)

In [879]:
# Criação das colunas uf, produto, unid, criado_em
dfma['uf']='MA'
dfma['produto']='Etanol Hidratado'
dfma['unid']='m3'
dfma['criado_em'] ='2022-09-10'

In [880]:
# Despivotar a tabela em ano e volume 
dfma.reset_index(inplace=True)

In [881]:
dfma=dfma.melt(id_vars = ['Mês', 'uf', 'produto', 'unid', 'criado_em'], value_vars = ['2000', '2001', '2002', '2003', '2004', '2005', '2006', '2007', '2008', '2009', '2010', '2011', '2012', '2013', '2014', '2015', '2016', '2017', '2018', '2019', '2020', '2021', '2022'], var_name='ano', value_name='venda')

In [882]:
# Visão geral da tabela

dfma

Mês  uf           produto unid   criado_em   ano    venda
0    01  MA  Etanol Hidratado   m3  2022-09-10  2000    1.596
1    02  MA  Etanol Hidratado   m3  2022-09-10  2000    1.373
2    03  MA  Etanol Hidratado   m3  2022-09-10  2000    1.136
3    04  MA  Etanol Hidratado   m3  2022-09-10  2000    1.226
4    05  MA  Etanol Hidratado   m3  2022-09-10  2000    1.306
5    06  MA  Etanol Hidratado   m3  2022-09-10  2000    1.255
6    07  MA  Etanol Hidratado   m3  2022-09-10  2000    1.896
7    08  MA  Etanol Hidratado   m3  2022-09-10  2000    1.407
8    09  MA  Etanol Hidratado   m3  2022-09-10  2000    1.523
9    10  MA  Etanol Hidratado   m3  2022-09-10  2000    1.461
10   11  MA  Etanol Hidratado   m3  2022-09-10  2000    1.362
11   12  MA  Etanol Hidratado   m3  2022-09-10  2000    1.212
12   01  MA  Etanol Hidratado   m3  2022-09-10  2001    1.182
13   02  MA  Etanol Hidratado   m3  2022-09-10  2001  988.000
14   03  MA  Etanol Hidratado   m3  2022-09-10  2001    1.017
15   04  MA  Etanol Hidratado   m3  2022-09-10  2001    1.064
16   05  MA  Etanol Hidratado   m3  2022-09-10  2001  954.000
17   06  MA  Etanol Hidratado   m3  2022-09-10  2001  857.000
18   07  MA  Etanol Hidratado   m3  2022-09-10  2001    1.078
19   08  MA  Etanol Hidratado   m3  2022-09-10  2001    1.067
20   09  MA  Etanol Hidratado   m3  2022-09-10  2001  856.000
21   10  MA  Etanol Hidratado   m3  2022-09-10  2001  851.000
22   11  MA  Etanol Hidratado   m3  2022-09-10  2001  702.000
23   12  MA  Etanol Hidratado   m3  2022-09-10  2001  811.000
24   01  MA  Etanol Hidratado   m3  2022-09-10  2002  881.000
25   02  MA  Etanol Hidratado   m3  2022-09-10  2002  769.000
26   03  MA  Etanol Hidratado   m3  2022-09-10  2002  696.000
27   04  MA  Etanol Hidratado   m3  2022-09-10  2002  819.000
28   05  MA  Etanol Hidratado   m3  2022-09-10  2002  715.000
29   06  MA  Etanol Hidratado   m3  2022-09-10  2002  716.000
30   07  MA  Etanol Hidratado   m3  2022-09-10  2002  853.000
31   08  MA  Etanol Hidratado   m3  2022-09-10  2002  856.000
32   09  MA  Etanol Hidratado   m3  2022-09-10  2002  772.000
33   10  MA  Etanol Hidratado   m3  2022-09-10  2002  954.000
34   11  MA  Etanol Hidratado   m3  2022-09-10  2002  694.000
35   12  MA  Etanol Hidratado   m3  2022-09-10  2002  808.000
36   01  MA  Etanol Hidratado   m3  2022-09-10  2003    1.065
37   02  MA  Etanol Hidratado   m3  2022-09-10  2003  679.000
38   03  MA  Etanol Hidratado   m3  2022-09-10  2003  625.000
39   04  MA  Etanol Hidratado   m3  2022-09-10  2003  509.000
40   05  MA  Etanol Hidratado   m3  2022-09-10  2003  532.000
41   06  MA  Etanol Hidratado   m3  2022-09-10  2003  610.000
42   07  MA  Etanol Hidratado   m3  2022-09-10  2003  704.000
43   08  MA  Etanol Hidratado   m3  2022-09-10  2003  793.000
44   09  MA  Etanol Hidratado   m3  2022-09-10  2003  759.000
45   10  MA  Etanol Hidratado   m3  2022-09-10  2003  787.000
46   11  MA  Etanol Hidratado   m3  2022-09-10  2003  675.000
47   12  MA  Etanol Hidratado   m3  2022-09-10  2003  866.000
48   01  MA  Etanol Hidratado   m3  2022-09-10  2004  713.000
49   02  MA  Etanol Hidratado   m3  2022-09-10  2004  656.000
50   03  MA  Etanol Hidratado   m3  2022-09-10  2004  670.000
51   04  MA  Etanol Hidratado   m3  2022-09-10  2004  629.000
52   05  MA  Etanol Hidratado   m3  2022-09-10  2004  714.000
53   06  MA  Etanol Hidratado   m3  2022-09-10  2004  646.000
54   07  MA  Etanol Hidratado   m3  2022-09-10  2004  724.000
55   08  MA  Etanol Hidratado   m3  2022-09-10  2004  587.000
56   09  MA  Etanol Hidratado   m3  2022-09-10  2004  789.000
57   10  MA  Etanol Hidratado   m3  2022-09-10  2004  748.000
58   11  MA  Etanol Hidratado   m3  2022-09-10  2004  675.000
59   12  MA  Etanol Hidratado   m3  2022-09-10  2004  704.000
60   01  MA  Etanol Hidratado   m3  2022-09-10  2005    1.066
61   02  MA  Etanol Hidratado   m3  2022-09-10  2005  655.000
62   03  MA  Etanol Hidratado   m3  2022-09-10  2005  688.000
63   04  MA  Etanol Hidratado   m3  

In [883]:
# Concatenando as colunas ano e Mês
dfma['ano_mês'] = dfma[['ano', 'Mês']].agg('-'.join, axis=1)

In [884]:
# Eliminando as colunas Mês e ano

dfma.drop(["Mês"], axis=1, inplace=True)
dfma.drop(["ano"], axis=1, inplace=True)

In [885]:
# Organização da ordem das colunas

dfma=dfma[['ano_mês', 'uf', 'produto', 'unid', 'venda', 'criado_em']]

In [886]:
# Levantamento de possíveis inconsistências

dfma.isna().sum()

ano_mês      0
uf           0
produto      0
unid         0
venda        6
criado_em    0
dtype: int64

In [887]:
# Tratamento das inconsistências

dfma.replace(['Na', 'nA', 'na','NA', 'NaN', 'NAN', 'nan', '', ' '],pd.NA,inplace=True)


In [888]:
# Visão geral da tabela

dfma

ano_mês  uf           produto unid    venda   criado_em
0    2000-01  MA  Etanol Hidratado   m3    1.596  2022-09-10
1    2000-02  MA  Etanol Hidratado   m3    1.373  2022-09-10
2    2000-03  MA  Etanol Hidratado   m3    1.136  2022-09-10
3    2000-04  MA  Etanol Hidratado   m3    1.226  2022-09-10
4    2000-05  MA  Etanol Hidratado   m3    1.306  2022-09-10
5    2000-06  MA  Etanol Hidratado   m3    1.255  2022-09-10
6    2000-07  MA  Etanol Hidratado   m3    1.896  2022-09-10
7    2000-08  MA  Etanol Hidratado   m3    1.407  2022-09-10
8    2000-09  MA  Etanol Hidratado   m3    1.523  2022-09-10
9    2000-10  MA  Etanol Hidratado   m3    1.461  2022-09-10
10   2000-11  MA  Etanol Hidratado   m3    1.362  2022-09-10
11   2000-12  MA  Etanol Hidratado   m3    1.212  2022-09-10
12   2001-01  MA  Etanol Hidratado   m3    1.182  2022-09-10
13   2001-02  MA  Etanol Hidratado   m3  988.000  2022-09-10
14   2001-03  MA  Etanol Hidratado   m3    1.017  2022-09-10
15   2001-04  MA  Etanol Hidratado   m3    1.064  2022-09-10
16   2001-05  MA  Etanol Hidratado   m3  954.000  2022-09-10
17   2001-06  MA  Etanol Hidratado   m3  857.000  2022-09-10
18   2001-07  MA  Etanol Hidratado   m3    1.078  2022-09-10
19   2001-08  MA  Etanol Hidratado   m3    1.067  2022-09-10
20   2001-09  MA  Etanol Hidratado   m3  856.000  2022-09-10
21   2001-10  MA  Etanol Hidratado   m3  851.000  2022-09-10
22   2001-11  MA  Etanol Hidratado   m3  702.000  2022-09-10
23   2001-12  MA  Etanol Hidratado   m3  811.000  2022-09-10
24   2002-01  MA  Etanol Hidratado   m3  881.000  2022-09-10
25   2002-02  MA  Etanol Hidratado   m3  769.000  2022-09-10
26   2002-03  MA  Etanol Hidratado   m3  696.000  2022-09-10
27   2002-04  MA  Etanol Hidratado   m3  819.000  2022-09-10
28   2002-05  MA  Etanol Hidratado   m3  715.000  2022-09-10
29   2002-06  MA  Etanol Hidratado   m3  716.000  2022-09-10
30   2002-07  MA  Etanol Hidratado   m3  853.000  2022-09-10
31   2002-08  MA  Etanol Hidratado   m3  856.000  2022-09-10
32   2002-09  MA  Etanol Hidratado   m3  772.000  2022-09-10
33   2002-10  MA  Etanol Hidratado   m3  954.000  2022-09-10
34   2002-11  MA  Etanol Hidratado   m3  694.000  2022-09-10
35   2002-12  MA  Etanol Hidratado   m3  808.000  2022-09-10
36   2003-01  MA  Etanol Hidratado   m3    1.065  2022-09-10
37   2003-02  MA  Etanol Hidratado   m3  679.000  2022-09-10
38   2003-03  MA  Etanol Hidratado   m3  625.000  2022-09-10
39   2003-04  MA  Etanol Hidratado   m3  509.000  2022-09-10
40   2003-05  MA  Etanol Hidratado   m3  532.000  2022-09-10
41   2003-06  MA  Etanol Hidratado   m3  610.000  2022-09-10
42   2003-07  MA  Etanol Hidratado   m3  704.000  2022-09-10
43   2003-08  MA  Etanol Hidratado   m3  793.000  2022-09-10
44   2003-09  MA  Etanol Hidratado   m3  759.000  2022-09-10
45   2003-10  MA  Etanol Hidratado   m3  787.000  2022-09-10
46   2003-11  MA  Etanol Hidratado   m3  675.000  2022-09-10
47   2003-12  MA  Etanol Hidratado   m3  866.000  2022-09-10
48   2004-01  MA  Etanol Hidratado   m3  713.000  2022-09-10
49   2004-02  MA  Etanol Hidratado   m3  656.000  2022-09-10
50   2004-03  MA  Etanol Hidratado   m3  670.000  2022-09-10
51   2004-04  MA  Etanol Hidratado   m3  629.000  2022-09-10
52   2004-05  MA  Etanol Hidratado   m3  714.000  2022-09-10
53   2004-06  MA  Etanol Hidratado   m3  646.000  2022-09-10
54   2004-07  MA  Etanol Hidratado   m3  724.000  2022-09-10
55   2004-08  MA  Etanol Hidratado   m3  587.000  2022-09-10
56   2004-09  MA  Etanol Hidratado   m3  789.000  2022-09-10
57   2004-10  MA  Etanol Hidratado   m3  748.000  2022-09-10
58   2004-11  MA  Etanol Hidratado   m3  675.000  2022-09-10
59   2004-12  MA  Etanol Hidratado   m3  704.000  2022-09-10
60   2005-01  MA  Etanol Hidratado   m3    1.066  2022-09-10
61   2005-02  MA  Etanol Hidratado   m3  655.000  2022-09-10
62   2005-03  MA  Etanol Hidratado   m3  688.000  2022-09-10
63   2005-04  MA  Etanol Hidratado   m3  661.000  2022-09-10
64   2005-05  MA  Etanol Hidratado   m3 

In [889]:
# Verificando os tipos

dfma.dtypes

ano_mês       object
uf            object
produto       object
unid          object
venda        float64
criado_em     object
dtype: object

In [890]:
# Validação

schema = pa.DataFrameSchema(
    columns = {
        'ano_mês': pa.Column(pa.String, nullable=True),
        'uf': pa.Column(pa.String, nullable = True),
        'produto': pa.Column(pa.String, nullable = True),
        'unid': pa.Column(pa.String, nullable = True),
        'venda': pa.Column(pa.Float, nullable = True),
        'criado_em': pa.Column(pa.String, nullable = True),
                
    }
)
schema.validate(dfma)

ano_mês  uf           produto unid    venda   criado_em
0    2000-01  MA  Etanol Hidratado   m3    1.596  2022-09-10
1    2000-02  MA  Etanol Hidratado   m3    1.373  2022-09-10
2    2000-03  MA  Etanol Hidratado   m3    1.136  2022-09-10
3    2000-04  MA  Etanol Hidratado   m3    1.226  2022-09-10
4    2000-05  MA  Etanol Hidratado   m3    1.306  2022-09-10
5    2000-06  MA  Etanol Hidratado   m3    1.255  2022-09-10
6    2000-07  MA  Etanol Hidratado   m3    1.896  2022-09-10
7    2000-08  MA  Etanol Hidratado   m3    1.407  2022-09-10
8    2000-09  MA  Etanol Hidratado   m3    1.523  2022-09-10
9    2000-10  MA  Etanol Hidratado   m3    1.461  2022-09-10
10   2000-11  MA  Etanol Hidratado   m3    1.362  2022-09-10
11   2000-12  MA  Etanol Hidratado   m3    1.212  2022-09-10
12   2001-01  MA  Etanol Hidratado   m3    1.182  2022-09-10
13   2001-02  MA  Etanol Hidratado   m3  988.000  2022-09-10
14   2001-03  MA  Etanol Hidratado   m3    1.017  2022-09-10
15   2001-04  MA  Etanol Hidratado   m3    1.064  2022-09-10
16   2001-05  MA  Etanol Hidratado   m3  954.000  2022-09-10
17   2001-06  MA  Etanol Hidratado   m3  857.000  2022-09-10
18   2001-07  MA  Etanol Hidratado   m3    1.078  2022-09-10
19   2001-08  MA  Etanol Hidratado   m3    1.067  2022-09-10
20   2001-09  MA  Etanol Hidratado   m3  856.000  2022-09-10
21   2001-10  MA  Etanol Hidratado   m3  851.000  2022-09-10
22   2001-11  MA  Etanol Hidratado   m3  702.000  2022-09-10
23   2001-12  MA  Etanol Hidratado   m3  811.000  2022-09-10
24   2002-01  MA  Etanol Hidratado   m3  881.000  2022-09-10
25   2002-02  MA  Etanol Hidratado   m3  769.000  2022-09-10
26   2002-03  MA  Etanol Hidratado   m3  696.000  2022-09-10
27   2002-04  MA  Etanol Hidratado   m3  819.000  2022-09-10
28   2002-05  MA  Etanol Hidratado   m3  715.000  2022-09-10
29   2002-06  MA  Etanol Hidratado   m3  716.000  2022-09-10
30   2002-07  MA  Etanol Hidratado   m3  853.000  2022-09-10
31   2002-08  MA  Etanol Hidratado   m3  856.000  2022-09-10
32   2002-09  MA  Etanol Hidratado   m3  772.000  2022-09-10
33   2002-10  MA  Etanol Hidratado   m3  954.000  2022-09-10
34   2002-11  MA  Etanol Hidratado   m3  694.000  2022-09-10
35   2002-12  MA  Etanol Hidratado   m3  808.000  2022-09-10
36   2003-01  MA  Etanol Hidratado   m3    1.065  2022-09-10
37   2003-02  MA  Etanol Hidratado   m3  679.000  2022-09-10
38   2003-03  MA  Etanol Hidratado   m3  625.000  2022-09-10
39   2003-04  MA  Etanol Hidratado   m3  509.000  2022-09-10
40   2003-05  MA  Etanol Hidratado   m3  532.000  2022-09-10
41   2003-06  MA  Etanol Hidratado   m3  610.000  2022-09-10
42   2003-07  MA  Etanol Hidratado   m3  704.000  2022-09-10
43   2003-08  MA  Etanol Hidratado   m3  793.000  2022-09-10
44   2003-09  MA  Etanol Hidratado   m3  759.000  2022-09-10
45   2003-10  MA  Etanol Hidratado   m3  787.000  2022-09-10
46   2003-11  MA  Etanol Hidratado   m3  675.000  2022-09-10
47   2003-12  MA  Etanol Hidratado   m3  866.000  2022-09-10
48   2004-01  MA  Etanol Hidratado   m3  713.000  2022-09-10
49   2004-02  MA  Etanol Hidratado   m3  656.000  2022-09-10
50   2004-03  MA  Etanol Hidratado   m3  670.000  2022-09-10
51   2004-04  MA  Etanol Hidratado   m3  629.000  2022-09-10
52   2004-05  MA  Etanol Hidratado   m3  714.000  2022-09-10
53   2004-06  MA  Etanol Hidratado   m3  646.000  2022-09-10
54   2004-07  MA  Etanol Hidratado   m3  724.000  2022-09-10
55   2004-08  MA  Etanol Hidratado   m3  587.000  2022-09-10
56   2004-09  MA  Etanol Hidratado   m3  789.000  2022-09-10
57   2004-10  MA  Etanol Hidratado   m3  748.000  2022-09-10
58   2004-11  MA  Etanol Hidratado   m3  675.000  2022-09-10
59   2004-12  MA  Etanol Hidratado   m3  704.000  2022-09-10
60   2005-01  MA  Etanol Hidratado   m3    1.066  2022-09-10
61   2005-02  MA  Etanol Hidratado   m3  655.000  2022-09-10
62   2005-03  MA  Etanol Hidratado   m3  688.000  2022-09-10
63   2005-04  MA  Etanol Hidratado   m3  661.000  2022-09-10
64   2005-05  MA  Etanol Hidratado   m3 

In [891]:
dfma_pandas = dfma.copy()

##MINAS GERAIS

In [892]:
# Conector

dfmg = pd.read_csv('/content/minas_gerais.csv',sep=';')

In [893]:
# Backup
dfmg_backup = dfmg.copy()

In [894]:
# Configurando a quantidade de linhas máximas mostradas em tela

pd.set_option('display.max_columns',1000)
pd.set_option('display.max_rows',1000)

In [895]:
# Visualização da Tabela

dfmg

Mês    2000    2001    2002    2003    2004    2005    2006    2007  \
0     Janeiro  47.585  35.371  27.588  39.539  34.891  32.096  35.624  43.644   
1   Fevereiro  52.737  28.849  24.446  31.462  32.137  27.275  27.750  34.850   
2       Março  48.458  35.484  22.087  28.772  34.161  29.712  24.778  38.889   
3       Abril  46.727  31.924  28.238  29.365  33.503  28.446  22.700  35.760   
4        Maio  53.943  37.098  36.090  29.438  35.008  30.100  27.865  39.031   
5       Junho  46.728  36.284  35.295  26.013  32.716  29.786  28.572  42.971   
6       Julho  49.472  31.751  40.687  33.266  39.088  31.486  32.285  50.977   
7      Agosto  44.236  33.723  36.348  30.460  33.570  35.524  30.555  53.870   
8    Setembro  42.570  28.158  35.679  28.422  36.181  38.680  33.913  55.943   
9     Outubro  41.070  28.825  47.216  29.904  36.532  32.995  34.362  67.096   
10   Novembro  38.942  28.851  35.272  28.310  33.288  34.180  32.339  66.580   
11   Dezembro  38.622  35.348  39.580  39.311  39.830  41.201  40.671  73.131   

       2008     2009    2010    2011    2012    2013    2014     2015  \
0    70.149   91.519  58.768  62.326  39.119  50.946  70.327   77.322   
1    63.337   84.373  39.216  55.127  40.351  51.100  62.180   82.846   
2    67.776   92.266  51.765  47.115  41.682  49.491  52.139  106.232   
3    74.585  100.249  68.011  32.474  39.435  61.217  56.718  141.119   
4    76.636  102.049  72.585  48.476  41.118  50.477  52.818  144.302   
5    75.420  101.280  78.597  52.849  40.103  55.634  54.189  161.694   
6    83.053  116.055  87.208  47.868  42.439  65.123  59.753  184.977   
7    79.875  107.644  80.878  51.075  42.984  64.431  58.873  186.041   
8    85.222  112.883  83.824  42.672  43.188  63.833  62.093  197.828   
9    91.731  107.304  74.597  42.584  51.340  69.905  67.616  205.864   
10   83.550   85.392  68.218  40.645  48.939  67.359  67.471  147.450   
11  105.865  103.415  74.493  45.553  53.394  77.380  85.481  154.262   

       2016     2017     2018     2019     2020     2021     2022  
0   114.404   81.348  167.814  254.649  264.537  249.167  128.562  
1    94.476   72.639  145.775  239.158  237.695  237.411  154.615  
2    89.797   85.154  157.390  240.448  196.267  209.422  210.331  
3   100.900   87.119  157.549  246.560  171.020  214.484  196.145  
4   148.179   95.729  153.488  258.251  190.792  214.706  174.497  
5   144.603  102.075  194.808  246.401  195.568  180.432  190.399  
6   149.502  109.252  219.567  279.445  218.064  191.592      NaN  
7   147.611  137.358  243.840  269.578  224.458  186.698      NaN  
8   146.962  159.819  240.703  271.952  245.895  177.987      NaN  
9   117.074  173.316  276.755  295.379  270.740  174.669      NaN  
10   88.256  172.873  254.276  284.794  246.950  139.079      NaN  
11  105.527  191.901  276.349  304.301  281.698  168.196      NaN

In [896]:
# Replace do Mês para numérico

dfmg["Mês"].replace("Janeiro", "01", inplace=True)
dfmg["Mês"].replace("Fevereiro", "02", inplace=True)
dfmg["Mês"].replace("Março", "03", inplace=True)
dfmg["Mês"].replace("Abril", "04", inplace=True)
dfmg["Mês"].replace("Maio", "05", inplace=True)
dfmg["Mês"].replace("Junho", "06", inplace=True)
dfmg["Mês"].replace("Julho", "07", inplace=True)
dfmg["Mês"].replace("Agosto", "08", inplace=True)
dfmg["Mês"].replace("Setembro", "09", inplace=True)
dfmg["Mês"].replace("Outubro", "10", inplace=True)
dfmg["Mês"].replace("Novembro", "11", inplace=True)
dfmg["Mês"].replace("Dezembro", "12", inplace=True)

In [897]:
# Criação das colunas uf, produto, unid, criado_em
dfmg['uf']='MG'
dfmg['produto']='Etanol Hidratado'
dfmg['unid']='m3'
dfmg['criado_em'] ='2022-09-10'

In [898]:
# Despivotar a tabela em ano e volume 
dfmg.reset_index(inplace=True)

In [899]:
dfmg=dfmg.melt(id_vars = ['Mês', 'uf', 'produto', 'unid', 'criado_em'], value_vars = ['2000', '2001', '2002', '2003', '2004', '2005', '2006', '2007', '2008', '2009', '2010', '2011', '2012', '2013', '2014', '2015', '2016', '2017', '2018', '2019', '2020', '2021', '2022'], var_name='ano', value_name='venda')

In [900]:
# Visão geral da tabela

dfmg

Mês  uf           produto unid   criado_em   ano    venda
0    01  MG  Etanol Hidratado   m3  2022-09-10  2000   47.585
1    02  MG  Etanol Hidratado   m3  2022-09-10  2000   52.737
2    03  MG  Etanol Hidratado   m3  2022-09-10  2000   48.458
3    04  MG  Etanol Hidratado   m3  2022-09-10  2000   46.727
4    05  MG  Etanol Hidratado   m3  2022-09-10  2000   53.943
5    06  MG  Etanol Hidratado   m3  2022-09-10  2000   46.728
6    07  MG  Etanol Hidratado   m3  2022-09-10  2000   49.472
7    08  MG  Etanol Hidratado   m3  2022-09-10  2000   44.236
8    09  MG  Etanol Hidratado   m3  2022-09-10  2000   42.570
9    10  MG  Etanol Hidratado   m3  2022-09-10  2000   41.070
10   11  MG  Etanol Hidratado   m3  2022-09-10  2000   38.942
11   12  MG  Etanol Hidratado   m3  2022-09-10  2000   38.622
12   01  MG  Etanol Hidratado   m3  2022-09-10  2001   35.371
13   02  MG  Etanol Hidratado   m3  2022-09-10  2001   28.849
14   03  MG  Etanol Hidratado   m3  2022-09-10  2001   35.484
15   04  MG  Etanol Hidratado   m3  2022-09-10  2001   31.924
16   05  MG  Etanol Hidratado   m3  2022-09-10  2001   37.098
17   06  MG  Etanol Hidratado   m3  2022-09-10  2001   36.284
18   07  MG  Etanol Hidratado   m3  2022-09-10  2001   31.751
19   08  MG  Etanol Hidratado   m3  2022-09-10  2001   33.723
20   09  MG  Etanol Hidratado   m3  2022-09-10  2001   28.158
21   10  MG  Etanol Hidratado   m3  2022-09-10  2001   28.825
22   11  MG  Etanol Hidratado   m3  2022-09-10  2001   28.851
23   12  MG  Etanol Hidratado   m3  2022-09-10  2001   35.348
24   01  MG  Etanol Hidratado   m3  2022-09-10  2002   27.588
25   02  MG  Etanol Hidratado   m3  2022-09-10  2002   24.446
26   03  MG  Etanol Hidratado   m3  2022-09-10  2002   22.087
27   04  MG  Etanol Hidratado   m3  2022-09-10  2002   28.238
28   05  MG  Etanol Hidratado   m3  2022-09-10  2002   36.090
29   06  MG  Etanol Hidratado   m3  2022-09-10  2002   35.295
30   07  MG  Etanol Hidratado   m3  2022-09-10  2002   40.687
31   08  MG  Etanol Hidratado   m3  2022-09-10  2002   36.348
32   09  MG  Etanol Hidratado   m3  2022-09-10  2002   35.679
33   10  MG  Etanol Hidratado   m3  2022-09-10  2002   47.216
34   11  MG  Etanol Hidratado   m3  2022-09-10  2002   35.272
35   12  MG  Etanol Hidratado   m3  2022-09-10  2002   39.580
36   01  MG  Etanol Hidratado   m3  2022-09-10  2003   39.539
37   02  MG  Etanol Hidratado   m3  2022-09-10  2003   31.462
38   03  MG  Etanol Hidratado   m3  2022-09-10  2003   28.772
39   04  MG  Etanol Hidratado   m3  2022-09-10  2003   29.365
40   05  MG  Etanol Hidratado   m3  2022-09-10  2003   29.438
41   06  MG  Etanol Hidratado   m3  2022-09-10  2003   26.013
42   07  MG  Etanol Hidratado   m3  2022-09-10  2003   33.266
43   08  MG  Etanol Hidratado   m3  2022-09-10  2003   30.460
44   09  MG  Etanol Hidratado   m3  2022-09-10  2003   28.422
45   10  MG  Etanol Hidratado   m3  2022-09-10  2003   29.904
46   11  MG  Etanol Hidratado   m3  2022-09-10  2003   28.310
47   12  MG  Etanol Hidratado   m3  2022-09-10  2003   39.311
48   01  MG  Etanol Hidratado   m3  2022-09-10  2004   34.891
49   02  MG  Etanol Hidratado   m3  2022-09-10  2004   32.137
50   03  MG  Etanol Hidratado   m3  2022-09-10  2004   34.161
51   04  MG  Etanol Hidratado   m3  2022-09-10  2004   33.503
52   05  MG  Etanol Hidratado   m3  2022-09-10  2004   35.008
53   06  MG  Etanol Hidratado   m3  2022-09-10  2004   32.716
54   07  MG  Etanol Hidratado   m3  2022-09-10  2004   39.088
55   08  MG  Etanol Hidratado   m3  2022-09-10  2004   33.570
56   09  MG  Etanol Hidratado   m3  2022-09-10  2004   36.181
57   10  MG  Etanol Hidratado   m3  2022-09-10  2004   36.532
58   11  MG  Etanol Hidratado   m3  2022-09-10  2004   33.288
59   12  MG  Etanol Hidratado   m3  2022-09-10  2004   39.830
60   01  MG  Etanol Hidratado   m3  2022-09-10  2005   32.096
61   02  MG  Etanol Hidratado   m3  2022-09-10  2005   27.275
62   03  MG  Etanol Hidratado   m3  2022-09-10  2005   29.712
63   04  MG  Etanol Hidratado   m3  

In [901]:
# Concatenando as colunas ano e Mês
dfmg['ano_mês'] = dfmg[['ano', 'Mês']].agg('-'.join, axis=1)

In [902]:
# Eliminando as colunas Mês e ano

dfmg.drop(["Mês"], axis=1, inplace=True)
dfmg.drop(["ano"], axis=1, inplace=True)

In [903]:
# Organização da ordem das colunas

dfmg=dfmg[['ano_mês', 'uf', 'produto', 'unid', 'venda', 'criado_em']]

In [904]:
# Levantamento de possíveis inconsistências

dfmg.isna().sum()

ano_mês      0
uf           0
produto      0
unid         0
venda        6
criado_em    0
dtype: int64

In [905]:
# Tratamento das inconsistências

dfmg.replace(['Na', 'nA', 'na','NA', 'NaN', 'NAN', 'nan', '', ' '],pd.NA,inplace=True)


In [906]:
# Visão geral da tabela

dfmg

ano_mês  uf           produto unid    venda   criado_em
0    2000-01  MG  Etanol Hidratado   m3   47.585  2022-09-10
1    2000-02  MG  Etanol Hidratado   m3   52.737  2022-09-10
2    2000-03  MG  Etanol Hidratado   m3   48.458  2022-09-10
3    2000-04  MG  Etanol Hidratado   m3   46.727  2022-09-10
4    2000-05  MG  Etanol Hidratado   m3   53.943  2022-09-10
5    2000-06  MG  Etanol Hidratado   m3   46.728  2022-09-10
6    2000-07  MG  Etanol Hidratado   m3   49.472  2022-09-10
7    2000-08  MG  Etanol Hidratado   m3   44.236  2022-09-10
8    2000-09  MG  Etanol Hidratado   m3   42.570  2022-09-10
9    2000-10  MG  Etanol Hidratado   m3   41.070  2022-09-10
10   2000-11  MG  Etanol Hidratado   m3   38.942  2022-09-10
11   2000-12  MG  Etanol Hidratado   m3   38.622  2022-09-10
12   2001-01  MG  Etanol Hidratado   m3   35.371  2022-09-10
13   2001-02  MG  Etanol Hidratado   m3   28.849  2022-09-10
14   2001-03  MG  Etanol Hidratado   m3   35.484  2022-09-10
15   2001-04  MG  Etanol Hidratado   m3   31.924  2022-09-10
16   2001-05  MG  Etanol Hidratado   m3   37.098  2022-09-10
17   2001-06  MG  Etanol Hidratado   m3   36.284  2022-09-10
18   2001-07  MG  Etanol Hidratado   m3   31.751  2022-09-10
19   2001-08  MG  Etanol Hidratado   m3   33.723  2022-09-10
20   2001-09  MG  Etanol Hidratado   m3   28.158  2022-09-10
21   2001-10  MG  Etanol Hidratado   m3   28.825  2022-09-10
22   2001-11  MG  Etanol Hidratado   m3   28.851  2022-09-10
23   2001-12  MG  Etanol Hidratado   m3   35.348  2022-09-10
24   2002-01  MG  Etanol Hidratado   m3   27.588  2022-09-10
25   2002-02  MG  Etanol Hidratado   m3   24.446  2022-09-10
26   2002-03  MG  Etanol Hidratado   m3   22.087  2022-09-10
27   2002-04  MG  Etanol Hidratado   m3   28.238  2022-09-10
28   2002-05  MG  Etanol Hidratado   m3   36.090  2022-09-10
29   2002-06  MG  Etanol Hidratado   m3   35.295  2022-09-10
30   2002-07  MG  Etanol Hidratado   m3   40.687  2022-09-10
31   2002-08  MG  Etanol Hidratado   m3   36.348  2022-09-10
32   2002-09  MG  Etanol Hidratado   m3   35.679  2022-09-10
33   2002-10  MG  Etanol Hidratado   m3   47.216  2022-09-10
34   2002-11  MG  Etanol Hidratado   m3   35.272  2022-09-10
35   2002-12  MG  Etanol Hidratado   m3   39.580  2022-09-10
36   2003-01  MG  Etanol Hidratado   m3   39.539  2022-09-10
37   2003-02  MG  Etanol Hidratado   m3   31.462  2022-09-10
38   2003-03  MG  Etanol Hidratado   m3   28.772  2022-09-10
39   2003-04  MG  Etanol Hidratado   m3   29.365  2022-09-10
40   2003-05  MG  Etanol Hidratado   m3   29.438  2022-09-10
41   2003-06  MG  Etanol Hidratado   m3   26.013  2022-09-10
42   2003-07  MG  Etanol Hidratado   m3   33.266  2022-09-10
43   2003-08  MG  Etanol Hidratado   m3   30.460  2022-09-10
44   2003-09  MG  Etanol Hidratado   m3   28.422  2022-09-10
45   2003-10  MG  Etanol Hidratado   m3   29.904  2022-09-10
46   2003-11  MG  Etanol Hidratado   m3   28.310  2022-09-10
47   2003-12  MG  Etanol Hidratado   m3   39.311  2022-09-10
48   2004-01  MG  Etanol Hidratado   m3   34.891  2022-09-10
49   2004-02  MG  Etanol Hidratado   m3   32.137  2022-09-10
50   2004-03  MG  Etanol Hidratado   m3   34.161  2022-09-10
51   2004-04  MG  Etanol Hidratado   m3   33.503  2022-09-10
52   2004-05  MG  Etanol Hidratado   m3   35.008  2022-09-10
53   2004-06  MG  Etanol Hidratado   m3   32.716  2022-09-10
54   2004-07  MG  Etanol Hidratado   m3   39.088  2022-09-10
55   2004-08  MG  Etanol Hidratado   m3   33.570  2022-09-10
56   2004-09  MG  Etanol Hidratado   m3   36.181  2022-09-10
57   2004-10  MG  Etanol Hidratado   m3   36.532  2022-09-10
58   2004-11  MG  Etanol Hidratado   m3   33.288  2022-09-10
59   2004-12  MG  Etanol Hidratado   m3   39.830  2022-09-10
60   2005-01  MG  Etanol Hidratado   m3   32.096  2022-09-10
61   2005-02  MG  Etanol Hidratado   m3   27.275  2022-09-10
62   2005-03  MG  Etanol Hidratado   m3   29.712  2022-09-10
63   2005-04  MG  Etanol Hidratado   m3   28.446  2022-09-10
64   2005-05  MG  Etanol Hidratado   m3 

In [907]:
# Verificando os tipos

dfmg.dtypes

ano_mês       object
uf            object
produto       object
unid          object
venda        float64
criado_em     object
dtype: object

In [908]:
# Validação

schema = pa.DataFrameSchema(
    columns = {
        'ano_mês': pa.Column(pa.String, nullable=True),
        'uf': pa.Column(pa.String, nullable = True),
        'produto': pa.Column(pa.String, nullable = True),
        'unid': pa.Column(pa.String, nullable = True),
        'venda': pa.Column(pa.Float, nullable = True),
        'criado_em': pa.Column(pa.String, nullable = True),
                
    }
)
schema.validate(dfmg)

ano_mês  uf           produto unid    venda   criado_em
0    2000-01  MG  Etanol Hidratado   m3   47.585  2022-09-10
1    2000-02  MG  Etanol Hidratado   m3   52.737  2022-09-10
2    2000-03  MG  Etanol Hidratado   m3   48.458  2022-09-10
3    2000-04  MG  Etanol Hidratado   m3   46.727  2022-09-10
4    2000-05  MG  Etanol Hidratado   m3   53.943  2022-09-10
5    2000-06  MG  Etanol Hidratado   m3   46.728  2022-09-10
6    2000-07  MG  Etanol Hidratado   m3   49.472  2022-09-10
7    2000-08  MG  Etanol Hidratado   m3   44.236  2022-09-10
8    2000-09  MG  Etanol Hidratado   m3   42.570  2022-09-10
9    2000-10  MG  Etanol Hidratado   m3   41.070  2022-09-10
10   2000-11  MG  Etanol Hidratado   m3   38.942  2022-09-10
11   2000-12  MG  Etanol Hidratado   m3   38.622  2022-09-10
12   2001-01  MG  Etanol Hidratado   m3   35.371  2022-09-10
13   2001-02  MG  Etanol Hidratado   m3   28.849  2022-09-10
14   2001-03  MG  Etanol Hidratado   m3   35.484  2022-09-10
15   2001-04  MG  Etanol Hidratado   m3   31.924  2022-09-10
16   2001-05  MG  Etanol Hidratado   m3   37.098  2022-09-10
17   2001-06  MG  Etanol Hidratado   m3   36.284  2022-09-10
18   2001-07  MG  Etanol Hidratado   m3   31.751  2022-09-10
19   2001-08  MG  Etanol Hidratado   m3   33.723  2022-09-10
20   2001-09  MG  Etanol Hidratado   m3   28.158  2022-09-10
21   2001-10  MG  Etanol Hidratado   m3   28.825  2022-09-10
22   2001-11  MG  Etanol Hidratado   m3   28.851  2022-09-10
23   2001-12  MG  Etanol Hidratado   m3   35.348  2022-09-10
24   2002-01  MG  Etanol Hidratado   m3   27.588  2022-09-10
25   2002-02  MG  Etanol Hidratado   m3   24.446  2022-09-10
26   2002-03  MG  Etanol Hidratado   m3   22.087  2022-09-10
27   2002-04  MG  Etanol Hidratado   m3   28.238  2022-09-10
28   2002-05  MG  Etanol Hidratado   m3   36.090  2022-09-10
29   2002-06  MG  Etanol Hidratado   m3   35.295  2022-09-10
30   2002-07  MG  Etanol Hidratado   m3   40.687  2022-09-10
31   2002-08  MG  Etanol Hidratado   m3   36.348  2022-09-10
32   2002-09  MG  Etanol Hidratado   m3   35.679  2022-09-10
33   2002-10  MG  Etanol Hidratado   m3   47.216  2022-09-10
34   2002-11  MG  Etanol Hidratado   m3   35.272  2022-09-10
35   2002-12  MG  Etanol Hidratado   m3   39.580  2022-09-10
36   2003-01  MG  Etanol Hidratado   m3   39.539  2022-09-10
37   2003-02  MG  Etanol Hidratado   m3   31.462  2022-09-10
38   2003-03  MG  Etanol Hidratado   m3   28.772  2022-09-10
39   2003-04  MG  Etanol Hidratado   m3   29.365  2022-09-10
40   2003-05  MG  Etanol Hidratado   m3   29.438  2022-09-10
41   2003-06  MG  Etanol Hidratado   m3   26.013  2022-09-10
42   2003-07  MG  Etanol Hidratado   m3   33.266  2022-09-10
43   2003-08  MG  Etanol Hidratado   m3   30.460  2022-09-10
44   2003-09  MG  Etanol Hidratado   m3   28.422  2022-09-10
45   2003-10  MG  Etanol Hidratado   m3   29.904  2022-09-10
46   2003-11  MG  Etanol Hidratado   m3   28.310  2022-09-10
47   2003-12  MG  Etanol Hidratado   m3   39.311  2022-09-10
48   2004-01  MG  Etanol Hidratado   m3   34.891  2022-09-10
49   2004-02  MG  Etanol Hidratado   m3   32.137  2022-09-10
50   2004-03  MG  Etanol Hidratado   m3   34.161  2022-09-10
51   2004-04  MG  Etanol Hidratado   m3   33.503  2022-09-10
52   2004-05  MG  Etanol Hidratado   m3   35.008  2022-09-10
53   2004-06  MG  Etanol Hidratado   m3   32.716  2022-09-10
54   2004-07  MG  Etanol Hidratado   m3   39.088  2022-09-10
55   2004-08  MG  Etanol Hidratado   m3   33.570  2022-09-10
56   2004-09  MG  Etanol Hidratado   m3   36.181  2022-09-10
57   2004-10  MG  Etanol Hidratado   m3   36.532  2022-09-10
58   2004-11  MG  Etanol Hidratado   m3   33.288  2022-09-10
59   2004-12  MG  Etanol Hidratado   m3   39.830  2022-09-10
60   2005-01  MG  Etanol Hidratado   m3   32.096  2022-09-10
61   2005-02  MG  Etanol Hidratado   m3   27.275  2022-09-10
62   2005-03  MG  Etanol Hidratado   m3   29.712  2022-09-10
63   2005-04  MG  Etanol Hidratado   m3   28.446  2022-09-10
64   2005-05  MG  Etanol Hidratado   m3 

In [909]:
dfmg_pandas = dfmg.copy()

##MATO GROSSO DO SUL

In [910]:
# Conector

dfms = pd.read_csv('/content/mato_grosso_do_sul.csv',sep=';')

In [911]:
# Backup
dfms_backup = dfms.copy()

In [912]:
# Configurando a quantidade de linhas máximas mostradas em tela

pd.set_option('display.max_columns',1000)
pd.set_option('display.max_rows',1000)

In [913]:
# Visualização da Tabela

dfms

Mês   2000   2001   2002   2003   2004   2005   2006    2007  \
0     Janeiro  5.872  5.249  4.954  6.194  5.448  5.375  6.343   7.129   
1   Fevereiro  5.657  4.529  4.300  4.420  5.079  4.700  4.736   6.032   
2       Março  5.716  5.086  4.814  4.565  5.483  5.896  4.455   6.984   
3       Abril  6.205  4.898  5.258  4.842  5.854  5.323  3.839   6.620   
4        Maio  5.678  5.002  5.014  4.812  5.901  5.657  4.296   6.748   
5       Junho  4.982  5.015  4.434  4.537  5.179  5.531  4.820   7.087   
6       Julho  6.391  4.821  5.927  5.646  7.874  5.679  5.568   8.660   
7      Agosto  5.603  4.698  5.528  4.645  5.650  5.960  5.605   9.308   
8    Setembro  5.956  4.562  5.442  4.921  6.343  6.664  5.907  10.004   
9     Outubro  5.596  4.813  6.750  5.623  6.434  6.253  5.904  12.322   
10   Novembro  5.365  4.621  5.586  4.670  5.312  6.359  5.961  11.303   
11   Dezembro  6.079  5.212  6.148  6.309  6.656  8.189  7.859  13.276   

      2008    2009    2010    2011    2012    2013    2014    2015    2016  \
0   11.731  16.983  10.586  14.497   6.638   9.158  14.524  18.372  13.041   
1   11.076  14.945   7.189  11.347   6.141  10.257  13.419  19.073  10.754   
2   11.812  17.234   9.769   8.354   6.879  10.271  12.396  19.721   9.473   
3   12.104  18.638  12.963   5.558   6.421   9.483  11.873  21.255   9.538   
4   12.701  16.879  13.089   8.825   6.381   8.835  10.244  18.599   9.684   
5   11.797  16.433  14.244   8.885   6.270   9.395   9.873  17.944   8.827   
6   14.450  18.400  16.993   8.259   8.291  10.578  11.010  19.092   9.582   
7   14.245  17.266  15.948   8.252   7.950  10.734  11.046  20.084   9.617   
8   15.116  18.297  16.960   7.891   7.928  10.794  12.149  21.461   9.410   
9   16.631  19.164  16.379   8.137   8.864  12.475  14.469  22.653   9.298   
10  15.171  15.426  15.671   7.716   8.577  12.217  15.115  15.845   7.604   
11  19.446  18.312  18.481   8.073  10.419  16.671  19.961  17.597   9.367   

      2017    2018    2019    2020    2021    2022  
0    6.901   9.393  10.623   9.332  16.682  10.431  
1    6.124   7.652   8.503   9.663  19.384  11.082  
2    6.943   7.805   8.552   9.276  20.400  16.102  
3    6.545   7.496   9.226   7.839  17.143  15.102  
4    6.408   8.886   8.919   8.309  15.447  12.294  
5    5.825  11.378   7.937   9.117  12.769  12.996  
6    6.517  12.386   8.419  10.709  12.571     NaN  
7    7.461  12.886   7.876  12.247  12.880     NaN  
8    8.886  13.689   8.400  16.126  13.248     NaN  
9    8.437  15.430   9.461  18.243  13.417     NaN  
10   9.561  13.064   9.185  15.814  11.767     NaN  
11  11.455  13.316  11.481  19.051  13.155     NaN

In [914]:
# Replace do Mês para numérico

dfms["Mês"].replace("Janeiro", "01", inplace=True)
dfms["Mês"].replace("Fevereiro", "02", inplace=True)
dfms["Mês"].replace("Março", "03", inplace=True)
dfms["Mês"].replace("Abril", "04", inplace=True)
dfms["Mês"].replace("Maio", "05", inplace=True)
dfms["Mês"].replace("Junho", "06", inplace=True)
dfms["Mês"].replace("Julho", "07", inplace=True)
dfms["Mês"].replace("Agosto", "08", inplace=True)
dfms["Mês"].replace("Setembro", "09", inplace=True)
dfms["Mês"].replace("Outubro", "10", inplace=True)
dfms["Mês"].replace("Novembro", "11", inplace=True)
dfms["Mês"].replace("Dezembro", "12", inplace=True)

In [915]:
# Criação das colunas uf, produto, unid, criado_em
dfms['uf']='MS'
dfms['produto']='Etanol Hidratado'
dfms['unid']='m3'
dfms['criado_em'] ='2022-09-10'

In [916]:
# Despivotar a tabela em ano e volume 
dfms.reset_index(inplace=True)

In [917]:
dfms=dfms.melt(id_vars = ['Mês', 'uf', 'produto', 'unid', 'criado_em'], value_vars = ['2000', '2001', '2002', '2003', '2004', '2005', '2006', '2007', '2008', '2009', '2010', '2011', '2012', '2013', '2014', '2015', '2016', '2017', '2018', '2019', '2020', '2021', '2022'], var_name='ano', value_name='venda')

In [918]:
# Visão geral da tabela

dfms

Mês  uf           produto unid   criado_em   ano   venda
0    01  MS  Etanol Hidratado   m3  2022-09-10  2000   5.872
1    02  MS  Etanol Hidratado   m3  2022-09-10  2000   5.657
2    03  MS  Etanol Hidratado   m3  2022-09-10  2000   5.716
3    04  MS  Etanol Hidratado   m3  2022-09-10  2000   6.205
4    05  MS  Etanol Hidratado   m3  2022-09-10  2000   5.678
5    06  MS  Etanol Hidratado   m3  2022-09-10  2000   4.982
6    07  MS  Etanol Hidratado   m3  2022-09-10  2000   6.391
7    08  MS  Etanol Hidratado   m3  2022-09-10  2000   5.603
8    09  MS  Etanol Hidratado   m3  2022-09-10  2000   5.956
9    10  MS  Etanol Hidratado   m3  2022-09-10  2000   5.596
10   11  MS  Etanol Hidratado   m3  2022-09-10  2000   5.365
11   12  MS  Etanol Hidratado   m3  2022-09-10  2000   6.079
12   01  MS  Etanol Hidratado   m3  2022-09-10  2001   5.249
13   02  MS  Etanol Hidratado   m3  2022-09-10  2001   4.529
14   03  MS  Etanol Hidratado   m3  2022-09-10  2001   5.086
15   04  MS  Etanol Hidratado   m3  2022-09-10  2001   4.898
16   05  MS  Etanol Hidratado   m3  2022-09-10  2001   5.002
17   06  MS  Etanol Hidratado   m3  2022-09-10  2001   5.015
18   07  MS  Etanol Hidratado   m3  2022-09-10  2001   4.821
19   08  MS  Etanol Hidratado   m3  2022-09-10  2001   4.698
20   09  MS  Etanol Hidratado   m3  2022-09-10  2001   4.562
21   10  MS  Etanol Hidratado   m3  2022-09-10  2001   4.813
22   11  MS  Etanol Hidratado   m3  2022-09-10  2001   4.621
23   12  MS  Etanol Hidratado   m3  2022-09-10  2001   5.212
24   01  MS  Etanol Hidratado   m3  2022-09-10  2002   4.954
25   02  MS  Etanol Hidratado   m3  2022-09-10  2002   4.300
26   03  MS  Etanol Hidratado   m3  2022-09-10  2002   4.814
27   04  MS  Etanol Hidratado   m3  2022-09-10  2002   5.258
28   05  MS  Etanol Hidratado   m3  2022-09-10  2002   5.014
29   06  MS  Etanol Hidratado   m3  2022-09-10  2002   4.434
30   07  MS  Etanol Hidratado   m3  2022-09-10  2002   5.927
31   08  MS  Etanol Hidratado   m3  2022-09-10  2002   5.528
32   09  MS  Etanol Hidratado   m3  2022-09-10  2002   5.442
33   10  MS  Etanol Hidratado   m3  2022-09-10  2002   6.750
34   11  MS  Etanol Hidratado   m3  2022-09-10  2002   5.586
35   12  MS  Etanol Hidratado   m3  2022-09-10  2002   6.148
36   01  MS  Etanol Hidratado   m3  2022-09-10  2003   6.194
37   02  MS  Etanol Hidratado   m3  2022-09-10  2003   4.420
38   03  MS  Etanol Hidratado   m3  2022-09-10  2003   4.565
39   04  MS  Etanol Hidratado   m3  2022-09-10  2003   4.842
40   05  MS  Etanol Hidratado   m3  2022-09-10  2003   4.812
41   06  MS  Etanol Hidratado   m3  2022-09-10  2003   4.537
42   07  MS  Etanol Hidratado   m3  2022-09-10  2003   5.646
43   08  MS  Etanol Hidratado   m3  2022-09-10  2003   4.645
44   09  MS  Etanol Hidratado   m3  2022-09-10  2003   4.921
45   10  MS  Etanol Hidratado   m3  2022-09-10  2003   5.623
46   11  MS  Etanol Hidratado   m3  2022-09-10  2003   4.670
47   12  MS  Etanol Hidratado   m3  2022-09-10  2003   6.309
48   01  MS  Etanol Hidratado   m3  2022-09-10  2004   5.448
49   02  MS  Etanol Hidratado   m3  2022-09-10  2004   5.079
50   03  MS  Etanol Hidratado   m3  2022-09-10  2004   5.483
51   04  MS  Etanol Hidratado   m3  2022-09-10  2004   5.854
52   05  MS  Etanol Hidratado   m3  2022-09-10  2004   5.901
53   06  MS  Etanol Hidratado   m3  2022-09-10  2004   5.179
54   07  MS  Etanol Hidratado   m3  2022-09-10  2004   7.874
55   08  MS  Etanol Hidratado   m3  2022-09-10  2004   5.650
56   09  MS  Etanol Hidratado   m3  2022-09-10  2004   6.343
57   10  MS  Etanol Hidratado   m3  2022-09-10  2004   6.434
58   11  MS  Etanol Hidratado   m3  2022-09-10  2004   5.312
59   12  MS  Etanol Hidratado   m3  2022-09-10  2004   6.656
60   01  MS  Etanol Hidratado   m3  2022-09-10  2005   5.375
61   02  MS  Etanol Hidratado   m3  2022-09-10  2005   4.700
62   03  MS  Etanol Hidratado   m3  2022-09-10  2005   5.896
63   04  MS  Etanol Hidratado   m3  2022-09-10  2005   5.323
64   05  MS  Etanol Hidratado   m3  202

In [919]:
# Concatenando as colunas ano e Mês
dfms['ano_mês'] = dfms[['ano', 'Mês']].agg('-'.join, axis=1)

In [920]:
# Eliminando as colunas Mês e ano

dfms.drop(["Mês"], axis=1, inplace=True)
dfms.drop(["ano"], axis=1, inplace=True)

In [921]:
# Organização da ordem das colunas

dfms=dfms[['ano_mês', 'uf', 'produto', 'unid', 'venda', 'criado_em']]

In [922]:
# Tratamento de possíveis inconsistências

dfms.isna().sum()

ano_mês      0
uf           0
produto      0
unid         0
venda        6
criado_em    0
dtype: int64

In [923]:
# Levantamento das inconsistências

dfms.replace(['Na', 'nA', 'na','NA', 'NaN', 'NAN', 'nan', '', ' '],pd.NA,inplace=True)


In [924]:
# Visão geral da tabela

dfms

ano_mês  uf           produto unid   venda   criado_em
0    2000-01  MS  Etanol Hidratado   m3   5.872  2022-09-10
1    2000-02  MS  Etanol Hidratado   m3   5.657  2022-09-10
2    2000-03  MS  Etanol Hidratado   m3   5.716  2022-09-10
3    2000-04  MS  Etanol Hidratado   m3   6.205  2022-09-10
4    2000-05  MS  Etanol Hidratado   m3   5.678  2022-09-10
5    2000-06  MS  Etanol Hidratado   m3   4.982  2022-09-10
6    2000-07  MS  Etanol Hidratado   m3   6.391  2022-09-10
7    2000-08  MS  Etanol Hidratado   m3   5.603  2022-09-10
8    2000-09  MS  Etanol Hidratado   m3   5.956  2022-09-10
9    2000-10  MS  Etanol Hidratado   m3   5.596  2022-09-10
10   2000-11  MS  Etanol Hidratado   m3   5.365  2022-09-10
11   2000-12  MS  Etanol Hidratado   m3   6.079  2022-09-10
12   2001-01  MS  Etanol Hidratado   m3   5.249  2022-09-10
13   2001-02  MS  Etanol Hidratado   m3   4.529  2022-09-10
14   2001-03  MS  Etanol Hidratado   m3   5.086  2022-09-10
15   2001-04  MS  Etanol Hidratado   m3   4.898  2022-09-10
16   2001-05  MS  Etanol Hidratado   m3   5.002  2022-09-10
17   2001-06  MS  Etanol Hidratado   m3   5.015  2022-09-10
18   2001-07  MS  Etanol Hidratado   m3   4.821  2022-09-10
19   2001-08  MS  Etanol Hidratado   m3   4.698  2022-09-10
20   2001-09  MS  Etanol Hidratado   m3   4.562  2022-09-10
21   2001-10  MS  Etanol Hidratado   m3   4.813  2022-09-10
22   2001-11  MS  Etanol Hidratado   m3   4.621  2022-09-10
23   2001-12  MS  Etanol Hidratado   m3   5.212  2022-09-10
24   2002-01  MS  Etanol Hidratado   m3   4.954  2022-09-10
25   2002-02  MS  Etanol Hidratado   m3   4.300  2022-09-10
26   2002-03  MS  Etanol Hidratado   m3   4.814  2022-09-10
27   2002-04  MS  Etanol Hidratado   m3   5.258  2022-09-10
28   2002-05  MS  Etanol Hidratado   m3   5.014  2022-09-10
29   2002-06  MS  Etanol Hidratado   m3   4.434  2022-09-10
30   2002-07  MS  Etanol Hidratado   m3   5.927  2022-09-10
31   2002-08  MS  Etanol Hidratado   m3   5.528  2022-09-10
32   2002-09  MS  Etanol Hidratado   m3   5.442  2022-09-10
33   2002-10  MS  Etanol Hidratado   m3   6.750  2022-09-10
34   2002-11  MS  Etanol Hidratado   m3   5.586  2022-09-10
35   2002-12  MS  Etanol Hidratado   m3   6.148  2022-09-10
36   2003-01  MS  Etanol Hidratado   m3   6.194  2022-09-10
37   2003-02  MS  Etanol Hidratado   m3   4.420  2022-09-10
38   2003-03  MS  Etanol Hidratado   m3   4.565  2022-09-10
39   2003-04  MS  Etanol Hidratado   m3   4.842  2022-09-10
40   2003-05  MS  Etanol Hidratado   m3   4.812  2022-09-10
41   2003-06  MS  Etanol Hidratado   m3   4.537  2022-09-10
42   2003-07  MS  Etanol Hidratado   m3   5.646  2022-09-10
43   2003-08  MS  Etanol Hidratado   m3   4.645  2022-09-10
44   2003-09  MS  Etanol Hidratado   m3   4.921  2022-09-10
45   2003-10  MS  Etanol Hidratado   m3   5.623  2022-09-10
46   2003-11  MS  Etanol Hidratado   m3   4.670  2022-09-10
47   2003-12  MS  Etanol Hidratado   m3   6.309  2022-09-10
48   2004-01  MS  Etanol Hidratado   m3   5.448  2022-09-10
49   2004-02  MS  Etanol Hidratado   m3   5.079  2022-09-10
50   2004-03  MS  Etanol Hidratado   m3   5.483  2022-09-10
51   2004-04  MS  Etanol Hidratado   m3   5.854  2022-09-10
52   2004-05  MS  Etanol Hidratado   m3   5.901  2022-09-10
53   2004-06  MS  Etanol Hidratado   m3   5.179  2022-09-10
54   2004-07  MS  Etanol Hidratado   m3   7.874  2022-09-10
55   2004-08  MS  Etanol Hidratado   m3   5.650  2022-09-10
56   2004-09  MS  Etanol Hidratado   m3   6.343  2022-09-10
57   2004-10  MS  Etanol Hidratado   m3   6.434  2022-09-10
58   2004-11  MS  Etanol Hidratado   m3   5.312  2022-09-10
59   2004-12  MS  Etanol Hidratado   m3   6.656  2022-09-10
60   2005-01  MS  Etanol Hidratado   m3   5.375  2022-09-10
61   2005-02  MS  Etanol Hidratado   m3   4.700  2022-09-10
62   2005-03  MS  Etanol Hidratado   m3   5.896  2022-09-10
63   2005-04  MS  Etanol Hidratado   m3   5.323  2022-09-10
64   2005-05  MS  Etanol Hidratado   m3   5.657  2022-09-10
65   2005-06  MS  Etanol Hidratado   m3   5.5

In [925]:
# Verificando os tipos

dfms.dtypes

ano_mês       object
uf            object
produto       object
unid          object
venda        float64
criado_em     object
dtype: object

In [926]:
# Validação

schema = pa.DataFrameSchema(
    columns = {
        'ano_mês': pa.Column(pa.String, nullable=True),
        'uf': pa.Column(pa.String, nullable = True),
        'produto': pa.Column(pa.String, nullable = True),
        'unid': pa.Column(pa.String, nullable = True),
        'venda': pa.Column(pa.Float, nullable = True),
        'criado_em': pa.Column(pa.String, nullable = True),
                
    }
)
schema.validate(dfms)

ano_mês  uf           produto unid   venda   criado_em
0    2000-01  MS  Etanol Hidratado   m3   5.872  2022-09-10
1    2000-02  MS  Etanol Hidratado   m3   5.657  2022-09-10
2    2000-03  MS  Etanol Hidratado   m3   5.716  2022-09-10
3    2000-04  MS  Etanol Hidratado   m3   6.205  2022-09-10
4    2000-05  MS  Etanol Hidratado   m3   5.678  2022-09-10
5    2000-06  MS  Etanol Hidratado   m3   4.982  2022-09-10
6    2000-07  MS  Etanol Hidratado   m3   6.391  2022-09-10
7    2000-08  MS  Etanol Hidratado   m3   5.603  2022-09-10
8    2000-09  MS  Etanol Hidratado   m3   5.956  2022-09-10
9    2000-10  MS  Etanol Hidratado   m3   5.596  2022-09-10
10   2000-11  MS  Etanol Hidratado   m3   5.365  2022-09-10
11   2000-12  MS  Etanol Hidratado   m3   6.079  2022-09-10
12   2001-01  MS  Etanol Hidratado   m3   5.249  2022-09-10
13   2001-02  MS  Etanol Hidratado   m3   4.529  2022-09-10
14   2001-03  MS  Etanol Hidratado   m3   5.086  2022-09-10
15   2001-04  MS  Etanol Hidratado   m3   4.898  2022-09-10
16   2001-05  MS  Etanol Hidratado   m3   5.002  2022-09-10
17   2001-06  MS  Etanol Hidratado   m3   5.015  2022-09-10
18   2001-07  MS  Etanol Hidratado   m3   4.821  2022-09-10
19   2001-08  MS  Etanol Hidratado   m3   4.698  2022-09-10
20   2001-09  MS  Etanol Hidratado   m3   4.562  2022-09-10
21   2001-10  MS  Etanol Hidratado   m3   4.813  2022-09-10
22   2001-11  MS  Etanol Hidratado   m3   4.621  2022-09-10
23   2001-12  MS  Etanol Hidratado   m3   5.212  2022-09-10
24   2002-01  MS  Etanol Hidratado   m3   4.954  2022-09-10
25   2002-02  MS  Etanol Hidratado   m3   4.300  2022-09-10
26   2002-03  MS  Etanol Hidratado   m3   4.814  2022-09-10
27   2002-04  MS  Etanol Hidratado   m3   5.258  2022-09-10
28   2002-05  MS  Etanol Hidratado   m3   5.014  2022-09-10
29   2002-06  MS  Etanol Hidratado   m3   4.434  2022-09-10
30   2002-07  MS  Etanol Hidratado   m3   5.927  2022-09-10
31   2002-08  MS  Etanol Hidratado   m3   5.528  2022-09-10
32   2002-09  MS  Etanol Hidratado   m3   5.442  2022-09-10
33   2002-10  MS  Etanol Hidratado   m3   6.750  2022-09-10
34   2002-11  MS  Etanol Hidratado   m3   5.586  2022-09-10
35   2002-12  MS  Etanol Hidratado   m3   6.148  2022-09-10
36   2003-01  MS  Etanol Hidratado   m3   6.194  2022-09-10
37   2003-02  MS  Etanol Hidratado   m3   4.420  2022-09-10
38   2003-03  MS  Etanol Hidratado   m3   4.565  2022-09-10
39   2003-04  MS  Etanol Hidratado   m3   4.842  2022-09-10
40   2003-05  MS  Etanol Hidratado   m3   4.812  2022-09-10
41   2003-06  MS  Etanol Hidratado   m3   4.537  2022-09-10
42   2003-07  MS  Etanol Hidratado   m3   5.646  2022-09-10
43   2003-08  MS  Etanol Hidratado   m3   4.645  2022-09-10
44   2003-09  MS  Etanol Hidratado   m3   4.921  2022-09-10
45   2003-10  MS  Etanol Hidratado   m3   5.623  2022-09-10
46   2003-11  MS  Etanol Hidratado   m3   4.670  2022-09-10
47   2003-12  MS  Etanol Hidratado   m3   6.309  2022-09-10
48   2004-01  MS  Etanol Hidratado   m3   5.448  2022-09-10
49   2004-02  MS  Etanol Hidratado   m3   5.079  2022-09-10
50   2004-03  MS  Etanol Hidratado   m3   5.483  2022-09-10
51   2004-04  MS  Etanol Hidratado   m3   5.854  2022-09-10
52   2004-05  MS  Etanol Hidratado   m3   5.901  2022-09-10
53   2004-06  MS  Etanol Hidratado   m3   5.179  2022-09-10
54   2004-07  MS  Etanol Hidratado   m3   7.874  2022-09-10
55   2004-08  MS  Etanol Hidratado   m3   5.650  2022-09-10
56   2004-09  MS  Etanol Hidratado   m3   6.343  2022-09-10
57   2004-10  MS  Etanol Hidratado   m3   6.434  2022-09-10
58   2004-11  MS  Etanol Hidratado   m3   5.312  2022-09-10
59   2004-12  MS  Etanol Hidratado   m3   6.656  2022-09-10
60   2005-01  MS  Etanol Hidratado   m3   5.375  2022-09-10
61   2005-02  MS  Etanol Hidratado   m3   4.700  2022-09-10
62   2005-03  MS  Etanol Hidratado   m3   5.896  2022-09-10
63   2005-04  MS  Etanol Hidratado   m3   5.323  2022-09-10
64   2005-05  MS  Etanol Hidratado   m3   5.657  2022-09-10
65   2005-06  MS  Etanol Hidratado   m3   5.5

In [927]:
dfms_pandas = dfms.copy()

##MATO GROSO

In [928]:
# Conector

dfmt = pd.read_csv('/content/mato_grosso.csv',sep=';')

In [929]:
# Backup
dfmt_backup = dfmt.copy()

In [930]:
# Configurando a quantidade de linhas máximas mostradas em tela

pd.set_option('display.max_columns',1000)
pd.set_option('display.max_rows',1000)

In [931]:
# Visualização da Tabela

dfmt

Mês   2000   2001    2002   2003   2004   2005   2006    2007  \
0     Janeiro  5.863  3.152   4.038  4.808  4.839  4.287  7.671   7.095   
1   Fevereiro  6.017  2.599   3.618  3.929  4.071  4.162  6.479   6.499   
2       Março  6.458  3.825   3.728  3.562  4.709  5.280  5.526   7.199   
3       Abril  5.429  2.780   3.582  3.395  4.417  5.294  4.500   7.008   
4        Maio  7.824  2.650   3.526  2.210  5.158  5.342  4.551   5.605   
5       Junho  4.748  3.156   2.927  2.029  4.380  5.550  4.697   6.508   
6       Julho  3.741  5.782   4.032  3.232  6.155  5.657  5.587   7.378   
7      Agosto  6.040  5.965   5.185  2.713  4.924  6.206  6.480   8.552   
8    Setembro  4.618  3.226  36.469  2.591  5.046  5.908  5.980  10.387   
9     Outubro  3.380  3.084   5.052  2.978  5.181  6.237  6.153  14.083   
10   Novembro  3.488  3.834   5.726  3.528  4.771  7.782  6.961  12.855   
11   Dezembro  3.566  4.936   6.320  5.047  5.600  9.271  7.880  14.034   

      2008    2009    2010    2011    2012    2013    2014    2015    2016  \
0   19.292  30.463  32.800  27.062  19.537  37.374  43.707  50.005  49.115   
1   17.736  27.492  28.477  26.058  20.160  35.616  37.685  46.576  48.345   
2   18.625  30.329  32.360  27.165  22.117  38.234  37.736  53.768  50.044   
3   19.094  32.420  32.368  17.806  25.305  38.985  38.769  56.416  49.350   
4   19.147  29.174  34.217  25.432  29.742  39.507  39.894  53.813  47.454   
5   20.824  30.835  34.174  31.839  31.050  38.310  35.174  56.383  48.069   
6   24.328  35.643  36.091  32.021  33.982  41.225  39.711  60.042  49.697   
7   24.325  32.817  36.669  32.335  35.305  40.504  44.255  59.531  52.177   
8   26.899  34.587  37.149  30.251  34.564  40.706  46.650  63.415  50.517   
9   26.772  37.743  38.644  33.204  40.957  45.434  49.431  69.810  52.510   
10  26.896  33.835  36.203  29.916  38.000  44.352  45.820  62.996  49.124   
11  32.912  38.603  37.160  25.556  41.140  48.278  55.214  66.544  53.547   

      2017    2018    2019    2020    2021    2022  
0   46.260  68.765  76.132  84.074  76.140  53.395  
1   42.907  61.716  73.307  78.627  73.975  57.730  
2   51.416  69.030  78.348  69.805  74.083  70.347  
3   48.314  58.153  81.008  62.245  74.758  66.700  
4   52.222  58.393  81.568  66.183  73.359  66.093  
5   51.890  65.387  74.438  66.952  71.954  65.149  
6   54.827  70.766  85.641  69.601  72.478     NaN  
7   59.672  77.318  84.283  75.510  71.517     NaN  
8   61.753  73.833  84.649  81.678  69.591     NaN  
9   64.422  81.049  92.384  90.453  68.372     NaN  
10  66.532  79.259  89.404  80.699  55.149     NaN  
11  74.228  76.954  98.907  89.786  65.149     NaN

In [932]:
# Replace do Mês para numérico

dfmt["Mês"].replace("Janeiro", "01", inplace=True)
dfmt["Mês"].replace("Fevereiro", "02", inplace=True)
dfmt["Mês"].replace("Março", "03", inplace=True)
dfmt["Mês"].replace("Abril", "04", inplace=True)
dfmt["Mês"].replace("Maio", "05", inplace=True)
dfmt["Mês"].replace("Junho", "06", inplace=True)
dfmt["Mês"].replace("Julho", "07", inplace=True)
dfmt["Mês"].replace("Agosto", "08", inplace=True)
dfmt["Mês"].replace("Setembro", "09", inplace=True)
dfmt["Mês"].replace("Outubro", "10", inplace=True)
dfmt["Mês"].replace("Novembro", "11", inplace=True)
dfmt["Mês"].replace("Dezembro", "12", inplace=True)

In [933]:
# Criação das colunas uf, produto, unid, criado_em
dfmt['uf']='MT'
dfmt['produto']='Etanol Hidratado'
dfmt['unid']='m3'
dfmt['criado_em'] ='2022-09-10'

In [934]:
# Despivotar a tabela em ano e volume 
dfmt.reset_index(inplace=True)

In [935]:
dfmt=dfmt.melt(id_vars = ['Mês', 'uf', 'produto', 'unid', 'criado_em'], value_vars = ['2000', '2001', '2002', '2003', '2004', '2005', '2006', '2007', '2008', '2009', '2010', '2011', '2012', '2013', '2014', '2015', '2016', '2017', '2018', '2019', '2020', '2021', '2022'], var_name='ano', value_name='venda')

In [936]:
# Visão geral da tabela

dfmt

Mês  uf           produto unid   criado_em   ano   venda
0    01  MT  Etanol Hidratado   m3  2022-09-10  2000   5.863
1    02  MT  Etanol Hidratado   m3  2022-09-10  2000   6.017
2    03  MT  Etanol Hidratado   m3  2022-09-10  2000   6.458
3    04  MT  Etanol Hidratado   m3  2022-09-10  2000   5.429
4    05  MT  Etanol Hidratado   m3  2022-09-10  2000   7.824
5    06  MT  Etanol Hidratado   m3  2022-09-10  2000   4.748
6    07  MT  Etanol Hidratado   m3  2022-09-10  2000   3.741
7    08  MT  Etanol Hidratado   m3  2022-09-10  2000   6.040
8    09  MT  Etanol Hidratado   m3  2022-09-10  2000   4.618
9    10  MT  Etanol Hidratado   m3  2022-09-10  2000   3.380
10   11  MT  Etanol Hidratado   m3  2022-09-10  2000   3.488
11   12  MT  Etanol Hidratado   m3  2022-09-10  2000   3.566
12   01  MT  Etanol Hidratado   m3  2022-09-10  2001   3.152
13   02  MT  Etanol Hidratado   m3  2022-09-10  2001   2.599
14   03  MT  Etanol Hidratado   m3  2022-09-10  2001   3.825
15   04  MT  Etanol Hidratado   m3  2022-09-10  2001   2.780
16   05  MT  Etanol Hidratado   m3  2022-09-10  2001   2.650
17   06  MT  Etanol Hidratado   m3  2022-09-10  2001   3.156
18   07  MT  Etanol Hidratado   m3  2022-09-10  2001   5.782
19   08  MT  Etanol Hidratado   m3  2022-09-10  2001   5.965
20   09  MT  Etanol Hidratado   m3  2022-09-10  2001   3.226
21   10  MT  Etanol Hidratado   m3  2022-09-10  2001   3.084
22   11  MT  Etanol Hidratado   m3  2022-09-10  2001   3.834
23   12  MT  Etanol Hidratado   m3  2022-09-10  2001   4.936
24   01  MT  Etanol Hidratado   m3  2022-09-10  2002   4.038
25   02  MT  Etanol Hidratado   m3  2022-09-10  2002   3.618
26   03  MT  Etanol Hidratado   m3  2022-09-10  2002   3.728
27   04  MT  Etanol Hidratado   m3  2022-09-10  2002   3.582
28   05  MT  Etanol Hidratado   m3  2022-09-10  2002   3.526
29   06  MT  Etanol Hidratado   m3  2022-09-10  2002   2.927
30   07  MT  Etanol Hidratado   m3  2022-09-10  2002   4.032
31   08  MT  Etanol Hidratado   m3  2022-09-10  2002   5.185
32   09  MT  Etanol Hidratado   m3  2022-09-10  2002  36.469
33   10  MT  Etanol Hidratado   m3  2022-09-10  2002   5.052
34   11  MT  Etanol Hidratado   m3  2022-09-10  2002   5.726
35   12  MT  Etanol Hidratado   m3  2022-09-10  2002   6.320
36   01  MT  Etanol Hidratado   m3  2022-09-10  2003   4.808
37   02  MT  Etanol Hidratado   m3  2022-09-10  2003   3.929
38   03  MT  Etanol Hidratado   m3  2022-09-10  2003   3.562
39   04  MT  Etanol Hidratado   m3  2022-09-10  2003   3.395
40   05  MT  Etanol Hidratado   m3  2022-09-10  2003   2.210
41   06  MT  Etanol Hidratado   m3  2022-09-10  2003   2.029
42   07  MT  Etanol Hidratado   m3  2022-09-10  2003   3.232
43   08  MT  Etanol Hidratado   m3  2022-09-10  2003   2.713
44   09  MT  Etanol Hidratado   m3  2022-09-10  2003   2.591
45   10  MT  Etanol Hidratado   m3  2022-09-10  2003   2.978
46   11  MT  Etanol Hidratado   m3  2022-09-10  2003   3.528
47   12  MT  Etanol Hidratado   m3  2022-09-10  2003   5.047
48   01  MT  Etanol Hidratado   m3  2022-09-10  2004   4.839
49   02  MT  Etanol Hidratado   m3  2022-09-10  2004   4.071
50   03  MT  Etanol Hidratado   m3  2022-09-10  2004   4.709
51   04  MT  Etanol Hidratado   m3  2022-09-10  2004   4.417
52   05  MT  Etanol Hidratado   m3  2022-09-10  2004   5.158
53   06  MT  Etanol Hidratado   m3  2022-09-10  2004   4.380
54   07  MT  Etanol Hidratado   m3  2022-09-10  2004   6.155
55   08  MT  Etanol Hidratado   m3  2022-09-10  2004   4.924
56   09  MT  Etanol Hidratado   m3  2022-09-10  2004   5.046
57   10  MT  Etanol Hidratado   m3  2022-09-10  2004   5.181
58   11  MT  Etanol Hidratado   m3  2022-09-10  2004   4.771
59   12  MT  Etanol Hidratado   m3  2022-09-10  2004   5.600
60   01  MT  Etanol Hidratado   m3  2022-09-10  2005   4.287
61   02  MT  Etanol Hidratado   m3  2022-09-10  2005   4.162
62   03  MT  Etanol Hidratado   m3  2022-09-10  2005   5.280
63   04  MT  Etanol Hidratado   m3  2022-09-10  2005   5.294
64   05  MT  Etanol Hidratado   m3  202

In [937]:
# Concatenando as colunas ano e Mês
dfmt['ano_mês'] = dfmt[['ano', 'Mês']].agg('-'.join, axis=1)

In [938]:
# Eliminando as colunas Mês e ano

dfmt.drop(["Mês"], axis=1, inplace=True)
dfmt.drop(["ano"], axis=1, inplace=True)

In [939]:
# Organização da ordem das colunas

dfmt=dfmt[['ano_mês', 'uf', 'produto', 'unid', 'venda', 'criado_em']]

In [940]:
# Levantamento de possíveis inconsistências

dfmt.isna().sum()

ano_mês      0
uf           0
produto      0
unid         0
venda        6
criado_em    0
dtype: int64

In [941]:
# Tratamento das inconsistências

dfmt.replace(['Na', 'nA', 'na','NA', 'NaN', 'NAN', 'nan', '', ' '],pd.NA,inplace=True)


In [942]:
# Visão geral da tabela

dfmt

ano_mês  uf           produto unid   venda   criado_em
0    2000-01  MT  Etanol Hidratado   m3   5.863  2022-09-10
1    2000-02  MT  Etanol Hidratado   m3   6.017  2022-09-10
2    2000-03  MT  Etanol Hidratado   m3   6.458  2022-09-10
3    2000-04  MT  Etanol Hidratado   m3   5.429  2022-09-10
4    2000-05  MT  Etanol Hidratado   m3   7.824  2022-09-10
5    2000-06  MT  Etanol Hidratado   m3   4.748  2022-09-10
6    2000-07  MT  Etanol Hidratado   m3   3.741  2022-09-10
7    2000-08  MT  Etanol Hidratado   m3   6.040  2022-09-10
8    2000-09  MT  Etanol Hidratado   m3   4.618  2022-09-10
9    2000-10  MT  Etanol Hidratado   m3   3.380  2022-09-10
10   2000-11  MT  Etanol Hidratado   m3   3.488  2022-09-10
11   2000-12  MT  Etanol Hidratado   m3   3.566  2022-09-10
12   2001-01  MT  Etanol Hidratado   m3   3.152  2022-09-10
13   2001-02  MT  Etanol Hidratado   m3   2.599  2022-09-10
14   2001-03  MT  Etanol Hidratado   m3   3.825  2022-09-10
15   2001-04  MT  Etanol Hidratado   m3   2.780  2022-09-10
16   2001-05  MT  Etanol Hidratado   m3   2.650  2022-09-10
17   2001-06  MT  Etanol Hidratado   m3   3.156  2022-09-10
18   2001-07  MT  Etanol Hidratado   m3   5.782  2022-09-10
19   2001-08  MT  Etanol Hidratado   m3   5.965  2022-09-10
20   2001-09  MT  Etanol Hidratado   m3   3.226  2022-09-10
21   2001-10  MT  Etanol Hidratado   m3   3.084  2022-09-10
22   2001-11  MT  Etanol Hidratado   m3   3.834  2022-09-10
23   2001-12  MT  Etanol Hidratado   m3   4.936  2022-09-10
24   2002-01  MT  Etanol Hidratado   m3   4.038  2022-09-10
25   2002-02  MT  Etanol Hidratado   m3   3.618  2022-09-10
26   2002-03  MT  Etanol Hidratado   m3   3.728  2022-09-10
27   2002-04  MT  Etanol Hidratado   m3   3.582  2022-09-10
28   2002-05  MT  Etanol Hidratado   m3   3.526  2022-09-10
29   2002-06  MT  Etanol Hidratado   m3   2.927  2022-09-10
30   2002-07  MT  Etanol Hidratado   m3   4.032  2022-09-10
31   2002-08  MT  Etanol Hidratado   m3   5.185  2022-09-10
32   2002-09  MT  Etanol Hidratado   m3  36.469  2022-09-10
33   2002-10  MT  Etanol Hidratado   m3   5.052  2022-09-10
34   2002-11  MT  Etanol Hidratado   m3   5.726  2022-09-10
35   2002-12  MT  Etanol Hidratado   m3   6.320  2022-09-10
36   2003-01  MT  Etanol Hidratado   m3   4.808  2022-09-10
37   2003-02  MT  Etanol Hidratado   m3   3.929  2022-09-10
38   2003-03  MT  Etanol Hidratado   m3   3.562  2022-09-10
39   2003-04  MT  Etanol Hidratado   m3   3.395  2022-09-10
40   2003-05  MT  Etanol Hidratado   m3   2.210  2022-09-10
41   2003-06  MT  Etanol Hidratado   m3   2.029  2022-09-10
42   2003-07  MT  Etanol Hidratado   m3   3.232  2022-09-10
43   2003-08  MT  Etanol Hidratado   m3   2.713  2022-09-10
44   2003-09  MT  Etanol Hidratado   m3   2.591  2022-09-10
45   2003-10  MT  Etanol Hidratado   m3   2.978  2022-09-10
46   2003-11  MT  Etanol Hidratado   m3   3.528  2022-09-10
47   2003-12  MT  Etanol Hidratado   m3   5.047  2022-09-10
48   2004-01  MT  Etanol Hidratado   m3   4.839  2022-09-10
49   2004-02  MT  Etanol Hidratado   m3   4.071  2022-09-10
50   2004-03  MT  Etanol Hidratado   m3   4.709  2022-09-10
51   2004-04  MT  Etanol Hidratado   m3   4.417  2022-09-10
52   2004-05  MT  Etanol Hidratado   m3   5.158  2022-09-10
53   2004-06  MT  Etanol Hidratado   m3   4.380  2022-09-10
54   2004-07  MT  Etanol Hidratado   m3   6.155  2022-09-10
55   2004-08  MT  Etanol Hidratado   m3   4.924  2022-09-10
56   2004-09  MT  Etanol Hidratado   m3   5.046  2022-09-10
57   2004-10  MT  Etanol Hidratado   m3   5.181  2022-09-10
58   2004-11  MT  Etanol Hidratado   m3   4.771  2022-09-10
59   2004-12  MT  Etanol Hidratado   m3   5.600  2022-09-10
60   2005-01  MT  Etanol Hidratado   m3   4.287  2022-09-10
61   2005-02  MT  Etanol Hidratado   m3   4.162  2022-09-10
62   2005-03  MT  Etanol Hidratado   m3   5.280  2022-09-10
63   2005-04  MT  Etanol Hidratado   m3   5.294  2022-09-10
64   2005-05  MT  Etanol Hidratado   m3   5.342  2022-09-10
65   2005-06  MT  Etanol Hidratado   m3   5.5

In [943]:
# Verificando os tipos

dfmt.dtypes

ano_mês       object
uf            object
produto       object
unid          object
venda        float64
criado_em     object
dtype: object

In [944]:
# Validação

schema = pa.DataFrameSchema(
    columns = {
        'ano_mês': pa.Column(pa.String, nullable=True),
        'uf': pa.Column(pa.String, nullable = True),
        'produto': pa.Column(pa.String, nullable = True),
        'unid': pa.Column(pa.String, nullable = True),
        'venda': pa.Column(pa.Float, nullable = True),
        'criado_em': pa.Column(pa.String, nullable = True),
                
    }
)
schema.validate(dfmt)

ano_mês  uf           produto unid   venda   criado_em
0    2000-01  MT  Etanol Hidratado   m3   5.863  2022-09-10
1    2000-02  MT  Etanol Hidratado   m3   6.017  2022-09-10
2    2000-03  MT  Etanol Hidratado   m3   6.458  2022-09-10
3    2000-04  MT  Etanol Hidratado   m3   5.429  2022-09-10
4    2000-05  MT  Etanol Hidratado   m3   7.824  2022-09-10
5    2000-06  MT  Etanol Hidratado   m3   4.748  2022-09-10
6    2000-07  MT  Etanol Hidratado   m3   3.741  2022-09-10
7    2000-08  MT  Etanol Hidratado   m3   6.040  2022-09-10
8    2000-09  MT  Etanol Hidratado   m3   4.618  2022-09-10
9    2000-10  MT  Etanol Hidratado   m3   3.380  2022-09-10
10   2000-11  MT  Etanol Hidratado   m3   3.488  2022-09-10
11   2000-12  MT  Etanol Hidratado   m3   3.566  2022-09-10
12   2001-01  MT  Etanol Hidratado   m3   3.152  2022-09-10
13   2001-02  MT  Etanol Hidratado   m3   2.599  2022-09-10
14   2001-03  MT  Etanol Hidratado   m3   3.825  2022-09-10
15   2001-04  MT  Etanol Hidratado   m3   2.780  2022-09-10
16   2001-05  MT  Etanol Hidratado   m3   2.650  2022-09-10
17   2001-06  MT  Etanol Hidratado   m3   3.156  2022-09-10
18   2001-07  MT  Etanol Hidratado   m3   5.782  2022-09-10
19   2001-08  MT  Etanol Hidratado   m3   5.965  2022-09-10
20   2001-09  MT  Etanol Hidratado   m3   3.226  2022-09-10
21   2001-10  MT  Etanol Hidratado   m3   3.084  2022-09-10
22   2001-11  MT  Etanol Hidratado   m3   3.834  2022-09-10
23   2001-12  MT  Etanol Hidratado   m3   4.936  2022-09-10
24   2002-01  MT  Etanol Hidratado   m3   4.038  2022-09-10
25   2002-02  MT  Etanol Hidratado   m3   3.618  2022-09-10
26   2002-03  MT  Etanol Hidratado   m3   3.728  2022-09-10
27   2002-04  MT  Etanol Hidratado   m3   3.582  2022-09-10
28   2002-05  MT  Etanol Hidratado   m3   3.526  2022-09-10
29   2002-06  MT  Etanol Hidratado   m3   2.927  2022-09-10
30   2002-07  MT  Etanol Hidratado   m3   4.032  2022-09-10
31   2002-08  MT  Etanol Hidratado   m3   5.185  2022-09-10
32   2002-09  MT  Etanol Hidratado   m3  36.469  2022-09-10
33   2002-10  MT  Etanol Hidratado   m3   5.052  2022-09-10
34   2002-11  MT  Etanol Hidratado   m3   5.726  2022-09-10
35   2002-12  MT  Etanol Hidratado   m3   6.320  2022-09-10
36   2003-01  MT  Etanol Hidratado   m3   4.808  2022-09-10
37   2003-02  MT  Etanol Hidratado   m3   3.929  2022-09-10
38   2003-03  MT  Etanol Hidratado   m3   3.562  2022-09-10
39   2003-04  MT  Etanol Hidratado   m3   3.395  2022-09-10
40   2003-05  MT  Etanol Hidratado   m3   2.210  2022-09-10
41   2003-06  MT  Etanol Hidratado   m3   2.029  2022-09-10
42   2003-07  MT  Etanol Hidratado   m3   3.232  2022-09-10
43   2003-08  MT  Etanol Hidratado   m3   2.713  2022-09-10
44   2003-09  MT  Etanol Hidratado   m3   2.591  2022-09-10
45   2003-10  MT  Etanol Hidratado   m3   2.978  2022-09-10
46   2003-11  MT  Etanol Hidratado   m3   3.528  2022-09-10
47   2003-12  MT  Etanol Hidratado   m3   5.047  2022-09-10
48   2004-01  MT  Etanol Hidratado   m3   4.839  2022-09-10
49   2004-02  MT  Etanol Hidratado   m3   4.071  2022-09-10
50   2004-03  MT  Etanol Hidratado   m3   4.709  2022-09-10
51   2004-04  MT  Etanol Hidratado   m3   4.417  2022-09-10
52   2004-05  MT  Etanol Hidratado   m3   5.158  2022-09-10
53   2004-06  MT  Etanol Hidratado   m3   4.380  2022-09-10
54   2004-07  MT  Etanol Hidratado   m3   6.155  2022-09-10
55   2004-08  MT  Etanol Hidratado   m3   4.924  2022-09-10
56   2004-09  MT  Etanol Hidratado   m3   5.046  2022-09-10
57   2004-10  MT  Etanol Hidratado   m3   5.181  2022-09-10
58   2004-11  MT  Etanol Hidratado   m3   4.771  2022-09-10
59   2004-12  MT  Etanol Hidratado   m3   5.600  2022-09-10
60   2005-01  MT  Etanol Hidratado   m3   4.287  2022-09-10
61   2005-02  MT  Etanol Hidratado   m3   4.162  2022-09-10
62   2005-03  MT  Etanol Hidratado   m3   5.280  2022-09-10
63   2005-04  MT  Etanol Hidratado   m3   5.294  2022-09-10
64   2005-05  MT  Etanol Hidratado   m3   5.342  2022-09-10
65   2005-06  MT  Etanol Hidratado   m3   5.5

In [945]:
dfmt_pandas = dfmt.copy()

##PARÁ

In [946]:
# Conector

dfpa= pd.read_csv('/content/para.csv',sep=';')

In [947]:
# Backup
dfpa_backup = dfpa.copy()

In [948]:
# Configurando a quantidade de linhas máximas mostradas em tela

pd.set_option('display.max_columns',1000)
pd.set_option('display.max_rows',1000)

In [949]:
# Visualização da Tabela

dfpa

Mês   2000     2001     2002     2003     2004     2005     2006  \
0     Janeiro  2.224    1.605  832.000    1.158  782.000  722.000    1.094   
1   Fevereiro  2.431    1.284  576.000  756.000  802.000  664.000  853.000   
2       Março  2.230    1.570  705.000  759.000    1.313  902.000  748.000   
3       Abril  2.804    1.445  718.000  756.000  788.000  715.000  672.000   
4        Maio  2.811    1.605  784.000    1.090  880.000  776.000  846.000   
5       Junho  2.211    1.256  740.000  652.000  627.000  806.000  715.000   
6       Julho  3.350    1.403  925.000  600.000  842.000  905.000  848.000   
7      Agosto  3.156  954.000  843.000  482.000  850.000  799.000  744.000   
8    Setembro  2.705    1.000  893.000  570.000  996.000    1.033  824.000   
9     Outubro  2.457    1.047  867.000  548.000  880.000    1.033  934.000   
10   Novembro  1.716  835.000    1.115  457.000  840.000    1.172  994.000   
11   Dezembro  1.945  812.000  704.000    1.000  914.000    1.282    1.095   

       2007   2008   2009   2010   2011   2012   2013   2014   2015   2016  \
0     1.116  2.104  3.359  2.483  3.397  2.537  2.721  3.162  3.297  3.680   
1   814.000  2.001  3.192  2.393  3.026  2.321  2.577  2.779  3.868  3.561   
2   956.000  2.171  3.423  2.533  2.775  2.513  2.826  2.683  4.342  3.450   
3   968.000  2.118  3.686  3.168  1.879  2.524  2.586  2.616  4.193  3.062   
4     1.028  2.366  3.630  3.463  2.904  2.614  2.457  2.678  3.909  3.559   
5     1.144  2.428  4.034  4.029  3.109  2.409  2.606  2.406  3.920  3.152   
6     1.554  2.836  4.508  4.991  2.772  2.498  2.662  2.701  3.975  3.135   
7     1.747  2.651  4.409  4.972  2.737  2.542  2.847  2.521  4.282  3.013   
8     1.772  3.207  4.697  5.112  2.675  2.440  2.594  2.560  6.651  2.845   
9     2.277  3.184  4.343  4.932  2.722  2.951  3.075  2.814  5.205  2.638   
10    2.096  2.933  3.481  4.514  2.615  2.636  2.759  2.936  4.743  2.249   
11    2.278  3.550  3.430  4.377  2.954  2.731  3.247  3.624  4.582  2.571   

     2017   2018   2019   2020   2021   2022  
0   2.204  3.395  4.834  5.233  4.351  2.846  
1   1.694  2.736  4.181  4.483  4.443  2.795  
2   2.071  3.089  4.560  3.633  5.367  4.180  
3   1.546  3.000  4.674  2.160  4.384  3.789  
4   1.766  3.084  4.960  1.848  3.842  3.568  
5   1.845  4.265  4.683  2.575  3.492  9.829  
6   1.685  4.281  4.812  3.354  3.167    NaN  
7   2.474  4.956  4.715  4.158  3.319    NaN  
8   2.710  5.938  4.669  4.047  2.778    NaN  
9   2.672  6.918  5.157  4.341  3.346    NaN  
10  3.040  6.265  4.983  3.719  3.285    NaN  
11  3.548  5.719  6.150  4.534  3.448    NaN

In [950]:
# Replace do Mês para numérico

dfpa["Mês"].replace("Janeiro", "01", inplace=True)
dfpa["Mês"].replace("Fevereiro", "02", inplace=True)
dfpa["Mês"].replace("Março", "03", inplace=True)
dfpa["Mês"].replace("Abril", "04", inplace=True)
dfpa["Mês"].replace("Maio", "05", inplace=True)
dfpa["Mês"].replace("Junho", "06", inplace=True)
dfpa["Mês"].replace("Julho", "07", inplace=True)
dfpa["Mês"].replace("Agosto", "08", inplace=True)
dfpa["Mês"].replace("Setembro", "09", inplace=True)
dfpa["Mês"].replace("Outubro", "10", inplace=True)
dfpa["Mês"].replace("Novembro", "11", inplace=True)
dfpa["Mês"].replace("Dezembro", "12", inplace=True)

In [951]:
# Criação das colunas uf, produto, unid, criado_em
dfpa['uf']='PA'
dfpa['produto']='Etanol Hidratado'
dfpa['unid']='m3'
dfpa['criado_em'] ='2022-09-10'

In [952]:
# Despivotar a tabela em ano e volume 
dfpa.reset_index(inplace=True)

In [953]:
dfpa=dfpa.melt(id_vars = ['Mês', 'uf', 'produto', 'unid', 'criado_em'], value_vars = ['2000', '2001', '2002', '2003', '2004', '2005', '2006', '2007', '2008', '2009', '2010', '2011', '2012', '2013', '2014', '2015', '2016', '2017', '2018', '2019', '2020', '2021', '2022'], var_name='ano', value_name='venda')

In [954]:
# Visão geral da tabela

dfpa

Mês  uf           produto unid   criado_em   ano    venda
0    01  PA  Etanol Hidratado   m3  2022-09-10  2000    2.224
1    02  PA  Etanol Hidratado   m3  2022-09-10  2000    2.431
2    03  PA  Etanol Hidratado   m3  2022-09-10  2000    2.230
3    04  PA  Etanol Hidratado   m3  2022-09-10  2000    2.804
4    05  PA  Etanol Hidratado   m3  2022-09-10  2000    2.811
5    06  PA  Etanol Hidratado   m3  2022-09-10  2000    2.211
6    07  PA  Etanol Hidratado   m3  2022-09-10  2000    3.350
7    08  PA  Etanol Hidratado   m3  2022-09-10  2000    3.156
8    09  PA  Etanol Hidratado   m3  2022-09-10  2000    2.705
9    10  PA  Etanol Hidratado   m3  2022-09-10  2000    2.457
10   11  PA  Etanol Hidratado   m3  2022-09-10  2000    1.716
11   12  PA  Etanol Hidratado   m3  2022-09-10  2000    1.945
12   01  PA  Etanol Hidratado   m3  2022-09-10  2001    1.605
13   02  PA  Etanol Hidratado   m3  2022-09-10  2001    1.284
14   03  PA  Etanol Hidratado   m3  2022-09-10  2001    1.570
15   04  PA  Etanol Hidratado   m3  2022-09-10  2001    1.445
16   05  PA  Etanol Hidratado   m3  2022-09-10  2001    1.605
17   06  PA  Etanol Hidratado   m3  2022-09-10  2001    1.256
18   07  PA  Etanol Hidratado   m3  2022-09-10  2001    1.403
19   08  PA  Etanol Hidratado   m3  2022-09-10  2001  954.000
20   09  PA  Etanol Hidratado   m3  2022-09-10  2001    1.000
21   10  PA  Etanol Hidratado   m3  2022-09-10  2001    1.047
22   11  PA  Etanol Hidratado   m3  2022-09-10  2001  835.000
23   12  PA  Etanol Hidratado   m3  2022-09-10  2001  812.000
24   01  PA  Etanol Hidratado   m3  2022-09-10  2002  832.000
25   02  PA  Etanol Hidratado   m3  2022-09-10  2002  576.000
26   03  PA  Etanol Hidratado   m3  2022-09-10  2002  705.000
27   04  PA  Etanol Hidratado   m3  2022-09-10  2002  718.000
28   05  PA  Etanol Hidratado   m3  2022-09-10  2002  784.000
29   06  PA  Etanol Hidratado   m3  2022-09-10  2002  740.000
30   07  PA  Etanol Hidratado   m3  2022-09-10  2002  925.000
31   08  PA  Etanol Hidratado   m3  2022-09-10  2002  843.000
32   09  PA  Etanol Hidratado   m3  2022-09-10  2002  893.000
33   10  PA  Etanol Hidratado   m3  2022-09-10  2002  867.000
34   11  PA  Etanol Hidratado   m3  2022-09-10  2002    1.115
35   12  PA  Etanol Hidratado   m3  2022-09-10  2002  704.000
36   01  PA  Etanol Hidratado   m3  2022-09-10  2003    1.158
37   02  PA  Etanol Hidratado   m3  2022-09-10  2003  756.000
38   03  PA  Etanol Hidratado   m3  2022-09-10  2003  759.000
39   04  PA  Etanol Hidratado   m3  2022-09-10  2003  756.000
40   05  PA  Etanol Hidratado   m3  2022-09-10  2003    1.090
41   06  PA  Etanol Hidratado   m3  2022-09-10  2003  652.000
42   07  PA  Etanol Hidratado   m3  2022-09-10  2003  600.000
43   08  PA  Etanol Hidratado   m3  2022-09-10  2003  482.000
44   09  PA  Etanol Hidratado   m3  2022-09-10  2003  570.000
45   10  PA  Etanol Hidratado   m3  2022-09-10  2003  548.000
46   11  PA  Etanol Hidratado   m3  2022-09-10  2003  457.000
47   12  PA  Etanol Hidratado   m3  2022-09-10  2003    1.000
48   01  PA  Etanol Hidratado   m3  2022-09-10  2004  782.000
49   02  PA  Etanol Hidratado   m3  2022-09-10  2004  802.000
50   03  PA  Etanol Hidratado   m3  2022-09-10  2004    1.313
51   04  PA  Etanol Hidratado   m3  2022-09-10  2004  788.000
52   05  PA  Etanol Hidratado   m3  2022-09-10  2004  880.000
53   06  PA  Etanol Hidratado   m3  2022-09-10  2004  627.000
54   07  PA  Etanol Hidratado   m3  2022-09-10  2004  842.000
55   08  PA  Etanol Hidratado   m3  2022-09-10  2004  850.000
56   09  PA  Etanol Hidratado   m3  2022-09-10  2004  996.000
57   10  PA  Etanol Hidratado   m3  2022-09-10  2004  880.000
58   11  PA  Etanol Hidratado   m3  2022-09-10  2004  840.000
59   12  PA  Etanol Hidratado   m3  2022-09-10  2004  914.000
60   01  PA  Etanol Hidratado   m3  2022-09-10  2005  722.000
61   02  PA  Etanol Hidratado   m3  2022-09-10  2005  664.000
62   03  PA  Etanol Hidratado   m3  2022-09-10  2005  902.000
63   04  PA  Etanol Hidratado   m3  

In [955]:
# Concatenando as colunas ano e Mês
dfpa['ano_mês'] = dfpa[['ano', 'Mês']].agg('-'.join, axis=1)

In [956]:
# Eliminando as colunas Mês e ano

dfpa.drop(["Mês"], axis=1, inplace=True)
dfpa.drop(["ano"], axis=1, inplace=True)

In [957]:
# Organização da ordem das colunas

dfpa=dfpa[['ano_mês', 'uf', 'produto', 'unid', 'venda', 'criado_em']]

In [958]:
# Levantamento de possíveis inconsistências

dfpa.isna().sum()

ano_mês      0
uf           0
produto      0
unid         0
venda        6
criado_em    0
dtype: int64

In [959]:
# Tratamento das inconsistências

dfpa.replace(['Na', 'nA', 'na','NA', 'NaN', 'NAN', 'nan', '', ' '],pd.NA,inplace=True)


In [960]:
# Visão geral da tabela

dfpa

ano_mês  uf           produto unid    venda   criado_em
0    2000-01  PA  Etanol Hidratado   m3    2.224  2022-09-10
1    2000-02  PA  Etanol Hidratado   m3    2.431  2022-09-10
2    2000-03  PA  Etanol Hidratado   m3    2.230  2022-09-10
3    2000-04  PA  Etanol Hidratado   m3    2.804  2022-09-10
4    2000-05  PA  Etanol Hidratado   m3    2.811  2022-09-10
5    2000-06  PA  Etanol Hidratado   m3    2.211  2022-09-10
6    2000-07  PA  Etanol Hidratado   m3    3.350  2022-09-10
7    2000-08  PA  Etanol Hidratado   m3    3.156  2022-09-10
8    2000-09  PA  Etanol Hidratado   m3    2.705  2022-09-10
9    2000-10  PA  Etanol Hidratado   m3    2.457  2022-09-10
10   2000-11  PA  Etanol Hidratado   m3    1.716  2022-09-10
11   2000-12  PA  Etanol Hidratado   m3    1.945  2022-09-10
12   2001-01  PA  Etanol Hidratado   m3    1.605  2022-09-10
13   2001-02  PA  Etanol Hidratado   m3    1.284  2022-09-10
14   2001-03  PA  Etanol Hidratado   m3    1.570  2022-09-10
15   2001-04  PA  Etanol Hidratado   m3    1.445  2022-09-10
16   2001-05  PA  Etanol Hidratado   m3    1.605  2022-09-10
17   2001-06  PA  Etanol Hidratado   m3    1.256  2022-09-10
18   2001-07  PA  Etanol Hidratado   m3    1.403  2022-09-10
19   2001-08  PA  Etanol Hidratado   m3  954.000  2022-09-10
20   2001-09  PA  Etanol Hidratado   m3    1.000  2022-09-10
21   2001-10  PA  Etanol Hidratado   m3    1.047  2022-09-10
22   2001-11  PA  Etanol Hidratado   m3  835.000  2022-09-10
23   2001-12  PA  Etanol Hidratado   m3  812.000  2022-09-10
24   2002-01  PA  Etanol Hidratado   m3  832.000  2022-09-10
25   2002-02  PA  Etanol Hidratado   m3  576.000  2022-09-10
26   2002-03  PA  Etanol Hidratado   m3  705.000  2022-09-10
27   2002-04  PA  Etanol Hidratado   m3  718.000  2022-09-10
28   2002-05  PA  Etanol Hidratado   m3  784.000  2022-09-10
29   2002-06  PA  Etanol Hidratado   m3  740.000  2022-09-10
30   2002-07  PA  Etanol Hidratado   m3  925.000  2022-09-10
31   2002-08  PA  Etanol Hidratado   m3  843.000  2022-09-10
32   2002-09  PA  Etanol Hidratado   m3  893.000  2022-09-10
33   2002-10  PA  Etanol Hidratado   m3  867.000  2022-09-10
34   2002-11  PA  Etanol Hidratado   m3    1.115  2022-09-10
35   2002-12  PA  Etanol Hidratado   m3  704.000  2022-09-10
36   2003-01  PA  Etanol Hidratado   m3    1.158  2022-09-10
37   2003-02  PA  Etanol Hidratado   m3  756.000  2022-09-10
38   2003-03  PA  Etanol Hidratado   m3  759.000  2022-09-10
39   2003-04  PA  Etanol Hidratado   m3  756.000  2022-09-10
40   2003-05  PA  Etanol Hidratado   m3    1.090  2022-09-10
41   2003-06  PA  Etanol Hidratado   m3  652.000  2022-09-10
42   2003-07  PA  Etanol Hidratado   m3  600.000  2022-09-10
43   2003-08  PA  Etanol Hidratado   m3  482.000  2022-09-10
44   2003-09  PA  Etanol Hidratado   m3  570.000  2022-09-10
45   2003-10  PA  Etanol Hidratado   m3  548.000  2022-09-10
46   2003-11  PA  Etanol Hidratado   m3  457.000  2022-09-10
47   2003-12  PA  Etanol Hidratado   m3    1.000  2022-09-10
48   2004-01  PA  Etanol Hidratado   m3  782.000  2022-09-10
49   2004-02  PA  Etanol Hidratado   m3  802.000  2022-09-10
50   2004-03  PA  Etanol Hidratado   m3    1.313  2022-09-10
51   2004-04  PA  Etanol Hidratado   m3  788.000  2022-09-10
52   2004-05  PA  Etanol Hidratado   m3  880.000  2022-09-10
53   2004-06  PA  Etanol Hidratado   m3  627.000  2022-09-10
54   2004-07  PA  Etanol Hidratado   m3  842.000  2022-09-10
55   2004-08  PA  Etanol Hidratado   m3  850.000  2022-09-10
56   2004-09  PA  Etanol Hidratado   m3  996.000  2022-09-10
57   2004-10  PA  Etanol Hidratado   m3  880.000  2022-09-10
58   2004-11  PA  Etanol Hidratado   m3  840.000  2022-09-10
59   2004-12  PA  Etanol Hidratado   m3  914.000  2022-09-10
60   2005-01  PA  Etanol Hidratado   m3  722.000  2022-09-10
61   2005-02  PA  Etanol Hidratado   m3  664.000  2022-09-10
62   2005-03  PA  Etanol Hidratado   m3  902.000  2022-09-10
63   2005-04  PA  Etanol Hidratado   m3  715.000  2022-09-10
64   2005-05  PA  Etanol Hidratado   m3 

In [961]:
# Verificando os tipos

dfpa.dtypes

ano_mês       object
uf            object
produto       object
unid          object
venda        float64
criado_em     object
dtype: object

In [962]:
# Validação

schema = pa.DataFrameSchema(
    columns = {
        'ano_mês': pa.Column(pa.String, nullable=True),
        'uf': pa.Column(pa.String, nullable = True),
        'produto': pa.Column(pa.String, nullable = True),
        'unid': pa.Column(pa.String, nullable = True),
        'venda': pa.Column(pa.Float, nullable = True),
        'criado_em': pa.Column(pa.String, nullable = True),
                
    }
)
schema.validate(dfpa)

ano_mês  uf           produto unid    venda   criado_em
0    2000-01  PA  Etanol Hidratado   m3    2.224  2022-09-10
1    2000-02  PA  Etanol Hidratado   m3    2.431  2022-09-10
2    2000-03  PA  Etanol Hidratado   m3    2.230  2022-09-10
3    2000-04  PA  Etanol Hidratado   m3    2.804  2022-09-10
4    2000-05  PA  Etanol Hidratado   m3    2.811  2022-09-10
5    2000-06  PA  Etanol Hidratado   m3    2.211  2022-09-10
6    2000-07  PA  Etanol Hidratado   m3    3.350  2022-09-10
7    2000-08  PA  Etanol Hidratado   m3    3.156  2022-09-10
8    2000-09  PA  Etanol Hidratado   m3    2.705  2022-09-10
9    2000-10  PA  Etanol Hidratado   m3    2.457  2022-09-10
10   2000-11  PA  Etanol Hidratado   m3    1.716  2022-09-10
11   2000-12  PA  Etanol Hidratado   m3    1.945  2022-09-10
12   2001-01  PA  Etanol Hidratado   m3    1.605  2022-09-10
13   2001-02  PA  Etanol Hidratado   m3    1.284  2022-09-10
14   2001-03  PA  Etanol Hidratado   m3    1.570  2022-09-10
15   2001-04  PA  Etanol Hidratado   m3    1.445  2022-09-10
16   2001-05  PA  Etanol Hidratado   m3    1.605  2022-09-10
17   2001-06  PA  Etanol Hidratado   m3    1.256  2022-09-10
18   2001-07  PA  Etanol Hidratado   m3    1.403  2022-09-10
19   2001-08  PA  Etanol Hidratado   m3  954.000  2022-09-10
20   2001-09  PA  Etanol Hidratado   m3    1.000  2022-09-10
21   2001-10  PA  Etanol Hidratado   m3    1.047  2022-09-10
22   2001-11  PA  Etanol Hidratado   m3  835.000  2022-09-10
23   2001-12  PA  Etanol Hidratado   m3  812.000  2022-09-10
24   2002-01  PA  Etanol Hidratado   m3  832.000  2022-09-10
25   2002-02  PA  Etanol Hidratado   m3  576.000  2022-09-10
26   2002-03  PA  Etanol Hidratado   m3  705.000  2022-09-10
27   2002-04  PA  Etanol Hidratado   m3  718.000  2022-09-10
28   2002-05  PA  Etanol Hidratado   m3  784.000  2022-09-10
29   2002-06  PA  Etanol Hidratado   m3  740.000  2022-09-10
30   2002-07  PA  Etanol Hidratado   m3  925.000  2022-09-10
31   2002-08  PA  Etanol Hidratado   m3  843.000  2022-09-10
32   2002-09  PA  Etanol Hidratado   m3  893.000  2022-09-10
33   2002-10  PA  Etanol Hidratado   m3  867.000  2022-09-10
34   2002-11  PA  Etanol Hidratado   m3    1.115  2022-09-10
35   2002-12  PA  Etanol Hidratado   m3  704.000  2022-09-10
36   2003-01  PA  Etanol Hidratado   m3    1.158  2022-09-10
37   2003-02  PA  Etanol Hidratado   m3  756.000  2022-09-10
38   2003-03  PA  Etanol Hidratado   m3  759.000  2022-09-10
39   2003-04  PA  Etanol Hidratado   m3  756.000  2022-09-10
40   2003-05  PA  Etanol Hidratado   m3    1.090  2022-09-10
41   2003-06  PA  Etanol Hidratado   m3  652.000  2022-09-10
42   2003-07  PA  Etanol Hidratado   m3  600.000  2022-09-10
43   2003-08  PA  Etanol Hidratado   m3  482.000  2022-09-10
44   2003-09  PA  Etanol Hidratado   m3  570.000  2022-09-10
45   2003-10  PA  Etanol Hidratado   m3  548.000  2022-09-10
46   2003-11  PA  Etanol Hidratado   m3  457.000  2022-09-10
47   2003-12  PA  Etanol Hidratado   m3    1.000  2022-09-10
48   2004-01  PA  Etanol Hidratado   m3  782.000  2022-09-10
49   2004-02  PA  Etanol Hidratado   m3  802.000  2022-09-10
50   2004-03  PA  Etanol Hidratado   m3    1.313  2022-09-10
51   2004-04  PA  Etanol Hidratado   m3  788.000  2022-09-10
52   2004-05  PA  Etanol Hidratado   m3  880.000  2022-09-10
53   2004-06  PA  Etanol Hidratado   m3  627.000  2022-09-10
54   2004-07  PA  Etanol Hidratado   m3  842.000  2022-09-10
55   2004-08  PA  Etanol Hidratado   m3  850.000  2022-09-10
56   2004-09  PA  Etanol Hidratado   m3  996.000  2022-09-10
57   2004-10  PA  Etanol Hidratado   m3  880.000  2022-09-10
58   2004-11  PA  Etanol Hidratado   m3  840.000  2022-09-10
59   2004-12  PA  Etanol Hidratado   m3  914.000  2022-09-10
60   2005-01  PA  Etanol Hidratado   m3  722.000  2022-09-10
61   2005-02  PA  Etanol Hidratado   m3  664.000  2022-09-10
62   2005-03  PA  Etanol Hidratado   m3  902.000  2022-09-10
63   2005-04  PA  Etanol Hidratado   m3  715.000  2022-09-10
64   2005-05  PA  Etanol Hidratado   m3 

In [963]:
dfpa_pandas = dfpa.copy()

##PARAÍBA

In [964]:
# Conector

dfpb = pd.read_csv('/content/paraiba.csv',sep=';')

In [965]:
# Backup

dfpb_backup = dfpb.copy()

In [966]:
# Configurando a quantidade de linhas máximas mostradas em tela

pd.set_option('display.max_columns',1000)
pd.set_option('display.max_rows',1000)

In [967]:
# Visualização da Tabela

dfpb

Mês   2000   2001   2002   2003   2004   2005   2006   2007   2008  \
0     Janeiro  4.163  2.435  1.720  2.538  2.536  2.400  3.465  5.241  7.496   
1   Fevereiro  3.490  1.696  1.737  2.421  2.050  2.202  2.866  4.797  7.091   
2       Março  3.562  1.993  1.723  2.444  2.535  2.816  3.424  5.575  7.656   
3       Abril  3.360  2.086  1.653  2.652  2.686  2.611  2.623  4.705  7.784   
4        Maio  3.611  2.166  1.955  2.737  2.922  2.579  2.878  4.565  8.300   
5       Junho  2.875  2.072  1.843  2.444  2.596  2.835  2.710  4.765  8.532   
6       Julho  3.567  2.049  2.078  2.372  2.929  2.786  2.446  4.751  7.689   
7      Agosto  3.096  2.018  2.200  2.561  2.839  2.985  2.904  4.951  6.366   
8    Setembro  2.679  1.846  1.893  2.406  2.906  3.326  2.788  4.850  6.629   
9     Outubro  2.381  1.762  2.254  2.477  2.821  2.784  3.025  5.862  7.040   
10   Novembro  2.382  1.555  1.617  2.331  2.542  2.982  3.417  6.579  6.540   
11   Dezembro  2.712  1.950  1.952  3.063  2.691  3.723  4.051  6.947  8.538   

      2009   2010   2011   2012   2013   2014    2015    2016   2017    2018  \
0    8.583  8.510  8.241  3.958  4.313  6.495   8.069  11.809  6.443  11.103   
1    7.665  5.792  7.583  3.708  4.672  5.319  11.102   8.198  5.909  10.431   
2    8.449  6.036  6.819  3.994  4.212  5.436  13.419   7.034  6.419   9.704   
3    8.820  6.445  4.176  3.408  4.904  5.596  12.683   6.191  5.556   7.761   
4    8.364  6.626  4.122  3.524  4.287  5.412  11.783   6.385  5.911  10.559   
5    9.771  6.832  4.470  3.968  4.132  5.290  11.224   6.807  5.123  11.186   
6   10.440  8.116  3.589  3.214  4.249  5.152  10.633   6.333  4.573   9.761   
7    9.717  7.679  3.728  3.175  4.327  5.087   9.810   6.649  6.254  10.329   
8   10.385  7.279  3.554  3.235  4.052  5.601   9.725   6.278  6.582  14.431   
9   10.440  7.047  3.355  4.260  4.682  5.796  11.421   6.237  6.578  22.456   
10   9.166  7.350  3.845  3.990  4.375  6.637  10.138   5.934  7.743  23.385   
11  11.178  8.848  4.537  4.283  6.051  8.108  11.562   7.190  9.907  24.079   

      2019    2020    2021    2022  
0   20.973  21.104  17.712  10.508  
1   17.507  16.788  20.842  10.369  
2   15.505  12.065  18.055  15.499  
3   14.900   5.777   9.604  14.236  
4   13.149   4.823   8.717  12.163  
5   11.287   6.536   6.971  10.920  
6   11.418   9.341   5.832     NaN  
7   10.410  11.496   6.040     NaN  
8   10.817  13.134   6.016     NaN  
9   13.243  14.421  10.323     NaN  
10  15.532  14.497  11.472     NaN  
11  22.220  16.249  15.794     NaN

In [968]:
# Replace do Mês para numérico

dfpb["Mês"].replace("Janeiro", "01", inplace=True)
dfpb["Mês"].replace("Fevereiro", "02", inplace=True)
dfpb["Mês"].replace("Março", "03", inplace=True)
dfpb["Mês"].replace("Abril", "04", inplace=True)
dfpb["Mês"].replace("Maio", "05", inplace=True)
dfpb["Mês"].replace("Junho", "06", inplace=True)
dfpb["Mês"].replace("Julho", "07", inplace=True)
dfpb["Mês"].replace("Agosto", "08", inplace=True)
dfpb["Mês"].replace("Setembro", "09", inplace=True)
dfpb["Mês"].replace("Outubro", "10", inplace=True)
dfpb["Mês"].replace("Novembro", "11", inplace=True)
dfpb["Mês"].replace("Dezembro", "12", inplace=True)

In [969]:
# Criação das colunas uf, produto, unid, criado_em
dfpb['uf']='PB'
dfpb['produto']='Etanol Hidratado'
dfpb['unid']='m3'
dfpb['criado_em'] ='2022-09-10'

In [970]:
# Despivotar a tabela em ano e volume 
dfpb.reset_index(inplace=True)

In [971]:
dfpb=dfpb.melt(id_vars = ['Mês', 'uf', 'produto', 'unid', 'criado_em'], value_vars = ['2000', '2001', '2002', '2003', '2004', '2005', '2006', '2007', '2008', '2009', '2010', '2011', '2012', '2013', '2014', '2015', '2016', '2017', '2018', '2019', '2020', '2021', '2022'], var_name='ano', value_name='venda')

In [972]:
# Visão geral da tabela

dfpb

Mês  uf           produto unid   criado_em   ano   venda
0    01  PB  Etanol Hidratado   m3  2022-09-10  2000   4.163
1    02  PB  Etanol Hidratado   m3  2022-09-10  2000   3.490
2    03  PB  Etanol Hidratado   m3  2022-09-10  2000   3.562
3    04  PB  Etanol Hidratado   m3  2022-09-10  2000   3.360
4    05  PB  Etanol Hidratado   m3  2022-09-10  2000   3.611
5    06  PB  Etanol Hidratado   m3  2022-09-10  2000   2.875
6    07  PB  Etanol Hidratado   m3  2022-09-10  2000   3.567
7    08  PB  Etanol Hidratado   m3  2022-09-10  2000   3.096
8    09  PB  Etanol Hidratado   m3  2022-09-10  2000   2.679
9    10  PB  Etanol Hidratado   m3  2022-09-10  2000   2.381
10   11  PB  Etanol Hidratado   m3  2022-09-10  2000   2.382
11   12  PB  Etanol Hidratado   m3  2022-09-10  2000   2.712
12   01  PB  Etanol Hidratado   m3  2022-09-10  2001   2.435
13   02  PB  Etanol Hidratado   m3  2022-09-10  2001   1.696
14   03  PB  Etanol Hidratado   m3  2022-09-10  2001   1.993
15   04  PB  Etanol Hidratado   m3  2022-09-10  2001   2.086
16   05  PB  Etanol Hidratado   m3  2022-09-10  2001   2.166
17   06  PB  Etanol Hidratado   m3  2022-09-10  2001   2.072
18   07  PB  Etanol Hidratado   m3  2022-09-10  2001   2.049
19   08  PB  Etanol Hidratado   m3  2022-09-10  2001   2.018
20   09  PB  Etanol Hidratado   m3  2022-09-10  2001   1.846
21   10  PB  Etanol Hidratado   m3  2022-09-10  2001   1.762
22   11  PB  Etanol Hidratado   m3  2022-09-10  2001   1.555
23   12  PB  Etanol Hidratado   m3  2022-09-10  2001   1.950
24   01  PB  Etanol Hidratado   m3  2022-09-10  2002   1.720
25   02  PB  Etanol Hidratado   m3  2022-09-10  2002   1.737
26   03  PB  Etanol Hidratado   m3  2022-09-10  2002   1.723
27   04  PB  Etanol Hidratado   m3  2022-09-10  2002   1.653
28   05  PB  Etanol Hidratado   m3  2022-09-10  2002   1.955
29   06  PB  Etanol Hidratado   m3  2022-09-10  2002   1.843
30   07  PB  Etanol Hidratado   m3  2022-09-10  2002   2.078
31   08  PB  Etanol Hidratado   m3  2022-09-10  2002   2.200
32   09  PB  Etanol Hidratado   m3  2022-09-10  2002   1.893
33   10  PB  Etanol Hidratado   m3  2022-09-10  2002   2.254
34   11  PB  Etanol Hidratado   m3  2022-09-10  2002   1.617
35   12  PB  Etanol Hidratado   m3  2022-09-10  2002   1.952
36   01  PB  Etanol Hidratado   m3  2022-09-10  2003   2.538
37   02  PB  Etanol Hidratado   m3  2022-09-10  2003   2.421
38   03  PB  Etanol Hidratado   m3  2022-09-10  2003   2.444
39   04  PB  Etanol Hidratado   m3  2022-09-10  2003   2.652
40   05  PB  Etanol Hidratado   m3  2022-09-10  2003   2.737
41   06  PB  Etanol Hidratado   m3  2022-09-10  2003   2.444
42   07  PB  Etanol Hidratado   m3  2022-09-10  2003   2.372
43   08  PB  Etanol Hidratado   m3  2022-09-10  2003   2.561
44   09  PB  Etanol Hidratado   m3  2022-09-10  2003   2.406
45   10  PB  Etanol Hidratado   m3  2022-09-10  2003   2.477
46   11  PB  Etanol Hidratado   m3  2022-09-10  2003   2.331
47   12  PB  Etanol Hidratado   m3  2022-09-10  2003   3.063
48   01  PB  Etanol Hidratado   m3  2022-09-10  2004   2.536
49   02  PB  Etanol Hidratado   m3  2022-09-10  2004   2.050
50   03  PB  Etanol Hidratado   m3  2022-09-10  2004   2.535
51   04  PB  Etanol Hidratado   m3  2022-09-10  2004   2.686
52   05  PB  Etanol Hidratado   m3  2022-09-10  2004   2.922
53   06  PB  Etanol Hidratado   m3  2022-09-10  2004   2.596
54   07  PB  Etanol Hidratado   m3  2022-09-10  2004   2.929
55   08  PB  Etanol Hidratado   m3  2022-09-10  2004   2.839
56   09  PB  Etanol Hidratado   m3  2022-09-10  2004   2.906
57   10  PB  Etanol Hidratado   m3  2022-09-10  2004   2.821
58   11  PB  Etanol Hidratado   m3  2022-09-10  2004   2.542
59   12  PB  Etanol Hidratado   m3  2022-09-10  2004   2.691
60   01  PB  Etanol Hidratado   m3  2022-09-10  2005   2.400
61   02  PB  Etanol Hidratado   m3  2022-09-10  2005   2.202
62   03  PB  Etanol Hidratado   m3  2022-09-10  2005   2.816
63   04  PB  Etanol Hidratado   m3  2022-09-10  2005   2.611
64   05  PB  Etanol Hidratado   m3  202

In [973]:
# Concatenando as colunas ano e Mês
dfpb['ano_mês'] = dfpb[['ano', 'Mês']].agg('-'.join, axis=1)

In [974]:
# Eliminando as colunas Mês e ano

dfpb.drop(["Mês"], axis=1, inplace=True)
dfpb.drop(["ano"], axis=1, inplace=True)

In [975]:
# Organização da ordem das colunas

dfpb=dfpb[['ano_mês', 'uf', 'produto', 'unid', 'venda', 'criado_em']]

In [976]:
# Levantamento de possíveis inconsistências

dfpb.isna().sum()

ano_mês      0
uf           0
produto      0
unid         0
venda        6
criado_em    0
dtype: int64

In [977]:
# Tratamento das inconsistências

dfpb.replace(['Na', 'nA', 'na','NA', 'NaN', 'NAN', 'nan', '', ' '],pd.NA,inplace=True)


In [978]:
# Visão geral da tabela

dfpb

ano_mês  uf           produto unid   venda   criado_em
0    2000-01  PB  Etanol Hidratado   m3   4.163  2022-09-10
1    2000-02  PB  Etanol Hidratado   m3   3.490  2022-09-10
2    2000-03  PB  Etanol Hidratado   m3   3.562  2022-09-10
3    2000-04  PB  Etanol Hidratado   m3   3.360  2022-09-10
4    2000-05  PB  Etanol Hidratado   m3   3.611  2022-09-10
5    2000-06  PB  Etanol Hidratado   m3   2.875  2022-09-10
6    2000-07  PB  Etanol Hidratado   m3   3.567  2022-09-10
7    2000-08  PB  Etanol Hidratado   m3   3.096  2022-09-10
8    2000-09  PB  Etanol Hidratado   m3   2.679  2022-09-10
9    2000-10  PB  Etanol Hidratado   m3   2.381  2022-09-10
10   2000-11  PB  Etanol Hidratado   m3   2.382  2022-09-10
11   2000-12  PB  Etanol Hidratado   m3   2.712  2022-09-10
12   2001-01  PB  Etanol Hidratado   m3   2.435  2022-09-10
13   2001-02  PB  Etanol Hidratado   m3   1.696  2022-09-10
14   2001-03  PB  Etanol Hidratado   m3   1.993  2022-09-10
15   2001-04  PB  Etanol Hidratado   m3   2.086  2022-09-10
16   2001-05  PB  Etanol Hidratado   m3   2.166  2022-09-10
17   2001-06  PB  Etanol Hidratado   m3   2.072  2022-09-10
18   2001-07  PB  Etanol Hidratado   m3   2.049  2022-09-10
19   2001-08  PB  Etanol Hidratado   m3   2.018  2022-09-10
20   2001-09  PB  Etanol Hidratado   m3   1.846  2022-09-10
21   2001-10  PB  Etanol Hidratado   m3   1.762  2022-09-10
22   2001-11  PB  Etanol Hidratado   m3   1.555  2022-09-10
23   2001-12  PB  Etanol Hidratado   m3   1.950  2022-09-10
24   2002-01  PB  Etanol Hidratado   m3   1.720  2022-09-10
25   2002-02  PB  Etanol Hidratado   m3   1.737  2022-09-10
26   2002-03  PB  Etanol Hidratado   m3   1.723  2022-09-10
27   2002-04  PB  Etanol Hidratado   m3   1.653  2022-09-10
28   2002-05  PB  Etanol Hidratado   m3   1.955  2022-09-10
29   2002-06  PB  Etanol Hidratado   m3   1.843  2022-09-10
30   2002-07  PB  Etanol Hidratado   m3   2.078  2022-09-10
31   2002-08  PB  Etanol Hidratado   m3   2.200  2022-09-10
32   2002-09  PB  Etanol Hidratado   m3   1.893  2022-09-10
33   2002-10  PB  Etanol Hidratado   m3   2.254  2022-09-10
34   2002-11  PB  Etanol Hidratado   m3   1.617  2022-09-10
35   2002-12  PB  Etanol Hidratado   m3   1.952  2022-09-10
36   2003-01  PB  Etanol Hidratado   m3   2.538  2022-09-10
37   2003-02  PB  Etanol Hidratado   m3   2.421  2022-09-10
38   2003-03  PB  Etanol Hidratado   m3   2.444  2022-09-10
39   2003-04  PB  Etanol Hidratado   m3   2.652  2022-09-10
40   2003-05  PB  Etanol Hidratado   m3   2.737  2022-09-10
41   2003-06  PB  Etanol Hidratado   m3   2.444  2022-09-10
42   2003-07  PB  Etanol Hidratado   m3   2.372  2022-09-10
43   2003-08  PB  Etanol Hidratado   m3   2.561  2022-09-10
44   2003-09  PB  Etanol Hidratado   m3   2.406  2022-09-10
45   2003-10  PB  Etanol Hidratado   m3   2.477  2022-09-10
46   2003-11  PB  Etanol Hidratado   m3   2.331  2022-09-10
47   2003-12  PB  Etanol Hidratado   m3   3.063  2022-09-10
48   2004-01  PB  Etanol Hidratado   m3   2.536  2022-09-10
49   2004-02  PB  Etanol Hidratado   m3   2.050  2022-09-10
50   2004-03  PB  Etanol Hidratado   m3   2.535  2022-09-10
51   2004-04  PB  Etanol Hidratado   m3   2.686  2022-09-10
52   2004-05  PB  Etanol Hidratado   m3   2.922  2022-09-10
53   2004-06  PB  Etanol Hidratado   m3   2.596  2022-09-10
54   2004-07  PB  Etanol Hidratado   m3   2.929  2022-09-10
55   2004-08  PB  Etanol Hidratado   m3   2.839  2022-09-10
56   2004-09  PB  Etanol Hidratado   m3   2.906  2022-09-10
57   2004-10  PB  Etanol Hidratado   m3   2.821  2022-09-10
58   2004-11  PB  Etanol Hidratado   m3   2.542  2022-09-10
59   2004-12  PB  Etanol Hidratado   m3   2.691  2022-09-10
60   2005-01  PB  Etanol Hidratado   m3   2.400  2022-09-10
61   2005-02  PB  Etanol Hidratado   m3   2.202  2022-09-10
62   2005-03  PB  Etanol Hidratado   m3   2.816  2022-09-10
63   2005-04  PB  Etanol Hidratado   m3   2.611  2022-09-10
64   2005-05  PB  Etanol Hidratado   m3   2.579  2022-09-10
65   2005-06  PB  Etanol Hidratado   m3   2.8

In [979]:
# Verificando os tipos

dfpb.dtypes

ano_mês       object
uf            object
produto       object
unid          object
venda        float64
criado_em     object
dtype: object

In [980]:
# Validação

schema = pa.DataFrameSchema(
    columns = {
        'ano_mês': pa.Column(pa.String, nullable=True),
        'uf': pa.Column(pa.String, nullable = True),
        'produto': pa.Column(pa.String, nullable = True),
        'unid': pa.Column(pa.String, nullable = True),
        'venda': pa.Column(pa.Float, nullable = True),
        'criado_em': pa.Column(pa.String, nullable = True),
                
    }
)
schema.validate(dfpb)

ano_mês  uf           produto unid   venda   criado_em
0    2000-01  PB  Etanol Hidratado   m3   4.163  2022-09-10
1    2000-02  PB  Etanol Hidratado   m3   3.490  2022-09-10
2    2000-03  PB  Etanol Hidratado   m3   3.562  2022-09-10
3    2000-04  PB  Etanol Hidratado   m3   3.360  2022-09-10
4    2000-05  PB  Etanol Hidratado   m3   3.611  2022-09-10
5    2000-06  PB  Etanol Hidratado   m3   2.875  2022-09-10
6    2000-07  PB  Etanol Hidratado   m3   3.567  2022-09-10
7    2000-08  PB  Etanol Hidratado   m3   3.096  2022-09-10
8    2000-09  PB  Etanol Hidratado   m3   2.679  2022-09-10
9    2000-10  PB  Etanol Hidratado   m3   2.381  2022-09-10
10   2000-11  PB  Etanol Hidratado   m3   2.382  2022-09-10
11   2000-12  PB  Etanol Hidratado   m3   2.712  2022-09-10
12   2001-01  PB  Etanol Hidratado   m3   2.435  2022-09-10
13   2001-02  PB  Etanol Hidratado   m3   1.696  2022-09-10
14   2001-03  PB  Etanol Hidratado   m3   1.993  2022-09-10
15   2001-04  PB  Etanol Hidratado   m3   2.086  2022-09-10
16   2001-05  PB  Etanol Hidratado   m3   2.166  2022-09-10
17   2001-06  PB  Etanol Hidratado   m3   2.072  2022-09-10
18   2001-07  PB  Etanol Hidratado   m3   2.049  2022-09-10
19   2001-08  PB  Etanol Hidratado   m3   2.018  2022-09-10
20   2001-09  PB  Etanol Hidratado   m3   1.846  2022-09-10
21   2001-10  PB  Etanol Hidratado   m3   1.762  2022-09-10
22   2001-11  PB  Etanol Hidratado   m3   1.555  2022-09-10
23   2001-12  PB  Etanol Hidratado   m3   1.950  2022-09-10
24   2002-01  PB  Etanol Hidratado   m3   1.720  2022-09-10
25   2002-02  PB  Etanol Hidratado   m3   1.737  2022-09-10
26   2002-03  PB  Etanol Hidratado   m3   1.723  2022-09-10
27   2002-04  PB  Etanol Hidratado   m3   1.653  2022-09-10
28   2002-05  PB  Etanol Hidratado   m3   1.955  2022-09-10
29   2002-06  PB  Etanol Hidratado   m3   1.843  2022-09-10
30   2002-07  PB  Etanol Hidratado   m3   2.078  2022-09-10
31   2002-08  PB  Etanol Hidratado   m3   2.200  2022-09-10
32   2002-09  PB  Etanol Hidratado   m3   1.893  2022-09-10
33   2002-10  PB  Etanol Hidratado   m3   2.254  2022-09-10
34   2002-11  PB  Etanol Hidratado   m3   1.617  2022-09-10
35   2002-12  PB  Etanol Hidratado   m3   1.952  2022-09-10
36   2003-01  PB  Etanol Hidratado   m3   2.538  2022-09-10
37   2003-02  PB  Etanol Hidratado   m3   2.421  2022-09-10
38   2003-03  PB  Etanol Hidratado   m3   2.444  2022-09-10
39   2003-04  PB  Etanol Hidratado   m3   2.652  2022-09-10
40   2003-05  PB  Etanol Hidratado   m3   2.737  2022-09-10
41   2003-06  PB  Etanol Hidratado   m3   2.444  2022-09-10
42   2003-07  PB  Etanol Hidratado   m3   2.372  2022-09-10
43   2003-08  PB  Etanol Hidratado   m3   2.561  2022-09-10
44   2003-09  PB  Etanol Hidratado   m3   2.406  2022-09-10
45   2003-10  PB  Etanol Hidratado   m3   2.477  2022-09-10
46   2003-11  PB  Etanol Hidratado   m3   2.331  2022-09-10
47   2003-12  PB  Etanol Hidratado   m3   3.063  2022-09-10
48   2004-01  PB  Etanol Hidratado   m3   2.536  2022-09-10
49   2004-02  PB  Etanol Hidratado   m3   2.050  2022-09-10
50   2004-03  PB  Etanol Hidratado   m3   2.535  2022-09-10
51   2004-04  PB  Etanol Hidratado   m3   2.686  2022-09-10
52   2004-05  PB  Etanol Hidratado   m3   2.922  2022-09-10
53   2004-06  PB  Etanol Hidratado   m3   2.596  2022-09-10
54   2004-07  PB  Etanol Hidratado   m3   2.929  2022-09-10
55   2004-08  PB  Etanol Hidratado   m3   2.839  2022-09-10
56   2004-09  PB  Etanol Hidratado   m3   2.906  2022-09-10
57   2004-10  PB  Etanol Hidratado   m3   2.821  2022-09-10
58   2004-11  PB  Etanol Hidratado   m3   2.542  2022-09-10
59   2004-12  PB  Etanol Hidratado   m3   2.691  2022-09-10
60   2005-01  PB  Etanol Hidratado   m3   2.400  2022-09-10
61   2005-02  PB  Etanol Hidratado   m3   2.202  2022-09-10
62   2005-03  PB  Etanol Hidratado   m3   2.816  2022-09-10
63   2005-04  PB  Etanol Hidratado   m3   2.611  2022-09-10
64   2005-05  PB  Etanol Hidratado   m3   2.579  2022-09-10
65   2005-06  PB  Etanol Hidratado   m3   2.8

In [981]:
dfpb_pandas = dfpb.copy()

##PERNAMBUCO

In [982]:
# Conector

dfpe = pd.read_csv('/content/pernambuco.csv',sep=';')

In [983]:
# Backup
dfpe_backup = dfpe.copy()

In [984]:
# Configurando a quantidade de linhas máximas mostradas em tela

pd.set_option('display.max_columns',1000)
pd.set_option('display.max_rows',1000)

In [985]:
# Visualização da Tabela

dfpe

Mês    2000   2001   2002   2003   2004    2005    2006    2007  \
0     Janeiro   9.657  5.783  3.689  5.252  5.251   4.462   9.502  10.799   
1   Fevereiro   8.995  5.258  3.081  4.492  5.996   5.336   8.946   9.598   
2       Março   9.602  5.746  3.572  3.677  6.279   6.643   9.798  11.267   
3       Abril  10.197  5.088  4.091  3.391  6.242   6.601   7.670  11.148   
4        Maio  10.766  5.105  5.353  3.494  5.783   6.494   8.834  12.568   
5       Junho   8.168  5.037  4.565  3.337  6.493   7.570   8.338  13.331   
6       Julho   9.612  4.527  4.437  3.524  7.321   8.444   8.207  14.039   
7      Agosto   8.753  4.351  4.609  2.833  6.727   9.573   8.283  15.387   
8    Setembro   6.346  3.930  4.687  3.071  5.245   9.783   8.802  14.711   
9     Outubro   6.131  4.092  4.846  3.274  5.260   8.335   9.159  15.481   
10   Novembro   5.277  4.166  3.859  3.540  3.904   8.903   9.410  15.733   
11   Dezembro   6.201  4.558  4.351  3.420  4.719  11.388  10.557  19.245   

      2008    2009    2010    2011    2012    2013    2014    2015    2016  \
0   21.323  27.152  28.930  26.249  12.535  14.689  14.785  13.284  22.368   
1   20.201  22.611  17.543  24.075  12.796  14.175  12.591  21.396  16.855   
2   23.167  26.913  21.260  22.539  14.074  14.055  12.353  21.912  16.981   
3   23.486  26.660  23.824  13.271  14.908  14.554  13.088  19.544  15.829   
4   26.985  29.120  26.089  13.939  14.459  12.351  12.043  22.146  18.109   
5   25.250  33.085  28.338  15.302  12.659  10.299  11.355  25.875  19.047   
6   24.466  34.045  28.500  10.841  11.984  11.070  11.577  24.728  16.986   
7   19.888  32.685  29.162  11.665  13.111  11.597  11.406  24.314  15.569   
8   21.122  33.997  29.379  10.053  12.712  11.395  11.688  25.190  14.497   
9   22.632  32.454  27.253  10.481  14.325  13.191  11.555  30.529  15.751   
10  23.668  28.925  25.607  11.496  14.631  11.848  11.537  23.240  15.971   
11  28.516  37.840  29.522  14.904  15.150  14.678  14.219  26.525  17.756   

      2017    2018    2019    2020    2021    2022  
0   14.214  30.320  38.908  35.848  27.342  20.735  
1   12.519  28.590  34.362  29.703  28.806  21.700  
2   14.340  23.658  33.666  21.402  27.401  33.694  
3   15.870  22.907  30.100  10.340  19.197  25.183  
4   15.466  25.737  25.787  10.769  17.745  19.773  
5   13.530  28.277  22.836  15.493  14.492  19.614  
6   12.638  24.753  22.675  19.144  15.902     NaN  
7   21.014  24.632  21.090  21.027  13.535     NaN  
8   18.041  31.254  21.960  22.763  12.788     NaN  
9   16.703  44.059  27.063  24.629  20.090     NaN  
10  24.335  43.564  29.688  22.966  27.598     NaN  
11  29.358  44.553  39.800  29.988  26.001     NaN

In [986]:
# Replace do Mês para numérico

dfpe["Mês"].replace("Janeiro", "01", inplace=True)
dfpe["Mês"].replace("Fevereiro", "02", inplace=True)
dfpe["Mês"].replace("Março", "03", inplace=True)
dfpe["Mês"].replace("Abril", "04", inplace=True)
dfpe["Mês"].replace("Maio", "05", inplace=True)
dfpe["Mês"].replace("Junho", "06", inplace=True)
dfpe["Mês"].replace("Julho", "07", inplace=True)
dfpe["Mês"].replace("Agosto", "08", inplace=True)
dfpe["Mês"].replace("Setembro", "09", inplace=True)
dfpe["Mês"].replace("Outubro", "10", inplace=True)
dfpe["Mês"].replace("Novembro", "11", inplace=True)
dfpe["Mês"].replace("Dezembro", "12", inplace=True)

In [987]:
# Criação das colunas uf, produto, unid, criado_em
dfpe['uf']='PE'
dfpe['produto']='Etanol Hidratado'
dfpe['unid']='m3'
dfpe['criado_em'] ='2022-09-10'

In [988]:
# Despivotar a tabela em ano e volume 
dfpe.reset_index(inplace=True)

In [989]:
dfpe=dfpe.melt(id_vars = ['Mês', 'uf', 'produto', 'unid', 'criado_em'], value_vars = ['2000', '2001', '2002', '2003', '2004', '2005', '2006', '2007', '2008', '2009', '2010', '2011', '2012', '2013', '2014', '2015', '2016', '2017', '2018', '2019', '2020', '2021', '2022'], var_name='ano', value_name='venda')

In [990]:
# Visão geral da tabela

dfpe

Mês  uf           produto unid   criado_em   ano   venda
0    01  PE  Etanol Hidratado   m3  2022-09-10  2000   9.657
1    02  PE  Etanol Hidratado   m3  2022-09-10  2000   8.995
2    03  PE  Etanol Hidratado   m3  2022-09-10  2000   9.602
3    04  PE  Etanol Hidratado   m3  2022-09-10  2000  10.197
4    05  PE  Etanol Hidratado   m3  2022-09-10  2000  10.766
5    06  PE  Etanol Hidratado   m3  2022-09-10  2000   8.168
6    07  PE  Etanol Hidratado   m3  2022-09-10  2000   9.612
7    08  PE  Etanol Hidratado   m3  2022-09-10  2000   8.753
8    09  PE  Etanol Hidratado   m3  2022-09-10  2000   6.346
9    10  PE  Etanol Hidratado   m3  2022-09-10  2000   6.131
10   11  PE  Etanol Hidratado   m3  2022-09-10  2000   5.277
11   12  PE  Etanol Hidratado   m3  2022-09-10  2000   6.201
12   01  PE  Etanol Hidratado   m3  2022-09-10  2001   5.783
13   02  PE  Etanol Hidratado   m3  2022-09-10  2001   5.258
14   03  PE  Etanol Hidratado   m3  2022-09-10  2001   5.746
15   04  PE  Etanol Hidratado   m3  2022-09-10  2001   5.088
16   05  PE  Etanol Hidratado   m3  2022-09-10  2001   5.105
17   06  PE  Etanol Hidratado   m3  2022-09-10  2001   5.037
18   07  PE  Etanol Hidratado   m3  2022-09-10  2001   4.527
19   08  PE  Etanol Hidratado   m3  2022-09-10  2001   4.351
20   09  PE  Etanol Hidratado   m3  2022-09-10  2001   3.930
21   10  PE  Etanol Hidratado   m3  2022-09-10  2001   4.092
22   11  PE  Etanol Hidratado   m3  2022-09-10  2001   4.166
23   12  PE  Etanol Hidratado   m3  2022-09-10  2001   4.558
24   01  PE  Etanol Hidratado   m3  2022-09-10  2002   3.689
25   02  PE  Etanol Hidratado   m3  2022-09-10  2002   3.081
26   03  PE  Etanol Hidratado   m3  2022-09-10  2002   3.572
27   04  PE  Etanol Hidratado   m3  2022-09-10  2002   4.091
28   05  PE  Etanol Hidratado   m3  2022-09-10  2002   5.353
29   06  PE  Etanol Hidratado   m3  2022-09-10  2002   4.565
30   07  PE  Etanol Hidratado   m3  2022-09-10  2002   4.437
31   08  PE  Etanol Hidratado   m3  2022-09-10  2002   4.609
32   09  PE  Etanol Hidratado   m3  2022-09-10  2002   4.687
33   10  PE  Etanol Hidratado   m3  2022-09-10  2002   4.846
34   11  PE  Etanol Hidratado   m3  2022-09-10  2002   3.859
35   12  PE  Etanol Hidratado   m3  2022-09-10  2002   4.351
36   01  PE  Etanol Hidratado   m3  2022-09-10  2003   5.252
37   02  PE  Etanol Hidratado   m3  2022-09-10  2003   4.492
38   03  PE  Etanol Hidratado   m3  2022-09-10  2003   3.677
39   04  PE  Etanol Hidratado   m3  2022-09-10  2003   3.391
40   05  PE  Etanol Hidratado   m3  2022-09-10  2003   3.494
41   06  PE  Etanol Hidratado   m3  2022-09-10  2003   3.337
42   07  PE  Etanol Hidratado   m3  2022-09-10  2003   3.524
43   08  PE  Etanol Hidratado   m3  2022-09-10  2003   2.833
44   09  PE  Etanol Hidratado   m3  2022-09-10  2003   3.071
45   10  PE  Etanol Hidratado   m3  2022-09-10  2003   3.274
46   11  PE  Etanol Hidratado   m3  2022-09-10  2003   3.540
47   12  PE  Etanol Hidratado   m3  2022-09-10  2003   3.420
48   01  PE  Etanol Hidratado   m3  2022-09-10  2004   5.251
49   02  PE  Etanol Hidratado   m3  2022-09-10  2004   5.996
50   03  PE  Etanol Hidratado   m3  2022-09-10  2004   6.279
51   04  PE  Etanol Hidratado   m3  2022-09-10  2004   6.242
52   05  PE  Etanol Hidratado   m3  2022-09-10  2004   5.783
53   06  PE  Etanol Hidratado   m3  2022-09-10  2004   6.493
54   07  PE  Etanol Hidratado   m3  2022-09-10  2004   7.321
55   08  PE  Etanol Hidratado   m3  2022-09-10  2004   6.727
56   09  PE  Etanol Hidratado   m3  2022-09-10  2004   5.245
57   10  PE  Etanol Hidratado   m3  2022-09-10  2004   5.260
58   11  PE  Etanol Hidratado   m3  2022-09-10  2004   3.904
59   12  PE  Etanol Hidratado   m3  2022-09-10  2004   4.719
60   01  PE  Etanol Hidratado   m3  2022-09-10  2005   4.462
61   02  PE  Etanol Hidratado   m3  2022-09-10  2005   5.336
62   03  PE  Etanol Hidratado   m3  2022-09-10  2005   6.643
63   04  PE  Etanol Hidratado   m3  2022-09-10  2005   6.601
64   05  PE  Etanol Hidratado   m3  202

In [991]:
# Concatenando as colunas ano e Mês

dfpe['ano_mês'] = dfpe[['ano', 'Mês']].agg('-'.join, axis=1)

In [992]:
# Eliminando as colunas Mês e ano

dfpe.drop(["Mês"], axis=1, inplace=True)
dfpe.drop(["ano"], axis=1, inplace=True)

In [993]:
# Organização da ordem das colunas

dfpe=dfpe[['ano_mês', 'uf', 'produto', 'unid', 'venda', 'criado_em']]

In [994]:
# Levantamento de possíveis inconsistências

dfpe.isna().sum()

ano_mês      0
uf           0
produto      0
unid         0
venda        6
criado_em    0
dtype: int64

In [995]:
# Tratamento das inconsistências

dfpe.replace(['Na', 'nA', 'na','NA', 'NaN', 'NAN', 'nan', '', ' '],pd.NA,inplace=True)


In [996]:
# Visão geral da tabela

dfpe

ano_mês  uf           produto unid   venda   criado_em
0    2000-01  PE  Etanol Hidratado   m3   9.657  2022-09-10
1    2000-02  PE  Etanol Hidratado   m3   8.995  2022-09-10
2    2000-03  PE  Etanol Hidratado   m3   9.602  2022-09-10
3    2000-04  PE  Etanol Hidratado   m3  10.197  2022-09-10
4    2000-05  PE  Etanol Hidratado   m3  10.766  2022-09-10
5    2000-06  PE  Etanol Hidratado   m3   8.168  2022-09-10
6    2000-07  PE  Etanol Hidratado   m3   9.612  2022-09-10
7    2000-08  PE  Etanol Hidratado   m3   8.753  2022-09-10
8    2000-09  PE  Etanol Hidratado   m3   6.346  2022-09-10
9    2000-10  PE  Etanol Hidratado   m3   6.131  2022-09-10
10   2000-11  PE  Etanol Hidratado   m3   5.277  2022-09-10
11   2000-12  PE  Etanol Hidratado   m3   6.201  2022-09-10
12   2001-01  PE  Etanol Hidratado   m3   5.783  2022-09-10
13   2001-02  PE  Etanol Hidratado   m3   5.258  2022-09-10
14   2001-03  PE  Etanol Hidratado   m3   5.746  2022-09-10
15   2001-04  PE  Etanol Hidratado   m3   5.088  2022-09-10
16   2001-05  PE  Etanol Hidratado   m3   5.105  2022-09-10
17   2001-06  PE  Etanol Hidratado   m3   5.037  2022-09-10
18   2001-07  PE  Etanol Hidratado   m3   4.527  2022-09-10
19   2001-08  PE  Etanol Hidratado   m3   4.351  2022-09-10
20   2001-09  PE  Etanol Hidratado   m3   3.930  2022-09-10
21   2001-10  PE  Etanol Hidratado   m3   4.092  2022-09-10
22   2001-11  PE  Etanol Hidratado   m3   4.166  2022-09-10
23   2001-12  PE  Etanol Hidratado   m3   4.558  2022-09-10
24   2002-01  PE  Etanol Hidratado   m3   3.689  2022-09-10
25   2002-02  PE  Etanol Hidratado   m3   3.081  2022-09-10
26   2002-03  PE  Etanol Hidratado   m3   3.572  2022-09-10
27   2002-04  PE  Etanol Hidratado   m3   4.091  2022-09-10
28   2002-05  PE  Etanol Hidratado   m3   5.353  2022-09-10
29   2002-06  PE  Etanol Hidratado   m3   4.565  2022-09-10
30   2002-07  PE  Etanol Hidratado   m3   4.437  2022-09-10
31   2002-08  PE  Etanol Hidratado   m3   4.609  2022-09-10
32   2002-09  PE  Etanol Hidratado   m3   4.687  2022-09-10
33   2002-10  PE  Etanol Hidratado   m3   4.846  2022-09-10
34   2002-11  PE  Etanol Hidratado   m3   3.859  2022-09-10
35   2002-12  PE  Etanol Hidratado   m3   4.351  2022-09-10
36   2003-01  PE  Etanol Hidratado   m3   5.252  2022-09-10
37   2003-02  PE  Etanol Hidratado   m3   4.492  2022-09-10
38   2003-03  PE  Etanol Hidratado   m3   3.677  2022-09-10
39   2003-04  PE  Etanol Hidratado   m3   3.391  2022-09-10
40   2003-05  PE  Etanol Hidratado   m3   3.494  2022-09-10
41   2003-06  PE  Etanol Hidratado   m3   3.337  2022-09-10
42   2003-07  PE  Etanol Hidratado   m3   3.524  2022-09-10
43   2003-08  PE  Etanol Hidratado   m3   2.833  2022-09-10
44   2003-09  PE  Etanol Hidratado   m3   3.071  2022-09-10
45   2003-10  PE  Etanol Hidratado   m3   3.274  2022-09-10
46   2003-11  PE  Etanol Hidratado   m3   3.540  2022-09-10
47   2003-12  PE  Etanol Hidratado   m3   3.420  2022-09-10
48   2004-01  PE  Etanol Hidratado   m3   5.251  2022-09-10
49   2004-02  PE  Etanol Hidratado   m3   5.996  2022-09-10
50   2004-03  PE  Etanol Hidratado   m3   6.279  2022-09-10
51   2004-04  PE  Etanol Hidratado   m3   6.242  2022-09-10
52   2004-05  PE  Etanol Hidratado   m3   5.783  2022-09-10
53   2004-06  PE  Etanol Hidratado   m3   6.493  2022-09-10
54   2004-07  PE  Etanol Hidratado   m3   7.321  2022-09-10
55   2004-08  PE  Etanol Hidratado   m3   6.727  2022-09-10
56   2004-09  PE  Etanol Hidratado   m3   5.245  2022-09-10
57   2004-10  PE  Etanol Hidratado   m3   5.260  2022-09-10
58   2004-11  PE  Etanol Hidratado   m3   3.904  2022-09-10
59   2004-12  PE  Etanol Hidratado   m3   4.719  2022-09-10
60   2005-01  PE  Etanol Hidratado   m3   4.462  2022-09-10
61   2005-02  PE  Etanol Hidratado   m3   5.336  2022-09-10
62   2005-03  PE  Etanol Hidratado   m3   6.643  2022-09-10
63   2005-04  PE  Etanol Hidratado   m3   6.601  2022-09-10
64   2005-05  PE  Etanol Hidratado   m3   6.494  2022-09-10
65   2005-06  PE  Etanol Hidratado   m3   7.5

In [997]:
# Verificando os tipos

dfpe.dtypes

ano_mês       object
uf            object
produto       object
unid          object
venda        float64
criado_em     object
dtype: object

In [998]:
# Validação

schema = pa.DataFrameSchema(
    columns = {
        'ano_mês': pa.Column(pa.String, nullable=True),
        'uf': pa.Column(pa.String, nullable = True),
        'produto': pa.Column(pa.String, nullable = True),
        'unid': pa.Column(pa.String, nullable = True),
        'venda': pa.Column(pa.Float, nullable = True),
        'criado_em': pa.Column(pa.String, nullable = True),
                
    }
)
schema.validate(dfpe)

ano_mês  uf           produto unid   venda   criado_em
0    2000-01  PE  Etanol Hidratado   m3   9.657  2022-09-10
1    2000-02  PE  Etanol Hidratado   m3   8.995  2022-09-10
2    2000-03  PE  Etanol Hidratado   m3   9.602  2022-09-10
3    2000-04  PE  Etanol Hidratado   m3  10.197  2022-09-10
4    2000-05  PE  Etanol Hidratado   m3  10.766  2022-09-10
5    2000-06  PE  Etanol Hidratado   m3   8.168  2022-09-10
6    2000-07  PE  Etanol Hidratado   m3   9.612  2022-09-10
7    2000-08  PE  Etanol Hidratado   m3   8.753  2022-09-10
8    2000-09  PE  Etanol Hidratado   m3   6.346  2022-09-10
9    2000-10  PE  Etanol Hidratado   m3   6.131  2022-09-10
10   2000-11  PE  Etanol Hidratado   m3   5.277  2022-09-10
11   2000-12  PE  Etanol Hidratado   m3   6.201  2022-09-10
12   2001-01  PE  Etanol Hidratado   m3   5.783  2022-09-10
13   2001-02  PE  Etanol Hidratado   m3   5.258  2022-09-10
14   2001-03  PE  Etanol Hidratado   m3   5.746  2022-09-10
15   2001-04  PE  Etanol Hidratado   m3   5.088  2022-09-10
16   2001-05  PE  Etanol Hidratado   m3   5.105  2022-09-10
17   2001-06  PE  Etanol Hidratado   m3   5.037  2022-09-10
18   2001-07  PE  Etanol Hidratado   m3   4.527  2022-09-10
19   2001-08  PE  Etanol Hidratado   m3   4.351  2022-09-10
20   2001-09  PE  Etanol Hidratado   m3   3.930  2022-09-10
21   2001-10  PE  Etanol Hidratado   m3   4.092  2022-09-10
22   2001-11  PE  Etanol Hidratado   m3   4.166  2022-09-10
23   2001-12  PE  Etanol Hidratado   m3   4.558  2022-09-10
24   2002-01  PE  Etanol Hidratado   m3   3.689  2022-09-10
25   2002-02  PE  Etanol Hidratado   m3   3.081  2022-09-10
26   2002-03  PE  Etanol Hidratado   m3   3.572  2022-09-10
27   2002-04  PE  Etanol Hidratado   m3   4.091  2022-09-10
28   2002-05  PE  Etanol Hidratado   m3   5.353  2022-09-10
29   2002-06  PE  Etanol Hidratado   m3   4.565  2022-09-10
30   2002-07  PE  Etanol Hidratado   m3   4.437  2022-09-10
31   2002-08  PE  Etanol Hidratado   m3   4.609  2022-09-10
32   2002-09  PE  Etanol Hidratado   m3   4.687  2022-09-10
33   2002-10  PE  Etanol Hidratado   m3   4.846  2022-09-10
34   2002-11  PE  Etanol Hidratado   m3   3.859  2022-09-10
35   2002-12  PE  Etanol Hidratado   m3   4.351  2022-09-10
36   2003-01  PE  Etanol Hidratado   m3   5.252  2022-09-10
37   2003-02  PE  Etanol Hidratado   m3   4.492  2022-09-10
38   2003-03  PE  Etanol Hidratado   m3   3.677  2022-09-10
39   2003-04  PE  Etanol Hidratado   m3   3.391  2022-09-10
40   2003-05  PE  Etanol Hidratado   m3   3.494  2022-09-10
41   2003-06  PE  Etanol Hidratado   m3   3.337  2022-09-10
42   2003-07  PE  Etanol Hidratado   m3   3.524  2022-09-10
43   2003-08  PE  Etanol Hidratado   m3   2.833  2022-09-10
44   2003-09  PE  Etanol Hidratado   m3   3.071  2022-09-10
45   2003-10  PE  Etanol Hidratado   m3   3.274  2022-09-10
46   2003-11  PE  Etanol Hidratado   m3   3.540  2022-09-10
47   2003-12  PE  Etanol Hidratado   m3   3.420  2022-09-10
48   2004-01  PE  Etanol Hidratado   m3   5.251  2022-09-10
49   2004-02  PE  Etanol Hidratado   m3   5.996  2022-09-10
50   2004-03  PE  Etanol Hidratado   m3   6.279  2022-09-10
51   2004-04  PE  Etanol Hidratado   m3   6.242  2022-09-10
52   2004-05  PE  Etanol Hidratado   m3   5.783  2022-09-10
53   2004-06  PE  Etanol Hidratado   m3   6.493  2022-09-10
54   2004-07  PE  Etanol Hidratado   m3   7.321  2022-09-10
55   2004-08  PE  Etanol Hidratado   m3   6.727  2022-09-10
56   2004-09  PE  Etanol Hidratado   m3   5.245  2022-09-10
57   2004-10  PE  Etanol Hidratado   m3   5.260  2022-09-10
58   2004-11  PE  Etanol Hidratado   m3   3.904  2022-09-10
59   2004-12  PE  Etanol Hidratado   m3   4.719  2022-09-10
60   2005-01  PE  Etanol Hidratado   m3   4.462  2022-09-10
61   2005-02  PE  Etanol Hidratado   m3   5.336  2022-09-10
62   2005-03  PE  Etanol Hidratado   m3   6.643  2022-09-10
63   2005-04  PE  Etanol Hidratado   m3   6.601  2022-09-10
64   2005-05  PE  Etanol Hidratado   m3   6.494  2022-09-10
65   2005-06  PE  Etanol Hidratado   m3   7.5

In [999]:
dfpe_pandas = dfpe.copy()

##PIAUÍ

In [1000]:
# Conector

dfpi = pd.read_csv('/content/piaui.csv',sep=';')

In [1001]:
# Backup
dfpi_backup = dfpi.copy()

In [1002]:
# Configurando a quantidade de linhas máximas mostradas em tela

pd.set_option('display.max_columns',1000)
pd.set_option('display.max_rows',1000)

In [1003]:
# Visualização da Tabela

dfpi

Mês   2000   2001   2002   2003   2004   2005     2006   2007  \
0     Janeiro  1.993  2.175  1.729  1.633  1.459  1.275    1.419  1.346   
1   Fevereiro  1.925  1.843  1.426  1.194  1.179  1.126    1.133  1.138   
2       Março  1.916  1.866  1.355  1.096  1.318  1.156    1.239  1.341   
3       Abril  1.713  1.668  1.418  1.120  1.317  1.022  928.000  1.274   
4        Maio  2.014  1.718  1.477  1.058  1.363  1.185    1.082  1.253   
5       Junho  1.663  1.674  1.484  1.090  1.415  1.200    1.067  1.422   
6       Julho  2.363  1.818  1.557  1.326  1.391  1.246    1.162  1.628   
7      Agosto  2.256  1.841  1.654  1.359  1.392  1.241    1.098  1.832   
8    Setembro  2.483  1.533  1.622  1.360  1.320  1.359    1.190  1.723   
9     Outubro  2.429  1.728  1.752  1.409  1.412  1.344    1.166  2.160   
10   Novembro  2.385  1.513  1.325  1.265  1.298  1.192    1.159  2.188   
11   Dezembro  2.624  1.603  1.512  1.541  1.352  1.623    1.396  2.136   

     2008   2009   2010     2011   2012   2013   2014   2015   2016   2017  \
0   2.286  2.818  2.144    1.836  1.347  1.608  2.040  2.540  3.181  2.873   
1   1.857  2.433  1.250    1.397  1.157  1.516  1.805  2.996  2.726  2.441   
2   2.095  2.668  1.503    1.303  1.179  1.443  1.631  3.416  2.583  2.712   
3   2.161  2.551  1.366  787.000  1.119  1.521  1.693  2.905  2.681  2.243   
4   2.274  2.733  1.470  820.000  1.181  1.384  1.622  2.974  3.058  2.650   
5   2.141  2.930  1.564  767.000  1.178  1.306  1.463  2.905  3.184  2.578   
6   2.391  3.093  1.778  751.000  1.265  1.422  1.685  3.006  3.282  2.506   
7   2.457  2.921  1.696  896.000  1.321  1.365  1.589  3.199  3.321  3.273   
8   2.563  2.928  1.729    1.181  1.293  1.279  1.627  3.352  3.147  3.428   
9   2.728  3.105  1.511    1.334  1.758  1.674  1.829  4.415  2.812  3.503   
10  2.408  2.258  1.455    1.332  1.564  1.502  2.136  3.367  2.718  4.073   
11  2.913  2.673  1.789    1.459  1.622  1.920  2.720  3.325  3.222  4.905   

     2018   2019   2020   2021    2022  
0   4.925  7.955  9.291  6.985   5.943  
1   3.967  6.640  7.588  7.259   8.493  
2   3.964  6.548  5.631  7.265  18.183  
3   3.582  7.374  3.043  6.512  21.137  
4   4.221  7.324  3.701  7.358  18.254  
5   5.375  6.543  4.444  5.592   8.285  
6   6.097  6.964  4.868  6.865     NaN  
7   6.702  7.415  5.335  5.520     NaN  
8   7.442  7.715  6.690  9.334     NaN  
9   8.877  8.548  6.916  5.696     NaN  
10  8.531  8.496  6.401  8.732     NaN  
11  8.600  9.822  7.344  7.274     NaN

In [1004]:
# Replace do Mês para numérico

dfpi["Mês"].replace("Janeiro", "01", inplace=True)
dfpi["Mês"].replace("Fevereiro", "02", inplace=True)
dfpi["Mês"].replace("Março", "03", inplace=True)
dfpi["Mês"].replace("Abril", "04", inplace=True)
dfpi["Mês"].replace("Maio", "05", inplace=True)
dfpi["Mês"].replace("Junho", "06", inplace=True)
dfpi["Mês"].replace("Julho", "07", inplace=True)
dfpi["Mês"].replace("Agosto", "08", inplace=True)
dfpi["Mês"].replace("Setembro", "09", inplace=True)
dfpi["Mês"].replace("Outubro", "10", inplace=True)
dfpi["Mês"].replace("Novembro", "11", inplace=True)
dfpi["Mês"].replace("Dezembro", "12", inplace=True)

In [1005]:
# Criação das colunas uf, produto, unid, criado_em
dfpi['uf']='PI'
dfpi['produto']='Etanol Hidratado'
dfpi['unid']='m3'
dfpi['criado_em'] ='2022-09-10'

In [1006]:
# Despivotar a tabela em ano e volume 
dfpi.reset_index(inplace=True)

In [1007]:
dfpi=dfpi.melt(id_vars = ['Mês', 'uf', 'produto', 'unid', 'criado_em'], value_vars = ['2000', '2001', '2002', '2003', '2004', '2005', '2006', '2007', '2008', '2009', '2010', '2011', '2012', '2013', '2014', '2015', '2016', '2017', '2018', '2019', '2020', '2021', '2022'], var_name='ano', value_name='venda')

In [1008]:
# Visão geral da tabela

dfpi

Mês  uf           produto unid   criado_em   ano    venda
0    01  PI  Etanol Hidratado   m3  2022-09-10  2000    1.993
1    02  PI  Etanol Hidratado   m3  2022-09-10  2000    1.925
2    03  PI  Etanol Hidratado   m3  2022-09-10  2000    1.916
3    04  PI  Etanol Hidratado   m3  2022-09-10  2000    1.713
4    05  PI  Etanol Hidratado   m3  2022-09-10  2000    2.014
5    06  PI  Etanol Hidratado   m3  2022-09-10  2000    1.663
6    07  PI  Etanol Hidratado   m3  2022-09-10  2000    2.363
7    08  PI  Etanol Hidratado   m3  2022-09-10  2000    2.256
8    09  PI  Etanol Hidratado   m3  2022-09-10  2000    2.483
9    10  PI  Etanol Hidratado   m3  2022-09-10  2000    2.429
10   11  PI  Etanol Hidratado   m3  2022-09-10  2000    2.385
11   12  PI  Etanol Hidratado   m3  2022-09-10  2000    2.624
12   01  PI  Etanol Hidratado   m3  2022-09-10  2001    2.175
13   02  PI  Etanol Hidratado   m3  2022-09-10  2001    1.843
14   03  PI  Etanol Hidratado   m3  2022-09-10  2001    1.866
15   04  PI  Etanol Hidratado   m3  2022-09-10  2001    1.668
16   05  PI  Etanol Hidratado   m3  2022-09-10  2001    1.718
17   06  PI  Etanol Hidratado   m3  2022-09-10  2001    1.674
18   07  PI  Etanol Hidratado   m3  2022-09-10  2001    1.818
19   08  PI  Etanol Hidratado   m3  2022-09-10  2001    1.841
20   09  PI  Etanol Hidratado   m3  2022-09-10  2001    1.533
21   10  PI  Etanol Hidratado   m3  2022-09-10  2001    1.728
22   11  PI  Etanol Hidratado   m3  2022-09-10  2001    1.513
23   12  PI  Etanol Hidratado   m3  2022-09-10  2001    1.603
24   01  PI  Etanol Hidratado   m3  2022-09-10  2002    1.729
25   02  PI  Etanol Hidratado   m3  2022-09-10  2002    1.426
26   03  PI  Etanol Hidratado   m3  2022-09-10  2002    1.355
27   04  PI  Etanol Hidratado   m3  2022-09-10  2002    1.418
28   05  PI  Etanol Hidratado   m3  2022-09-10  2002    1.477
29   06  PI  Etanol Hidratado   m3  2022-09-10  2002    1.484
30   07  PI  Etanol Hidratado   m3  2022-09-10  2002    1.557
31   08  PI  Etanol Hidratado   m3  2022-09-10  2002    1.654
32   09  PI  Etanol Hidratado   m3  2022-09-10  2002    1.622
33   10  PI  Etanol Hidratado   m3  2022-09-10  2002    1.752
34   11  PI  Etanol Hidratado   m3  2022-09-10  2002    1.325
35   12  PI  Etanol Hidratado   m3  2022-09-10  2002    1.512
36   01  PI  Etanol Hidratado   m3  2022-09-10  2003    1.633
37   02  PI  Etanol Hidratado   m3  2022-09-10  2003    1.194
38   03  PI  Etanol Hidratado   m3  2022-09-10  2003    1.096
39   04  PI  Etanol Hidratado   m3  2022-09-10  2003    1.120
40   05  PI  Etanol Hidratado   m3  2022-09-10  2003    1.058
41   06  PI  Etanol Hidratado   m3  2022-09-10  2003    1.090
42   07  PI  Etanol Hidratado   m3  2022-09-10  2003    1.326
43   08  PI  Etanol Hidratado   m3  2022-09-10  2003    1.359
44   09  PI  Etanol Hidratado   m3  2022-09-10  2003    1.360
45   10  PI  Etanol Hidratado   m3  2022-09-10  2003    1.409
46   11  PI  Etanol Hidratado   m3  2022-09-10  2003    1.265
47   12  PI  Etanol Hidratado   m3  2022-09-10  2003    1.541
48   01  PI  Etanol Hidratado   m3  2022-09-10  2004    1.459
49   02  PI  Etanol Hidratado   m3  2022-09-10  2004    1.179
50   03  PI  Etanol Hidratado   m3  2022-09-10  2004    1.318
51   04  PI  Etanol Hidratado   m3  2022-09-10  2004    1.317
52   05  PI  Etanol Hidratado   m3  2022-09-10  2004    1.363
53   06  PI  Etanol Hidratado   m3  2022-09-10  2004    1.415
54   07  PI  Etanol Hidratado   m3  2022-09-10  2004    1.391
55   08  PI  Etanol Hidratado   m3  2022-09-10  2004    1.392
56   09  PI  Etanol Hidratado   m3  2022-09-10  2004    1.320
57   10  PI  Etanol Hidratado   m3  2022-09-10  2004    1.412
58   11  PI  Etanol Hidratado   m3  2022-09-10  2004    1.298
59   12  PI  Etanol Hidratado   m3  2022-09-10  2004    1.352
60   01  PI  Etanol Hidratado   m3  2022-09-10  2005    1.275
61   02  PI  Etanol Hidratado   m3  2022-09-10  2005    1.126
62   03  PI  Etanol Hidratado   m3  2022-09-10  2005    1.156
63   04  PI  Etanol Hidratado   m3  

In [1009]:
# Concatenando as colunas ano e Mês
dfpi['ano_mês'] = dfpi[['ano', 'Mês']].agg('-'.join, axis=1)

In [1010]:
# Eliminando as colunas Mês e ano

dfpi.drop(["Mês"], axis=1, inplace=True)
dfpi.drop(["ano"], axis=1, inplace=True)

In [1011]:
# Organização da ordem das colunas

dfpi=dfpi[['ano_mês', 'uf', 'produto', 'unid', 'venda', 'criado_em']]

In [1012]:
# Levantamento de possíveis inconsistências

dfpi.isna().sum()

ano_mês      0
uf           0
produto      0
unid         0
venda        6
criado_em    0
dtype: int64

In [1013]:
# Tratamento das inconsistências

dfpi.replace(['Na', 'nA', 'na','NA', 'NaN', 'NAN', 'nan', '', ' '],pd.NA,inplace=True)


In [1014]:
# Visão geral da tabela

dfpi

ano_mês  uf           produto unid    venda   criado_em
0    2000-01  PI  Etanol Hidratado   m3    1.993  2022-09-10
1    2000-02  PI  Etanol Hidratado   m3    1.925  2022-09-10
2    2000-03  PI  Etanol Hidratado   m3    1.916  2022-09-10
3    2000-04  PI  Etanol Hidratado   m3    1.713  2022-09-10
4    2000-05  PI  Etanol Hidratado   m3    2.014  2022-09-10
5    2000-06  PI  Etanol Hidratado   m3    1.663  2022-09-10
6    2000-07  PI  Etanol Hidratado   m3    2.363  2022-09-10
7    2000-08  PI  Etanol Hidratado   m3    2.256  2022-09-10
8    2000-09  PI  Etanol Hidratado   m3    2.483  2022-09-10
9    2000-10  PI  Etanol Hidratado   m3    2.429  2022-09-10
10   2000-11  PI  Etanol Hidratado   m3    2.385  2022-09-10
11   2000-12  PI  Etanol Hidratado   m3    2.624  2022-09-10
12   2001-01  PI  Etanol Hidratado   m3    2.175  2022-09-10
13   2001-02  PI  Etanol Hidratado   m3    1.843  2022-09-10
14   2001-03  PI  Etanol Hidratado   m3    1.866  2022-09-10
15   2001-04  PI  Etanol Hidratado   m3    1.668  2022-09-10
16   2001-05  PI  Etanol Hidratado   m3    1.718  2022-09-10
17   2001-06  PI  Etanol Hidratado   m3    1.674  2022-09-10
18   2001-07  PI  Etanol Hidratado   m3    1.818  2022-09-10
19   2001-08  PI  Etanol Hidratado   m3    1.841  2022-09-10
20   2001-09  PI  Etanol Hidratado   m3    1.533  2022-09-10
21   2001-10  PI  Etanol Hidratado   m3    1.728  2022-09-10
22   2001-11  PI  Etanol Hidratado   m3    1.513  2022-09-10
23   2001-12  PI  Etanol Hidratado   m3    1.603  2022-09-10
24   2002-01  PI  Etanol Hidratado   m3    1.729  2022-09-10
25   2002-02  PI  Etanol Hidratado   m3    1.426  2022-09-10
26   2002-03  PI  Etanol Hidratado   m3    1.355  2022-09-10
27   2002-04  PI  Etanol Hidratado   m3    1.418  2022-09-10
28   2002-05  PI  Etanol Hidratado   m3    1.477  2022-09-10
29   2002-06  PI  Etanol Hidratado   m3    1.484  2022-09-10
30   2002-07  PI  Etanol Hidratado   m3    1.557  2022-09-10
31   2002-08  PI  Etanol Hidratado   m3    1.654  2022-09-10
32   2002-09  PI  Etanol Hidratado   m3    1.622  2022-09-10
33   2002-10  PI  Etanol Hidratado   m3    1.752  2022-09-10
34   2002-11  PI  Etanol Hidratado   m3    1.325  2022-09-10
35   2002-12  PI  Etanol Hidratado   m3    1.512  2022-09-10
36   2003-01  PI  Etanol Hidratado   m3    1.633  2022-09-10
37   2003-02  PI  Etanol Hidratado   m3    1.194  2022-09-10
38   2003-03  PI  Etanol Hidratado   m3    1.096  2022-09-10
39   2003-04  PI  Etanol Hidratado   m3    1.120  2022-09-10
40   2003-05  PI  Etanol Hidratado   m3    1.058  2022-09-10
41   2003-06  PI  Etanol Hidratado   m3    1.090  2022-09-10
42   2003-07  PI  Etanol Hidratado   m3    1.326  2022-09-10
43   2003-08  PI  Etanol Hidratado   m3    1.359  2022-09-10
44   2003-09  PI  Etanol Hidratado   m3    1.360  2022-09-10
45   2003-10  PI  Etanol Hidratado   m3    1.409  2022-09-10
46   2003-11  PI  Etanol Hidratado   m3    1.265  2022-09-10
47   2003-12  PI  Etanol Hidratado   m3    1.541  2022-09-10
48   2004-01  PI  Etanol Hidratado   m3    1.459  2022-09-10
49   2004-02  PI  Etanol Hidratado   m3    1.179  2022-09-10
50   2004-03  PI  Etanol Hidratado   m3    1.318  2022-09-10
51   2004-04  PI  Etanol Hidratado   m3    1.317  2022-09-10
52   2004-05  PI  Etanol Hidratado   m3    1.363  2022-09-10
53   2004-06  PI  Etanol Hidratado   m3    1.415  2022-09-10
54   2004-07  PI  Etanol Hidratado   m3    1.391  2022-09-10
55   2004-08  PI  Etanol Hidratado   m3    1.392  2022-09-10
56   2004-09  PI  Etanol Hidratado   m3    1.320  2022-09-10
57   2004-10  PI  Etanol Hidratado   m3    1.412  2022-09-10
58   2004-11  PI  Etanol Hidratado   m3    1.298  2022-09-10
59   2004-12  PI  Etanol Hidratado   m3    1.352  2022-09-10
60   2005-01  PI  Etanol Hidratado   m3    1.275  2022-09-10
61   2005-02  PI  Etanol Hidratado   m3    1.126  2022-09-10
62   2005-03  PI  Etanol Hidratado   m3    1.156  2022-09-10
63   2005-04  PI  Etanol Hidratado   m3    1.022  2022-09-10
64   2005-05  PI  Etanol Hidratado   m3 

In [1015]:
# Verificando os tipos

dfpi.dtypes

ano_mês       object
uf            object
produto       object
unid          object
venda        float64
criado_em     object
dtype: object

In [1016]:
# Validação

schema = pa.DataFrameSchema(
    columns = {
        'ano_mês': pa.Column(pa.String, nullable=True),
        'uf': pa.Column(pa.String, nullable = True),
        'produto': pa.Column(pa.String, nullable = True),
        'unid': pa.Column(pa.String, nullable = True),
        'venda': pa.Column(pa.Float, nullable = True),
        'criado_em': pa.Column(pa.String, nullable = True),
                
    }
)
schema.validate(dfpi)

ano_mês  uf           produto unid    venda   criado_em
0    2000-01  PI  Etanol Hidratado   m3    1.993  2022-09-10
1    2000-02  PI  Etanol Hidratado   m3    1.925  2022-09-10
2    2000-03  PI  Etanol Hidratado   m3    1.916  2022-09-10
3    2000-04  PI  Etanol Hidratado   m3    1.713  2022-09-10
4    2000-05  PI  Etanol Hidratado   m3    2.014  2022-09-10
5    2000-06  PI  Etanol Hidratado   m3    1.663  2022-09-10
6    2000-07  PI  Etanol Hidratado   m3    2.363  2022-09-10
7    2000-08  PI  Etanol Hidratado   m3    2.256  2022-09-10
8    2000-09  PI  Etanol Hidratado   m3    2.483  2022-09-10
9    2000-10  PI  Etanol Hidratado   m3    2.429  2022-09-10
10   2000-11  PI  Etanol Hidratado   m3    2.385  2022-09-10
11   2000-12  PI  Etanol Hidratado   m3    2.624  2022-09-10
12   2001-01  PI  Etanol Hidratado   m3    2.175  2022-09-10
13   2001-02  PI  Etanol Hidratado   m3    1.843  2022-09-10
14   2001-03  PI  Etanol Hidratado   m3    1.866  2022-09-10
15   2001-04  PI  Etanol Hidratado   m3    1.668  2022-09-10
16   2001-05  PI  Etanol Hidratado   m3    1.718  2022-09-10
17   2001-06  PI  Etanol Hidratado   m3    1.674  2022-09-10
18   2001-07  PI  Etanol Hidratado   m3    1.818  2022-09-10
19   2001-08  PI  Etanol Hidratado   m3    1.841  2022-09-10
20   2001-09  PI  Etanol Hidratado   m3    1.533  2022-09-10
21   2001-10  PI  Etanol Hidratado   m3    1.728  2022-09-10
22   2001-11  PI  Etanol Hidratado   m3    1.513  2022-09-10
23   2001-12  PI  Etanol Hidratado   m3    1.603  2022-09-10
24   2002-01  PI  Etanol Hidratado   m3    1.729  2022-09-10
25   2002-02  PI  Etanol Hidratado   m3    1.426  2022-09-10
26   2002-03  PI  Etanol Hidratado   m3    1.355  2022-09-10
27   2002-04  PI  Etanol Hidratado   m3    1.418  2022-09-10
28   2002-05  PI  Etanol Hidratado   m3    1.477  2022-09-10
29   2002-06  PI  Etanol Hidratado   m3    1.484  2022-09-10
30   2002-07  PI  Etanol Hidratado   m3    1.557  2022-09-10
31   2002-08  PI  Etanol Hidratado   m3    1.654  2022-09-10
32   2002-09  PI  Etanol Hidratado   m3    1.622  2022-09-10
33   2002-10  PI  Etanol Hidratado   m3    1.752  2022-09-10
34   2002-11  PI  Etanol Hidratado   m3    1.325  2022-09-10
35   2002-12  PI  Etanol Hidratado   m3    1.512  2022-09-10
36   2003-01  PI  Etanol Hidratado   m3    1.633  2022-09-10
37   2003-02  PI  Etanol Hidratado   m3    1.194  2022-09-10
38   2003-03  PI  Etanol Hidratado   m3    1.096  2022-09-10
39   2003-04  PI  Etanol Hidratado   m3    1.120  2022-09-10
40   2003-05  PI  Etanol Hidratado   m3    1.058  2022-09-10
41   2003-06  PI  Etanol Hidratado   m3    1.090  2022-09-10
42   2003-07  PI  Etanol Hidratado   m3    1.326  2022-09-10
43   2003-08  PI  Etanol Hidratado   m3    1.359  2022-09-10
44   2003-09  PI  Etanol Hidratado   m3    1.360  2022-09-10
45   2003-10  PI  Etanol Hidratado   m3    1.409  2022-09-10
46   2003-11  PI  Etanol Hidratado   m3    1.265  2022-09-10
47   2003-12  PI  Etanol Hidratado   m3    1.541  2022-09-10
48   2004-01  PI  Etanol Hidratado   m3    1.459  2022-09-10
49   2004-02  PI  Etanol Hidratado   m3    1.179  2022-09-10
50   2004-03  PI  Etanol Hidratado   m3    1.318  2022-09-10
51   2004-04  PI  Etanol Hidratado   m3    1.317  2022-09-10
52   2004-05  PI  Etanol Hidratado   m3    1.363  2022-09-10
53   2004-06  PI  Etanol Hidratado   m3    1.415  2022-09-10
54   2004-07  PI  Etanol Hidratado   m3    1.391  2022-09-10
55   2004-08  PI  Etanol Hidratado   m3    1.392  2022-09-10
56   2004-09  PI  Etanol Hidratado   m3    1.320  2022-09-10
57   2004-10  PI  Etanol Hidratado   m3    1.412  2022-09-10
58   2004-11  PI  Etanol Hidratado   m3    1.298  2022-09-10
59   2004-12  PI  Etanol Hidratado   m3    1.352  2022-09-10
60   2005-01  PI  Etanol Hidratado   m3    1.275  2022-09-10
61   2005-02  PI  Etanol Hidratado   m3    1.126  2022-09-10
62   2005-03  PI  Etanol Hidratado   m3    1.156  2022-09-10
63   2005-04  PI  Etanol Hidratado   m3    1.022  2022-09-10
64   2005-05  PI  Etanol Hidratado   m3 

In [1017]:
dfpi_pandas = dfpi.copy()

##PARANÁ

In [1018]:
# Conector

dfpr = pd.read_csv('/content/parana.csv',sep=';')

In [1019]:
# Backup
dfpr_backup = dfpr.copy()

In [1020]:
# Configurando a quantidade de linhas máximas mostradas em tela

pd.set_option('display.max_columns',1000)
pd.set_option('display.max_rows',1000)

In [1021]:
# Visualização da Tabela

dfpr

Mês    2000    2001    2002    2003    2004    2005    2006    2007  \
0     Janeiro  34.871  35.206  34.147  30.498  37.393  40.978  39.473  40.753   
1   Fevereiro  38.284  31.051  27.302  23.564  35.061  37.994  39.442  37.181   
2       Março  36.015  41.729  29.567  29.096  44.328  41.526  34.311  48.703   
3       Abril  38.467  41.250  30.783  25.793  44.213  38.014  30.647  40.911   
4        Maio  38.721  39.851  30.701  24.479  49.897  40.906  36.117  45.307   
5       Junho  36.209  36.434  28.845  33.278  38.458  44.140  39.022  55.746   
6       Julho  44.646  31.246  37.215  36.311  48.689  42.895  44.632  59.018   
7      Agosto  34.766  30.133  31.743  30.359  43.825  44.511  45.096  62.809   
8    Setembro  35.393  30.717  30.694  29.548  42.854  47.354  49.015  65.361   
9     Outubro  33.533  37.483  32.388  36.731  49.277  41.949  49.152  81.571   
10   Novembro  35.032  36.967  25.918  35.266  48.138  44.149  52.557  79.768   
11   Dezembro  39.275  38.763  31.115  42.155  56.631  53.819  61.121  84.126   

      2008     2009     2010     2011    2012     2013     2014     2015  \
0   62.070   92.520   73.121  101.541  56.294   84.791  105.433  122.398   
1   64.960   83.914   64.652   94.799  60.450   89.051  102.408  120.426   
2   67.602   94.625  101.224   57.899  58.884   90.279   85.810  131.486   
3   70.991  100.771  115.257   38.919  59.277   84.234   87.888  146.954   
4   73.161   94.055  117.959   77.987  61.446   81.111   91.860  136.647   
5   72.885   97.086  120.261   85.263  62.214   87.355   90.599  138.193   
6   79.286  101.827  128.958   71.519  64.399   89.067   93.403  145.928   
7   77.466   99.836  127.287   65.430  72.511   91.383  109.271  148.759   
8   80.643  108.689  131.055   53.725  69.518   87.828  106.571  154.512   
9   83.738  110.044  117.829   57.632  80.960  109.233  116.223  163.674   
10  79.368   99.637  118.291   51.657  84.243  109.306  111.021  133.055   
11  92.160  110.025  131.106   54.999  84.429  125.264  135.235  148.402   

       2016     2017     2018     2019     2020     2021    2022  
0   115.879   65.416  110.214  146.897  138.459  111.395  54.196  
1   108.829   64.644   96.239  139.739  139.123  111.221  67.184  
2   103.284   77.995  104.227  138.429  116.402   98.709  91.148  
3   102.004   75.473  105.705  144.855   94.490  108.334  82.306  
4   104.675   74.035  107.978  146.628   91.954   90.106  70.583  
5    98.900   73.783  119.709  134.962   86.172   72.277  70.088  
6   107.738   76.569  132.777  144.920   94.254   76.057     NaN  
7   110.715   92.418  151.291  148.625   98.950   72.444     NaN  
8   114.406  107.638  146.962  151.641  110.919   70.947     NaN  
9   101.259  112.958  163.344  160.192  122.794   72.051     NaN  
10   82.006  115.721  158.967  155.790  107.408   55.896     NaN  
11   95.546  130.381  168.669  163.767  128.548   72.126     NaN

In [1022]:
# Replace do Mês para numérico

dfpr["Mês"].replace("Janeiro", "01", inplace=True)
dfpr["Mês"].replace("Fevereiro", "02", inplace=True)
dfpr["Mês"].replace("Março", "03", inplace=True)
dfpr["Mês"].replace("Abril", "04", inplace=True)
dfpr["Mês"].replace("Maio", "05", inplace=True)
dfpr["Mês"].replace("Junho", "06", inplace=True)
dfpr["Mês"].replace("Julho", "07", inplace=True)
dfpr["Mês"].replace("Agosto", "08", inplace=True)
dfpr["Mês"].replace("Setembro", "09", inplace=True)
dfpr["Mês"].replace("Outubro", "10", inplace=True)
dfpr["Mês"].replace("Novembro", "11", inplace=True)
dfpr["Mês"].replace("Dezembro", "12", inplace=True)

In [1023]:
# Criação das colunas uf, produto, unid, criado_em
dfpr['uf']='PR'
dfpr['produto']='Etanol Hidratado'
dfpr['unid']='m3'
dfpr['criado_em'] ='2022-09-10'

In [1024]:
# Despivotar a tabela em ano e volume 
dfpr.reset_index(inplace=True)

In [1025]:
dfpr=dfpr.melt(id_vars = ['Mês', 'uf', 'produto', 'unid', 'criado_em'], value_vars = ['2000', '2001', '2002', '2003', '2004', '2005', '2006', '2007', '2008', '2009', '2010', '2011', '2012', '2013', '2014', '2015', '2016', '2017', '2018', '2019', '2020', '2021', '2022'], var_name='ano', value_name='venda')

In [1026]:
# Visão geral da tabela

dfpr

Mês  uf           produto unid   criado_em   ano    venda
0    01  PR  Etanol Hidratado   m3  2022-09-10  2000   34.871
1    02  PR  Etanol Hidratado   m3  2022-09-10  2000   38.284
2    03  PR  Etanol Hidratado   m3  2022-09-10  2000   36.015
3    04  PR  Etanol Hidratado   m3  2022-09-10  2000   38.467
4    05  PR  Etanol Hidratado   m3  2022-09-10  2000   38.721
5    06  PR  Etanol Hidratado   m3  2022-09-10  2000   36.209
6    07  PR  Etanol Hidratado   m3  2022-09-10  2000   44.646
7    08  PR  Etanol Hidratado   m3  2022-09-10  2000   34.766
8    09  PR  Etanol Hidratado   m3  2022-09-10  2000   35.393
9    10  PR  Etanol Hidratado   m3  2022-09-10  2000   33.533
10   11  PR  Etanol Hidratado   m3  2022-09-10  2000   35.032
11   12  PR  Etanol Hidratado   m3  2022-09-10  2000   39.275
12   01  PR  Etanol Hidratado   m3  2022-09-10  2001   35.206
13   02  PR  Etanol Hidratado   m3  2022-09-10  2001   31.051
14   03  PR  Etanol Hidratado   m3  2022-09-10  2001   41.729
15   04  PR  Etanol Hidratado   m3  2022-09-10  2001   41.250
16   05  PR  Etanol Hidratado   m3  2022-09-10  2001   39.851
17   06  PR  Etanol Hidratado   m3  2022-09-10  2001   36.434
18   07  PR  Etanol Hidratado   m3  2022-09-10  2001   31.246
19   08  PR  Etanol Hidratado   m3  2022-09-10  2001   30.133
20   09  PR  Etanol Hidratado   m3  2022-09-10  2001   30.717
21   10  PR  Etanol Hidratado   m3  2022-09-10  2001   37.483
22   11  PR  Etanol Hidratado   m3  2022-09-10  2001   36.967
23   12  PR  Etanol Hidratado   m3  2022-09-10  2001   38.763
24   01  PR  Etanol Hidratado   m3  2022-09-10  2002   34.147
25   02  PR  Etanol Hidratado   m3  2022-09-10  2002   27.302
26   03  PR  Etanol Hidratado   m3  2022-09-10  2002   29.567
27   04  PR  Etanol Hidratado   m3  2022-09-10  2002   30.783
28   05  PR  Etanol Hidratado   m3  2022-09-10  2002   30.701
29   06  PR  Etanol Hidratado   m3  2022-09-10  2002   28.845
30   07  PR  Etanol Hidratado   m3  2022-09-10  2002   37.215
31   08  PR  Etanol Hidratado   m3  2022-09-10  2002   31.743
32   09  PR  Etanol Hidratado   m3  2022-09-10  2002   30.694
33   10  PR  Etanol Hidratado   m3  2022-09-10  2002   32.388
34   11  PR  Etanol Hidratado   m3  2022-09-10  2002   25.918
35   12  PR  Etanol Hidratado   m3  2022-09-10  2002   31.115
36   01  PR  Etanol Hidratado   m3  2022-09-10  2003   30.498
37   02  PR  Etanol Hidratado   m3  2022-09-10  2003   23.564
38   03  PR  Etanol Hidratado   m3  2022-09-10  2003   29.096
39   04  PR  Etanol Hidratado   m3  2022-09-10  2003   25.793
40   05  PR  Etanol Hidratado   m3  2022-09-10  2003   24.479
41   06  PR  Etanol Hidratado   m3  2022-09-10  2003   33.278
42   07  PR  Etanol Hidratado   m3  2022-09-10  2003   36.311
43   08  PR  Etanol Hidratado   m3  2022-09-10  2003   30.359
44   09  PR  Etanol Hidratado   m3  2022-09-10  2003   29.548
45   10  PR  Etanol Hidratado   m3  2022-09-10  2003   36.731
46   11  PR  Etanol Hidratado   m3  2022-09-10  2003   35.266
47   12  PR  Etanol Hidratado   m3  2022-09-10  2003   42.155
48   01  PR  Etanol Hidratado   m3  2022-09-10  2004   37.393
49   02  PR  Etanol Hidratado   m3  2022-09-10  2004   35.061
50   03  PR  Etanol Hidratado   m3  2022-09-10  2004   44.328
51   04  PR  Etanol Hidratado   m3  2022-09-10  2004   44.213
52   05  PR  Etanol Hidratado   m3  2022-09-10  2004   49.897
53   06  PR  Etanol Hidratado   m3  2022-09-10  2004   38.458
54   07  PR  Etanol Hidratado   m3  2022-09-10  2004   48.689
55   08  PR  Etanol Hidratado   m3  2022-09-10  2004   43.825
56   09  PR  Etanol Hidratado   m3  2022-09-10  2004   42.854
57   10  PR  Etanol Hidratado   m3  2022-09-10  2004   49.277
58   11  PR  Etanol Hidratado   m3  2022-09-10  2004   48.138
59   12  PR  Etanol Hidratado   m3  2022-09-10  2004   56.631
60   01  PR  Etanol Hidratado   m3  2022-09-10  2005   40.978
61   02  PR  Etanol Hidratado   m3  2022-09-10  2005   37.994
62   03  PR  Etanol Hidratado   m3  2022-09-10  2005   41.526
63   04  PR  Etanol Hidratado   m3  

In [1027]:
# Concatenando as colunas ano e Mês
dfpr['ano_mês'] = dfpr[['ano', 'Mês']].agg('-'.join, axis=1)

In [1028]:
# Eliminando as colunas Mês e ano

dfpr.drop(["Mês"], axis=1, inplace=True)
dfpr.drop(["ano"], axis=1, inplace=True)

In [1029]:
# Organização da ordem das colunas

dfpr=dfpr[['ano_mês', 'uf', 'produto', 'unid', 'venda', 'criado_em']]

In [1030]:
# Levantamento de possíveis inconsistências

dfpr.isna().sum()

ano_mês      0
uf           0
produto      0
unid         0
venda        6
criado_em    0
dtype: int64

In [1031]:
# Tratamento das inconsistências

dfpr.replace(['Na', 'nA', 'na','NA', 'NaN', 'NAN', 'nan', '', ' '],pd.NA,inplace=True)


In [1032]:
# Visão geral da tabela

dfpr

ano_mês  uf           produto unid    venda   criado_em
0    2000-01  PR  Etanol Hidratado   m3   34.871  2022-09-10
1    2000-02  PR  Etanol Hidratado   m3   38.284  2022-09-10
2    2000-03  PR  Etanol Hidratado   m3   36.015  2022-09-10
3    2000-04  PR  Etanol Hidratado   m3   38.467  2022-09-10
4    2000-05  PR  Etanol Hidratado   m3   38.721  2022-09-10
5    2000-06  PR  Etanol Hidratado   m3   36.209  2022-09-10
6    2000-07  PR  Etanol Hidratado   m3   44.646  2022-09-10
7    2000-08  PR  Etanol Hidratado   m3   34.766  2022-09-10
8    2000-09  PR  Etanol Hidratado   m3   35.393  2022-09-10
9    2000-10  PR  Etanol Hidratado   m3   33.533  2022-09-10
10   2000-11  PR  Etanol Hidratado   m3   35.032  2022-09-10
11   2000-12  PR  Etanol Hidratado   m3   39.275  2022-09-10
12   2001-01  PR  Etanol Hidratado   m3   35.206  2022-09-10
13   2001-02  PR  Etanol Hidratado   m3   31.051  2022-09-10
14   2001-03  PR  Etanol Hidratado   m3   41.729  2022-09-10
15   2001-04  PR  Etanol Hidratado   m3   41.250  2022-09-10
16   2001-05  PR  Etanol Hidratado   m3   39.851  2022-09-10
17   2001-06  PR  Etanol Hidratado   m3   36.434  2022-09-10
18   2001-07  PR  Etanol Hidratado   m3   31.246  2022-09-10
19   2001-08  PR  Etanol Hidratado   m3   30.133  2022-09-10
20   2001-09  PR  Etanol Hidratado   m3   30.717  2022-09-10
21   2001-10  PR  Etanol Hidratado   m3   37.483  2022-09-10
22   2001-11  PR  Etanol Hidratado   m3   36.967  2022-09-10
23   2001-12  PR  Etanol Hidratado   m3   38.763  2022-09-10
24   2002-01  PR  Etanol Hidratado   m3   34.147  2022-09-10
25   2002-02  PR  Etanol Hidratado   m3   27.302  2022-09-10
26   2002-03  PR  Etanol Hidratado   m3   29.567  2022-09-10
27   2002-04  PR  Etanol Hidratado   m3   30.783  2022-09-10
28   2002-05  PR  Etanol Hidratado   m3   30.701  2022-09-10
29   2002-06  PR  Etanol Hidratado   m3   28.845  2022-09-10
30   2002-07  PR  Etanol Hidratado   m3   37.215  2022-09-10
31   2002-08  PR  Etanol Hidratado   m3   31.743  2022-09-10
32   2002-09  PR  Etanol Hidratado   m3   30.694  2022-09-10
33   2002-10  PR  Etanol Hidratado   m3   32.388  2022-09-10
34   2002-11  PR  Etanol Hidratado   m3   25.918  2022-09-10
35   2002-12  PR  Etanol Hidratado   m3   31.115  2022-09-10
36   2003-01  PR  Etanol Hidratado   m3   30.498  2022-09-10
37   2003-02  PR  Etanol Hidratado   m3   23.564  2022-09-10
38   2003-03  PR  Etanol Hidratado   m3   29.096  2022-09-10
39   2003-04  PR  Etanol Hidratado   m3   25.793  2022-09-10
40   2003-05  PR  Etanol Hidratado   m3   24.479  2022-09-10
41   2003-06  PR  Etanol Hidratado   m3   33.278  2022-09-10
42   2003-07  PR  Etanol Hidratado   m3   36.311  2022-09-10
43   2003-08  PR  Etanol Hidratado   m3   30.359  2022-09-10
44   2003-09  PR  Etanol Hidratado   m3   29.548  2022-09-10
45   2003-10  PR  Etanol Hidratado   m3   36.731  2022-09-10
46   2003-11  PR  Etanol Hidratado   m3   35.266  2022-09-10
47   2003-12  PR  Etanol Hidratado   m3   42.155  2022-09-10
48   2004-01  PR  Etanol Hidratado   m3   37.393  2022-09-10
49   2004-02  PR  Etanol Hidratado   m3   35.061  2022-09-10
50   2004-03  PR  Etanol Hidratado   m3   44.328  2022-09-10
51   2004-04  PR  Etanol Hidratado   m3   44.213  2022-09-10
52   2004-05  PR  Etanol Hidratado   m3   49.897  2022-09-10
53   2004-06  PR  Etanol Hidratado   m3   38.458  2022-09-10
54   2004-07  PR  Etanol Hidratado   m3   48.689  2022-09-10
55   2004-08  PR  Etanol Hidratado   m3   43.825  2022-09-10
56   2004-09  PR  Etanol Hidratado   m3   42.854  2022-09-10
57   2004-10  PR  Etanol Hidratado   m3   49.277  2022-09-10
58   2004-11  PR  Etanol Hidratado   m3   48.138  2022-09-10
59   2004-12  PR  Etanol Hidratado   m3   56.631  2022-09-10
60   2005-01  PR  Etanol Hidratado   m3   40.978  2022-09-10
61   2005-02  PR  Etanol Hidratado   m3   37.994  2022-09-10
62   2005-03  PR  Etanol Hidratado   m3   41.526  2022-09-10
63   2005-04  PR  Etanol Hidratado   m3   38.014  2022-09-10
64   2005-05  PR  Etanol Hidratado   m3 

In [1033]:
# Verificando os tipos

dfpr.dtypes

ano_mês       object
uf            object
produto       object
unid          object
venda        float64
criado_em     object
dtype: object

In [1034]:
# Validação

schema = pa.DataFrameSchema(
    columns = {
        'ano_mês': pa.Column(pa.String, nullable=True),
        'uf': pa.Column(pa.String, nullable = True),
        'produto': pa.Column(pa.String, nullable = True),
        'unid': pa.Column(pa.String, nullable = True),
        'venda': pa.Column(pa.Float, nullable = True),
        'criado_em': pa.Column(pa.String, nullable = True),
                
    }
)
schema.validate(dfpr)

ano_mês  uf           produto unid    venda   criado_em
0    2000-01  PR  Etanol Hidratado   m3   34.871  2022-09-10
1    2000-02  PR  Etanol Hidratado   m3   38.284  2022-09-10
2    2000-03  PR  Etanol Hidratado   m3   36.015  2022-09-10
3    2000-04  PR  Etanol Hidratado   m3   38.467  2022-09-10
4    2000-05  PR  Etanol Hidratado   m3   38.721  2022-09-10
5    2000-06  PR  Etanol Hidratado   m3   36.209  2022-09-10
6    2000-07  PR  Etanol Hidratado   m3   44.646  2022-09-10
7    2000-08  PR  Etanol Hidratado   m3   34.766  2022-09-10
8    2000-09  PR  Etanol Hidratado   m3   35.393  2022-09-10
9    2000-10  PR  Etanol Hidratado   m3   33.533  2022-09-10
10   2000-11  PR  Etanol Hidratado   m3   35.032  2022-09-10
11   2000-12  PR  Etanol Hidratado   m3   39.275  2022-09-10
12   2001-01  PR  Etanol Hidratado   m3   35.206  2022-09-10
13   2001-02  PR  Etanol Hidratado   m3   31.051  2022-09-10
14   2001-03  PR  Etanol Hidratado   m3   41.729  2022-09-10
15   2001-04  PR  Etanol Hidratado   m3   41.250  2022-09-10
16   2001-05  PR  Etanol Hidratado   m3   39.851  2022-09-10
17   2001-06  PR  Etanol Hidratado   m3   36.434  2022-09-10
18   2001-07  PR  Etanol Hidratado   m3   31.246  2022-09-10
19   2001-08  PR  Etanol Hidratado   m3   30.133  2022-09-10
20   2001-09  PR  Etanol Hidratado   m3   30.717  2022-09-10
21   2001-10  PR  Etanol Hidratado   m3   37.483  2022-09-10
22   2001-11  PR  Etanol Hidratado   m3   36.967  2022-09-10
23   2001-12  PR  Etanol Hidratado   m3   38.763  2022-09-10
24   2002-01  PR  Etanol Hidratado   m3   34.147  2022-09-10
25   2002-02  PR  Etanol Hidratado   m3   27.302  2022-09-10
26   2002-03  PR  Etanol Hidratado   m3   29.567  2022-09-10
27   2002-04  PR  Etanol Hidratado   m3   30.783  2022-09-10
28   2002-05  PR  Etanol Hidratado   m3   30.701  2022-09-10
29   2002-06  PR  Etanol Hidratado   m3   28.845  2022-09-10
30   2002-07  PR  Etanol Hidratado   m3   37.215  2022-09-10
31   2002-08  PR  Etanol Hidratado   m3   31.743  2022-09-10
32   2002-09  PR  Etanol Hidratado   m3   30.694  2022-09-10
33   2002-10  PR  Etanol Hidratado   m3   32.388  2022-09-10
34   2002-11  PR  Etanol Hidratado   m3   25.918  2022-09-10
35   2002-12  PR  Etanol Hidratado   m3   31.115  2022-09-10
36   2003-01  PR  Etanol Hidratado   m3   30.498  2022-09-10
37   2003-02  PR  Etanol Hidratado   m3   23.564  2022-09-10
38   2003-03  PR  Etanol Hidratado   m3   29.096  2022-09-10
39   2003-04  PR  Etanol Hidratado   m3   25.793  2022-09-10
40   2003-05  PR  Etanol Hidratado   m3   24.479  2022-09-10
41   2003-06  PR  Etanol Hidratado   m3   33.278  2022-09-10
42   2003-07  PR  Etanol Hidratado   m3   36.311  2022-09-10
43   2003-08  PR  Etanol Hidratado   m3   30.359  2022-09-10
44   2003-09  PR  Etanol Hidratado   m3   29.548  2022-09-10
45   2003-10  PR  Etanol Hidratado   m3   36.731  2022-09-10
46   2003-11  PR  Etanol Hidratado   m3   35.266  2022-09-10
47   2003-12  PR  Etanol Hidratado   m3   42.155  2022-09-10
48   2004-01  PR  Etanol Hidratado   m3   37.393  2022-09-10
49   2004-02  PR  Etanol Hidratado   m3   35.061  2022-09-10
50   2004-03  PR  Etanol Hidratado   m3   44.328  2022-09-10
51   2004-04  PR  Etanol Hidratado   m3   44.213  2022-09-10
52   2004-05  PR  Etanol Hidratado   m3   49.897  2022-09-10
53   2004-06  PR  Etanol Hidratado   m3   38.458  2022-09-10
54   2004-07  PR  Etanol Hidratado   m3   48.689  2022-09-10
55   2004-08  PR  Etanol Hidratado   m3   43.825  2022-09-10
56   2004-09  PR  Etanol Hidratado   m3   42.854  2022-09-10
57   2004-10  PR  Etanol Hidratado   m3   49.277  2022-09-10
58   2004-11  PR  Etanol Hidratado   m3   48.138  2022-09-10
59   2004-12  PR  Etanol Hidratado   m3   56.631  2022-09-10
60   2005-01  PR  Etanol Hidratado   m3   40.978  2022-09-10
61   2005-02  PR  Etanol Hidratado   m3   37.994  2022-09-10
62   2005-03  PR  Etanol Hidratado   m3   41.526  2022-09-10
63   2005-04  PR  Etanol Hidratado   m3   38.014  2022-09-10
64   2005-05  PR  Etanol Hidratado   m3 

In [1035]:
dfpr_pandas = dfpr.copy()

##RIO DE JANEIRO

In [1036]:
# Conector

dfrj = pd.read_csv('/content/rio_de_janeiro.csv',sep=';')

In [1037]:
# Backup
dfrj_backup = dfrj.copy()

In [1038]:
# Configurando a quantidade de linhas máximas mostradas em tela

pd.set_option('display.max_columns',1000)
pd.set_option('display.max_rows',1000)

In [1039]:
# Visualização da Tabela

dfrj

Mês    2000    2001    2002    2003    2004    2005    2006    2007  \
0     Janeiro  24.091  15.149   9.921  16.896   6.934  13.027  22.012  21.398   
1   Fevereiro  21.798  13.999   8.755  16.189   6.018  10.838  19.661  19.896   
2       Março  22.463  15.726   9.329  10.315   5.943  12.453  13.710  31.536   
3       Abril  19.821  12.378  11.251   7.618   7.220  12.792  11.615  31.379   
4        Maio  18.887  12.172   9.872   6.389   7.929  12.828  14.102  21.936   
5       Junho  18.428  14.234  10.551   5.252   6.722  12.884  14.593  23.035   
6       Julho  21.406  14.223  16.627   5.846   9.215  14.526  16.831  26.145   
7      Agosto  16.109  12.168  15.742   4.906   7.425  16.426  17.486  27.838   
8    Setembro  16.305  10.177  17.121   5.275   9.174  18.177  20.931  26.912   
9     Outubro  17.833  12.927  20.339   5.504  11.421  16.626  20.324  33.631   
10   Novembro  18.411  11.025  12.850   5.219  16.105  17.154  27.036  45.489   
11   Dezembro  16.637  11.393  15.208   8.769  15.711  22.797  25.953  50.209   

      2008    2009    2010    2011    2012    2013    2014    2015    2016  \
0   45.297  82.615  52.293  67.301  34.052  38.402  59.548  53.956  43.579   
1   43.035  66.727  36.057  65.908  35.499  40.229  55.168  48.695  40.706   
2   49.616  72.006  38.444  52.914  37.483  41.344  49.045  56.049  40.195   
3   53.339  72.193  54.854  32.365  34.451  42.123  48.346  56.688  39.446   
4   53.322  69.365  68.772  39.800  35.377  43.633  47.703  52.261  40.657   
5   51.440  71.289  71.453  45.917  33.830  49.369  43.859  52.640  39.201   
6   54.684  74.320  81.570  36.107  34.058  49.372  45.451  56.140  41.294   
7   55.489  70.265  68.123  40.142  37.807  54.861  45.232  57.553  41.890   
8   59.767  81.295  65.436  35.753  35.576  52.485  46.286  58.529  42.622   
9   70.993  75.680  66.731  37.915  39.038  55.311  48.602  66.537  39.149   
10  65.498  66.503  60.648  36.903  37.026  54.954  45.598  50.552  32.956   
11  74.579  70.555  82.076  40.735  41.080  60.993  55.467  54.714  39.115   

      2017    2018    2019    2020    2021    2022  
0   31.789  49.958  73.913  62.293  56.644  48.583  
1   29.989  43.621  64.489  52.902  50.853  43.063  
2   33.899  49.022  57.507  38.277  52.369  55.017  
3   32.573  44.827  59.917  28.550  46.048  48.968  
4   32.873  45.118  68.794  31.601  55.606  45.010  
5   33.455  52.022  66.513  37.191  47.385  44.110  
6   35.008  57.447  72.010  45.540  54.906     NaN  
7   45.167  71.136  65.349  48.113  53.873     NaN  
8   46.768  75.133  62.760  51.915  58.087     NaN  
9   48.705  84.181  69.158  58.869  56.603     NaN  
10  47.789  79.195  63.714  51.088  51.531     NaN  
11  55.747  94.692  72.856  58.258  58.736     NaN

In [1040]:
# Replace do Mês para numérico

dfrj["Mês"].replace("Janeiro", "01", inplace=True)
dfrj["Mês"].replace("Fevereiro", "02", inplace=True)
dfrj["Mês"].replace("Março", "03", inplace=True)
dfrj["Mês"].replace("Abril", "04", inplace=True)
dfrj["Mês"].replace("Maio", "05", inplace=True)
dfrj["Mês"].replace("Junho", "06", inplace=True)
dfrj["Mês"].replace("Julho", "07", inplace=True)
dfrj["Mês"].replace("Agosto", "08", inplace=True)
dfrj["Mês"].replace("Setembro", "09", inplace=True)
dfrj["Mês"].replace("Outubro", "10", inplace=True)
dfrj["Mês"].replace("Novembro", "11", inplace=True)
dfrj["Mês"].replace("Dezembro", "12", inplace=True)

In [1041]:
# Criação das colunas uf, produto, unid, criado_em
dfrj['uf']='RJ'
dfrj['produto']='Etanol Hidratado'
dfrj['unid']='m3'
dfrj['criado_em'] ='2022-09-10'

In [1042]:
# Despivotar a tabela em ano e volume 
dfrj.reset_index(inplace=True)

In [1043]:
dfrj=dfrj.melt(id_vars = ['Mês', 'uf', 'produto', 'unid', 'criado_em'], value_vars = ['2000', '2001', '2002', '2003', '2004', '2005', '2006', '2007', '2008', '2009', '2010', '2011', '2012', '2013', '2014', '2015', '2016', '2017', '2018', '2019', '2020', '2021', '2022'], var_name='ano', value_name='venda')

In [1044]:
# Visão geral da tabela

dfrj

Mês  uf           produto unid   criado_em   ano   venda
0    01  RJ  Etanol Hidratado   m3  2022-09-10  2000  24.091
1    02  RJ  Etanol Hidratado   m3  2022-09-10  2000  21.798
2    03  RJ  Etanol Hidratado   m3  2022-09-10  2000  22.463
3    04  RJ  Etanol Hidratado   m3  2022-09-10  2000  19.821
4    05  RJ  Etanol Hidratado   m3  2022-09-10  2000  18.887
5    06  RJ  Etanol Hidratado   m3  2022-09-10  2000  18.428
6    07  RJ  Etanol Hidratado   m3  2022-09-10  2000  21.406
7    08  RJ  Etanol Hidratado   m3  2022-09-10  2000  16.109
8    09  RJ  Etanol Hidratado   m3  2022-09-10  2000  16.305
9    10  RJ  Etanol Hidratado   m3  2022-09-10  2000  17.833
10   11  RJ  Etanol Hidratado   m3  2022-09-10  2000  18.411
11   12  RJ  Etanol Hidratado   m3  2022-09-10  2000  16.637
12   01  RJ  Etanol Hidratado   m3  2022-09-10  2001  15.149
13   02  RJ  Etanol Hidratado   m3  2022-09-10  2001  13.999
14   03  RJ  Etanol Hidratado   m3  2022-09-10  2001  15.726
15   04  RJ  Etanol Hidratado   m3  2022-09-10  2001  12.378
16   05  RJ  Etanol Hidratado   m3  2022-09-10  2001  12.172
17   06  RJ  Etanol Hidratado   m3  2022-09-10  2001  14.234
18   07  RJ  Etanol Hidratado   m3  2022-09-10  2001  14.223
19   08  RJ  Etanol Hidratado   m3  2022-09-10  2001  12.168
20   09  RJ  Etanol Hidratado   m3  2022-09-10  2001  10.177
21   10  RJ  Etanol Hidratado   m3  2022-09-10  2001  12.927
22   11  RJ  Etanol Hidratado   m3  2022-09-10  2001  11.025
23   12  RJ  Etanol Hidratado   m3  2022-09-10  2001  11.393
24   01  RJ  Etanol Hidratado   m3  2022-09-10  2002   9.921
25   02  RJ  Etanol Hidratado   m3  2022-09-10  2002   8.755
26   03  RJ  Etanol Hidratado   m3  2022-09-10  2002   9.329
27   04  RJ  Etanol Hidratado   m3  2022-09-10  2002  11.251
28   05  RJ  Etanol Hidratado   m3  2022-09-10  2002   9.872
29   06  RJ  Etanol Hidratado   m3  2022-09-10  2002  10.551
30   07  RJ  Etanol Hidratado   m3  2022-09-10  2002  16.627
31   08  RJ  Etanol Hidratado   m3  2022-09-10  2002  15.742
32   09  RJ  Etanol Hidratado   m3  2022-09-10  2002  17.121
33   10  RJ  Etanol Hidratado   m3  2022-09-10  2002  20.339
34   11  RJ  Etanol Hidratado   m3  2022-09-10  2002  12.850
35   12  RJ  Etanol Hidratado   m3  2022-09-10  2002  15.208
36   01  RJ  Etanol Hidratado   m3  2022-09-10  2003  16.896
37   02  RJ  Etanol Hidratado   m3  2022-09-10  2003  16.189
38   03  RJ  Etanol Hidratado   m3  2022-09-10  2003  10.315
39   04  RJ  Etanol Hidratado   m3  2022-09-10  2003   7.618
40   05  RJ  Etanol Hidratado   m3  2022-09-10  2003   6.389
41   06  RJ  Etanol Hidratado   m3  2022-09-10  2003   5.252
42   07  RJ  Etanol Hidratado   m3  2022-09-10  2003   5.846
43   08  RJ  Etanol Hidratado   m3  2022-09-10  2003   4.906
44   09  RJ  Etanol Hidratado   m3  2022-09-10  2003   5.275
45   10  RJ  Etanol Hidratado   m3  2022-09-10  2003   5.504
46   11  RJ  Etanol Hidratado   m3  2022-09-10  2003   5.219
47   12  RJ  Etanol Hidratado   m3  2022-09-10  2003   8.769
48   01  RJ  Etanol Hidratado   m3  2022-09-10  2004   6.934
49   02  RJ  Etanol Hidratado   m3  2022-09-10  2004   6.018
50   03  RJ  Etanol Hidratado   m3  2022-09-10  2004   5.943
51   04  RJ  Etanol Hidratado   m3  2022-09-10  2004   7.220
52   05  RJ  Etanol Hidratado   m3  2022-09-10  2004   7.929
53   06  RJ  Etanol Hidratado   m3  2022-09-10  2004   6.722
54   07  RJ  Etanol Hidratado   m3  2022-09-10  2004   9.215
55   08  RJ  Etanol Hidratado   m3  2022-09-10  2004   7.425
56   09  RJ  Etanol Hidratado   m3  2022-09-10  2004   9.174
57   10  RJ  Etanol Hidratado   m3  2022-09-10  2004  11.421
58   11  RJ  Etanol Hidratado   m3  2022-09-10  2004  16.105
59   12  RJ  Etanol Hidratado   m3  2022-09-10  2004  15.711
60   01  RJ  Etanol Hidratado   m3  2022-09-10  2005  13.027
61   02  RJ  Etanol Hidratado   m3  2022-09-10  2005  10.838
62   03  RJ  Etanol Hidratado   m3  2022-09-10  2005  12.453
63   04  RJ  Etanol Hidratado   m3  2022-09-10  2005  12.792
64   05  RJ  Etanol Hidratado   m3  202

In [1045]:
# Concatenando as colunas ano e Mês
dfrj['ano_mês'] = dfrj[['ano', 'Mês']].agg('-'.join, axis=1)

In [1046]:
# Eliminando as colunas Mês e ano

dfrj.drop(["Mês"], axis=1, inplace=True)
dfrj.drop(["ano"], axis=1, inplace=True)

In [1047]:
# Organização da ordem das colunas

dfrj=dfrj[['ano_mês', 'uf', 'produto', 'unid', 'venda', 'criado_em']]

In [1048]:
# Levantamento de possíveis inconsistências

dfrj.isna().sum()

ano_mês      0
uf           0
produto      0
unid         0
venda        6
criado_em    0
dtype: int64

In [1049]:
# Tratamento das inconsistências

dfrj.replace(['Na', 'nA', 'na','NA', 'NaN', 'NAN', 'nan', '', ' '],pd.NA,inplace=True)


In [1050]:
# Visão geral da tabela

dfrj

ano_mês  uf           produto unid   venda   criado_em
0    2000-01  RJ  Etanol Hidratado   m3  24.091  2022-09-10
1    2000-02  RJ  Etanol Hidratado   m3  21.798  2022-09-10
2    2000-03  RJ  Etanol Hidratado   m3  22.463  2022-09-10
3    2000-04  RJ  Etanol Hidratado   m3  19.821  2022-09-10
4    2000-05  RJ  Etanol Hidratado   m3  18.887  2022-09-10
5    2000-06  RJ  Etanol Hidratado   m3  18.428  2022-09-10
6    2000-07  RJ  Etanol Hidratado   m3  21.406  2022-09-10
7    2000-08  RJ  Etanol Hidratado   m3  16.109  2022-09-10
8    2000-09  RJ  Etanol Hidratado   m3  16.305  2022-09-10
9    2000-10  RJ  Etanol Hidratado   m3  17.833  2022-09-10
10   2000-11  RJ  Etanol Hidratado   m3  18.411  2022-09-10
11   2000-12  RJ  Etanol Hidratado   m3  16.637  2022-09-10
12   2001-01  RJ  Etanol Hidratado   m3  15.149  2022-09-10
13   2001-02  RJ  Etanol Hidratado   m3  13.999  2022-09-10
14   2001-03  RJ  Etanol Hidratado   m3  15.726  2022-09-10
15   2001-04  RJ  Etanol Hidratado   m3  12.378  2022-09-10
16   2001-05  RJ  Etanol Hidratado   m3  12.172  2022-09-10
17   2001-06  RJ  Etanol Hidratado   m3  14.234  2022-09-10
18   2001-07  RJ  Etanol Hidratado   m3  14.223  2022-09-10
19   2001-08  RJ  Etanol Hidratado   m3  12.168  2022-09-10
20   2001-09  RJ  Etanol Hidratado   m3  10.177  2022-09-10
21   2001-10  RJ  Etanol Hidratado   m3  12.927  2022-09-10
22   2001-11  RJ  Etanol Hidratado   m3  11.025  2022-09-10
23   2001-12  RJ  Etanol Hidratado   m3  11.393  2022-09-10
24   2002-01  RJ  Etanol Hidratado   m3   9.921  2022-09-10
25   2002-02  RJ  Etanol Hidratado   m3   8.755  2022-09-10
26   2002-03  RJ  Etanol Hidratado   m3   9.329  2022-09-10
27   2002-04  RJ  Etanol Hidratado   m3  11.251  2022-09-10
28   2002-05  RJ  Etanol Hidratado   m3   9.872  2022-09-10
29   2002-06  RJ  Etanol Hidratado   m3  10.551  2022-09-10
30   2002-07  RJ  Etanol Hidratado   m3  16.627  2022-09-10
31   2002-08  RJ  Etanol Hidratado   m3  15.742  2022-09-10
32   2002-09  RJ  Etanol Hidratado   m3  17.121  2022-09-10
33   2002-10  RJ  Etanol Hidratado   m3  20.339  2022-09-10
34   2002-11  RJ  Etanol Hidratado   m3  12.850  2022-09-10
35   2002-12  RJ  Etanol Hidratado   m3  15.208  2022-09-10
36   2003-01  RJ  Etanol Hidratado   m3  16.896  2022-09-10
37   2003-02  RJ  Etanol Hidratado   m3  16.189  2022-09-10
38   2003-03  RJ  Etanol Hidratado   m3  10.315  2022-09-10
39   2003-04  RJ  Etanol Hidratado   m3   7.618  2022-09-10
40   2003-05  RJ  Etanol Hidratado   m3   6.389  2022-09-10
41   2003-06  RJ  Etanol Hidratado   m3   5.252  2022-09-10
42   2003-07  RJ  Etanol Hidratado   m3   5.846  2022-09-10
43   2003-08  RJ  Etanol Hidratado   m3   4.906  2022-09-10
44   2003-09  RJ  Etanol Hidratado   m3   5.275  2022-09-10
45   2003-10  RJ  Etanol Hidratado   m3   5.504  2022-09-10
46   2003-11  RJ  Etanol Hidratado   m3   5.219  2022-09-10
47   2003-12  RJ  Etanol Hidratado   m3   8.769  2022-09-10
48   2004-01  RJ  Etanol Hidratado   m3   6.934  2022-09-10
49   2004-02  RJ  Etanol Hidratado   m3   6.018  2022-09-10
50   2004-03  RJ  Etanol Hidratado   m3   5.943  2022-09-10
51   2004-04  RJ  Etanol Hidratado   m3   7.220  2022-09-10
52   2004-05  RJ  Etanol Hidratado   m3   7.929  2022-09-10
53   2004-06  RJ  Etanol Hidratado   m3   6.722  2022-09-10
54   2004-07  RJ  Etanol Hidratado   m3   9.215  2022-09-10
55   2004-08  RJ  Etanol Hidratado   m3   7.425  2022-09-10
56   2004-09  RJ  Etanol Hidratado   m3   9.174  2022-09-10
57   2004-10  RJ  Etanol Hidratado   m3  11.421  2022-09-10
58   2004-11  RJ  Etanol Hidratado   m3  16.105  2022-09-10
59   2004-12  RJ  Etanol Hidratado   m3  15.711  2022-09-10
60   2005-01  RJ  Etanol Hidratado   m3  13.027  2022-09-10
61   2005-02  RJ  Etanol Hidratado   m3  10.838  2022-09-10
62   2005-03  RJ  Etanol Hidratado   m3  12.453  2022-09-10
63   2005-04  RJ  Etanol Hidratado   m3  12.792  2022-09-10
64   2005-05  RJ  Etanol Hidratado   m3  12.828  2022-09-10
65   2005-06  RJ  Etanol Hidratado   m3  12.8

In [1051]:
# Verificando os tipos

dfrj.dtypes

ano_mês       object
uf            object
produto       object
unid          object
venda        float64
criado_em     object
dtype: object

In [1052]:
# Validação

schema = pa.DataFrameSchema(
    columns = {
        'ano_mês': pa.Column(pa.String, nullable=True),
        'uf': pa.Column(pa.String, nullable = True),
        'produto': pa.Column(pa.String, nullable = True),
        'unid': pa.Column(pa.String, nullable = True),
        'venda': pa.Column(pa.Float, nullable = True),
        'criado_em': pa.Column(pa.String, nullable = True),
                
    }
)
schema.validate(dfrj)

ano_mês  uf           produto unid   venda   criado_em
0    2000-01  RJ  Etanol Hidratado   m3  24.091  2022-09-10
1    2000-02  RJ  Etanol Hidratado   m3  21.798  2022-09-10
2    2000-03  RJ  Etanol Hidratado   m3  22.463  2022-09-10
3    2000-04  RJ  Etanol Hidratado   m3  19.821  2022-09-10
4    2000-05  RJ  Etanol Hidratado   m3  18.887  2022-09-10
5    2000-06  RJ  Etanol Hidratado   m3  18.428  2022-09-10
6    2000-07  RJ  Etanol Hidratado   m3  21.406  2022-09-10
7    2000-08  RJ  Etanol Hidratado   m3  16.109  2022-09-10
8    2000-09  RJ  Etanol Hidratado   m3  16.305  2022-09-10
9    2000-10  RJ  Etanol Hidratado   m3  17.833  2022-09-10
10   2000-11  RJ  Etanol Hidratado   m3  18.411  2022-09-10
11   2000-12  RJ  Etanol Hidratado   m3  16.637  2022-09-10
12   2001-01  RJ  Etanol Hidratado   m3  15.149  2022-09-10
13   2001-02  RJ  Etanol Hidratado   m3  13.999  2022-09-10
14   2001-03  RJ  Etanol Hidratado   m3  15.726  2022-09-10
15   2001-04  RJ  Etanol Hidratado   m3  12.378  2022-09-10
16   2001-05  RJ  Etanol Hidratado   m3  12.172  2022-09-10
17   2001-06  RJ  Etanol Hidratado   m3  14.234  2022-09-10
18   2001-07  RJ  Etanol Hidratado   m3  14.223  2022-09-10
19   2001-08  RJ  Etanol Hidratado   m3  12.168  2022-09-10
20   2001-09  RJ  Etanol Hidratado   m3  10.177  2022-09-10
21   2001-10  RJ  Etanol Hidratado   m3  12.927  2022-09-10
22   2001-11  RJ  Etanol Hidratado   m3  11.025  2022-09-10
23   2001-12  RJ  Etanol Hidratado   m3  11.393  2022-09-10
24   2002-01  RJ  Etanol Hidratado   m3   9.921  2022-09-10
25   2002-02  RJ  Etanol Hidratado   m3   8.755  2022-09-10
26   2002-03  RJ  Etanol Hidratado   m3   9.329  2022-09-10
27   2002-04  RJ  Etanol Hidratado   m3  11.251  2022-09-10
28   2002-05  RJ  Etanol Hidratado   m3   9.872  2022-09-10
29   2002-06  RJ  Etanol Hidratado   m3  10.551  2022-09-10
30   2002-07  RJ  Etanol Hidratado   m3  16.627  2022-09-10
31   2002-08  RJ  Etanol Hidratado   m3  15.742  2022-09-10
32   2002-09  RJ  Etanol Hidratado   m3  17.121  2022-09-10
33   2002-10  RJ  Etanol Hidratado   m3  20.339  2022-09-10
34   2002-11  RJ  Etanol Hidratado   m3  12.850  2022-09-10
35   2002-12  RJ  Etanol Hidratado   m3  15.208  2022-09-10
36   2003-01  RJ  Etanol Hidratado   m3  16.896  2022-09-10
37   2003-02  RJ  Etanol Hidratado   m3  16.189  2022-09-10
38   2003-03  RJ  Etanol Hidratado   m3  10.315  2022-09-10
39   2003-04  RJ  Etanol Hidratado   m3   7.618  2022-09-10
40   2003-05  RJ  Etanol Hidratado   m3   6.389  2022-09-10
41   2003-06  RJ  Etanol Hidratado   m3   5.252  2022-09-10
42   2003-07  RJ  Etanol Hidratado   m3   5.846  2022-09-10
43   2003-08  RJ  Etanol Hidratado   m3   4.906  2022-09-10
44   2003-09  RJ  Etanol Hidratado   m3   5.275  2022-09-10
45   2003-10  RJ  Etanol Hidratado   m3   5.504  2022-09-10
46   2003-11  RJ  Etanol Hidratado   m3   5.219  2022-09-10
47   2003-12  RJ  Etanol Hidratado   m3   8.769  2022-09-10
48   2004-01  RJ  Etanol Hidratado   m3   6.934  2022-09-10
49   2004-02  RJ  Etanol Hidratado   m3   6.018  2022-09-10
50   2004-03  RJ  Etanol Hidratado   m3   5.943  2022-09-10
51   2004-04  RJ  Etanol Hidratado   m3   7.220  2022-09-10
52   2004-05  RJ  Etanol Hidratado   m3   7.929  2022-09-10
53   2004-06  RJ  Etanol Hidratado   m3   6.722  2022-09-10
54   2004-07  RJ  Etanol Hidratado   m3   9.215  2022-09-10
55   2004-08  RJ  Etanol Hidratado   m3   7.425  2022-09-10
56   2004-09  RJ  Etanol Hidratado   m3   9.174  2022-09-10
57   2004-10  RJ  Etanol Hidratado   m3  11.421  2022-09-10
58   2004-11  RJ  Etanol Hidratado   m3  16.105  2022-09-10
59   2004-12  RJ  Etanol Hidratado   m3  15.711  2022-09-10
60   2005-01  RJ  Etanol Hidratado   m3  13.027  2022-09-10
61   2005-02  RJ  Etanol Hidratado   m3  10.838  2022-09-10
62   2005-03  RJ  Etanol Hidratado   m3  12.453  2022-09-10
63   2005-04  RJ  Etanol Hidratado   m3  12.792  2022-09-10
64   2005-05  RJ  Etanol Hidratado   m3  12.828  2022-09-10
65   2005-06  RJ  Etanol Hidratado   m3  12.8

In [1053]:
dfrj_pandas = dfrj.copy()

##RIO GRANDE DO NORTE


In [1054]:
# Conector

dfrn = pd.read_csv('/content/rio_grande_do_norte.csv',sep=';')

In [1055]:
# Backup
dfrn_backup = dfrn.copy()

In [1056]:
# Configurando a quantidade de linhas máximas mostradas em tela

pd.set_option('display.max_columns',1000)
pd.set_option('display.max_rows',1000)

In [1057]:
# Visualização da Tabela

dfrn

Mês   2000   2001   2002   2003   2004   2005   2006   2007   2008  \
0     Janeiro  3.851  2.298  1.747  1.886  1.620  1.740  2.860  4.623  8.048   
1   Fevereiro  3.151  2.344  1.612  1.651  1.504  1.535  2.663  4.072  7.039   
2       Março  3.412  1.987  1.544  1.307  1.624  1.984  3.060  4.828  8.868   
3       Abril  3.038  2.196  2.076  1.316  1.929  1.969  2.280  4.593  8.151   
4        Maio  3.106  2.095  2.070  1.213  2.470  1.920  2.169  4.863  8.377   
5       Junho  2.490  2.305  1.735  1.172  2.272  2.011  2.345  4.833  8.230   
6       Julho  3.636  2.034  1.972  1.378  2.286  2.257  2.388  5.822  8.500   
7      Agosto  3.381  2.202  1.987  1.659  1.945  2.651  2.736  6.246  6.877   
8    Setembro  3.020  2.072  1.922  1.509  1.961  2.311  2.590  5.870  7.341   
9     Outubro  2.985  2.422  2.298  1.605  2.052  2.324  2.927  6.832  7.718   
10   Novembro  2.739  1.883  1.630  1.528  1.798  2.530  3.396  7.371  7.060   
11   Dezembro  2.769  1.831  1.639  1.788  1.894  3.269  3.958  7.433  8.504   

     2009   2010   2011   2012   2013   2014   2015   2016   2017    2018  \
0   8.455  7.217  7.932  3.530  4.592  4.462  4.045  5.624  4.865   8.101   
1   6.770  4.044  6.902  3.519  4.578  3.683  5.485  5.119  4.166   7.220   
2   8.072  5.336  5.937  4.161  4.166  3.510  5.943  4.945  4.427   7.126   
3   8.498  6.137  3.800  3.869  4.207  3.580  5.820  4.183  3.629   5.736   
4   7.654  6.684  3.974  3.991  3.897  3.506  5.498  4.467  3.682   6.285   
5   7.888  7.027  4.412  3.724  3.610  3.184  5.511  4.274  3.346   8.396   
6   9.125  7.747  4.244  3.681  3.757  3.323  5.385  4.056  3.422   6.348   
7   8.952  6.711  3.955  3.724  3.823  3.093  5.357  4.254  4.443   7.435   
8   8.665  6.880  3.426  3.553  3.511  3.232  5.316  4.225  4.541   9.738   
9   8.739  6.440  3.150  3.973  3.766  3.515  7.502  4.327  4.542  11.521   
10  7.803  6.802  3.414  3.810  3.416  3.415  6.081  4.309  5.887  10.857   
11  7.752  8.131  4.125  4.517  4.695  4.155  6.957  5.020  7.391  12.205   

      2019    2020   2021   2022  
0   10.473  10.125  8.619  5.123  
1    8.381   8.627  9.493  4.994  
2    8.868   6.644  8.799  7.641  
3    8.880   3.897  6.379  8.102  
4    8.670   2.906  6.387  6.832  
5    6.656   3.646  5.499  5.686  
6    7.214   5.267  4.664    NaN  
7    6.445   5.488  3.601    NaN  
8    6.638   5.797  7.437    NaN  
9    7.839   7.351  4.728    NaN  
10   7.516   7.730  6.223    NaN  
11  10.464   8.683  5.124    NaN

In [1058]:
# Replace do Mês para numérico

dfrn["Mês"].replace("Janeiro", "01", inplace=True)
dfrn["Mês"].replace("Fevereiro", "02", inplace=True)
dfrn["Mês"].replace("Março", "03", inplace=True)
dfrn["Mês"].replace("Abril", "04", inplace=True)
dfrn["Mês"].replace("Maio", "05", inplace=True)
dfrn["Mês"].replace("Junho", "06", inplace=True)
dfrn["Mês"].replace("Julho", "07", inplace=True)
dfrn["Mês"].replace("Agosto", "08", inplace=True)
dfrn["Mês"].replace("Setembro", "09", inplace=True)
dfrn["Mês"].replace("Outubro", "10", inplace=True)
dfrn["Mês"].replace("Novembro", "11", inplace=True)
dfrn["Mês"].replace("Dezembro", "12", inplace=True)

In [1059]:
# Criação das colunas uf, produto, unid, criado_em
dfrn['uf']='RN'
dfrn['produto']='Etanol Hidratado'
dfrn['unid']='m3'
dfrn['criado_em'] ='2022-09-10'

In [1060]:
# Despivotar a tabela em ano e volume 
dfrn.reset_index(inplace=True)

In [1061]:
dfrn=dfrn.melt(id_vars = ['Mês', 'uf', 'produto', 'unid', 'criado_em'], value_vars = ['2000', '2001', '2002', '2003', '2004', '2005', '2006', '2007', '2008', '2009', '2010', '2011', '2012', '2013', '2014', '2015', '2016', '2017', '2018', '2019', '2020', '2021', '2022'], var_name='ano', value_name='venda')

In [1062]:
# Visão geral da tabela

dfrn

Mês  uf           produto unid   criado_em   ano   venda
0    01  RN  Etanol Hidratado   m3  2022-09-10  2000   3.851
1    02  RN  Etanol Hidratado   m3  2022-09-10  2000   3.151
2    03  RN  Etanol Hidratado   m3  2022-09-10  2000   3.412
3    04  RN  Etanol Hidratado   m3  2022-09-10  2000   3.038
4    05  RN  Etanol Hidratado   m3  2022-09-10  2000   3.106
5    06  RN  Etanol Hidratado   m3  2022-09-10  2000   2.490
6    07  RN  Etanol Hidratado   m3  2022-09-10  2000   3.636
7    08  RN  Etanol Hidratado   m3  2022-09-10  2000   3.381
8    09  RN  Etanol Hidratado   m3  2022-09-10  2000   3.020
9    10  RN  Etanol Hidratado   m3  2022-09-10  2000   2.985
10   11  RN  Etanol Hidratado   m3  2022-09-10  2000   2.739
11   12  RN  Etanol Hidratado   m3  2022-09-10  2000   2.769
12   01  RN  Etanol Hidratado   m3  2022-09-10  2001   2.298
13   02  RN  Etanol Hidratado   m3  2022-09-10  2001   2.344
14   03  RN  Etanol Hidratado   m3  2022-09-10  2001   1.987
15   04  RN  Etanol Hidratado   m3  2022-09-10  2001   2.196
16   05  RN  Etanol Hidratado   m3  2022-09-10  2001   2.095
17   06  RN  Etanol Hidratado   m3  2022-09-10  2001   2.305
18   07  RN  Etanol Hidratado   m3  2022-09-10  2001   2.034
19   08  RN  Etanol Hidratado   m3  2022-09-10  2001   2.202
20   09  RN  Etanol Hidratado   m3  2022-09-10  2001   2.072
21   10  RN  Etanol Hidratado   m3  2022-09-10  2001   2.422
22   11  RN  Etanol Hidratado   m3  2022-09-10  2001   1.883
23   12  RN  Etanol Hidratado   m3  2022-09-10  2001   1.831
24   01  RN  Etanol Hidratado   m3  2022-09-10  2002   1.747
25   02  RN  Etanol Hidratado   m3  2022-09-10  2002   1.612
26   03  RN  Etanol Hidratado   m3  2022-09-10  2002   1.544
27   04  RN  Etanol Hidratado   m3  2022-09-10  2002   2.076
28   05  RN  Etanol Hidratado   m3  2022-09-10  2002   2.070
29   06  RN  Etanol Hidratado   m3  2022-09-10  2002   1.735
30   07  RN  Etanol Hidratado   m3  2022-09-10  2002   1.972
31   08  RN  Etanol Hidratado   m3  2022-09-10  2002   1.987
32   09  RN  Etanol Hidratado   m3  2022-09-10  2002   1.922
33   10  RN  Etanol Hidratado   m3  2022-09-10  2002   2.298
34   11  RN  Etanol Hidratado   m3  2022-09-10  2002   1.630
35   12  RN  Etanol Hidratado   m3  2022-09-10  2002   1.639
36   01  RN  Etanol Hidratado   m3  2022-09-10  2003   1.886
37   02  RN  Etanol Hidratado   m3  2022-09-10  2003   1.651
38   03  RN  Etanol Hidratado   m3  2022-09-10  2003   1.307
39   04  RN  Etanol Hidratado   m3  2022-09-10  2003   1.316
40   05  RN  Etanol Hidratado   m3  2022-09-10  2003   1.213
41   06  RN  Etanol Hidratado   m3  2022-09-10  2003   1.172
42   07  RN  Etanol Hidratado   m3  2022-09-10  2003   1.378
43   08  RN  Etanol Hidratado   m3  2022-09-10  2003   1.659
44   09  RN  Etanol Hidratado   m3  2022-09-10  2003   1.509
45   10  RN  Etanol Hidratado   m3  2022-09-10  2003   1.605
46   11  RN  Etanol Hidratado   m3  2022-09-10  2003   1.528
47   12  RN  Etanol Hidratado   m3  2022-09-10  2003   1.788
48   01  RN  Etanol Hidratado   m3  2022-09-10  2004   1.620
49   02  RN  Etanol Hidratado   m3  2022-09-10  2004   1.504
50   03  RN  Etanol Hidratado   m3  2022-09-10  2004   1.624
51   04  RN  Etanol Hidratado   m3  2022-09-10  2004   1.929
52   05  RN  Etanol Hidratado   m3  2022-09-10  2004   2.470
53   06  RN  Etanol Hidratado   m3  2022-09-10  2004   2.272
54   07  RN  Etanol Hidratado   m3  2022-09-10  2004   2.286
55   08  RN  Etanol Hidratado   m3  2022-09-10  2004   1.945
56   09  RN  Etanol Hidratado   m3  2022-09-10  2004   1.961
57   10  RN  Etanol Hidratado   m3  2022-09-10  2004   2.052
58   11  RN  Etanol Hidratado   m3  2022-09-10  2004   1.798
59   12  RN  Etanol Hidratado   m3  2022-09-10  2004   1.894
60   01  RN  Etanol Hidratado   m3  2022-09-10  2005   1.740
61   02  RN  Etanol Hidratado   m3  2022-09-10  2005   1.535
62   03  RN  Etanol Hidratado   m3  2022-09-10  2005   1.984
63   04  RN  Etanol Hidratado   m3  2022-09-10  2005   1.969
64   05  RN  Etanol Hidratado   m3  202

In [1063]:
# Concatenando as colunas ano e Mês
dfrn['ano_mês'] = dfrn[['ano', 'Mês']].agg('-'.join, axis=1)

In [1064]:
# Eliminando as colunas Mês e ano

dfrn.drop(["Mês"], axis=1, inplace=True)
dfrn.drop(["ano"], axis=1, inplace=True)

In [1065]:
# Organização da ordem das colunas

dfrn=dfrn[['ano_mês', 'uf', 'produto', 'unid', 'venda', 'criado_em']]

In [1066]:
# Levantamento de possíveis inconsistências

dfrn.isna().sum()

ano_mês      0
uf           0
produto      0
unid         0
venda        6
criado_em    0
dtype: int64

In [1067]:
# Tratamento das inconsistências

dfrn.replace(['Na', 'nA', 'na','NA', 'NaN', 'NAN', 'nan', '', ' '],pd.NA,inplace=True)


In [1068]:
# Visão geral da tabela

dfrn

ano_mês  uf           produto unid   venda   criado_em
0    2000-01  RN  Etanol Hidratado   m3   3.851  2022-09-10
1    2000-02  RN  Etanol Hidratado   m3   3.151  2022-09-10
2    2000-03  RN  Etanol Hidratado   m3   3.412  2022-09-10
3    2000-04  RN  Etanol Hidratado   m3   3.038  2022-09-10
4    2000-05  RN  Etanol Hidratado   m3   3.106  2022-09-10
5    2000-06  RN  Etanol Hidratado   m3   2.490  2022-09-10
6    2000-07  RN  Etanol Hidratado   m3   3.636  2022-09-10
7    2000-08  RN  Etanol Hidratado   m3   3.381  2022-09-10
8    2000-09  RN  Etanol Hidratado   m3   3.020  2022-09-10
9    2000-10  RN  Etanol Hidratado   m3   2.985  2022-09-10
10   2000-11  RN  Etanol Hidratado   m3   2.739  2022-09-10
11   2000-12  RN  Etanol Hidratado   m3   2.769  2022-09-10
12   2001-01  RN  Etanol Hidratado   m3   2.298  2022-09-10
13   2001-02  RN  Etanol Hidratado   m3   2.344  2022-09-10
14   2001-03  RN  Etanol Hidratado   m3   1.987  2022-09-10
15   2001-04  RN  Etanol Hidratado   m3   2.196  2022-09-10
16   2001-05  RN  Etanol Hidratado   m3   2.095  2022-09-10
17   2001-06  RN  Etanol Hidratado   m3   2.305  2022-09-10
18   2001-07  RN  Etanol Hidratado   m3   2.034  2022-09-10
19   2001-08  RN  Etanol Hidratado   m3   2.202  2022-09-10
20   2001-09  RN  Etanol Hidratado   m3   2.072  2022-09-10
21   2001-10  RN  Etanol Hidratado   m3   2.422  2022-09-10
22   2001-11  RN  Etanol Hidratado   m3   1.883  2022-09-10
23   2001-12  RN  Etanol Hidratado   m3   1.831  2022-09-10
24   2002-01  RN  Etanol Hidratado   m3   1.747  2022-09-10
25   2002-02  RN  Etanol Hidratado   m3   1.612  2022-09-10
26   2002-03  RN  Etanol Hidratado   m3   1.544  2022-09-10
27   2002-04  RN  Etanol Hidratado   m3   2.076  2022-09-10
28   2002-05  RN  Etanol Hidratado   m3   2.070  2022-09-10
29   2002-06  RN  Etanol Hidratado   m3   1.735  2022-09-10
30   2002-07  RN  Etanol Hidratado   m3   1.972  2022-09-10
31   2002-08  RN  Etanol Hidratado   m3   1.987  2022-09-10
32   2002-09  RN  Etanol Hidratado   m3   1.922  2022-09-10
33   2002-10  RN  Etanol Hidratado   m3   2.298  2022-09-10
34   2002-11  RN  Etanol Hidratado   m3   1.630  2022-09-10
35   2002-12  RN  Etanol Hidratado   m3   1.639  2022-09-10
36   2003-01  RN  Etanol Hidratado   m3   1.886  2022-09-10
37   2003-02  RN  Etanol Hidratado   m3   1.651  2022-09-10
38   2003-03  RN  Etanol Hidratado   m3   1.307  2022-09-10
39   2003-04  RN  Etanol Hidratado   m3   1.316  2022-09-10
40   2003-05  RN  Etanol Hidratado   m3   1.213  2022-09-10
41   2003-06  RN  Etanol Hidratado   m3   1.172  2022-09-10
42   2003-07  RN  Etanol Hidratado   m3   1.378  2022-09-10
43   2003-08  RN  Etanol Hidratado   m3   1.659  2022-09-10
44   2003-09  RN  Etanol Hidratado   m3   1.509  2022-09-10
45   2003-10  RN  Etanol Hidratado   m3   1.605  2022-09-10
46   2003-11  RN  Etanol Hidratado   m3   1.528  2022-09-10
47   2003-12  RN  Etanol Hidratado   m3   1.788  2022-09-10
48   2004-01  RN  Etanol Hidratado   m3   1.620  2022-09-10
49   2004-02  RN  Etanol Hidratado   m3   1.504  2022-09-10
50   2004-03  RN  Etanol Hidratado   m3   1.624  2022-09-10
51   2004-04  RN  Etanol Hidratado   m3   1.929  2022-09-10
52   2004-05  RN  Etanol Hidratado   m3   2.470  2022-09-10
53   2004-06  RN  Etanol Hidratado   m3   2.272  2022-09-10
54   2004-07  RN  Etanol Hidratado   m3   2.286  2022-09-10
55   2004-08  RN  Etanol Hidratado   m3   1.945  2022-09-10
56   2004-09  RN  Etanol Hidratado   m3   1.961  2022-09-10
57   2004-10  RN  Etanol Hidratado   m3   2.052  2022-09-10
58   2004-11  RN  Etanol Hidratado   m3   1.798  2022-09-10
59   2004-12  RN  Etanol Hidratado   m3   1.894  2022-09-10
60   2005-01  RN  Etanol Hidratado   m3   1.740  2022-09-10
61   2005-02  RN  Etanol Hidratado   m3   1.535  2022-09-10
62   2005-03  RN  Etanol Hidratado   m3   1.984  2022-09-10
63   2005-04  RN  Etanol Hidratado   m3   1.969  2022-09-10
64   2005-05  RN  Etanol Hidratado   m3   1.920  2022-09-10
65   2005-06  RN  Etanol Hidratado   m3   2.0

In [1069]:
# Verificando os tipos

dfrn.dtypes

ano_mês       object
uf            object
produto       object
unid          object
venda        float64
criado_em     object
dtype: object

In [1070]:
# Validação

schema = pa.DataFrameSchema(
    columns = {
        'ano_mês': pa.Column(pa.String, nullable=True),
        'uf': pa.Column(pa.String, nullable = True),
        'produto': pa.Column(pa.String, nullable = True),
        'unid': pa.Column(pa.String, nullable = True),
        'venda': pa.Column(pa.Float, nullable = True),
        'criado_em': pa.Column(pa.String, nullable = True),
                
    }
)
schema.validate(dfrn)

ano_mês  uf           produto unid   venda   criado_em
0    2000-01  RN  Etanol Hidratado   m3   3.851  2022-09-10
1    2000-02  RN  Etanol Hidratado   m3   3.151  2022-09-10
2    2000-03  RN  Etanol Hidratado   m3   3.412  2022-09-10
3    2000-04  RN  Etanol Hidratado   m3   3.038  2022-09-10
4    2000-05  RN  Etanol Hidratado   m3   3.106  2022-09-10
5    2000-06  RN  Etanol Hidratado   m3   2.490  2022-09-10
6    2000-07  RN  Etanol Hidratado   m3   3.636  2022-09-10
7    2000-08  RN  Etanol Hidratado   m3   3.381  2022-09-10
8    2000-09  RN  Etanol Hidratado   m3   3.020  2022-09-10
9    2000-10  RN  Etanol Hidratado   m3   2.985  2022-09-10
10   2000-11  RN  Etanol Hidratado   m3   2.739  2022-09-10
11   2000-12  RN  Etanol Hidratado   m3   2.769  2022-09-10
12   2001-01  RN  Etanol Hidratado   m3   2.298  2022-09-10
13   2001-02  RN  Etanol Hidratado   m3   2.344  2022-09-10
14   2001-03  RN  Etanol Hidratado   m3   1.987  2022-09-10
15   2001-04  RN  Etanol Hidratado   m3   2.196  2022-09-10
16   2001-05  RN  Etanol Hidratado   m3   2.095  2022-09-10
17   2001-06  RN  Etanol Hidratado   m3   2.305  2022-09-10
18   2001-07  RN  Etanol Hidratado   m3   2.034  2022-09-10
19   2001-08  RN  Etanol Hidratado   m3   2.202  2022-09-10
20   2001-09  RN  Etanol Hidratado   m3   2.072  2022-09-10
21   2001-10  RN  Etanol Hidratado   m3   2.422  2022-09-10
22   2001-11  RN  Etanol Hidratado   m3   1.883  2022-09-10
23   2001-12  RN  Etanol Hidratado   m3   1.831  2022-09-10
24   2002-01  RN  Etanol Hidratado   m3   1.747  2022-09-10
25   2002-02  RN  Etanol Hidratado   m3   1.612  2022-09-10
26   2002-03  RN  Etanol Hidratado   m3   1.544  2022-09-10
27   2002-04  RN  Etanol Hidratado   m3   2.076  2022-09-10
28   2002-05  RN  Etanol Hidratado   m3   2.070  2022-09-10
29   2002-06  RN  Etanol Hidratado   m3   1.735  2022-09-10
30   2002-07  RN  Etanol Hidratado   m3   1.972  2022-09-10
31   2002-08  RN  Etanol Hidratado   m3   1.987  2022-09-10
32   2002-09  RN  Etanol Hidratado   m3   1.922  2022-09-10
33   2002-10  RN  Etanol Hidratado   m3   2.298  2022-09-10
34   2002-11  RN  Etanol Hidratado   m3   1.630  2022-09-10
35   2002-12  RN  Etanol Hidratado   m3   1.639  2022-09-10
36   2003-01  RN  Etanol Hidratado   m3   1.886  2022-09-10
37   2003-02  RN  Etanol Hidratado   m3   1.651  2022-09-10
38   2003-03  RN  Etanol Hidratado   m3   1.307  2022-09-10
39   2003-04  RN  Etanol Hidratado   m3   1.316  2022-09-10
40   2003-05  RN  Etanol Hidratado   m3   1.213  2022-09-10
41   2003-06  RN  Etanol Hidratado   m3   1.172  2022-09-10
42   2003-07  RN  Etanol Hidratado   m3   1.378  2022-09-10
43   2003-08  RN  Etanol Hidratado   m3   1.659  2022-09-10
44   2003-09  RN  Etanol Hidratado   m3   1.509  2022-09-10
45   2003-10  RN  Etanol Hidratado   m3   1.605  2022-09-10
46   2003-11  RN  Etanol Hidratado   m3   1.528  2022-09-10
47   2003-12  RN  Etanol Hidratado   m3   1.788  2022-09-10
48   2004-01  RN  Etanol Hidratado   m3   1.620  2022-09-10
49   2004-02  RN  Etanol Hidratado   m3   1.504  2022-09-10
50   2004-03  RN  Etanol Hidratado   m3   1.624  2022-09-10
51   2004-04  RN  Etanol Hidratado   m3   1.929  2022-09-10
52   2004-05  RN  Etanol Hidratado   m3   2.470  2022-09-10
53   2004-06  RN  Etanol Hidratado   m3   2.272  2022-09-10
54   2004-07  RN  Etanol Hidratado   m3   2.286  2022-09-10
55   2004-08  RN  Etanol Hidratado   m3   1.945  2022-09-10
56   2004-09  RN  Etanol Hidratado   m3   1.961  2022-09-10
57   2004-10  RN  Etanol Hidratado   m3   2.052  2022-09-10
58   2004-11  RN  Etanol Hidratado   m3   1.798  2022-09-10
59   2004-12  RN  Etanol Hidratado   m3   1.894  2022-09-10
60   2005-01  RN  Etanol Hidratado   m3   1.740  2022-09-10
61   2005-02  RN  Etanol Hidratado   m3   1.535  2022-09-10
62   2005-03  RN  Etanol Hidratado   m3   1.984  2022-09-10
63   2005-04  RN  Etanol Hidratado   m3   1.969  2022-09-10
64   2005-05  RN  Etanol Hidratado   m3   1.920  2022-09-10
65   2005-06  RN  Etanol Hidratado   m3   2.0

In [1071]:
dfrn_pandas = dfrn.copy()

##RONDÔNIA

In [1072]:
# Conector

dfro = pd.read_csv('/content/rondonia.csv',sep=';')

In [1073]:
# Backup
dfro_backup = dfro.copy()

In [1074]:
# Configurando a quantidade de linhas máximas mostradas em tela

pd.set_option('display.max_columns',1000)
pd.set_option('display.max_rows',1000)

In [1075]:
# Visualização da Tabela

dfro

Mês   2000     2001     2002     2003     2004     2005     2006  \
0     Janeiro  1.499    1.197  958.000    1.363    1.172    1.065  920.000   
1   Fevereiro  3.594  905.000    1.014  998.000    1.014    1.083  849.000   
2       Março  2.596  924.000  934.000  989.000  891.000    1.051  565.000   
3       Abril  2.922    1.113    1.157  875.000  869.000  772.000  550.000   
4        Maio  3.446    1.108    1.194    1.085    1.117    1.055  845.000   
5       Junho  1.104    1.109  940.000    1.025  793.000    1.103  807.000   
6       Julho  1.331    1.098    1.253  951.000    1.017    1.323  888.000   
7      Agosto  1.749    1.147    1.246    1.012    1.208    1.279  971.000   
8    Setembro  1.531    1.032    1.363  949.000    1.027    1.211  947.000   
9     Outubro  1.517    1.126    1.691  923.000    1.091    1.049    1.085   
10   Novembro  1.181  648.000    1.344  774.000    1.171    1.223    1.027   
11   Dezembro  1.151  941.000    1.447    1.001    1.369    1.415    1.166   

     2007   2008   2009   2010   2011   2012   2013   2014   2015     2016  \
0   1.271  2.549  4.647  3.086  3.198  1.561  1.611  1.721  1.713    1.731   
1   1.027  2.325  3.810  1.758  2.538  1.511  1.727  1.336  2.302    1.253   
2   1.224  2.471  4.377  2.321  2.478  1.623  1.761  1.391  2.649    1.257   
3   1.085  2.763  4.422  2.564  1.848  1.614  1.691  1.598  2.234    1.221   
4   1.287  3.005  4.426  2.717  2.199  1.579  1.801  1.463  2.179    1.132   
5   1.307  3.086  4.854  3.089  2.224  1.650  1.603  1.291  2.262  990.000   
6   1.630  3.913  5.241  3.282  2.119  1.515  1.869  1.582  2.457    1.027   
7   1.982  3.832  5.414  3.689  2.242  1.797  1.715  1.390  2.402    1.146   
8   2.281  3.908  5.854  4.473  1.827  1.684  1.578  1.489  2.422    1.043   
9   2.861  4.035  5.165  4.238  1.907  1.674  1.731  1.445  3.418    1.156   
10  2.809  4.095  4.233  4.285  1.918  1.775  1.536  1.578  2.686    1.130   
11  2.771  4.601  4.744  4.578  2.013  1.716  2.126  1.850  2.471    1.445   

       2017     2018     2019     2020     2021   2022  
0   995.000    1.489  905.000    1.281    1.149  666.0  
1   740.000    1.201  817.000    1.205    1.353  629.0  
2   850.000    1.155    1.143  910.000    1.435  994.0  
3   637.000  935.000    1.507  695.000    1.287  991.0  
4   757.000  993.000    1.712  645.000    1.204  770.0  
5   589.000    1.343    1.218  698.000    1.054  801.0  
6   768.000    1.357    1.134  792.000  952.000    NaN  
7   913.000    1.729  989.000  883.000  911.000    NaN  
8     1.158    1.649    1.377    1.189  890.000    NaN  
9   985.000    1.520    1.534    1.340  805.000    NaN  
10    1.307    1.177    1.498    1.223  814.000    NaN  
11    1.634    1.093    1.635    1.383  712.000    NaN

In [1076]:
# Replace do Mês para numérico

dfro["Mês"].replace("Janeiro", "01", inplace=True)
dfro["Mês"].replace("Fevereiro", "02", inplace=True)
dfro["Mês"].replace("Março", "03", inplace=True)
dfro["Mês"].replace("Abril", "04", inplace=True)
dfro["Mês"].replace("Maio", "05", inplace=True)
dfro["Mês"].replace("Junho", "06", inplace=True)
dfro["Mês"].replace("Julho", "07", inplace=True)
dfro["Mês"].replace("Agosto", "08", inplace=True)
dfro["Mês"].replace("Setembro", "09", inplace=True)
dfro["Mês"].replace("Outubro", "10", inplace=True)
dfro["Mês"].replace("Novembro", "11", inplace=True)
dfro["Mês"].replace("Dezembro", "12", inplace=True)

In [1077]:
# Criação das colunas uf, produto, unid, criado_em
dfro['uf']='RO'
dfro['produto']='Etanol Hidratado'
dfro['unid']='m3'
dfro['criado_em'] ='2022-09-10'

In [1078]:
# Despivotar a tabela em ano e volume 
dfro.reset_index(inplace=True)

In [1079]:
dfro=dfro.melt(id_vars = ['Mês', 'uf', 'produto', 'unid', 'criado_em'], value_vars = ['2000', '2001', '2002', '2003', '2004', '2005', '2006', '2007', '2008', '2009', '2010', '2011', '2012', '2013', '2014', '2015', '2016', '2017', '2018', '2019', '2020', '2021', '2022'], var_name='ano', value_name='venda')

In [1080]:
# Visão geral da tabela

dfro

Mês  uf           produto unid   criado_em   ano    venda
0    01  RO  Etanol Hidratado   m3  2022-09-10  2000    1.499
1    02  RO  Etanol Hidratado   m3  2022-09-10  2000    3.594
2    03  RO  Etanol Hidratado   m3  2022-09-10  2000    2.596
3    04  RO  Etanol Hidratado   m3  2022-09-10  2000    2.922
4    05  RO  Etanol Hidratado   m3  2022-09-10  2000    3.446
5    06  RO  Etanol Hidratado   m3  2022-09-10  2000    1.104
6    07  RO  Etanol Hidratado   m3  2022-09-10  2000    1.331
7    08  RO  Etanol Hidratado   m3  2022-09-10  2000    1.749
8    09  RO  Etanol Hidratado   m3  2022-09-10  2000    1.531
9    10  RO  Etanol Hidratado   m3  2022-09-10  2000    1.517
10   11  RO  Etanol Hidratado   m3  2022-09-10  2000    1.181
11   12  RO  Etanol Hidratado   m3  2022-09-10  2000    1.151
12   01  RO  Etanol Hidratado   m3  2022-09-10  2001    1.197
13   02  RO  Etanol Hidratado   m3  2022-09-10  2001  905.000
14   03  RO  Etanol Hidratado   m3  2022-09-10  2001  924.000
15   04  RO  Etanol Hidratado   m3  2022-09-10  2001    1.113
16   05  RO  Etanol Hidratado   m3  2022-09-10  2001    1.108
17   06  RO  Etanol Hidratado   m3  2022-09-10  2001    1.109
18   07  RO  Etanol Hidratado   m3  2022-09-10  2001    1.098
19   08  RO  Etanol Hidratado   m3  2022-09-10  2001    1.147
20   09  RO  Etanol Hidratado   m3  2022-09-10  2001    1.032
21   10  RO  Etanol Hidratado   m3  2022-09-10  2001    1.126
22   11  RO  Etanol Hidratado   m3  2022-09-10  2001  648.000
23   12  RO  Etanol Hidratado   m3  2022-09-10  2001  941.000
24   01  RO  Etanol Hidratado   m3  2022-09-10  2002  958.000
25   02  RO  Etanol Hidratado   m3  2022-09-10  2002    1.014
26   03  RO  Etanol Hidratado   m3  2022-09-10  2002  934.000
27   04  RO  Etanol Hidratado   m3  2022-09-10  2002    1.157
28   05  RO  Etanol Hidratado   m3  2022-09-10  2002    1.194
29   06  RO  Etanol Hidratado   m3  2022-09-10  2002  940.000
30   07  RO  Etanol Hidratado   m3  2022-09-10  2002    1.253
31   08  RO  Etanol Hidratado   m3  2022-09-10  2002    1.246
32   09  RO  Etanol Hidratado   m3  2022-09-10  2002    1.363
33   10  RO  Etanol Hidratado   m3  2022-09-10  2002    1.691
34   11  RO  Etanol Hidratado   m3  2022-09-10  2002    1.344
35   12  RO  Etanol Hidratado   m3  2022-09-10  2002    1.447
36   01  RO  Etanol Hidratado   m3  2022-09-10  2003    1.363
37   02  RO  Etanol Hidratado   m3  2022-09-10  2003  998.000
38   03  RO  Etanol Hidratado   m3  2022-09-10  2003  989.000
39   04  RO  Etanol Hidratado   m3  2022-09-10  2003  875.000
40   05  RO  Etanol Hidratado   m3  2022-09-10  2003    1.085
41   06  RO  Etanol Hidratado   m3  2022-09-10  2003    1.025
42   07  RO  Etanol Hidratado   m3  2022-09-10  2003  951.000
43   08  RO  Etanol Hidratado   m3  2022-09-10  2003    1.012
44   09  RO  Etanol Hidratado   m3  2022-09-10  2003  949.000
45   10  RO  Etanol Hidratado   m3  2022-09-10  2003  923.000
46   11  RO  Etanol Hidratado   m3  2022-09-10  2003  774.000
47   12  RO  Etanol Hidratado   m3  2022-09-10  2003    1.001
48   01  RO  Etanol Hidratado   m3  2022-09-10  2004    1.172
49   02  RO  Etanol Hidratado   m3  2022-09-10  2004    1.014
50   03  RO  Etanol Hidratado   m3  2022-09-10  2004  891.000
51   04  RO  Etanol Hidratado   m3  2022-09-10  2004  869.000
52   05  RO  Etanol Hidratado   m3  2022-09-10  2004    1.117
53   06  RO  Etanol Hidratado   m3  2022-09-10  2004  793.000
54   07  RO  Etanol Hidratado   m3  2022-09-10  2004    1.017
55   08  RO  Etanol Hidratado   m3  2022-09-10  2004    1.208
56   09  RO  Etanol Hidratado   m3  2022-09-10  2004    1.027
57   10  RO  Etanol Hidratado   m3  2022-09-10  2004    1.091
58   11  RO  Etanol Hidratado   m3  2022-09-10  2004    1.171
59   12  RO  Etanol Hidratado   m3  2022-09-10  2004    1.369
60   01  RO  Etanol Hidratado   m3  2022-09-10  2005    1.065
61   02  RO  Etanol Hidratado   m3  2022-09-10  2005    1.083
62   03  RO  Etanol Hidratado   m3  2022-09-10  2005    1.051
63   04  RO  Etanol Hidratado   m3  

In [1081]:
# Concatenando as colunas ano e Mês
dfro['ano_mês'] = dfro[['ano', 'Mês']].agg('-'.join, axis=1)

In [1082]:
# Eliminando as colunas Mês e ano

dfro.drop(["Mês"], axis=1, inplace=True)
dfro.drop(["ano"], axis=1, inplace=True)

In [1083]:
# Organização da ordem das colunas

dfro=dfro[['ano_mês', 'uf', 'produto', 'unid', 'venda', 'criado_em']]

In [1084]:
# Levantamento de possíveis inconsistências

dfro.isna().sum()

ano_mês      0
uf           0
produto      0
unid         0
venda        6
criado_em    0
dtype: int64

In [1085]:
# Tratamento das inconsistências

dfro.replace(['Na', 'nA', 'na','NA', 'NaN', 'NAN', 'nan', '', ' '],pd.NA,inplace=True)

In [1086]:
# Visão geral da tabela

dfro

ano_mês  uf           produto unid    venda   criado_em
0    2000-01  RO  Etanol Hidratado   m3    1.499  2022-09-10
1    2000-02  RO  Etanol Hidratado   m3    3.594  2022-09-10
2    2000-03  RO  Etanol Hidratado   m3    2.596  2022-09-10
3    2000-04  RO  Etanol Hidratado   m3    2.922  2022-09-10
4    2000-05  RO  Etanol Hidratado   m3    3.446  2022-09-10
5    2000-06  RO  Etanol Hidratado   m3    1.104  2022-09-10
6    2000-07  RO  Etanol Hidratado   m3    1.331  2022-09-10
7    2000-08  RO  Etanol Hidratado   m3    1.749  2022-09-10
8    2000-09  RO  Etanol Hidratado   m3    1.531  2022-09-10
9    2000-10  RO  Etanol Hidratado   m3    1.517  2022-09-10
10   2000-11  RO  Etanol Hidratado   m3    1.181  2022-09-10
11   2000-12  RO  Etanol Hidratado   m3    1.151  2022-09-10
12   2001-01  RO  Etanol Hidratado   m3    1.197  2022-09-10
13   2001-02  RO  Etanol Hidratado   m3  905.000  2022-09-10
14   2001-03  RO  Etanol Hidratado   m3  924.000  2022-09-10
15   2001-04  RO  Etanol Hidratado   m3    1.113  2022-09-10
16   2001-05  RO  Etanol Hidratado   m3    1.108  2022-09-10
17   2001-06  RO  Etanol Hidratado   m3    1.109  2022-09-10
18   2001-07  RO  Etanol Hidratado   m3    1.098  2022-09-10
19   2001-08  RO  Etanol Hidratado   m3    1.147  2022-09-10
20   2001-09  RO  Etanol Hidratado   m3    1.032  2022-09-10
21   2001-10  RO  Etanol Hidratado   m3    1.126  2022-09-10
22   2001-11  RO  Etanol Hidratado   m3  648.000  2022-09-10
23   2001-12  RO  Etanol Hidratado   m3  941.000  2022-09-10
24   2002-01  RO  Etanol Hidratado   m3  958.000  2022-09-10
25   2002-02  RO  Etanol Hidratado   m3    1.014  2022-09-10
26   2002-03  RO  Etanol Hidratado   m3  934.000  2022-09-10
27   2002-04  RO  Etanol Hidratado   m3    1.157  2022-09-10
28   2002-05  RO  Etanol Hidratado   m3    1.194  2022-09-10
29   2002-06  RO  Etanol Hidratado   m3  940.000  2022-09-10
30   2002-07  RO  Etanol Hidratado   m3    1.253  2022-09-10
31   2002-08  RO  Etanol Hidratado   m3    1.246  2022-09-10
32   2002-09  RO  Etanol Hidratado   m3    1.363  2022-09-10
33   2002-10  RO  Etanol Hidratado   m3    1.691  2022-09-10
34   2002-11  RO  Etanol Hidratado   m3    1.344  2022-09-10
35   2002-12  RO  Etanol Hidratado   m3    1.447  2022-09-10
36   2003-01  RO  Etanol Hidratado   m3    1.363  2022-09-10
37   2003-02  RO  Etanol Hidratado   m3  998.000  2022-09-10
38   2003-03  RO  Etanol Hidratado   m3  989.000  2022-09-10
39   2003-04  RO  Etanol Hidratado   m3  875.000  2022-09-10
40   2003-05  RO  Etanol Hidratado   m3    1.085  2022-09-10
41   2003-06  RO  Etanol Hidratado   m3    1.025  2022-09-10
42   2003-07  RO  Etanol Hidratado   m3  951.000  2022-09-10
43   2003-08  RO  Etanol Hidratado   m3    1.012  2022-09-10
44   2003-09  RO  Etanol Hidratado   m3  949.000  2022-09-10
45   2003-10  RO  Etanol Hidratado   m3  923.000  2022-09-10
46   2003-11  RO  Etanol Hidratado   m3  774.000  2022-09-10
47   2003-12  RO  Etanol Hidratado   m3    1.001  2022-09-10
48   2004-01  RO  Etanol Hidratado   m3    1.172  2022-09-10
49   2004-02  RO  Etanol Hidratado   m3    1.014  2022-09-10
50   2004-03  RO  Etanol Hidratado   m3  891.000  2022-09-10
51   2004-04  RO  Etanol Hidratado   m3  869.000  2022-09-10
52   2004-05  RO  Etanol Hidratado   m3    1.117  2022-09-10
53   2004-06  RO  Etanol Hidratado   m3  793.000  2022-09-10
54   2004-07  RO  Etanol Hidratado   m3    1.017  2022-09-10
55   2004-08  RO  Etanol Hidratado   m3    1.208  2022-09-10
56   2004-09  RO  Etanol Hidratado   m3    1.027  2022-09-10
57   2004-10  RO  Etanol Hidratado   m3    1.091  2022-09-10
58   2004-11  RO  Etanol Hidratado   m3    1.171  2022-09-10
59   2004-12  RO  Etanol Hidratado   m3    1.369  2022-09-10
60   2005-01  RO  Etanol Hidratado   m3    1.065  2022-09-10
61   2005-02  RO  Etanol Hidratado   m3    1.083  2022-09-10
62   2005-03  RO  Etanol Hidratado   m3    1.051  2022-09-10
63   2005-04  RO  Etanol Hidratado   m3  772.000  2022-09-10
64   2005-05  RO  Etanol Hidratado   m3 

In [1087]:
# Verificando os tipos

dfro.dtypes

ano_mês       object
uf            object
produto       object
unid          object
venda        float64
criado_em     object
dtype: object

In [1088]:
# Validação

schema = pa.DataFrameSchema(
    columns = {
        'ano_mês': pa.Column(pa.String, nullable=True),
        'uf': pa.Column(pa.String, nullable = True),
        'produto': pa.Column(pa.String, nullable = True),
        'unid': pa.Column(pa.String, nullable = True),
        'venda': pa.Column(pa.Float, nullable = True),
        'criado_em': pa.Column(pa.String, nullable = True),
                
    }
)
schema.validate(dfro)

ano_mês  uf           produto unid    venda   criado_em
0    2000-01  RO  Etanol Hidratado   m3    1.499  2022-09-10
1    2000-02  RO  Etanol Hidratado   m3    3.594  2022-09-10
2    2000-03  RO  Etanol Hidratado   m3    2.596  2022-09-10
3    2000-04  RO  Etanol Hidratado   m3    2.922  2022-09-10
4    2000-05  RO  Etanol Hidratado   m3    3.446  2022-09-10
5    2000-06  RO  Etanol Hidratado   m3    1.104  2022-09-10
6    2000-07  RO  Etanol Hidratado   m3    1.331  2022-09-10
7    2000-08  RO  Etanol Hidratado   m3    1.749  2022-09-10
8    2000-09  RO  Etanol Hidratado   m3    1.531  2022-09-10
9    2000-10  RO  Etanol Hidratado   m3    1.517  2022-09-10
10   2000-11  RO  Etanol Hidratado   m3    1.181  2022-09-10
11   2000-12  RO  Etanol Hidratado   m3    1.151  2022-09-10
12   2001-01  RO  Etanol Hidratado   m3    1.197  2022-09-10
13   2001-02  RO  Etanol Hidratado   m3  905.000  2022-09-10
14   2001-03  RO  Etanol Hidratado   m3  924.000  2022-09-10
15   2001-04  RO  Etanol Hidratado   m3    1.113  2022-09-10
16   2001-05  RO  Etanol Hidratado   m3    1.108  2022-09-10
17   2001-06  RO  Etanol Hidratado   m3    1.109  2022-09-10
18   2001-07  RO  Etanol Hidratado   m3    1.098  2022-09-10
19   2001-08  RO  Etanol Hidratado   m3    1.147  2022-09-10
20   2001-09  RO  Etanol Hidratado   m3    1.032  2022-09-10
21   2001-10  RO  Etanol Hidratado   m3    1.126  2022-09-10
22   2001-11  RO  Etanol Hidratado   m3  648.000  2022-09-10
23   2001-12  RO  Etanol Hidratado   m3  941.000  2022-09-10
24   2002-01  RO  Etanol Hidratado   m3  958.000  2022-09-10
25   2002-02  RO  Etanol Hidratado   m3    1.014  2022-09-10
26   2002-03  RO  Etanol Hidratado   m3  934.000  2022-09-10
27   2002-04  RO  Etanol Hidratado   m3    1.157  2022-09-10
28   2002-05  RO  Etanol Hidratado   m3    1.194  2022-09-10
29   2002-06  RO  Etanol Hidratado   m3  940.000  2022-09-10
30   2002-07  RO  Etanol Hidratado   m3    1.253  2022-09-10
31   2002-08  RO  Etanol Hidratado   m3    1.246  2022-09-10
32   2002-09  RO  Etanol Hidratado   m3    1.363  2022-09-10
33   2002-10  RO  Etanol Hidratado   m3    1.691  2022-09-10
34   2002-11  RO  Etanol Hidratado   m3    1.344  2022-09-10
35   2002-12  RO  Etanol Hidratado   m3    1.447  2022-09-10
36   2003-01  RO  Etanol Hidratado   m3    1.363  2022-09-10
37   2003-02  RO  Etanol Hidratado   m3  998.000  2022-09-10
38   2003-03  RO  Etanol Hidratado   m3  989.000  2022-09-10
39   2003-04  RO  Etanol Hidratado   m3  875.000  2022-09-10
40   2003-05  RO  Etanol Hidratado   m3    1.085  2022-09-10
41   2003-06  RO  Etanol Hidratado   m3    1.025  2022-09-10
42   2003-07  RO  Etanol Hidratado   m3  951.000  2022-09-10
43   2003-08  RO  Etanol Hidratado   m3    1.012  2022-09-10
44   2003-09  RO  Etanol Hidratado   m3  949.000  2022-09-10
45   2003-10  RO  Etanol Hidratado   m3  923.000  2022-09-10
46   2003-11  RO  Etanol Hidratado   m3  774.000  2022-09-10
47   2003-12  RO  Etanol Hidratado   m3    1.001  2022-09-10
48   2004-01  RO  Etanol Hidratado   m3    1.172  2022-09-10
49   2004-02  RO  Etanol Hidratado   m3    1.014  2022-09-10
50   2004-03  RO  Etanol Hidratado   m3  891.000  2022-09-10
51   2004-04  RO  Etanol Hidratado   m3  869.000  2022-09-10
52   2004-05  RO  Etanol Hidratado   m3    1.117  2022-09-10
53   2004-06  RO  Etanol Hidratado   m3  793.000  2022-09-10
54   2004-07  RO  Etanol Hidratado   m3    1.017  2022-09-10
55   2004-08  RO  Etanol Hidratado   m3    1.208  2022-09-10
56   2004-09  RO  Etanol Hidratado   m3    1.027  2022-09-10
57   2004-10  RO  Etanol Hidratado   m3    1.091  2022-09-10
58   2004-11  RO  Etanol Hidratado   m3    1.171  2022-09-10
59   2004-12  RO  Etanol Hidratado   m3    1.369  2022-09-10
60   2005-01  RO  Etanol Hidratado   m3    1.065  2022-09-10
61   2005-02  RO  Etanol Hidratado   m3    1.083  2022-09-10
62   2005-03  RO  Etanol Hidratado   m3    1.051  2022-09-10
63   2005-04  RO  Etanol Hidratado   m3  772.000  2022-09-10
64   2005-05  RO  Etanol Hidratado   m3 

In [1089]:
dfro_pandas = dfro.copy()

##RORAIMA

In [1090]:
# Conector

dfrr = pd.read_csv('/content/roraima.csv',sep=';')

In [1091]:
# Backup
dfrr_backup = dfrr.copy()

In [1092]:
# Configurando a quantidade de linhas máximas mostradas em tela

pd.set_option('display.max_columns',1000)
pd.set_option('display.max_rows',1000)

In [1093]:
# Visualização da Tabela

dfrr

Mês  2000  2001  2002   2003  2004  2005  2006  2007  2008  2009  \
0     Janeiro   143   163    79    75     49    44   119   196   197   235   
1   Fevereiro   128   126    85    44     45    35   100   124   203   219   
2       Março   142   121    79    81     49    30    88   235   206   245   
3       Abril   137   138    79    35     59    44    41   280   206   224   
4        Maio   151   115    94    55     64    65    81   164   249   251   
5       Junho    40   126    79    40     49    35   113   101   240   236   
6       Julho   134   122    84    35     39    40    86   127   272   247   
7      Agosto   177    86   111    60     64    57   106   180   175   240   
8    Setembro   160    96    70    49     35    80   108   173   304   285   
9     Outubro   136    97    85    50     40    70   149   177   258   228   
10   Novembro   133    83    75   -       45    84   131   241   239   245   
11   Dezembro   146    97    80    44     40   152   177   259   319   253   

    2010  2011  2012  2013  2014  2015  2016  2017  2018  2019  2020  2021  \
0    259   223   137   156   142   222   142   106   157    81   157   177   
1    251   228   182   217   126   232   135    49   140    66   129   215   
2    254   200   115   133   108   305   135    59   136    90    99   291   
3    228   224   146   201    88   209   132    71   158   183    60   277   
4    213   196   158   148   124   201   137    68   169   218    42   271   
5    198   381   131   143   129   246   124    88   213   147   103   260   
6    220   154   132   183   133   237    94   114   164   143   106   205   
7    215   162   133   113   112   217   111    51   129   133   120   198   
8    245   133   222   119   151   237    99    61   206   132   176   159   
9    167   195   185   138   282   314   101    87   190   166   177   191   
10   229   167   194   120   253   242   122   107   218   139   142   159   
11   277   223   193   150   304   239   115   155   119   166   243   162   

     2022  
0   146.0  
1   118.0  
2   223.0  
3   210.0  
4   274.0  
5   256.0  
6     NaN  
7     NaN  
8     NaN  
9     NaN  
10    NaN  
11    NaN

In [1094]:
# Replace do Mês para numérico

dfrr["Mês"].replace("Janeiro", "01", inplace=True)
dfrr["Mês"].replace("Fevereiro", "02", inplace=True)
dfrr["Mês"].replace("Março", "03", inplace=True)
dfrr["Mês"].replace("Abril", "04", inplace=True)
dfrr["Mês"].replace("Maio", "05", inplace=True)
dfrr["Mês"].replace("Junho", "06", inplace=True)
dfrr["Mês"].replace("Julho", "07", inplace=True)
dfrr["Mês"].replace("Agosto", "08", inplace=True)
dfrr["Mês"].replace("Setembro", "09", inplace=True)
dfrr["Mês"].replace("Outubro", "10", inplace=True)
dfrr["Mês"].replace("Novembro", "11", inplace=True)
dfrr["Mês"].replace("Dezembro", "12", inplace=True)

In [1095]:
# Criação das colunas uf, produto, unid, criado_em
dfrr['uf']='RR'
dfrr['produto']='Etanol Hidratado'
dfrr['unid']='m3'
dfrr['criado_em'] ='2022-09-10'

In [1096]:
# Despivotar a tabela em ano e volume 
dfrr.reset_index(inplace=True)

In [1097]:
dfrr=dfrr.melt(id_vars = ['Mês', 'uf', 'produto', 'unid', 'criado_em'], value_vars = ['2000', '2001', '2002', '2003', '2004', '2005', '2006', '2007', '2008', '2009', '2010', '2011', '2012', '2013', '2014', '2015', '2016', '2017', '2018', '2019', '2020', '2021', '2022'], var_name='ano', value_name='venda')

In [1098]:
# Visão geral da tabela

dfrr

Mês  uf           produto unid   criado_em   ano  venda
0    01  RR  Etanol Hidratado   m3  2022-09-10  2000    143
1    02  RR  Etanol Hidratado   m3  2022-09-10  2000    128
2    03  RR  Etanol Hidratado   m3  2022-09-10  2000    142
3    04  RR  Etanol Hidratado   m3  2022-09-10  2000    137
4    05  RR  Etanol Hidratado   m3  2022-09-10  2000    151
5    06  RR  Etanol Hidratado   m3  2022-09-10  2000     40
6    07  RR  Etanol Hidratado   m3  2022-09-10  2000    134
7    08  RR  Etanol Hidratado   m3  2022-09-10  2000    177
8    09  RR  Etanol Hidratado   m3  2022-09-10  2000    160
9    10  RR  Etanol Hidratado   m3  2022-09-10  2000    136
10   11  RR  Etanol Hidratado   m3  2022-09-10  2000    133
11   12  RR  Etanol Hidratado   m3  2022-09-10  2000    146
12   01  RR  Etanol Hidratado   m3  2022-09-10  2001    163
13   02  RR  Etanol Hidratado   m3  2022-09-10  2001    126
14   03  RR  Etanol Hidratado   m3  2022-09-10  2001    121
15   04  RR  Etanol Hidratado   m3  2022-09-10  2001    138
16   05  RR  Etanol Hidratado   m3  2022-09-10  2001    115
17   06  RR  Etanol Hidratado   m3  2022-09-10  2001    126
18   07  RR  Etanol Hidratado   m3  2022-09-10  2001    122
19   08  RR  Etanol Hidratado   m3  2022-09-10  2001     86
20   09  RR  Etanol Hidratado   m3  2022-09-10  2001     96
21   10  RR  Etanol Hidratado   m3  2022-09-10  2001     97
22   11  RR  Etanol Hidratado   m3  2022-09-10  2001     83
23   12  RR  Etanol Hidratado   m3  2022-09-10  2001     97
24   01  RR  Etanol Hidratado   m3  2022-09-10  2002     79
25   02  RR  Etanol Hidratado   m3  2022-09-10  2002     85
26   03  RR  Etanol Hidratado   m3  2022-09-10  2002     79
27   04  RR  Etanol Hidratado   m3  2022-09-10  2002     79
28   05  RR  Etanol Hidratado   m3  2022-09-10  2002     94
29   06  RR  Etanol Hidratado   m3  2022-09-10  2002     79
30   07  RR  Etanol Hidratado   m3  2022-09-10  2002     84
31   08  RR  Etanol Hidratado   m3  2022-09-10  2002    111
32   09  RR  Etanol Hidratado   m3  2022-09-10  2002     70
33   10  RR  Etanol Hidratado   m3  2022-09-10  2002     85
34   11  RR  Etanol Hidratado   m3  2022-09-10  2002     75
35   12  RR  Etanol Hidratado   m3  2022-09-10  2002     80
36   01  RR  Etanol Hidratado   m3  2022-09-10  2003    75 
37   02  RR  Etanol Hidratado   m3  2022-09-10  2003    44 
38   03  RR  Etanol Hidratado   m3  2022-09-10  2003    81 
39   04  RR  Etanol Hidratado   m3  2022-09-10  2003    35 
40   05  RR  Etanol Hidratado   m3  2022-09-10  2003    55 
41   06  RR  Etanol Hidratado   m3  2022-09-10  2003    40 
42   07  RR  Etanol Hidratado   m3  2022-09-10  2003    35 
43   08  RR  Etanol Hidratado   m3  2022-09-10  2003    60 
44   09  RR  Etanol Hidratado   m3  2022-09-10  2003    49 
45   10  RR  Etanol Hidratado   m3  2022-09-10  2003    50 
46   11  RR  Etanol Hidratado   m3  2022-09-10  2003   -   
47   12  RR  Etanol Hidratado   m3  2022-09-10  2003    44 
48   01  RR  Etanol Hidratado   m3  2022-09-10  2004     49
49   02  RR  Etanol Hidratado   m3  2022-09-10  2004     45
50   03  RR  Etanol Hidratado   m3  2022-09-10  2004     49
51   04  RR  Etanol Hidratado   m3  2022-09-10  2004     59
52   05  RR  Etanol Hidratado   m3  2022-09-10  2004     64
53   06  RR  Etanol Hidratado   m3  2022-09-10  2004     49
54   07  RR  Etanol Hidratado   m3  2022-09-10  2004     39
55   08  RR  Etanol Hidratado   m3  2022-09-10  2004     64
56   09  RR  Etanol Hidratado   m3  2022-09-10  2004     35
57   10  RR  Etanol Hidratado   m3  2022-09-10  2004     40
58   11  RR  Etanol Hidratado   m3  2022-09-10  2004     45
59   12  RR  Etanol Hidratado   m3  2022-09-10  2004     40
60   01  RR  Etanol Hidratado   m3  2022-09-10  2005     44
61   02  RR  Etanol Hidratado   m3  2022-09-10  2005     35
62   03  RR  Etanol Hidratado   m3  2022-09-10  2005     30
63   04  RR  Etanol Hidratado   m3  2022-09-10  2005     44
64   05  RR  Etanol Hidratado   m3  2022-09-10  2005     65
65   06  RR  Etanol Hidratado   m3  2022-09-

In [1099]:
# Concatenando as colunas ano e Mês
dfrr['ano_mês'] = dfrr[['ano', 'Mês']].agg('-'.join, axis=1)

In [1100]:
# Eliminando as colunas Mês e ano

dfrr.drop(["Mês"], axis=1, inplace=True)
dfrr.drop(["ano"], axis=1, inplace=True)

In [1101]:
# Organização da ordem das colunas

dfrr=dfrr[['ano_mês', 'uf', 'produto', 'unid', 'venda', 'criado_em']]

In [1102]:
# Levantamento de possíveis inconsistências

dfrr.isna().sum()

ano_mês      0
uf           0
produto      0
unid         0
venda        6
criado_em    0
dtype: int64

In [1103]:
# Tratamento das inconsistências

dfrr.replace(['Na', 'nA', 'na','NA', 'NaN', 'NAN', 'nan', '', ' '],pd.NA,inplace=True)


In [1104]:
# Visão geral da tabela

dfrr

ano_mês  uf           produto unid  venda   criado_em
0    2000-01  RR  Etanol Hidratado   m3    143  2022-09-10
1    2000-02  RR  Etanol Hidratado   m3    128  2022-09-10
2    2000-03  RR  Etanol Hidratado   m3    142  2022-09-10
3    2000-04  RR  Etanol Hidratado   m3    137  2022-09-10
4    2000-05  RR  Etanol Hidratado   m3    151  2022-09-10
5    2000-06  RR  Etanol Hidratado   m3     40  2022-09-10
6    2000-07  RR  Etanol Hidratado   m3    134  2022-09-10
7    2000-08  RR  Etanol Hidratado   m3    177  2022-09-10
8    2000-09  RR  Etanol Hidratado   m3    160  2022-09-10
9    2000-10  RR  Etanol Hidratado   m3    136  2022-09-10
10   2000-11  RR  Etanol Hidratado   m3    133  2022-09-10
11   2000-12  RR  Etanol Hidratado   m3    146  2022-09-10
12   2001-01  RR  Etanol Hidratado   m3    163  2022-09-10
13   2001-02  RR  Etanol Hidratado   m3    126  2022-09-10
14   2001-03  RR  Etanol Hidratado   m3    121  2022-09-10
15   2001-04  RR  Etanol Hidratado   m3    138  2022-09-10
16   2001-05  RR  Etanol Hidratado   m3    115  2022-09-10
17   2001-06  RR  Etanol Hidratado   m3    126  2022-09-10
18   2001-07  RR  Etanol Hidratado   m3    122  2022-09-10
19   2001-08  RR  Etanol Hidratado   m3     86  2022-09-10
20   2001-09  RR  Etanol Hidratado   m3     96  2022-09-10
21   2001-10  RR  Etanol Hidratado   m3     97  2022-09-10
22   2001-11  RR  Etanol Hidratado   m3     83  2022-09-10
23   2001-12  RR  Etanol Hidratado   m3     97  2022-09-10
24   2002-01  RR  Etanol Hidratado   m3     79  2022-09-10
25   2002-02  RR  Etanol Hidratado   m3     85  2022-09-10
26   2002-03  RR  Etanol Hidratado   m3     79  2022-09-10
27   2002-04  RR  Etanol Hidratado   m3     79  2022-09-10
28   2002-05  RR  Etanol Hidratado   m3     94  2022-09-10
29   2002-06  RR  Etanol Hidratado   m3     79  2022-09-10
30   2002-07  RR  Etanol Hidratado   m3     84  2022-09-10
31   2002-08  RR  Etanol Hidratado   m3    111  2022-09-10
32   2002-09  RR  Etanol Hidratado   m3     70  2022-09-10
33   2002-10  RR  Etanol Hidratado   m3     85  2022-09-10
34   2002-11  RR  Etanol Hidratado   m3     75  2022-09-10
35   2002-12  RR  Etanol Hidratado   m3     80  2022-09-10
36   2003-01  RR  Etanol Hidratado   m3    75   2022-09-10
37   2003-02  RR  Etanol Hidratado   m3    44   2022-09-10
38   2003-03  RR  Etanol Hidratado   m3    81   2022-09-10
39   2003-04  RR  Etanol Hidratado   m3    35   2022-09-10
40   2003-05  RR  Etanol Hidratado   m3    55   2022-09-10
41   2003-06  RR  Etanol Hidratado   m3    40   2022-09-10
42   2003-07  RR  Etanol Hidratado   m3    35   2022-09-10
43   2003-08  RR  Etanol Hidratado   m3    60   2022-09-10
44   2003-09  RR  Etanol Hidratado   m3    49   2022-09-10
45   2003-10  RR  Etanol Hidratado   m3    50   2022-09-10
46   2003-11  RR  Etanol Hidratado   m3   -     2022-09-10
47   2003-12  RR  Etanol Hidratado   m3    44   2022-09-10
48   2004-01  RR  Etanol Hidratado   m3     49  2022-09-10
49   2004-02  RR  Etanol Hidratado   m3     45  2022-09-10
50   2004-03  RR  Etanol Hidratado   m3     49  2022-09-10
51   2004-04  RR  Etanol Hidratado   m3     59  2022-09-10
52   2004-05  RR  Etanol Hidratado   m3     64  2022-09-10
53   2004-06  RR  Etanol Hidratado   m3     49  2022-09-10
54   2004-07  RR  Etanol Hidratado   m3     39  2022-09-10
55   2004-08  RR  Etanol Hidratado   m3     64  2022-09-10
56   2004-09  RR  Etanol Hidratado   m3     35  2022-09-10
57   2004-10  RR  Etanol Hidratado   m3     40  2022-09-10
58   2004-11  RR  Etanol Hidratado   m3     45  2022-09-10
59   2004-12  RR  Etanol Hidratado   m3     40  2022-09-10
60   2005-01  RR  Etanol Hidratado   m3     44  2022-09-10
61   2005-02  RR  Etanol Hidratado   m3     35  2022-09-10
62   2005-03  RR  Etanol Hidratado   m3     30  2022-09-10
63   2005-04  RR  Etanol Hidratado   m3     44  2022-09-10
64   2005-05  RR  Etanol Hidratado   m3     65  2022-09-10
65   2005-06  RR  Etanol Hidratado   m3     35  2022-09-10
66   2005-07  RR  Etanol Hidratado   m3     40  2022

In [1105]:
# Verificando os tipos

dfrr.dtypes

ano_mês      object
uf           object
produto      object
unid         object
venda        object
criado_em    object
dtype: object

In [1106]:
# Validação

schema = pa.DataFrameSchema(
    columns = {
        'ano_mês': pa.Column(pa.String, nullable=True),
        'uf': pa.Column(pa.String, nullable = True),
        'produto': pa.Column(pa.String, nullable = True),
        'unid': pa.Column(pa.String, nullable = True),
        'venda': pa.Column(pa.String, nullable = True),
        'criado_em': pa.Column(pa.String, nullable = True),
                
    }
)
schema.validate(dfrr)

ano_mês  uf           produto unid  venda   criado_em
0    2000-01  RR  Etanol Hidratado   m3    143  2022-09-10
1    2000-02  RR  Etanol Hidratado   m3    128  2022-09-10
2    2000-03  RR  Etanol Hidratado   m3    142  2022-09-10
3    2000-04  RR  Etanol Hidratado   m3    137  2022-09-10
4    2000-05  RR  Etanol Hidratado   m3    151  2022-09-10
5    2000-06  RR  Etanol Hidratado   m3     40  2022-09-10
6    2000-07  RR  Etanol Hidratado   m3    134  2022-09-10
7    2000-08  RR  Etanol Hidratado   m3    177  2022-09-10
8    2000-09  RR  Etanol Hidratado   m3    160  2022-09-10
9    2000-10  RR  Etanol Hidratado   m3    136  2022-09-10
10   2000-11  RR  Etanol Hidratado   m3    133  2022-09-10
11   2000-12  RR  Etanol Hidratado   m3    146  2022-09-10
12   2001-01  RR  Etanol Hidratado   m3    163  2022-09-10
13   2001-02  RR  Etanol Hidratado   m3    126  2022-09-10
14   2001-03  RR  Etanol Hidratado   m3    121  2022-09-10
15   2001-04  RR  Etanol Hidratado   m3    138  2022-09-10
16   2001-05  RR  Etanol Hidratado   m3    115  2022-09-10
17   2001-06  RR  Etanol Hidratado   m3    126  2022-09-10
18   2001-07  RR  Etanol Hidratado   m3    122  2022-09-10
19   2001-08  RR  Etanol Hidratado   m3     86  2022-09-10
20   2001-09  RR  Etanol Hidratado   m3     96  2022-09-10
21   2001-10  RR  Etanol Hidratado   m3     97  2022-09-10
22   2001-11  RR  Etanol Hidratado   m3     83  2022-09-10
23   2001-12  RR  Etanol Hidratado   m3     97  2022-09-10
24   2002-01  RR  Etanol Hidratado   m3     79  2022-09-10
25   2002-02  RR  Etanol Hidratado   m3     85  2022-09-10
26   2002-03  RR  Etanol Hidratado   m3     79  2022-09-10
27   2002-04  RR  Etanol Hidratado   m3     79  2022-09-10
28   2002-05  RR  Etanol Hidratado   m3     94  2022-09-10
29   2002-06  RR  Etanol Hidratado   m3     79  2022-09-10
30   2002-07  RR  Etanol Hidratado   m3     84  2022-09-10
31   2002-08  RR  Etanol Hidratado   m3    111  2022-09-10
32   2002-09  RR  Etanol Hidratado   m3     70  2022-09-10
33   2002-10  RR  Etanol Hidratado   m3     85  2022-09-10
34   2002-11  RR  Etanol Hidratado   m3     75  2022-09-10
35   2002-12  RR  Etanol Hidratado   m3     80  2022-09-10
36   2003-01  RR  Etanol Hidratado   m3    75   2022-09-10
37   2003-02  RR  Etanol Hidratado   m3    44   2022-09-10
38   2003-03  RR  Etanol Hidratado   m3    81   2022-09-10
39   2003-04  RR  Etanol Hidratado   m3    35   2022-09-10
40   2003-05  RR  Etanol Hidratado   m3    55   2022-09-10
41   2003-06  RR  Etanol Hidratado   m3    40   2022-09-10
42   2003-07  RR  Etanol Hidratado   m3    35   2022-09-10
43   2003-08  RR  Etanol Hidratado   m3    60   2022-09-10
44   2003-09  RR  Etanol Hidratado   m3    49   2022-09-10
45   2003-10  RR  Etanol Hidratado   m3    50   2022-09-10
46   2003-11  RR  Etanol Hidratado   m3   -     2022-09-10
47   2003-12  RR  Etanol Hidratado   m3    44   2022-09-10
48   2004-01  RR  Etanol Hidratado   m3     49  2022-09-10
49   2004-02  RR  Etanol Hidratado   m3     45  2022-09-10
50   2004-03  RR  Etanol Hidratado   m3     49  2022-09-10
51   2004-04  RR  Etanol Hidratado   m3     59  2022-09-10
52   2004-05  RR  Etanol Hidratado   m3     64  2022-09-10
53   2004-06  RR  Etanol Hidratado   m3     49  2022-09-10
54   2004-07  RR  Etanol Hidratado   m3     39  2022-09-10
55   2004-08  RR  Etanol Hidratado   m3     64  2022-09-10
56   2004-09  RR  Etanol Hidratado   m3     35  2022-09-10
57   2004-10  RR  Etanol Hidratado   m3     40  2022-09-10
58   2004-11  RR  Etanol Hidratado   m3     45  2022-09-10
59   2004-12  RR  Etanol Hidratado   m3     40  2022-09-10
60   2005-01  RR  Etanol Hidratado   m3     44  2022-09-10
61   2005-02  RR  Etanol Hidratado   m3     35  2022-09-10
62   2005-03  RR  Etanol Hidratado   m3     30  2022-09-10
63   2005-04  RR  Etanol Hidratado   m3     44  2022-09-10
64   2005-05  RR  Etanol Hidratado   m3     65  2022-09-10
65   2005-06  RR  Etanol Hidratado   m3     35  2022-09-10
66   2005-07  RR  Etanol Hidratado   m3     40  2022

In [1107]:
dfrr_pandas = dfrr.copy()

##RIO GRANDE DO SUL

In [1108]:
# Conector

dfrs = pd.read_csv('/content/rio_grande_do_sul.csv',sep=';')

In [1109]:
# Backup
dfrs_backup = dfrs.copy()

In [1110]:
# Configurando a quantidade de linhas máximas mostradas em tela

pd.set_option('display.max_columns',1000)
pd.set_option('display.max_rows',1000)

In [1111]:
# Visualização da Tabela

dfrs

Mês    2000    2001    2002    2003    2004    2005    2006    2007  \
0     Janeiro  18.375  14.380  14.444  14.469  13.199  14.936  14.258  14.613   
1   Fevereiro  18.142  13.232  12.619  10.872  12.828  12.954  12.539  11.478   
2       Março  18.194  15.060  13.814  11.496  14.654  18.647  11.364  14.493   
3       Abril  19.261  14.012  13.889  11.439  15.736  10.909   9.988  11.976   
4        Maio  18.594  14.933  15.250  12.127  16.687  15.360  12.282  13.880   
5       Junho  14.793  13.442  14.332  11.269  16.271  15.327  12.408  14.350   
6       Julho  18.270  12.948  16.867  13.935  19.388  15.619  12.083  17.372   
7      Agosto  15.159  12.664  16.515  12.466  15.741  16.556  12.358  20.541   
8    Setembro  13.704  11.831  16.669  11.810  17.177  18.056  13.015  21.842   
9     Outubro  14.435  14.335  16.967  13.436  17.014  15.440  14.730  27.396   
10   Novembro  15.899  13.714  12.724  12.715  15.240  16.905  15.283  28.100   
11   Dezembro  16.167  14.709  15.027  15.711  18.075  19.189  18.452  24.257   

      2008    2009    2010    2011    2012    2013    2014    2015   2016  \
0   23.354  35.676  14.815  15.769   9.901  10.452  11.104  12.430  7.278   
1   21.008  31.525  11.255  13.246   9.637  10.320  10.094  13.711  6.376   
2   24.345  33.819  16.378  11.265   9.984   9.105   8.191  15.183  5.957   
3   25.107  37.360  20.393   8.552   9.226   8.605   8.462  12.937  5.963   
4   25.917  35.130  19.668  12.126   9.148   9.064   8.610  13.486  6.168   
5   24.077  36.872  27.243  12.498   8.220   8.147   7.849  15.369  5.381   
6   25.710  38.243  24.258  10.438   8.585   8.383   8.238  14.920  5.469   
7   25.662  35.888  22.450  10.587   9.426   8.166   8.246  15.373  6.202   
8   27.713  41.862  24.663  10.146   8.799   8.221   8.573  16.002  5.491   
9   29.705  30.441  20.746  10.306  11.361   9.288   9.793  15.805  4.769   
10  31.130  20.478  18.147  10.517  10.285   9.041  11.418  10.257  4.267   
11  41.162  25.734  20.878  11.672  10.643  12.656  13.496  12.158  5.602   

     2017   2018   2019   2020   2021   2022  
0   4.005  5.775  5.367  4.653  3.920  2.852  
1   3.426  4.132  3.952  2.953  4.203  2.134  
2   4.053  3.872  4.306  2.603  2.992  3.135  
3   3.342  4.127  4.693  1.550  2.231  2.225  
4   3.986  4.496  4.302  1.827  2.611  2.410  
5   3.806  7.846  3.932  2.432  2.961  3.058  
6   3.983  5.980  4.505  3.270  3.109    NaN  
7   5.036  6.230  3.956  2.933  2.572    NaN  
8   5.557  6.725  3.804  2.880  2.590    NaN  
9   5.010  7.755  4.282  3.145  2.315    NaN  
10  6.237  6.452  4.639  2.814  2.273    NaN  
11  6.289  5.821  5.299  3.912  2.518    NaN

In [1112]:
# Replace do Mês para numérico

dfrs["Mês"].replace("Janeiro", "01", inplace=True)
dfrs["Mês"].replace("Fevereiro", "02", inplace=True)
dfrs["Mês"].replace("Março", "03", inplace=True)
dfrs["Mês"].replace("Abril", "04", inplace=True)
dfrs["Mês"].replace("Maio", "05", inplace=True)
dfrs["Mês"].replace("Junho", "06", inplace=True)
dfrs["Mês"].replace("Julho", "07", inplace=True)
dfrs["Mês"].replace("Agosto", "08", inplace=True)
dfrs["Mês"].replace("Setembro", "09", inplace=True)
dfrs["Mês"].replace("Outubro", "10", inplace=True)
dfrs["Mês"].replace("Novembro", "11", inplace=True)
dfrs["Mês"].replace("Dezembro", "12", inplace=True)

In [1113]:
# Criação das colunas uf, produto, unid, criado_em
dfrs['uf']='RS'
dfrs['produto']='Etanol Hidratado'
dfrs['unid']='m3'
dfrs['criado_em'] ='2022-09-10'

In [1114]:
# Despivotar a tabela em ano e volume 
dfrs.reset_index(inplace=True)

In [1115]:
dfrs=dfrs.melt(id_vars = ['Mês', 'uf', 'produto', 'unid', 'criado_em'], value_vars = ['2000', '2001', '2002', '2003', '2004', '2005', '2006', '2007', '2008', '2009', '2010', '2011', '2012', '2013', '2014', '2015', '2016', '2017', '2018', '2019', '2020', '2021', '2022'], var_name='ano', value_name='venda')

In [1116]:
# Visão geral da tabela

dfrs

Mês  uf           produto unid   criado_em   ano   venda
0    01  RS  Etanol Hidratado   m3  2022-09-10  2000  18.375
1    02  RS  Etanol Hidratado   m3  2022-09-10  2000  18.142
2    03  RS  Etanol Hidratado   m3  2022-09-10  2000  18.194
3    04  RS  Etanol Hidratado   m3  2022-09-10  2000  19.261
4    05  RS  Etanol Hidratado   m3  2022-09-10  2000  18.594
5    06  RS  Etanol Hidratado   m3  2022-09-10  2000  14.793
6    07  RS  Etanol Hidratado   m3  2022-09-10  2000  18.270
7    08  RS  Etanol Hidratado   m3  2022-09-10  2000  15.159
8    09  RS  Etanol Hidratado   m3  2022-09-10  2000  13.704
9    10  RS  Etanol Hidratado   m3  2022-09-10  2000  14.435
10   11  RS  Etanol Hidratado   m3  2022-09-10  2000  15.899
11   12  RS  Etanol Hidratado   m3  2022-09-10  2000  16.167
12   01  RS  Etanol Hidratado   m3  2022-09-10  2001  14.380
13   02  RS  Etanol Hidratado   m3  2022-09-10  2001  13.232
14   03  RS  Etanol Hidratado   m3  2022-09-10  2001  15.060
15   04  RS  Etanol Hidratado   m3  2022-09-10  2001  14.012
16   05  RS  Etanol Hidratado   m3  2022-09-10  2001  14.933
17   06  RS  Etanol Hidratado   m3  2022-09-10  2001  13.442
18   07  RS  Etanol Hidratado   m3  2022-09-10  2001  12.948
19   08  RS  Etanol Hidratado   m3  2022-09-10  2001  12.664
20   09  RS  Etanol Hidratado   m3  2022-09-10  2001  11.831
21   10  RS  Etanol Hidratado   m3  2022-09-10  2001  14.335
22   11  RS  Etanol Hidratado   m3  2022-09-10  2001  13.714
23   12  RS  Etanol Hidratado   m3  2022-09-10  2001  14.709
24   01  RS  Etanol Hidratado   m3  2022-09-10  2002  14.444
25   02  RS  Etanol Hidratado   m3  2022-09-10  2002  12.619
26   03  RS  Etanol Hidratado   m3  2022-09-10  2002  13.814
27   04  RS  Etanol Hidratado   m3  2022-09-10  2002  13.889
28   05  RS  Etanol Hidratado   m3  2022-09-10  2002  15.250
29   06  RS  Etanol Hidratado   m3  2022-09-10  2002  14.332
30   07  RS  Etanol Hidratado   m3  2022-09-10  2002  16.867
31   08  RS  Etanol Hidratado   m3  2022-09-10  2002  16.515
32   09  RS  Etanol Hidratado   m3  2022-09-10  2002  16.669
33   10  RS  Etanol Hidratado   m3  2022-09-10  2002  16.967
34   11  RS  Etanol Hidratado   m3  2022-09-10  2002  12.724
35   12  RS  Etanol Hidratado   m3  2022-09-10  2002  15.027
36   01  RS  Etanol Hidratado   m3  2022-09-10  2003  14.469
37   02  RS  Etanol Hidratado   m3  2022-09-10  2003  10.872
38   03  RS  Etanol Hidratado   m3  2022-09-10  2003  11.496
39   04  RS  Etanol Hidratado   m3  2022-09-10  2003  11.439
40   05  RS  Etanol Hidratado   m3  2022-09-10  2003  12.127
41   06  RS  Etanol Hidratado   m3  2022-09-10  2003  11.269
42   07  RS  Etanol Hidratado   m3  2022-09-10  2003  13.935
43   08  RS  Etanol Hidratado   m3  2022-09-10  2003  12.466
44   09  RS  Etanol Hidratado   m3  2022-09-10  2003  11.810
45   10  RS  Etanol Hidratado   m3  2022-09-10  2003  13.436
46   11  RS  Etanol Hidratado   m3  2022-09-10  2003  12.715
47   12  RS  Etanol Hidratado   m3  2022-09-10  2003  15.711
48   01  RS  Etanol Hidratado   m3  2022-09-10  2004  13.199
49   02  RS  Etanol Hidratado   m3  2022-09-10  2004  12.828
50   03  RS  Etanol Hidratado   m3  2022-09-10  2004  14.654
51   04  RS  Etanol Hidratado   m3  2022-09-10  2004  15.736
52   05  RS  Etanol Hidratado   m3  2022-09-10  2004  16.687
53   06  RS  Etanol Hidratado   m3  2022-09-10  2004  16.271
54   07  RS  Etanol Hidratado   m3  2022-09-10  2004  19.388
55   08  RS  Etanol Hidratado   m3  2022-09-10  2004  15.741
56   09  RS  Etanol Hidratado   m3  2022-09-10  2004  17.177
57   10  RS  Etanol Hidratado   m3  2022-09-10  2004  17.014
58   11  RS  Etanol Hidratado   m3  2022-09-10  2004  15.240
59   12  RS  Etanol Hidratado   m3  2022-09-10  2004  18.075
60   01  RS  Etanol Hidratado   m3  2022-09-10  2005  14.936
61   02  RS  Etanol Hidratado   m3  2022-09-10  2005  12.954
62   03  RS  Etanol Hidratado   m3  2022-09-10  2005  18.647
63   04  RS  Etanol Hidratado   m3  2022-09-10  2005  10.909
64   05  RS  Etanol Hidratado   m3  202

In [1117]:
# Concatenando as colunas ano e Mês
dfrs['ano_mês'] = dfrs[['ano', 'Mês']].agg('-'.join, axis=1)

In [1118]:
# Eliminando as colunas Mês e ano

dfrs.drop(["Mês"], axis=1, inplace=True)
dfrs.drop(["ano"], axis=1, inplace=True)

In [1119]:
# Organização da ordem das colunas

dfrs=dfrs[['ano_mês', 'uf', 'produto', 'unid', 'venda', 'criado_em']]

In [1120]:
# Levantamento de possíveis inconsistências

dfrs.isna().sum()

ano_mês      0
uf           0
produto      0
unid         0
venda        6
criado_em    0
dtype: int64

In [1121]:
# Tratamento das inconsistências

dfrs.replace(['Na', 'nA', 'na','NA', 'NaN', 'NAN', 'nan', '', ' '],pd.NA,inplace=True)


In [1122]:
# Visão geral da tabela

dfrs

ano_mês  uf           produto unid   venda   criado_em
0    2000-01  RS  Etanol Hidratado   m3  18.375  2022-09-10
1    2000-02  RS  Etanol Hidratado   m3  18.142  2022-09-10
2    2000-03  RS  Etanol Hidratado   m3  18.194  2022-09-10
3    2000-04  RS  Etanol Hidratado   m3  19.261  2022-09-10
4    2000-05  RS  Etanol Hidratado   m3  18.594  2022-09-10
5    2000-06  RS  Etanol Hidratado   m3  14.793  2022-09-10
6    2000-07  RS  Etanol Hidratado   m3  18.270  2022-09-10
7    2000-08  RS  Etanol Hidratado   m3  15.159  2022-09-10
8    2000-09  RS  Etanol Hidratado   m3  13.704  2022-09-10
9    2000-10  RS  Etanol Hidratado   m3  14.435  2022-09-10
10   2000-11  RS  Etanol Hidratado   m3  15.899  2022-09-10
11   2000-12  RS  Etanol Hidratado   m3  16.167  2022-09-10
12   2001-01  RS  Etanol Hidratado   m3  14.380  2022-09-10
13   2001-02  RS  Etanol Hidratado   m3  13.232  2022-09-10
14   2001-03  RS  Etanol Hidratado   m3  15.060  2022-09-10
15   2001-04  RS  Etanol Hidratado   m3  14.012  2022-09-10
16   2001-05  RS  Etanol Hidratado   m3  14.933  2022-09-10
17   2001-06  RS  Etanol Hidratado   m3  13.442  2022-09-10
18   2001-07  RS  Etanol Hidratado   m3  12.948  2022-09-10
19   2001-08  RS  Etanol Hidratado   m3  12.664  2022-09-10
20   2001-09  RS  Etanol Hidratado   m3  11.831  2022-09-10
21   2001-10  RS  Etanol Hidratado   m3  14.335  2022-09-10
22   2001-11  RS  Etanol Hidratado   m3  13.714  2022-09-10
23   2001-12  RS  Etanol Hidratado   m3  14.709  2022-09-10
24   2002-01  RS  Etanol Hidratado   m3  14.444  2022-09-10
25   2002-02  RS  Etanol Hidratado   m3  12.619  2022-09-10
26   2002-03  RS  Etanol Hidratado   m3  13.814  2022-09-10
27   2002-04  RS  Etanol Hidratado   m3  13.889  2022-09-10
28   2002-05  RS  Etanol Hidratado   m3  15.250  2022-09-10
29   2002-06  RS  Etanol Hidratado   m3  14.332  2022-09-10
30   2002-07  RS  Etanol Hidratado   m3  16.867  2022-09-10
31   2002-08  RS  Etanol Hidratado   m3  16.515  2022-09-10
32   2002-09  RS  Etanol Hidratado   m3  16.669  2022-09-10
33   2002-10  RS  Etanol Hidratado   m3  16.967  2022-09-10
34   2002-11  RS  Etanol Hidratado   m3  12.724  2022-09-10
35   2002-12  RS  Etanol Hidratado   m3  15.027  2022-09-10
36   2003-01  RS  Etanol Hidratado   m3  14.469  2022-09-10
37   2003-02  RS  Etanol Hidratado   m3  10.872  2022-09-10
38   2003-03  RS  Etanol Hidratado   m3  11.496  2022-09-10
39   2003-04  RS  Etanol Hidratado   m3  11.439  2022-09-10
40   2003-05  RS  Etanol Hidratado   m3  12.127  2022-09-10
41   2003-06  RS  Etanol Hidratado   m3  11.269  2022-09-10
42   2003-07  RS  Etanol Hidratado   m3  13.935  2022-09-10
43   2003-08  RS  Etanol Hidratado   m3  12.466  2022-09-10
44   2003-09  RS  Etanol Hidratado   m3  11.810  2022-09-10
45   2003-10  RS  Etanol Hidratado   m3  13.436  2022-09-10
46   2003-11  RS  Etanol Hidratado   m3  12.715  2022-09-10
47   2003-12  RS  Etanol Hidratado   m3  15.711  2022-09-10
48   2004-01  RS  Etanol Hidratado   m3  13.199  2022-09-10
49   2004-02  RS  Etanol Hidratado   m3  12.828  2022-09-10
50   2004-03  RS  Etanol Hidratado   m3  14.654  2022-09-10
51   2004-04  RS  Etanol Hidratado   m3  15.736  2022-09-10
52   2004-05  RS  Etanol Hidratado   m3  16.687  2022-09-10
53   2004-06  RS  Etanol Hidratado   m3  16.271  2022-09-10
54   2004-07  RS  Etanol Hidratado   m3  19.388  2022-09-10
55   2004-08  RS  Etanol Hidratado   m3  15.741  2022-09-10
56   2004-09  RS  Etanol Hidratado   m3  17.177  2022-09-10
57   2004-10  RS  Etanol Hidratado   m3  17.014  2022-09-10
58   2004-11  RS  Etanol Hidratado   m3  15.240  2022-09-10
59   2004-12  RS  Etanol Hidratado   m3  18.075  2022-09-10
60   2005-01  RS  Etanol Hidratado   m3  14.936  2022-09-10
61   2005-02  RS  Etanol Hidratado   m3  12.954  2022-09-10
62   2005-03  RS  Etanol Hidratado   m3  18.647  2022-09-10
63   2005-04  RS  Etanol Hidratado   m3  10.909  2022-09-10
64   2005-05  RS  Etanol Hidratado   m3  15.360  2022-09-10
65   2005-06  RS  Etanol Hidratado   m3  15.3

In [1123]:
# Verificando os tipos

dfrs.dtypes

ano_mês       object
uf            object
produto       object
unid          object
venda        float64
criado_em     object
dtype: object

In [1124]:
# Validação

schema = pa.DataFrameSchema(
    columns = {
        'ano_mês': pa.Column(pa.String, nullable=True),
        'uf': pa.Column(pa.String, nullable = True),
        'produto': pa.Column(pa.String, nullable = True),
        'unid': pa.Column(pa.String, nullable = True),
        'venda': pa.Column(pa.Float, nullable = True),
        'criado_em': pa.Column(pa.String, nullable = True),
                
    }
)
schema.validate(dfrs)

ano_mês  uf           produto unid   venda   criado_em
0    2000-01  RS  Etanol Hidratado   m3  18.375  2022-09-10
1    2000-02  RS  Etanol Hidratado   m3  18.142  2022-09-10
2    2000-03  RS  Etanol Hidratado   m3  18.194  2022-09-10
3    2000-04  RS  Etanol Hidratado   m3  19.261  2022-09-10
4    2000-05  RS  Etanol Hidratado   m3  18.594  2022-09-10
5    2000-06  RS  Etanol Hidratado   m3  14.793  2022-09-10
6    2000-07  RS  Etanol Hidratado   m3  18.270  2022-09-10
7    2000-08  RS  Etanol Hidratado   m3  15.159  2022-09-10
8    2000-09  RS  Etanol Hidratado   m3  13.704  2022-09-10
9    2000-10  RS  Etanol Hidratado   m3  14.435  2022-09-10
10   2000-11  RS  Etanol Hidratado   m3  15.899  2022-09-10
11   2000-12  RS  Etanol Hidratado   m3  16.167  2022-09-10
12   2001-01  RS  Etanol Hidratado   m3  14.380  2022-09-10
13   2001-02  RS  Etanol Hidratado   m3  13.232  2022-09-10
14   2001-03  RS  Etanol Hidratado   m3  15.060  2022-09-10
15   2001-04  RS  Etanol Hidratado   m3  14.012  2022-09-10
16   2001-05  RS  Etanol Hidratado   m3  14.933  2022-09-10
17   2001-06  RS  Etanol Hidratado   m3  13.442  2022-09-10
18   2001-07  RS  Etanol Hidratado   m3  12.948  2022-09-10
19   2001-08  RS  Etanol Hidratado   m3  12.664  2022-09-10
20   2001-09  RS  Etanol Hidratado   m3  11.831  2022-09-10
21   2001-10  RS  Etanol Hidratado   m3  14.335  2022-09-10
22   2001-11  RS  Etanol Hidratado   m3  13.714  2022-09-10
23   2001-12  RS  Etanol Hidratado   m3  14.709  2022-09-10
24   2002-01  RS  Etanol Hidratado   m3  14.444  2022-09-10
25   2002-02  RS  Etanol Hidratado   m3  12.619  2022-09-10
26   2002-03  RS  Etanol Hidratado   m3  13.814  2022-09-10
27   2002-04  RS  Etanol Hidratado   m3  13.889  2022-09-10
28   2002-05  RS  Etanol Hidratado   m3  15.250  2022-09-10
29   2002-06  RS  Etanol Hidratado   m3  14.332  2022-09-10
30   2002-07  RS  Etanol Hidratado   m3  16.867  2022-09-10
31   2002-08  RS  Etanol Hidratado   m3  16.515  2022-09-10
32   2002-09  RS  Etanol Hidratado   m3  16.669  2022-09-10
33   2002-10  RS  Etanol Hidratado   m3  16.967  2022-09-10
34   2002-11  RS  Etanol Hidratado   m3  12.724  2022-09-10
35   2002-12  RS  Etanol Hidratado   m3  15.027  2022-09-10
36   2003-01  RS  Etanol Hidratado   m3  14.469  2022-09-10
37   2003-02  RS  Etanol Hidratado   m3  10.872  2022-09-10
38   2003-03  RS  Etanol Hidratado   m3  11.496  2022-09-10
39   2003-04  RS  Etanol Hidratado   m3  11.439  2022-09-10
40   2003-05  RS  Etanol Hidratado   m3  12.127  2022-09-10
41   2003-06  RS  Etanol Hidratado   m3  11.269  2022-09-10
42   2003-07  RS  Etanol Hidratado   m3  13.935  2022-09-10
43   2003-08  RS  Etanol Hidratado   m3  12.466  2022-09-10
44   2003-09  RS  Etanol Hidratado   m3  11.810  2022-09-10
45   2003-10  RS  Etanol Hidratado   m3  13.436  2022-09-10
46   2003-11  RS  Etanol Hidratado   m3  12.715  2022-09-10
47   2003-12  RS  Etanol Hidratado   m3  15.711  2022-09-10
48   2004-01  RS  Etanol Hidratado   m3  13.199  2022-09-10
49   2004-02  RS  Etanol Hidratado   m3  12.828  2022-09-10
50   2004-03  RS  Etanol Hidratado   m3  14.654  2022-09-10
51   2004-04  RS  Etanol Hidratado   m3  15.736  2022-09-10
52   2004-05  RS  Etanol Hidratado   m3  16.687  2022-09-10
53   2004-06  RS  Etanol Hidratado   m3  16.271  2022-09-10
54   2004-07  RS  Etanol Hidratado   m3  19.388  2022-09-10
55   2004-08  RS  Etanol Hidratado   m3  15.741  2022-09-10
56   2004-09  RS  Etanol Hidratado   m3  17.177  2022-09-10
57   2004-10  RS  Etanol Hidratado   m3  17.014  2022-09-10
58   2004-11  RS  Etanol Hidratado   m3  15.240  2022-09-10
59   2004-12  RS  Etanol Hidratado   m3  18.075  2022-09-10
60   2005-01  RS  Etanol Hidratado   m3  14.936  2022-09-10
61   2005-02  RS  Etanol Hidratado   m3  12.954  2022-09-10
62   2005-03  RS  Etanol Hidratado   m3  18.647  2022-09-10
63   2005-04  RS  Etanol Hidratado   m3  10.909  2022-09-10
64   2005-05  RS  Etanol Hidratado   m3  15.360  2022-09-10
65   2005-06  RS  Etanol Hidratado   m3  15.3

In [1125]:
dfrs_pandas = dfrs.copy()

##SANTA CATARINA

In [1126]:
# Conector

dfsc = pd.read_csv('/content/santa_catarina.csv',sep=';')

In [1127]:
# Backup
dfsc_backup = dfsc.copy()

In [1128]:
# Configurando a quantidade de linhas máximas mostradas em tela

pd.set_option('display.max_columns',1000)
pd.set_option('display.max_rows',1000)

In [1129]:
# Visualização da Tabela

dfsc

Mês    2000    2001    2002    2003    2004    2005    2006    2007  \
0     Janeiro  16.070  14.200  12.695  15.186  13.838  13.194  18.181  18.587   
1   Fevereiro  15.027  12.191  11.064  11.428  13.422  11.550  14.789  15.524   
2       Março  15.420  13.237  11.948  10.876  13.921  13.152  12.448  18.349   
3       Abril  16.052  12.171  12.944  12.471  13.998  12.818  11.613  15.985   
4        Maio  16.055  13.361  12.929  12.097  14.056  13.524  14.233  15.922   
5       Junho  14.066  12.878  12.699  12.103  14.554  13.630  13.907  15.952   
6       Julho  16.261  12.744  15.590  15.061  16.245  13.433  15.750  17.454   
7      Agosto  11.918  12.993  13.799  11.389  13.410  14.489  16.173  20.337   
8    Setembro  14.951  11.014  14.004  11.434  15.811  15.702  18.027  21.363   
9     Outubro  13.848  13.671  16.854  14.196  14.826  14.453  17.076  26.613   
10   Novembro  13.961  13.749  13.459  12.367  13.612  16.529  18.211  26.971   
11   Dezembro  14.550  14.434  16.040  16.396  16.179  22.799  22.650  29.339   

      2008    2009    2010    2011   2012    2013    2014    2015   2016  \
0   27.860  39.863  23.287  17.843  8.453   8.849  12.314  12.602  9.260   
1   26.719  37.418  15.291  14.994  8.101   9.092   9.107  15.540  6.335   
2   27.078  40.337  19.175  11.503  8.224   8.120   7.920  16.274  6.198   
3   28.702  42.234  22.540   6.644  7.799   7.043   9.720  13.315  5.808   
4   28.448  39.090  23.638   8.958  7.639   7.156   7.225  10.308  6.114   
5   27.400  39.770  25.721   9.986  6.947   6.979   6.446  11.331  5.118   
6   30.451  48.560  29.040   8.499  7.164   8.350   7.006  13.140  6.187   
7   30.201  46.224  29.556   9.285  7.880   8.277   7.519  13.346  6.565   
8   33.722  51.937  31.534   8.100  7.095   8.462   8.074  13.968  6.435   
9   35.653  43.882  26.054   8.570  8.349   9.972   9.013  16.117  5.317   
10  35.758  31.930  21.008   8.570  7.738  15.787  10.317  10.476  5.002   
11  44.167  37.406  23.749  10.128  9.275  12.408  13.112  10.716  6.528   

     2017    2018   2019   2020   2021   2022  
0   5.055   7.799  9.253  9.296  7.857  4.094  
1   4.128   5.413  6.211  6.514  8.871  4.044  
2   5.024   4.789  6.164  5.237  6.799  6.270  
3   4.399   5.154  7.341  8.822  6.834  5.564  
4   4.296   4.954  7.233  5.360  4.277  4.511  
5   4.177   9.471  5.418  5.224  4.141  4.289  
6   4.462   8.014  5.489  5.145  4.417    NaN  
7   5.698   8.379  4.919  5.129  4.273    NaN  
8   6.781  11.875  5.526  6.912  4.661    NaN  
9   6.644  12.433  7.149  6.511  4.301    NaN  
10  7.562   9.502  6.889  6.043  3.588    NaN  
11  9.159   8.521  9.963  7.190  4.439    NaN

In [1130]:
# Replace do Mês para numérico

dfsc["Mês"].replace("Janeiro", "01", inplace=True)
dfsc["Mês"].replace("Fevereiro", "02", inplace=True)
dfsc["Mês"].replace("Março", "03", inplace=True)
dfsc["Mês"].replace("Abril", "04", inplace=True)
dfsc["Mês"].replace("Maio", "05", inplace=True)
dfsc["Mês"].replace("Junho", "06", inplace=True)
dfsc["Mês"].replace("Julho", "07", inplace=True)
dfsc["Mês"].replace("Agosto", "08", inplace=True)
dfsc["Mês"].replace("Setembro", "09", inplace=True)
dfsc["Mês"].replace("Outubro", "10", inplace=True)
dfsc["Mês"].replace("Novembro", "11", inplace=True)
dfsc["Mês"].replace("Dezembro", "12", inplace=True)

In [1131]:
# Criação das colunas uf, produto, unid, criado_em
dfsc['uf']='SC'
dfsc['produto']='Etanol Hidratado'
dfsc['unid']='m3'
dfsc['criado_em'] ='2022-09-10'

In [1132]:
# Despivotar a tabela em ano e volume 
dfsc.reset_index(inplace=True)

In [1133]:
dfsc=dfsc.melt(id_vars = ['Mês', 'uf', 'produto', 'unid', 'criado_em'], value_vars = ['2000', '2001', '2002', '2003', '2004', '2005', '2006', '2007', '2008', '2009', '2010', '2011', '2012', '2013', '2014', '2015', '2016', '2017', '2018', '2019', '2020', '2021', '2022'], var_name='ano', value_name='venda')

In [1134]:
# Visão geral da tabela

dfsc

Mês  uf           produto unid   criado_em   ano   venda
0    01  SC  Etanol Hidratado   m3  2022-09-10  2000  16.070
1    02  SC  Etanol Hidratado   m3  2022-09-10  2000  15.027
2    03  SC  Etanol Hidratado   m3  2022-09-10  2000  15.420
3    04  SC  Etanol Hidratado   m3  2022-09-10  2000  16.052
4    05  SC  Etanol Hidratado   m3  2022-09-10  2000  16.055
5    06  SC  Etanol Hidratado   m3  2022-09-10  2000  14.066
6    07  SC  Etanol Hidratado   m3  2022-09-10  2000  16.261
7    08  SC  Etanol Hidratado   m3  2022-09-10  2000  11.918
8    09  SC  Etanol Hidratado   m3  2022-09-10  2000  14.951
9    10  SC  Etanol Hidratado   m3  2022-09-10  2000  13.848
10   11  SC  Etanol Hidratado   m3  2022-09-10  2000  13.961
11   12  SC  Etanol Hidratado   m3  2022-09-10  2000  14.550
12   01  SC  Etanol Hidratado   m3  2022-09-10  2001  14.200
13   02  SC  Etanol Hidratado   m3  2022-09-10  2001  12.191
14   03  SC  Etanol Hidratado   m3  2022-09-10  2001  13.237
15   04  SC  Etanol Hidratado   m3  2022-09-10  2001  12.171
16   05  SC  Etanol Hidratado   m3  2022-09-10  2001  13.361
17   06  SC  Etanol Hidratado   m3  2022-09-10  2001  12.878
18   07  SC  Etanol Hidratado   m3  2022-09-10  2001  12.744
19   08  SC  Etanol Hidratado   m3  2022-09-10  2001  12.993
20   09  SC  Etanol Hidratado   m3  2022-09-10  2001  11.014
21   10  SC  Etanol Hidratado   m3  2022-09-10  2001  13.671
22   11  SC  Etanol Hidratado   m3  2022-09-10  2001  13.749
23   12  SC  Etanol Hidratado   m3  2022-09-10  2001  14.434
24   01  SC  Etanol Hidratado   m3  2022-09-10  2002  12.695
25   02  SC  Etanol Hidratado   m3  2022-09-10  2002  11.064
26   03  SC  Etanol Hidratado   m3  2022-09-10  2002  11.948
27   04  SC  Etanol Hidratado   m3  2022-09-10  2002  12.944
28   05  SC  Etanol Hidratado   m3  2022-09-10  2002  12.929
29   06  SC  Etanol Hidratado   m3  2022-09-10  2002  12.699
30   07  SC  Etanol Hidratado   m3  2022-09-10  2002  15.590
31   08  SC  Etanol Hidratado   m3  2022-09-10  2002  13.799
32   09  SC  Etanol Hidratado   m3  2022-09-10  2002  14.004
33   10  SC  Etanol Hidratado   m3  2022-09-10  2002  16.854
34   11  SC  Etanol Hidratado   m3  2022-09-10  2002  13.459
35   12  SC  Etanol Hidratado   m3  2022-09-10  2002  16.040
36   01  SC  Etanol Hidratado   m3  2022-09-10  2003  15.186
37   02  SC  Etanol Hidratado   m3  2022-09-10  2003  11.428
38   03  SC  Etanol Hidratado   m3  2022-09-10  2003  10.876
39   04  SC  Etanol Hidratado   m3  2022-09-10  2003  12.471
40   05  SC  Etanol Hidratado   m3  2022-09-10  2003  12.097
41   06  SC  Etanol Hidratado   m3  2022-09-10  2003  12.103
42   07  SC  Etanol Hidratado   m3  2022-09-10  2003  15.061
43   08  SC  Etanol Hidratado   m3  2022-09-10  2003  11.389
44   09  SC  Etanol Hidratado   m3  2022-09-10  2003  11.434
45   10  SC  Etanol Hidratado   m3  2022-09-10  2003  14.196
46   11  SC  Etanol Hidratado   m3  2022-09-10  2003  12.367
47   12  SC  Etanol Hidratado   m3  2022-09-10  2003  16.396
48   01  SC  Etanol Hidratado   m3  2022-09-10  2004  13.838
49   02  SC  Etanol Hidratado   m3  2022-09-10  2004  13.422
50   03  SC  Etanol Hidratado   m3  2022-09-10  2004  13.921
51   04  SC  Etanol Hidratado   m3  2022-09-10  2004  13.998
52   05  SC  Etanol Hidratado   m3  2022-09-10  2004  14.056
53   06  SC  Etanol Hidratado   m3  2022-09-10  2004  14.554
54   07  SC  Etanol Hidratado   m3  2022-09-10  2004  16.245
55   08  SC  Etanol Hidratado   m3  2022-09-10  2004  13.410
56   09  SC  Etanol Hidratado   m3  2022-09-10  2004  15.811
57   10  SC  Etanol Hidratado   m3  2022-09-10  2004  14.826
58   11  SC  Etanol Hidratado   m3  2022-09-10  2004  13.612
59   12  SC  Etanol Hidratado   m3  2022-09-10  2004  16.179
60   01  SC  Etanol Hidratado   m3  2022-09-10  2005  13.194
61   02  SC  Etanol Hidratado   m3  2022-09-10  2005  11.550
62   03  SC  Etanol Hidratado   m3  2022-09-10  2005  13.152
63   04  SC  Etanol Hidratado   m3  2022-09-10  2005  12.818
64   05  SC  Etanol Hidratado   m3  202

In [1135]:
# Concatenando as colunas ano e Mês
dfsc['ano_mês'] = dfsc[['ano', 'Mês']].agg('-'.join, axis=1)

In [1136]:
# Eliminando as colunas Mês e ano

dfsc.drop(["Mês"], axis=1, inplace=True)
dfsc.drop(["ano"], axis=1, inplace=True)

In [1137]:
# Organização da ordem das colunas

dfsc=dfsc[['ano_mês', 'uf', 'produto', 'unid', 'venda', 'criado_em']]

In [1138]:
# Levantamento de possíveis inconsistências

dfsc.isna().sum()

ano_mês      0
uf           0
produto      0
unid         0
venda        6
criado_em    0
dtype: int64

In [1139]:
# Tratamento das inconsistências

dfsc.replace(['Na', 'nA', 'na','NA', 'NaN', 'NAN', 'nan', '', ' '],pd.NA,inplace=True)


In [1140]:
# Visão geral da tabela

dfsc

ano_mês  uf           produto unid   venda   criado_em
0    2000-01  SC  Etanol Hidratado   m3  16.070  2022-09-10
1    2000-02  SC  Etanol Hidratado   m3  15.027  2022-09-10
2    2000-03  SC  Etanol Hidratado   m3  15.420  2022-09-10
3    2000-04  SC  Etanol Hidratado   m3  16.052  2022-09-10
4    2000-05  SC  Etanol Hidratado   m3  16.055  2022-09-10
5    2000-06  SC  Etanol Hidratado   m3  14.066  2022-09-10
6    2000-07  SC  Etanol Hidratado   m3  16.261  2022-09-10
7    2000-08  SC  Etanol Hidratado   m3  11.918  2022-09-10
8    2000-09  SC  Etanol Hidratado   m3  14.951  2022-09-10
9    2000-10  SC  Etanol Hidratado   m3  13.848  2022-09-10
10   2000-11  SC  Etanol Hidratado   m3  13.961  2022-09-10
11   2000-12  SC  Etanol Hidratado   m3  14.550  2022-09-10
12   2001-01  SC  Etanol Hidratado   m3  14.200  2022-09-10
13   2001-02  SC  Etanol Hidratado   m3  12.191  2022-09-10
14   2001-03  SC  Etanol Hidratado   m3  13.237  2022-09-10
15   2001-04  SC  Etanol Hidratado   m3  12.171  2022-09-10
16   2001-05  SC  Etanol Hidratado   m3  13.361  2022-09-10
17   2001-06  SC  Etanol Hidratado   m3  12.878  2022-09-10
18   2001-07  SC  Etanol Hidratado   m3  12.744  2022-09-10
19   2001-08  SC  Etanol Hidratado   m3  12.993  2022-09-10
20   2001-09  SC  Etanol Hidratado   m3  11.014  2022-09-10
21   2001-10  SC  Etanol Hidratado   m3  13.671  2022-09-10
22   2001-11  SC  Etanol Hidratado   m3  13.749  2022-09-10
23   2001-12  SC  Etanol Hidratado   m3  14.434  2022-09-10
24   2002-01  SC  Etanol Hidratado   m3  12.695  2022-09-10
25   2002-02  SC  Etanol Hidratado   m3  11.064  2022-09-10
26   2002-03  SC  Etanol Hidratado   m3  11.948  2022-09-10
27   2002-04  SC  Etanol Hidratado   m3  12.944  2022-09-10
28   2002-05  SC  Etanol Hidratado   m3  12.929  2022-09-10
29   2002-06  SC  Etanol Hidratado   m3  12.699  2022-09-10
30   2002-07  SC  Etanol Hidratado   m3  15.590  2022-09-10
31   2002-08  SC  Etanol Hidratado   m3  13.799  2022-09-10
32   2002-09  SC  Etanol Hidratado   m3  14.004  2022-09-10
33   2002-10  SC  Etanol Hidratado   m3  16.854  2022-09-10
34   2002-11  SC  Etanol Hidratado   m3  13.459  2022-09-10
35   2002-12  SC  Etanol Hidratado   m3  16.040  2022-09-10
36   2003-01  SC  Etanol Hidratado   m3  15.186  2022-09-10
37   2003-02  SC  Etanol Hidratado   m3  11.428  2022-09-10
38   2003-03  SC  Etanol Hidratado   m3  10.876  2022-09-10
39   2003-04  SC  Etanol Hidratado   m3  12.471  2022-09-10
40   2003-05  SC  Etanol Hidratado   m3  12.097  2022-09-10
41   2003-06  SC  Etanol Hidratado   m3  12.103  2022-09-10
42   2003-07  SC  Etanol Hidratado   m3  15.061  2022-09-10
43   2003-08  SC  Etanol Hidratado   m3  11.389  2022-09-10
44   2003-09  SC  Etanol Hidratado   m3  11.434  2022-09-10
45   2003-10  SC  Etanol Hidratado   m3  14.196  2022-09-10
46   2003-11  SC  Etanol Hidratado   m3  12.367  2022-09-10
47   2003-12  SC  Etanol Hidratado   m3  16.396  2022-09-10
48   2004-01  SC  Etanol Hidratado   m3  13.838  2022-09-10
49   2004-02  SC  Etanol Hidratado   m3  13.422  2022-09-10
50   2004-03  SC  Etanol Hidratado   m3  13.921  2022-09-10
51   2004-04  SC  Etanol Hidratado   m3  13.998  2022-09-10
52   2004-05  SC  Etanol Hidratado   m3  14.056  2022-09-10
53   2004-06  SC  Etanol Hidratado   m3  14.554  2022-09-10
54   2004-07  SC  Etanol Hidratado   m3  16.245  2022-09-10
55   2004-08  SC  Etanol Hidratado   m3  13.410  2022-09-10
56   2004-09  SC  Etanol Hidratado   m3  15.811  2022-09-10
57   2004-10  SC  Etanol Hidratado   m3  14.826  2022-09-10
58   2004-11  SC  Etanol Hidratado   m3  13.612  2022-09-10
59   2004-12  SC  Etanol Hidratado   m3  16.179  2022-09-10
60   2005-01  SC  Etanol Hidratado   m3  13.194  2022-09-10
61   2005-02  SC  Etanol Hidratado   m3  11.550  2022-09-10
62   2005-03  SC  Etanol Hidratado   m3  13.152  2022-09-10
63   2005-04  SC  Etanol Hidratado   m3  12.818  2022-09-10
64   2005-05  SC  Etanol Hidratado   m3  13.524  2022-09-10
65   2005-06  SC  Etanol Hidratado   m3  13.6

In [1141]:
# Verificando os tipos

dfsc.dtypes

ano_mês       object
uf            object
produto       object
unid          object
venda        float64
criado_em     object
dtype: object

In [1142]:
# Validação

schema = pa.DataFrameSchema(
    columns = {
        'ano_mês': pa.Column(pa.String, nullable=True),
        'uf': pa.Column(pa.String, nullable = True),
        'produto': pa.Column(pa.String, nullable = True),
        'unid': pa.Column(pa.String, nullable = True),
        'venda': pa.Column(pa.Float, nullable = True),
        'criado_em': pa.Column(pa.String, nullable = True),
                
    }
)
schema.validate(dfsc)

ano_mês  uf           produto unid   venda   criado_em
0    2000-01  SC  Etanol Hidratado   m3  16.070  2022-09-10
1    2000-02  SC  Etanol Hidratado   m3  15.027  2022-09-10
2    2000-03  SC  Etanol Hidratado   m3  15.420  2022-09-10
3    2000-04  SC  Etanol Hidratado   m3  16.052  2022-09-10
4    2000-05  SC  Etanol Hidratado   m3  16.055  2022-09-10
5    2000-06  SC  Etanol Hidratado   m3  14.066  2022-09-10
6    2000-07  SC  Etanol Hidratado   m3  16.261  2022-09-10
7    2000-08  SC  Etanol Hidratado   m3  11.918  2022-09-10
8    2000-09  SC  Etanol Hidratado   m3  14.951  2022-09-10
9    2000-10  SC  Etanol Hidratado   m3  13.848  2022-09-10
10   2000-11  SC  Etanol Hidratado   m3  13.961  2022-09-10
11   2000-12  SC  Etanol Hidratado   m3  14.550  2022-09-10
12   2001-01  SC  Etanol Hidratado   m3  14.200  2022-09-10
13   2001-02  SC  Etanol Hidratado   m3  12.191  2022-09-10
14   2001-03  SC  Etanol Hidratado   m3  13.237  2022-09-10
15   2001-04  SC  Etanol Hidratado   m3  12.171  2022-09-10
16   2001-05  SC  Etanol Hidratado   m3  13.361  2022-09-10
17   2001-06  SC  Etanol Hidratado   m3  12.878  2022-09-10
18   2001-07  SC  Etanol Hidratado   m3  12.744  2022-09-10
19   2001-08  SC  Etanol Hidratado   m3  12.993  2022-09-10
20   2001-09  SC  Etanol Hidratado   m3  11.014  2022-09-10
21   2001-10  SC  Etanol Hidratado   m3  13.671  2022-09-10
22   2001-11  SC  Etanol Hidratado   m3  13.749  2022-09-10
23   2001-12  SC  Etanol Hidratado   m3  14.434  2022-09-10
24   2002-01  SC  Etanol Hidratado   m3  12.695  2022-09-10
25   2002-02  SC  Etanol Hidratado   m3  11.064  2022-09-10
26   2002-03  SC  Etanol Hidratado   m3  11.948  2022-09-10
27   2002-04  SC  Etanol Hidratado   m3  12.944  2022-09-10
28   2002-05  SC  Etanol Hidratado   m3  12.929  2022-09-10
29   2002-06  SC  Etanol Hidratado   m3  12.699  2022-09-10
30   2002-07  SC  Etanol Hidratado   m3  15.590  2022-09-10
31   2002-08  SC  Etanol Hidratado   m3  13.799  2022-09-10
32   2002-09  SC  Etanol Hidratado   m3  14.004  2022-09-10
33   2002-10  SC  Etanol Hidratado   m3  16.854  2022-09-10
34   2002-11  SC  Etanol Hidratado   m3  13.459  2022-09-10
35   2002-12  SC  Etanol Hidratado   m3  16.040  2022-09-10
36   2003-01  SC  Etanol Hidratado   m3  15.186  2022-09-10
37   2003-02  SC  Etanol Hidratado   m3  11.428  2022-09-10
38   2003-03  SC  Etanol Hidratado   m3  10.876  2022-09-10
39   2003-04  SC  Etanol Hidratado   m3  12.471  2022-09-10
40   2003-05  SC  Etanol Hidratado   m3  12.097  2022-09-10
41   2003-06  SC  Etanol Hidratado   m3  12.103  2022-09-10
42   2003-07  SC  Etanol Hidratado   m3  15.061  2022-09-10
43   2003-08  SC  Etanol Hidratado   m3  11.389  2022-09-10
44   2003-09  SC  Etanol Hidratado   m3  11.434  2022-09-10
45   2003-10  SC  Etanol Hidratado   m3  14.196  2022-09-10
46   2003-11  SC  Etanol Hidratado   m3  12.367  2022-09-10
47   2003-12  SC  Etanol Hidratado   m3  16.396  2022-09-10
48   2004-01  SC  Etanol Hidratado   m3  13.838  2022-09-10
49   2004-02  SC  Etanol Hidratado   m3  13.422  2022-09-10
50   2004-03  SC  Etanol Hidratado   m3  13.921  2022-09-10
51   2004-04  SC  Etanol Hidratado   m3  13.998  2022-09-10
52   2004-05  SC  Etanol Hidratado   m3  14.056  2022-09-10
53   2004-06  SC  Etanol Hidratado   m3  14.554  2022-09-10
54   2004-07  SC  Etanol Hidratado   m3  16.245  2022-09-10
55   2004-08  SC  Etanol Hidratado   m3  13.410  2022-09-10
56   2004-09  SC  Etanol Hidratado   m3  15.811  2022-09-10
57   2004-10  SC  Etanol Hidratado   m3  14.826  2022-09-10
58   2004-11  SC  Etanol Hidratado   m3  13.612  2022-09-10
59   2004-12  SC  Etanol Hidratado   m3  16.179  2022-09-10
60   2005-01  SC  Etanol Hidratado   m3  13.194  2022-09-10
61   2005-02  SC  Etanol Hidratado   m3  11.550  2022-09-10
62   2005-03  SC  Etanol Hidratado   m3  13.152  2022-09-10
63   2005-04  SC  Etanol Hidratado   m3  12.818  2022-09-10
64   2005-05  SC  Etanol Hidratado   m3  13.524  2022-09-10
65   2005-06  SC  Etanol Hidratado   m3  13.6

In [1143]:
dfsc_pandas = dfsc.copy()

##SERGIPE


In [1144]:
# Conector

dfse = pd.read_csv('/content/sergipe.csv',sep=';')

In [1145]:
# Backup
dfse_backup = dfse.copy()

In [1146]:
# Configurando a quantidade de linhas máximas mostradas em tela

pd.set_option('display.max_columns',1000)
pd.set_option('display.max_rows',1000)

In [1147]:
# Visualização da Tabela

dfse

Mês   2000   2001   2002   2003   2004     2005     2006   2007  \
0     Janeiro  2.409  2.126  1.765  1.608  1.115    1.021    1.228  1.279   
1   Fevereiro  2.315  1.750  1.395  1.220  1.040  850.000    1.177  1.062   
2       Março  2.658  1.943  1.467  1.046  1.147    1.029    1.151  1.215   
3       Abril  2.627  1.821  1.425  1.042  1.186    1.022  995.000  1.117   
4        Maio  2.644  1.780  1.573  1.119  1.221    1.072  856.000  1.179   
5       Junho  1.929  1.724  1.530  1.125  1.336    1.187  955.000  1.282   
6       Julho  2.497  1.754  1.499  1.076  1.456    1.143  857.000  1.280   
7      Agosto  2.535  1.644  1.479  1.039  1.385    1.201    1.042  1.519   
8    Setembro  2.382  1.559  1.449  1.110  1.371    1.325    1.131  1.339   
9     Outubro  2.346  1.820  1.629  1.201  1.188    1.107    1.078  1.647   
10   Novembro  2.048  1.554  1.287  1.025  1.144    1.163    1.086  1.868   
11   Dezembro  2.297  1.651  1.508  1.271  1.174    1.396    1.220  2.061   

     2008   2009   2010   2011   2012   2013   2014   2015   2016   2017  \
0   2.374  3.714  3.991  3.318  1.852  1.824  2.089  2.487  3.180  1.991   
1   2.075  3.288  3.003  2.882  1.724  1.996  1.809  5.756  2.653  1.556   
2   2.052  3.672  3.299  2.988  1.717  1.811  1.711  4.051  2.429  1.513   
3   2.152  4.155  3.050  1.937  1.779  1.649  1.769  4.169  1.981  1.197   
4   2.351  3.948  3.121  2.098  1.763  1.535  1.648  3.409  2.028  1.236   
5   2.434  4.842  3.314  1.972  1.877  1.541  1.614  3.442  1.864  1.253   
6   2.549  5.069  3.154  1.544  1.674  1.486  1.604  3.315  1.779  1.205   
7   2.254  4.847  3.325  1.536  1.790  1.479  1.455  2.915  1.597  1.518   
8   2.496  5.238  3.395  1.648  1.521  1.477  1.569  2.981  1.703  1.943   
9   2.769  5.138  3.354  1.659  1.844  1.594  1.789  5.657  1.737  2.078   
10  2.540  4.019  2.859  1.715  1.647  1.696  1.909  3.468  1.706  3.203   
11  3.391  4.568  3.368  1.950  1.935  2.676  2.547  3.829  2.536  3.720   

     2018   2019   2020   2021   2022  
0   4.032  6.106  7.171  4.463  3.416  
1   2.757  4.573  5.334  5.357  2.761  
2   2.054  4.585  3.012  5.331  4.223  
3   1.823  4.186  1.709  3.828  3.671  
4   3.315  3.442  1.460  3.130  2.968  
5   2.440  2.945  2.055  2.135  2.682  
6   2.350  2.777  2.504  1.957    NaN  
7   2.782  2.629  2.760  1.741    NaN  
8   5.164  2.950  3.023  1.595    NaN  
9   7.483  4.314  3.582  1.790    NaN  
10  7.067  6.617  3.562  2.383    NaN  
11  7.169  8.995  4.414  3.182    NaN

In [1148]:
# Replace do Mês para numérico

dfse["Mês"].replace("Janeiro", "01", inplace=True)
dfse["Mês"].replace("Fevereiro", "02", inplace=True)
dfse["Mês"].replace("Março", "03", inplace=True)
dfse["Mês"].replace("Abril", "04", inplace=True)
dfse["Mês"].replace("Maio", "05", inplace=True)
dfse["Mês"].replace("Junho", "06", inplace=True)
dfse["Mês"].replace("Julho", "07", inplace=True)
dfse["Mês"].replace("Agosto", "08", inplace=True)
dfse["Mês"].replace("Setembro", "09", inplace=True)
dfse["Mês"].replace("Outubro", "10", inplace=True)
dfse["Mês"].replace("Novembro", "11", inplace=True)
dfse["Mês"].replace("Dezembro", "12", inplace=True)

In [1149]:
# Criação das colunas uf, produto, unid, criado_em
dfse['uf']='SE'
dfse['produto']='Etanol Hidratado'
dfse['unid']='m3'
dfse['criado_em'] ='2022-09-10'

In [1150]:
# Despivotar a tabela em ano e volume 
dfse.reset_index(inplace=True)

In [1151]:
dfse=dfse.melt(id_vars = ['Mês', 'uf', 'produto', 'unid', 'criado_em'], value_vars = ['2000', '2001', '2002', '2003', '2004', '2005', '2006', '2007', '2008', '2009', '2010', '2011', '2012', '2013', '2014', '2015', '2016', '2017', '2018', '2019', '2020', '2021', '2022'], var_name='ano', value_name='venda')

In [1152]:
# Visão geral da tabela

dfse

Mês  uf           produto unid   criado_em   ano    venda
0    01  SE  Etanol Hidratado   m3  2022-09-10  2000    2.409
1    02  SE  Etanol Hidratado   m3  2022-09-10  2000    2.315
2    03  SE  Etanol Hidratado   m3  2022-09-10  2000    2.658
3    04  SE  Etanol Hidratado   m3  2022-09-10  2000    2.627
4    05  SE  Etanol Hidratado   m3  2022-09-10  2000    2.644
5    06  SE  Etanol Hidratado   m3  2022-09-10  2000    1.929
6    07  SE  Etanol Hidratado   m3  2022-09-10  2000    2.497
7    08  SE  Etanol Hidratado   m3  2022-09-10  2000    2.535
8    09  SE  Etanol Hidratado   m3  2022-09-10  2000    2.382
9    10  SE  Etanol Hidratado   m3  2022-09-10  2000    2.346
10   11  SE  Etanol Hidratado   m3  2022-09-10  2000    2.048
11   12  SE  Etanol Hidratado   m3  2022-09-10  2000    2.297
12   01  SE  Etanol Hidratado   m3  2022-09-10  2001    2.126
13   02  SE  Etanol Hidratado   m3  2022-09-10  2001    1.750
14   03  SE  Etanol Hidratado   m3  2022-09-10  2001    1.943
15   04  SE  Etanol Hidratado   m3  2022-09-10  2001    1.821
16   05  SE  Etanol Hidratado   m3  2022-09-10  2001    1.780
17   06  SE  Etanol Hidratado   m3  2022-09-10  2001    1.724
18   07  SE  Etanol Hidratado   m3  2022-09-10  2001    1.754
19   08  SE  Etanol Hidratado   m3  2022-09-10  2001    1.644
20   09  SE  Etanol Hidratado   m3  2022-09-10  2001    1.559
21   10  SE  Etanol Hidratado   m3  2022-09-10  2001    1.820
22   11  SE  Etanol Hidratado   m3  2022-09-10  2001    1.554
23   12  SE  Etanol Hidratado   m3  2022-09-10  2001    1.651
24   01  SE  Etanol Hidratado   m3  2022-09-10  2002    1.765
25   02  SE  Etanol Hidratado   m3  2022-09-10  2002    1.395
26   03  SE  Etanol Hidratado   m3  2022-09-10  2002    1.467
27   04  SE  Etanol Hidratado   m3  2022-09-10  2002    1.425
28   05  SE  Etanol Hidratado   m3  2022-09-10  2002    1.573
29   06  SE  Etanol Hidratado   m3  2022-09-10  2002    1.530
30   07  SE  Etanol Hidratado   m3  2022-09-10  2002    1.499
31   08  SE  Etanol Hidratado   m3  2022-09-10  2002    1.479
32   09  SE  Etanol Hidratado   m3  2022-09-10  2002    1.449
33   10  SE  Etanol Hidratado   m3  2022-09-10  2002    1.629
34   11  SE  Etanol Hidratado   m3  2022-09-10  2002    1.287
35   12  SE  Etanol Hidratado   m3  2022-09-10  2002    1.508
36   01  SE  Etanol Hidratado   m3  2022-09-10  2003    1.608
37   02  SE  Etanol Hidratado   m3  2022-09-10  2003    1.220
38   03  SE  Etanol Hidratado   m3  2022-09-10  2003    1.046
39   04  SE  Etanol Hidratado   m3  2022-09-10  2003    1.042
40   05  SE  Etanol Hidratado   m3  2022-09-10  2003    1.119
41   06  SE  Etanol Hidratado   m3  2022-09-10  2003    1.125
42   07  SE  Etanol Hidratado   m3  2022-09-10  2003    1.076
43   08  SE  Etanol Hidratado   m3  2022-09-10  2003    1.039
44   09  SE  Etanol Hidratado   m3  2022-09-10  2003    1.110
45   10  SE  Etanol Hidratado   m3  2022-09-10  2003    1.201
46   11  SE  Etanol Hidratado   m3  2022-09-10  2003    1.025
47   12  SE  Etanol Hidratado   m3  2022-09-10  2003    1.271
48   01  SE  Etanol Hidratado   m3  2022-09-10  2004    1.115
49   02  SE  Etanol Hidratado   m3  2022-09-10  2004    1.040
50   03  SE  Etanol Hidratado   m3  2022-09-10  2004    1.147
51   04  SE  Etanol Hidratado   m3  2022-09-10  2004    1.186
52   05  SE  Etanol Hidratado   m3  2022-09-10  2004    1.221
53   06  SE  Etanol Hidratado   m3  2022-09-10  2004    1.336
54   07  SE  Etanol Hidratado   m3  2022-09-10  2004    1.456
55   08  SE  Etanol Hidratado   m3  2022-09-10  2004    1.385
56   09  SE  Etanol Hidratado   m3  2022-09-10  2004    1.371
57   10  SE  Etanol Hidratado   m3  2022-09-10  2004    1.188
58   11  SE  Etanol Hidratado   m3  2022-09-10  2004    1.144
59   12  SE  Etanol Hidratado   m3  2022-09-10  2004    1.174
60   01  SE  Etanol Hidratado   m3  2022-09-10  2005    1.021
61   02  SE  Etanol Hidratado   m3  2022-09-10  2005  850.000
62   03  SE  Etanol Hidratado   m3  2022-09-10  2005    1.029
63   04  SE  Etanol Hidratado   m3  

In [1153]:
# Concatenando as colunas ano e Mês
dfse['ano_mês'] = dfse[['ano', 'Mês']].agg('-'.join, axis=1)

In [1154]:
# Eliminando a coluna Mês

dfse.drop(["Mês"], axis=1, inplace=True)
dfse.drop(["ano"], axis=1, inplace=True)

In [1155]:
# Organização da ordem das colunas

dfse=dfse[['ano_mês', 'uf', 'produto', 'unid', 'venda', 'criado_em']]

In [1156]:
# Levantamento de possíveis inconsistências

dfse.isna().sum()

ano_mês      0
uf           0
produto      0
unid         0
venda        6
criado_em    0
dtype: int64

In [1157]:
# Tratamento das inconsistências

dfse.replace(['Na', 'nA', 'na','NA', 'NaN', 'NAN', 'nan', '', ' '],pd.NA,inplace=True)


In [1158]:
# Visão geral da tabela

dfse

ano_mês  uf           produto unid    venda   criado_em
0    2000-01  SE  Etanol Hidratado   m3    2.409  2022-09-10
1    2000-02  SE  Etanol Hidratado   m3    2.315  2022-09-10
2    2000-03  SE  Etanol Hidratado   m3    2.658  2022-09-10
3    2000-04  SE  Etanol Hidratado   m3    2.627  2022-09-10
4    2000-05  SE  Etanol Hidratado   m3    2.644  2022-09-10
5    2000-06  SE  Etanol Hidratado   m3    1.929  2022-09-10
6    2000-07  SE  Etanol Hidratado   m3    2.497  2022-09-10
7    2000-08  SE  Etanol Hidratado   m3    2.535  2022-09-10
8    2000-09  SE  Etanol Hidratado   m3    2.382  2022-09-10
9    2000-10  SE  Etanol Hidratado   m3    2.346  2022-09-10
10   2000-11  SE  Etanol Hidratado   m3    2.048  2022-09-10
11   2000-12  SE  Etanol Hidratado   m3    2.297  2022-09-10
12   2001-01  SE  Etanol Hidratado   m3    2.126  2022-09-10
13   2001-02  SE  Etanol Hidratado   m3    1.750  2022-09-10
14   2001-03  SE  Etanol Hidratado   m3    1.943  2022-09-10
15   2001-04  SE  Etanol Hidratado   m3    1.821  2022-09-10
16   2001-05  SE  Etanol Hidratado   m3    1.780  2022-09-10
17   2001-06  SE  Etanol Hidratado   m3    1.724  2022-09-10
18   2001-07  SE  Etanol Hidratado   m3    1.754  2022-09-10
19   2001-08  SE  Etanol Hidratado   m3    1.644  2022-09-10
20   2001-09  SE  Etanol Hidratado   m3    1.559  2022-09-10
21   2001-10  SE  Etanol Hidratado   m3    1.820  2022-09-10
22   2001-11  SE  Etanol Hidratado   m3    1.554  2022-09-10
23   2001-12  SE  Etanol Hidratado   m3    1.651  2022-09-10
24   2002-01  SE  Etanol Hidratado   m3    1.765  2022-09-10
25   2002-02  SE  Etanol Hidratado   m3    1.395  2022-09-10
26   2002-03  SE  Etanol Hidratado   m3    1.467  2022-09-10
27   2002-04  SE  Etanol Hidratado   m3    1.425  2022-09-10
28   2002-05  SE  Etanol Hidratado   m3    1.573  2022-09-10
29   2002-06  SE  Etanol Hidratado   m3    1.530  2022-09-10
30   2002-07  SE  Etanol Hidratado   m3    1.499  2022-09-10
31   2002-08  SE  Etanol Hidratado   m3    1.479  2022-09-10
32   2002-09  SE  Etanol Hidratado   m3    1.449  2022-09-10
33   2002-10  SE  Etanol Hidratado   m3    1.629  2022-09-10
34   2002-11  SE  Etanol Hidratado   m3    1.287  2022-09-10
35   2002-12  SE  Etanol Hidratado   m3    1.508  2022-09-10
36   2003-01  SE  Etanol Hidratado   m3    1.608  2022-09-10
37   2003-02  SE  Etanol Hidratado   m3    1.220  2022-09-10
38   2003-03  SE  Etanol Hidratado   m3    1.046  2022-09-10
39   2003-04  SE  Etanol Hidratado   m3    1.042  2022-09-10
40   2003-05  SE  Etanol Hidratado   m3    1.119  2022-09-10
41   2003-06  SE  Etanol Hidratado   m3    1.125  2022-09-10
42   2003-07  SE  Etanol Hidratado   m3    1.076  2022-09-10
43   2003-08  SE  Etanol Hidratado   m3    1.039  2022-09-10
44   2003-09  SE  Etanol Hidratado   m3    1.110  2022-09-10
45   2003-10  SE  Etanol Hidratado   m3    1.201  2022-09-10
46   2003-11  SE  Etanol Hidratado   m3    1.025  2022-09-10
47   2003-12  SE  Etanol Hidratado   m3    1.271  2022-09-10
48   2004-01  SE  Etanol Hidratado   m3    1.115  2022-09-10
49   2004-02  SE  Etanol Hidratado   m3    1.040  2022-09-10
50   2004-03  SE  Etanol Hidratado   m3    1.147  2022-09-10
51   2004-04  SE  Etanol Hidratado   m3    1.186  2022-09-10
52   2004-05  SE  Etanol Hidratado   m3    1.221  2022-09-10
53   2004-06  SE  Etanol Hidratado   m3    1.336  2022-09-10
54   2004-07  SE  Etanol Hidratado   m3    1.456  2022-09-10
55   2004-08  SE  Etanol Hidratado   m3    1.385  2022-09-10
56   2004-09  SE  Etanol Hidratado   m3    1.371  2022-09-10
57   2004-10  SE  Etanol Hidratado   m3    1.188  2022-09-10
58   2004-11  SE  Etanol Hidratado   m3    1.144  2022-09-10
59   2004-12  SE  Etanol Hidratado   m3    1.174  2022-09-10
60   2005-01  SE  Etanol Hidratado   m3    1.021  2022-09-10
61   2005-02  SE  Etanol Hidratado   m3  850.000  2022-09-10
62   2005-03  SE  Etanol Hidratado   m3    1.029  2022-09-10
63   2005-04  SE  Etanol Hidratado   m3    1.022  2022-09-10
64   2005-05  SE  Etanol Hidratado   m3 

In [1159]:
# Verificando os tipos

dfse.dtypes

ano_mês       object
uf            object
produto       object
unid          object
venda        float64
criado_em     object
dtype: object

In [1160]:
# Validação

schema = pa.DataFrameSchema(
    columns = {
        'ano_mês': pa.Column(pa.String, nullable=True),
        'uf': pa.Column(pa.String, nullable = True),
        'produto': pa.Column(pa.String, nullable = True),
        'unid': pa.Column(pa.String, nullable = True),
        'venda': pa.Column(pa.Float, nullable = True),
        'criado_em': pa.Column(pa.String, nullable = True),
                
    }
)
schema.validate(dfse)

ano_mês  uf           produto unid    venda   criado_em
0    2000-01  SE  Etanol Hidratado   m3    2.409  2022-09-10
1    2000-02  SE  Etanol Hidratado   m3    2.315  2022-09-10
2    2000-03  SE  Etanol Hidratado   m3    2.658  2022-09-10
3    2000-04  SE  Etanol Hidratado   m3    2.627  2022-09-10
4    2000-05  SE  Etanol Hidratado   m3    2.644  2022-09-10
5    2000-06  SE  Etanol Hidratado   m3    1.929  2022-09-10
6    2000-07  SE  Etanol Hidratado   m3    2.497  2022-09-10
7    2000-08  SE  Etanol Hidratado   m3    2.535  2022-09-10
8    2000-09  SE  Etanol Hidratado   m3    2.382  2022-09-10
9    2000-10  SE  Etanol Hidratado   m3    2.346  2022-09-10
10   2000-11  SE  Etanol Hidratado   m3    2.048  2022-09-10
11   2000-12  SE  Etanol Hidratado   m3    2.297  2022-09-10
12   2001-01  SE  Etanol Hidratado   m3    2.126  2022-09-10
13   2001-02  SE  Etanol Hidratado   m3    1.750  2022-09-10
14   2001-03  SE  Etanol Hidratado   m3    1.943  2022-09-10
15   2001-04  SE  Etanol Hidratado   m3    1.821  2022-09-10
16   2001-05  SE  Etanol Hidratado   m3    1.780  2022-09-10
17   2001-06  SE  Etanol Hidratado   m3    1.724  2022-09-10
18   2001-07  SE  Etanol Hidratado   m3    1.754  2022-09-10
19   2001-08  SE  Etanol Hidratado   m3    1.644  2022-09-10
20   2001-09  SE  Etanol Hidratado   m3    1.559  2022-09-10
21   2001-10  SE  Etanol Hidratado   m3    1.820  2022-09-10
22   2001-11  SE  Etanol Hidratado   m3    1.554  2022-09-10
23   2001-12  SE  Etanol Hidratado   m3    1.651  2022-09-10
24   2002-01  SE  Etanol Hidratado   m3    1.765  2022-09-10
25   2002-02  SE  Etanol Hidratado   m3    1.395  2022-09-10
26   2002-03  SE  Etanol Hidratado   m3    1.467  2022-09-10
27   2002-04  SE  Etanol Hidratado   m3    1.425  2022-09-10
28   2002-05  SE  Etanol Hidratado   m3    1.573  2022-09-10
29   2002-06  SE  Etanol Hidratado   m3    1.530  2022-09-10
30   2002-07  SE  Etanol Hidratado   m3    1.499  2022-09-10
31   2002-08  SE  Etanol Hidratado   m3    1.479  2022-09-10
32   2002-09  SE  Etanol Hidratado   m3    1.449  2022-09-10
33   2002-10  SE  Etanol Hidratado   m3    1.629  2022-09-10
34   2002-11  SE  Etanol Hidratado   m3    1.287  2022-09-10
35   2002-12  SE  Etanol Hidratado   m3    1.508  2022-09-10
36   2003-01  SE  Etanol Hidratado   m3    1.608  2022-09-10
37   2003-02  SE  Etanol Hidratado   m3    1.220  2022-09-10
38   2003-03  SE  Etanol Hidratado   m3    1.046  2022-09-10
39   2003-04  SE  Etanol Hidratado   m3    1.042  2022-09-10
40   2003-05  SE  Etanol Hidratado   m3    1.119  2022-09-10
41   2003-06  SE  Etanol Hidratado   m3    1.125  2022-09-10
42   2003-07  SE  Etanol Hidratado   m3    1.076  2022-09-10
43   2003-08  SE  Etanol Hidratado   m3    1.039  2022-09-10
44   2003-09  SE  Etanol Hidratado   m3    1.110  2022-09-10
45   2003-10  SE  Etanol Hidratado   m3    1.201  2022-09-10
46   2003-11  SE  Etanol Hidratado   m3    1.025  2022-09-10
47   2003-12  SE  Etanol Hidratado   m3    1.271  2022-09-10
48   2004-01  SE  Etanol Hidratado   m3    1.115  2022-09-10
49   2004-02  SE  Etanol Hidratado   m3    1.040  2022-09-10
50   2004-03  SE  Etanol Hidratado   m3    1.147  2022-09-10
51   2004-04  SE  Etanol Hidratado   m3    1.186  2022-09-10
52   2004-05  SE  Etanol Hidratado   m3    1.221  2022-09-10
53   2004-06  SE  Etanol Hidratado   m3    1.336  2022-09-10
54   2004-07  SE  Etanol Hidratado   m3    1.456  2022-09-10
55   2004-08  SE  Etanol Hidratado   m3    1.385  2022-09-10
56   2004-09  SE  Etanol Hidratado   m3    1.371  2022-09-10
57   2004-10  SE  Etanol Hidratado   m3    1.188  2022-09-10
58   2004-11  SE  Etanol Hidratado   m3    1.144  2022-09-10
59   2004-12  SE  Etanol Hidratado   m3    1.174  2022-09-10
60   2005-01  SE  Etanol Hidratado   m3    1.021  2022-09-10
61   2005-02  SE  Etanol Hidratado   m3  850.000  2022-09-10
62   2005-03  SE  Etanol Hidratado   m3    1.029  2022-09-10
63   2005-04  SE  Etanol Hidratado   m3    1.022  2022-09-10
64   2005-05  SE  Etanol Hidratado   m3 

In [1161]:
dfse_pandas = dfse.copy()

##SÃO PAULO

In [1162]:
# Conector

dfsp = pd.read_csv('/content/sao_paulo.csv',sep=';')

In [1163]:
# Backup
dfsp_backup = dfsp.copy()

In [1164]:
# Configurando a quantidade de linhas máximas mostradas em tela

pd.set_option('display.max_columns',1000)
pd.set_option('display.max_rows',1000)

In [1165]:
# Visualização da Tabela

dfsp

Mês     2000     2001     2002     2003     2004     2005     2006  \
0     Janeiro  187.685  128.141  117.060  127.924  174.188  177.653  277.456   
1   Fevereiro  180.934  115.759  109.904   98.273  166.462  167.570  281.969   
2       Março  170.812  129.912  120.822   98.421  204.315  178.347  257.521   
3       Abril  181.198  112.992  150.681  100.306  192.916  179.719  245.872   
4        Maio  189.448  116.332  149.566  105.659  208.096  190.541  300.793   
5       Junho  166.698  114.143  151.638   87.599  198.979  193.650  304.626   
6       Julho  155.771  113.152  159.304  107.448  212.862  189.346  317.084   
7      Agosto  135.219  116.811  157.027  106.937  170.048  211.019  333.676   
8    Setembro  131.356  112.398  165.622  112.227  190.082  232.164  346.616   
9     Outubro  142.420  126.382  182.121  143.751  195.640  213.787  343.433   
10   Novembro  139.590  112.928  126.286  132.085  191.691  218.715  344.345   
11   Dezembro  140.305  124.893  141.588  211.665  221.263  248.241  390.286   

       2007     2008     2009     2010     2011     2012     2013     2014  \
0   387.144  530.547  633.104  511.032  638.352  439.595  495.533  610.431   
1   364.149  532.679  617.721  465.377  665.082  487.041  499.562  607.368   
2   430.524  558.020  700.520  644.552  425.559  532.639  492.402  553.071   
3   404.925  589.464  737.570  697.390  298.335  482.637  490.833  586.983   
4   423.982  580.873  687.716  751.664  545.086  498.002  497.309  586.641   
5   433.100  570.126  715.570  743.879  646.786  439.833  515.030  560.580   
6   453.207  599.724  726.088  765.862  594.506  443.502  540.042  596.438   
7   493.069  627.610  724.844  754.246  619.380  474.612  588.497  622.960   
8   469.894  663.033  761.222  764.545  507.933  480.530  593.143  649.508   
9   563.464  658.867  787.766  733.748  533.662  532.642  644.874  720.267   
10  539.423  625.071  698.273  749.601  501.730  525.077  629.496  686.151   
11  582.239  715.238  819.605  792.360  513.896  498.349  670.034  796.195   

       2015     2016     2017         2018         2019     2020     2021  \
0   711.871  642.620  503.108     711.387      953.757   977.533  867.826   
1   698.570  642.490  516.231     661.307      901.277   934.391  827.624   
2   800.382  652.435  601.418     747.227      912.347   794.070  780.068   
3   805.151  681.714  591.644     698.660      947.254   652.730  774.508   
4   767.400  767.933  626.202     709.072      977.517   686.326  777.229   
5   786.020  722.291  630.409     758.689      894.082   717.123  649.798   
6   797.611  751.982  621.770     828.072      952.219   818.279  703.889   
7   821.787  782.392  680.184     941.760      978.785   828.867  667.095   
8   841.228  784.989  707.130     885.616      977.898   885.847  647.261   
9   884.190  695.073  749.960   1.008.272    1.076.486   967.739  645.283   
10  731.859  581.390  696.733     966.350    1.024.535   881.618  514.389   
11  809.991  651.161  763.327   1.040.349    1.077.622   995.166  620.310   

       2022  
0   489.391  
1   591.055  
2   748.966  
3   676.098  
4   637.547  
5   671.880  
6       NaN  
7       NaN  
8       NaN  
9       NaN  
10      NaN  
11      NaN

In [1166]:
# Replace do Mês para numérico

dfsp["Mês"].replace("Janeiro", "01", inplace=True)
dfsp["Mês"].replace("Fevereiro", "02", inplace=True)
dfsp["Mês"].replace("Março", "03", inplace=True)
dfsp["Mês"].replace("Abril", "04", inplace=True)
dfsp["Mês"].replace("Maio", "05", inplace=True)
dfsp["Mês"].replace("Junho", "06", inplace=True)
dfsp["Mês"].replace("Julho", "07", inplace=True)
dfsp["Mês"].replace("Agosto", "08", inplace=True)
dfsp["Mês"].replace("Setembro", "09", inplace=True)
dfsp["Mês"].replace("Outubro", "10", inplace=True)
dfsp["Mês"].replace("Novembro", "11", inplace=True)
dfsp["Mês"].replace("Dezembro", "12", inplace=True)

In [1167]:
# Criação das colunas uf, produto, unid, criado_em
dfsp['uf']='SP'
dfsp['produto']='Etanol Hidratado'
dfsp['unid']='m3'
dfsp['criado_em'] ='2022-09-10'

In [1168]:
# Despivotar a tabela em ano e volume 
dfsp.reset_index(inplace=True)

In [1169]:
dfsp=dfsp.melt(id_vars = ['Mês', 'uf', 'produto', 'unid', 'criado_em'], value_vars = ['2000', '2001', '2002', '2003', '2004', '2005', '2006', '2007', '2008', '2009', '2010', '2011', '2012', '2013', '2014', '2015', '2016', '2017', '2018', '2019', '2020', '2021', '2022'], var_name='ano', value_name='venda')

In [1170]:
# Visão geral da tabela

dfsp

Mês  uf           produto unid   criado_em   ano        venda
0    01  SP  Etanol Hidratado   m3  2022-09-10  2000      187.685
1    02  SP  Etanol Hidratado   m3  2022-09-10  2000      180.934
2    03  SP  Etanol Hidratado   m3  2022-09-10  2000      170.812
3    04  SP  Etanol Hidratado   m3  2022-09-10  2000      181.198
4    05  SP  Etanol Hidratado   m3  2022-09-10  2000      189.448
5    06  SP  Etanol Hidratado   m3  2022-09-10  2000      166.698
6    07  SP  Etanol Hidratado   m3  2022-09-10  2000      155.771
7    08  SP  Etanol Hidratado   m3  2022-09-10  2000      135.219
8    09  SP  Etanol Hidratado   m3  2022-09-10  2000      131.356
9    10  SP  Etanol Hidratado   m3  2022-09-10  2000       142.42
10   11  SP  Etanol Hidratado   m3  2022-09-10  2000       139.59
11   12  SP  Etanol Hidratado   m3  2022-09-10  2000      140.305
12   01  SP  Etanol Hidratado   m3  2022-09-10  2001      128.141
13   02  SP  Etanol Hidratado   m3  2022-09-10  2001      115.759
14   03  SP  Etanol Hidratado   m3  2022-09-10  2001      129.912
15   04  SP  Etanol Hidratado   m3  2022-09-10  2001      112.992
16   05  SP  Etanol Hidratado   m3  2022-09-10  2001      116.332
17   06  SP  Etanol Hidratado   m3  2022-09-10  2001      114.143
18   07  SP  Etanol Hidratado   m3  2022-09-10  2001      113.152
19   08  SP  Etanol Hidratado   m3  2022-09-10  2001      116.811
20   09  SP  Etanol Hidratado   m3  2022-09-10  2001      112.398
21   10  SP  Etanol Hidratado   m3  2022-09-10  2001      126.382
22   11  SP  Etanol Hidratado   m3  2022-09-10  2001      112.928
23   12  SP  Etanol Hidratado   m3  2022-09-10  2001      124.893
24   01  SP  Etanol Hidratado   m3  2022-09-10  2002       117.06
25   02  SP  Etanol Hidratado   m3  2022-09-10  2002      109.904
26   03  SP  Etanol Hidratado   m3  2022-09-10  2002      120.822
27   04  SP  Etanol Hidratado   m3  2022-09-10  2002      150.681
28   05  SP  Etanol Hidratado   m3  2022-09-10  2002      149.566
29   06  SP  Etanol Hidratado   m3  2022-09-10  2002      151.638
30   07  SP  Etanol Hidratado   m3  2022-09-10  2002      159.304
31   08  SP  Etanol Hidratado   m3  2022-09-10  2002      157.027
32   09  SP  Etanol Hidratado   m3  2022-09-10  2002      165.622
33   10  SP  Etanol Hidratado   m3  2022-09-10  2002      182.121
34   11  SP  Etanol Hidratado   m3  2022-09-10  2002      126.286
35   12  SP  Etanol Hidratado   m3  2022-09-10  2002      141.588
36   01  SP  Etanol Hidratado   m3  2022-09-10  2003      127.924
37   02  SP  Etanol Hidratado   m3  2022-09-10  2003       98.273
38   03  SP  Etanol Hidratado   m3  2022-09-10  2003       98.421
39   04  SP  Etanol Hidratado   m3  2022-09-10  2003      100.306
40   05  SP  Etanol Hidratado   m3  2022-09-10  2003      105.659
41   06  SP  Etanol Hidratado   m3  2022-09-10  2003       87.599
42   07  SP  Etanol Hidratado   m3  2022-09-10  2003      107.448
43   08  SP  Etanol Hidratado   m3  2022-09-10  2003      106.937
44   09  SP  Etanol Hidratado   m3  2022-09-10  2003      112.227
45   10  SP  Etanol Hidratado   m3  2022-09-10  2003      143.751
46   11  SP  Etanol Hidratado   m3  2022-09-10  2003      132.085
47   12  SP  Etanol Hidratado   m3  2022-09-10  2003      211.665
48   01  SP  Etanol Hidratado   m3  2022-09-10  2004      174.188
49   02  SP  Etanol Hidratado   m3  2022-09-10  2004      166.462
50   03  SP  Etanol Hidratado   m3  2022-09-10  2004      204.315
51   04  SP  Etanol Hidratado   m3  2022-09-10  2004      192.916
52   05  SP  Etanol Hidratado   m3  2022-09-10  2004      208.096
53   06  SP  Etanol Hidratado   m3  2022-09-10  2004      198.979
54   07  SP  Etanol Hidratado   m3  2022-09-10  2004      212.862
55   08  SP  Etanol Hidratado   m3  2022-09-10  2004      170.048
56   09  SP  Etanol Hidratado   m3  2022-09-10  2004      190.082
57   10  SP  Etanol Hidratado   m3  2022-09-10  2004       195.64
58   11  SP  Etanol Hidratado   m3  2022-09-10  2004      191.691
59   12  SP  Etanol Hidratado   m3  2022-09-

In [1171]:
# Concatenando as colunas ano e Mês
dfsp['ano_mês'] = dfsp[['ano', 'Mês']].agg('-'.join, axis=1)

In [1172]:
# Eliminando as colunas Mês e ano

dfsp.drop(["Mês"], axis=1, inplace=True)
dfsp.drop(["ano"], axis=1, inplace=True)

In [1173]:
# Organização da ordem das colunas

dfsp=dfsp[['ano_mês', 'uf', 'produto', 'unid', 'venda', 'criado_em']]

In [1174]:
# Levantamento de possíveis inconsistências

dfsp.isna().sum()

ano_mês      0
uf           0
produto      0
unid         0
venda        6
criado_em    0
dtype: int64

In [1175]:
# Tratamento das inconsistências

dfsp.replace(['Na', 'nA', 'na','NA', 'NaN', 'NAN', 'nan', '', ' '],pd.NA,inplace=True)


In [1176]:
# Visão geral da tabela

dfsp

ano_mês  uf           produto unid        venda   criado_em
0    2000-01  SP  Etanol Hidratado   m3      187.685  2022-09-10
1    2000-02  SP  Etanol Hidratado   m3      180.934  2022-09-10
2    2000-03  SP  Etanol Hidratado   m3      170.812  2022-09-10
3    2000-04  SP  Etanol Hidratado   m3      181.198  2022-09-10
4    2000-05  SP  Etanol Hidratado   m3      189.448  2022-09-10
5    2000-06  SP  Etanol Hidratado   m3      166.698  2022-09-10
6    2000-07  SP  Etanol Hidratado   m3      155.771  2022-09-10
7    2000-08  SP  Etanol Hidratado   m3      135.219  2022-09-10
8    2000-09  SP  Etanol Hidratado   m3      131.356  2022-09-10
9    2000-10  SP  Etanol Hidratado   m3       142.42  2022-09-10
10   2000-11  SP  Etanol Hidratado   m3       139.59  2022-09-10
11   2000-12  SP  Etanol Hidratado   m3      140.305  2022-09-10
12   2001-01  SP  Etanol Hidratado   m3      128.141  2022-09-10
13   2001-02  SP  Etanol Hidratado   m3      115.759  2022-09-10
14   2001-03  SP  Etanol Hidratado   m3      129.912  2022-09-10
15   2001-04  SP  Etanol Hidratado   m3      112.992  2022-09-10
16   2001-05  SP  Etanol Hidratado   m3      116.332  2022-09-10
17   2001-06  SP  Etanol Hidratado   m3      114.143  2022-09-10
18   2001-07  SP  Etanol Hidratado   m3      113.152  2022-09-10
19   2001-08  SP  Etanol Hidratado   m3      116.811  2022-09-10
20   2001-09  SP  Etanol Hidratado   m3      112.398  2022-09-10
21   2001-10  SP  Etanol Hidratado   m3      126.382  2022-09-10
22   2001-11  SP  Etanol Hidratado   m3      112.928  2022-09-10
23   2001-12  SP  Etanol Hidratado   m3      124.893  2022-09-10
24   2002-01  SP  Etanol Hidratado   m3       117.06  2022-09-10
25   2002-02  SP  Etanol Hidratado   m3      109.904  2022-09-10
26   2002-03  SP  Etanol Hidratado   m3      120.822  2022-09-10
27   2002-04  SP  Etanol Hidratado   m3      150.681  2022-09-10
28   2002-05  SP  Etanol Hidratado   m3      149.566  2022-09-10
29   2002-06  SP  Etanol Hidratado   m3      151.638  2022-09-10
30   2002-07  SP  Etanol Hidratado   m3      159.304  2022-09-10
31   2002-08  SP  Etanol Hidratado   m3      157.027  2022-09-10
32   2002-09  SP  Etanol Hidratado   m3      165.622  2022-09-10
33   2002-10  SP  Etanol Hidratado   m3      182.121  2022-09-10
34   2002-11  SP  Etanol Hidratado   m3      126.286  2022-09-10
35   2002-12  SP  Etanol Hidratado   m3      141.588  2022-09-10
36   2003-01  SP  Etanol Hidratado   m3      127.924  2022-09-10
37   2003-02  SP  Etanol Hidratado   m3       98.273  2022-09-10
38   2003-03  SP  Etanol Hidratado   m3       98.421  2022-09-10
39   2003-04  SP  Etanol Hidratado   m3      100.306  2022-09-10
40   2003-05  SP  Etanol Hidratado   m3      105.659  2022-09-10
41   2003-06  SP  Etanol Hidratado   m3       87.599  2022-09-10
42   2003-07  SP  Etanol Hidratado   m3      107.448  2022-09-10
43   2003-08  SP  Etanol Hidratado   m3      106.937  2022-09-10
44   2003-09  SP  Etanol Hidratado   m3      112.227  2022-09-10
45   2003-10  SP  Etanol Hidratado   m3      143.751  2022-09-10
46   2003-11  SP  Etanol Hidratado   m3      132.085  2022-09-10
47   2003-12  SP  Etanol Hidratado   m3      211.665  2022-09-10
48   2004-01  SP  Etanol Hidratado   m3      174.188  2022-09-10
49   2004-02  SP  Etanol Hidratado   m3      166.462  2022-09-10
50   2004-03  SP  Etanol Hidratado   m3      204.315  2022-09-10
51   2004-04  SP  Etanol Hidratado   m3      192.916  2022-09-10
52   2004-05  SP  Etanol Hidratado   m3      208.096  2022-09-10
53   2004-06  SP  Etanol Hidratado   m3      198.979  2022-09-10
54   2004-07  SP  Etanol Hidratado   m3      212.862  2022-09-10
55   2004-08  SP  Etanol Hidratado   m3      170.048  2022-09-10
56   2004-09  SP  Etanol Hidratado   m3      190.082  2022-09-10
57   2004-10  SP  Etanol Hidratado   m3       195.64  2022-09-10
58   2004-11  SP  Etanol Hidratado   m3      191.691  2022-09-10
59   2004-12  SP  Etanol Hidratado   m3      221.263  2022-09-10
60   2005-01  SP  Etanol Hidratado   m3 

In [1177]:
# Convertendo volume para tipo numérico

dfsp['venda'] = pd.to_numeric(dfsp['venda'],errors='coerce')

In [1178]:
# Verificando os tipos

dfsp.dtypes

ano_mês       object
uf            object
produto       object
unid          object
venda        float64
criado_em     object
dtype: object

In [1179]:
# Validação

schema = pa.DataFrameSchema(
    columns = {
        'ano_mês': pa.Column(pa.String, nullable=True),
        'uf': pa.Column(pa.String, nullable = True),
        'produto': pa.Column(pa.String, nullable = True),
        'unid': pa.Column(pa.String, nullable = True),
        'venda': pa.Column(pa.Float, nullable = True),
        'criado_em': pa.Column(pa.String, nullable = True),
                
    }
)
schema.validate(dfsp)

ano_mês  uf           produto unid    venda   criado_em
0    2000-01  SP  Etanol Hidratado   m3  187.685  2022-09-10
1    2000-02  SP  Etanol Hidratado   m3  180.934  2022-09-10
2    2000-03  SP  Etanol Hidratado   m3  170.812  2022-09-10
3    2000-04  SP  Etanol Hidratado   m3  181.198  2022-09-10
4    2000-05  SP  Etanol Hidratado   m3  189.448  2022-09-10
5    2000-06  SP  Etanol Hidratado   m3  166.698  2022-09-10
6    2000-07  SP  Etanol Hidratado   m3  155.771  2022-09-10
7    2000-08  SP  Etanol Hidratado   m3  135.219  2022-09-10
8    2000-09  SP  Etanol Hidratado   m3  131.356  2022-09-10
9    2000-10  SP  Etanol Hidratado   m3  142.420  2022-09-10
10   2000-11  SP  Etanol Hidratado   m3  139.590  2022-09-10
11   2000-12  SP  Etanol Hidratado   m3  140.305  2022-09-10
12   2001-01  SP  Etanol Hidratado   m3  128.141  2022-09-10
13   2001-02  SP  Etanol Hidratado   m3  115.759  2022-09-10
14   2001-03  SP  Etanol Hidratado   m3  129.912  2022-09-10
15   2001-04  SP  Etanol Hidratado   m3  112.992  2022-09-10
16   2001-05  SP  Etanol Hidratado   m3  116.332  2022-09-10
17   2001-06  SP  Etanol Hidratado   m3  114.143  2022-09-10
18   2001-07  SP  Etanol Hidratado   m3  113.152  2022-09-10
19   2001-08  SP  Etanol Hidratado   m3  116.811  2022-09-10
20   2001-09  SP  Etanol Hidratado   m3  112.398  2022-09-10
21   2001-10  SP  Etanol Hidratado   m3  126.382  2022-09-10
22   2001-11  SP  Etanol Hidratado   m3  112.928  2022-09-10
23   2001-12  SP  Etanol Hidratado   m3  124.893  2022-09-10
24   2002-01  SP  Etanol Hidratado   m3  117.060  2022-09-10
25   2002-02  SP  Etanol Hidratado   m3  109.904  2022-09-10
26   2002-03  SP  Etanol Hidratado   m3  120.822  2022-09-10
27   2002-04  SP  Etanol Hidratado   m3  150.681  2022-09-10
28   2002-05  SP  Etanol Hidratado   m3  149.566  2022-09-10
29   2002-06  SP  Etanol Hidratado   m3  151.638  2022-09-10
30   2002-07  SP  Etanol Hidratado   m3  159.304  2022-09-10
31   2002-08  SP  Etanol Hidratado   m3  157.027  2022-09-10
32   2002-09  SP  Etanol Hidratado   m3  165.622  2022-09-10
33   2002-10  SP  Etanol Hidratado   m3  182.121  2022-09-10
34   2002-11  SP  Etanol Hidratado   m3  126.286  2022-09-10
35   2002-12  SP  Etanol Hidratado   m3  141.588  2022-09-10
36   2003-01  SP  Etanol Hidratado   m3  127.924  2022-09-10
37   2003-02  SP  Etanol Hidratado   m3   98.273  2022-09-10
38   2003-03  SP  Etanol Hidratado   m3   98.421  2022-09-10
39   2003-04  SP  Etanol Hidratado   m3  100.306  2022-09-10
40   2003-05  SP  Etanol Hidratado   m3  105.659  2022-09-10
41   2003-06  SP  Etanol Hidratado   m3   87.599  2022-09-10
42   2003-07  SP  Etanol Hidratado   m3  107.448  2022-09-10
43   2003-08  SP  Etanol Hidratado   m3  106.937  2022-09-10
44   2003-09  SP  Etanol Hidratado   m3  112.227  2022-09-10
45   2003-10  SP  Etanol Hidratado   m3  143.751  2022-09-10
46   2003-11  SP  Etanol Hidratado   m3  132.085  2022-09-10
47   2003-12  SP  Etanol Hidratado   m3  211.665  2022-09-10
48   2004-01  SP  Etanol Hidratado   m3  174.188  2022-09-10
49   2004-02  SP  Etanol Hidratado   m3  166.462  2022-09-10
50   2004-03  SP  Etanol Hidratado   m3  204.315  2022-09-10
51   2004-04  SP  Etanol Hidratado   m3  192.916  2022-09-10
52   2004-05  SP  Etanol Hidratado   m3  208.096  2022-09-10
53   2004-06  SP  Etanol Hidratado   m3  198.979  2022-09-10
54   2004-07  SP  Etanol Hidratado   m3  212.862  2022-09-10
55   2004-08  SP  Etanol Hidratado   m3  170.048  2022-09-10
56   2004-09  SP  Etanol Hidratado   m3  190.082  2022-09-10
57   2004-10  SP  Etanol Hidratado   m3  195.640  2022-09-10
58   2004-11  SP  Etanol Hidratado   m3  191.691  2022-09-10
59   2004-12  SP  Etanol Hidratado   m3  221.263  2022-09-10
60   2005-01  SP  Etanol Hidratado   m3  177.653  2022-09-10
61   2005-02  SP  Etanol Hidratado   m3  167.570  2022-09-10
62   2005-03  SP  Etanol Hidratado   m3  178.347  2022-09-10
63   2005-04  SP  Etanol Hidratado   m3  179.719  2022-09-10
64   2005-05  SP  Etanol Hidratado   m3 

In [1180]:
dfsp_pandas = dfsp.copy()

##TOCANTINS

In [1181]:
# Conector

dfto = pd.read_csv('/content/to.csv',sep=';')

In [1182]:
# Backup
dfto_backup = dfto.copy()

In [1183]:
# Configurando a quantidade de linhas máximas mostradas em tela

pd.set_option('display.max_columns',1000)
pd.set_option('display.max_rows',1000)

In [1184]:
# Visualização da Tabela

dfto

Mês     2000     2001     2002     2003     2004     2005     2006  \
0     Janeiro    1.375    1.194  937.000    1.167    1.084    1.032    1.561   
1   Fevereiro    1.200    1.026  734.000    1.027    1.134  817.000    1.187   
2       Março    1.278    1.038  902.000  935.000    1.135  941.000  751.000   
3       Abril    1.323    1.044    1.013  759.000    1.041    1.035  669.000   
4        Maio    1.377    1.068    1.028  904.000  994.000  944.000  929.000   
5       Junho    1.234    1.038  992.000  875.000    1.110    1.042  844.000   
6       Julho    1.582    1.189    1.338    1.172    1.221    1.095    1.206   
7      Agosto    1.543    1.127    1.187  992.000    1.045    1.070    1.216   
8    Setembro    1.428  944.000    1.176    1.032    1.000    1.244    1.290   
9     Outubro    1.025  983.000    1.374    1.050    1.047    1.238    1.381   
10   Novembro  973.000  884.000    1.049    1.015    1.078    1.367    1.379   
11   Dezembro    1.144    1.017    1.315    1.243    1.203    1.776    1.747   

     2007   2008   2009   2010   2011   2012   2013   2014   2015   2016  \
0   1.771  3.558  4.826  3.072  4.433  2.354  2.801  3.304  3.704  3.485   
1   1.422  3.615  4.115  2.319  3.217  2.061  3.052  2.785  4.260  3.007   
2   1.546  3.543  5.399  2.997  1.820  2.092  3.002  2.516  4.542  2.439   
3   1.540  3.919  5.345  3.908  1.279  1.931  2.662  2.471  4.540  2.469   
4   1.761  4.189  5.323  4.867  2.841  2.273  2.504  2.525  4.367  2.603   
5   2.070  4.439  5.724  5.392  3.730  2.276  2.585  2.546  4.663  2.866   
6   3.138  5.853  6.761  6.803  4.294  2.628  3.523  3.381  5.509  3.215   
7   3.269  4.880  6.029  6.866  3.778  2.449  2.906  2.835  4.808  2.918   
8   3.487  5.543  6.718  6.569  3.489  2.309  3.051  2.928  4.897  2.345   
9   3.930  5.556  6.783  5.967  3.526  2.769  3.211  2.981  6.177  1.976   
10  3.792  4.643  5.678  5.309  2.603  2.506  2.966  2.927  4.571  1.678   
11  4.031  6.041  7.007  6.389  2.462  2.235  3.511  4.088  4.656  1.666   

       2017   2018   2019   2020   2021   2022  
0     1.447  2.225  2.838  3.518  4.042  1.879  
1     1.282  1.818  2.274  2.847  4.082  1.747  
2     1.262  1.909  2.266  2.489  3.953  3.161  
3   924.000  1.653  2.286  1.824  2.916  2.859  
4     1.169  1.645  2.422  1.856  2.456  2.267  
5   832.000  2.801  2.392  3.129  1.634  2.555  
6     1.255  3.222  2.955  3.435  1.849    NaN  
7     1.487  3.469  2.615  3.287  1.930    NaN  
8     1.623  3.936  2.453  3.831  1.956    NaN  
9     1.481  4.833  2.878  4.074  1.939    NaN  
10    1.850  3.807  3.440  3.488  2.268    NaN  
11    2.278  2.802  4.396  4.450  2.347    NaN

In [1185]:
# Replace do Mês para numérico

dfto["Mês"].replace("Janeiro", "01", inplace=True)
dfto["Mês"].replace("Fevereiro", "02", inplace=True)
dfto["Mês"].replace("Março", "03", inplace=True)
dfto["Mês"].replace("Abril", "04", inplace=True)
dfto["Mês"].replace("Maio", "05", inplace=True)
dfto["Mês"].replace("Junho", "06", inplace=True)
dfto["Mês"].replace("Julho", "07", inplace=True)
dfto["Mês"].replace("Agosto", "08", inplace=True)
dfto["Mês"].replace("Setembro", "09", inplace=True)
dfto["Mês"].replace("Outubro", "10", inplace=True)
dfto["Mês"].replace("Novembro", "11", inplace=True)
dfto["Mês"].replace("Dezembro", "12", inplace=True)

In [1186]:
# Criação das colunas uf, produto, unid, criado_em
dfto['uf']='TO'
dfto['produto']='Etanol Hidratado'
dfto['unid']='m3'
dfto['criado_em'] ='2022-09-10'

In [1187]:
# Despivotar a tabela em ano e volume 
dfto.reset_index(inplace=True)

In [1188]:
dfto=dfto.melt(id_vars = ['Mês', 'uf', 'produto', 'unid', 'criado_em'], value_vars = ['2000', '2001', '2002', '2003', '2004', '2005', '2006', '2007', '2008', '2009', '2010', '2011', '2012', '2013', '2014', '2015', '2016', '2017', '2018', '2019', '2020', '2021', '2022'], var_name='ano', value_name='venda')

In [1189]:
# Visão geral da tabela

dfto

Mês  uf           produto unid   criado_em   ano    venda
0    01  TO  Etanol Hidratado   m3  2022-09-10  2000    1.375
1    02  TO  Etanol Hidratado   m3  2022-09-10  2000    1.200
2    03  TO  Etanol Hidratado   m3  2022-09-10  2000    1.278
3    04  TO  Etanol Hidratado   m3  2022-09-10  2000    1.323
4    05  TO  Etanol Hidratado   m3  2022-09-10  2000    1.377
5    06  TO  Etanol Hidratado   m3  2022-09-10  2000    1.234
6    07  TO  Etanol Hidratado   m3  2022-09-10  2000    1.582
7    08  TO  Etanol Hidratado   m3  2022-09-10  2000    1.543
8    09  TO  Etanol Hidratado   m3  2022-09-10  2000    1.428
9    10  TO  Etanol Hidratado   m3  2022-09-10  2000    1.025
10   11  TO  Etanol Hidratado   m3  2022-09-10  2000  973.000
11   12  TO  Etanol Hidratado   m3  2022-09-10  2000    1.144
12   01  TO  Etanol Hidratado   m3  2022-09-10  2001    1.194
13   02  TO  Etanol Hidratado   m3  2022-09-10  2001    1.026
14   03  TO  Etanol Hidratado   m3  2022-09-10  2001    1.038
15   04  TO  Etanol Hidratado   m3  2022-09-10  2001    1.044
16   05  TO  Etanol Hidratado   m3  2022-09-10  2001    1.068
17   06  TO  Etanol Hidratado   m3  2022-09-10  2001    1.038
18   07  TO  Etanol Hidratado   m3  2022-09-10  2001    1.189
19   08  TO  Etanol Hidratado   m3  2022-09-10  2001    1.127
20   09  TO  Etanol Hidratado   m3  2022-09-10  2001  944.000
21   10  TO  Etanol Hidratado   m3  2022-09-10  2001  983.000
22   11  TO  Etanol Hidratado   m3  2022-09-10  2001  884.000
23   12  TO  Etanol Hidratado   m3  2022-09-10  2001    1.017
24   01  TO  Etanol Hidratado   m3  2022-09-10  2002  937.000
25   02  TO  Etanol Hidratado   m3  2022-09-10  2002  734.000
26   03  TO  Etanol Hidratado   m3  2022-09-10  2002  902.000
27   04  TO  Etanol Hidratado   m3  2022-09-10  2002    1.013
28   05  TO  Etanol Hidratado   m3  2022-09-10  2002    1.028
29   06  TO  Etanol Hidratado   m3  2022-09-10  2002  992.000
30   07  TO  Etanol Hidratado   m3  2022-09-10  2002    1.338
31   08  TO  Etanol Hidratado   m3  2022-09-10  2002    1.187
32   09  TO  Etanol Hidratado   m3  2022-09-10  2002    1.176
33   10  TO  Etanol Hidratado   m3  2022-09-10  2002    1.374
34   11  TO  Etanol Hidratado   m3  2022-09-10  2002    1.049
35   12  TO  Etanol Hidratado   m3  2022-09-10  2002    1.315
36   01  TO  Etanol Hidratado   m3  2022-09-10  2003    1.167
37   02  TO  Etanol Hidratado   m3  2022-09-10  2003    1.027
38   03  TO  Etanol Hidratado   m3  2022-09-10  2003  935.000
39   04  TO  Etanol Hidratado   m3  2022-09-10  2003  759.000
40   05  TO  Etanol Hidratado   m3  2022-09-10  2003  904.000
41   06  TO  Etanol Hidratado   m3  2022-09-10  2003  875.000
42   07  TO  Etanol Hidratado   m3  2022-09-10  2003    1.172
43   08  TO  Etanol Hidratado   m3  2022-09-10  2003  992.000
44   09  TO  Etanol Hidratado   m3  2022-09-10  2003    1.032
45   10  TO  Etanol Hidratado   m3  2022-09-10  2003    1.050
46   11  TO  Etanol Hidratado   m3  2022-09-10  2003    1.015
47   12  TO  Etanol Hidratado   m3  2022-09-10  2003    1.243
48   01  TO  Etanol Hidratado   m3  2022-09-10  2004    1.084
49   02  TO  Etanol Hidratado   m3  2022-09-10  2004    1.134
50   03  TO  Etanol Hidratado   m3  2022-09-10  2004    1.135
51   04  TO  Etanol Hidratado   m3  2022-09-10  2004    1.041
52   05  TO  Etanol Hidratado   m3  2022-09-10  2004  994.000
53   06  TO  Etanol Hidratado   m3  2022-09-10  2004    1.110
54   07  TO  Etanol Hidratado   m3  2022-09-10  2004    1.221
55   08  TO  Etanol Hidratado   m3  2022-09-10  2004    1.045
56   09  TO  Etanol Hidratado   m3  2022-09-10  2004    1.000
57   10  TO  Etanol Hidratado   m3  2022-09-10  2004    1.047
58   11  TO  Etanol Hidratado   m3  2022-09-10  2004    1.078
59   12  TO  Etanol Hidratado   m3  2022-09-10  2004    1.203
60   01  TO  Etanol Hidratado   m3  2022-09-10  2005    1.032
61   02  TO  Etanol Hidratado   m3  2022-09-10  2005  817.000
62   03  TO  Etanol Hidratado   m3  2022-09-10  2005  941.000
63   04  TO  Etanol Hidratado   m3  

In [1190]:
# Concatenando as colunas ano e Mês
dfto['ano_mês'] = dfto[['ano', 'Mês']].agg('-'.join, axis=1)

In [1191]:
# Eliminando as colunas Mês e ano

dfto.drop(["Mês"], axis=1, inplace=True)
dfto.drop(["ano"], axis=1, inplace=True)

In [1192]:
# Organização da ordem das colunas

dfto=dfto[['ano_mês', 'uf', 'produto', 'unid', 'venda', 'criado_em']]

In [1193]:
# Levantamento de possíveis inconsistências

dfto.isna().sum()

ano_mês      0
uf           0
produto      0
unid         0
venda        6
criado_em    0
dtype: int64

In [1194]:
# Tratamento das inconsistências

dfto.replace(['Na', 'nA', 'na','NA', 'NaN', 'NAN', 'nan', '', ' '],pd.NA,inplace=True)

In [1195]:
# Visão geral da tabela

dfto

ano_mês  uf           produto unid    venda   criado_em
0    2000-01  TO  Etanol Hidratado   m3    1.375  2022-09-10
1    2000-02  TO  Etanol Hidratado   m3    1.200  2022-09-10
2    2000-03  TO  Etanol Hidratado   m3    1.278  2022-09-10
3    2000-04  TO  Etanol Hidratado   m3    1.323  2022-09-10
4    2000-05  TO  Etanol Hidratado   m3    1.377  2022-09-10
5    2000-06  TO  Etanol Hidratado   m3    1.234  2022-09-10
6    2000-07  TO  Etanol Hidratado   m3    1.582  2022-09-10
7    2000-08  TO  Etanol Hidratado   m3    1.543  2022-09-10
8    2000-09  TO  Etanol Hidratado   m3    1.428  2022-09-10
9    2000-10  TO  Etanol Hidratado   m3    1.025  2022-09-10
10   2000-11  TO  Etanol Hidratado   m3  973.000  2022-09-10
11   2000-12  TO  Etanol Hidratado   m3    1.144  2022-09-10
12   2001-01  TO  Etanol Hidratado   m3    1.194  2022-09-10
13   2001-02  TO  Etanol Hidratado   m3    1.026  2022-09-10
14   2001-03  TO  Etanol Hidratado   m3    1.038  2022-09-10
15   2001-04  TO  Etanol Hidratado   m3    1.044  2022-09-10
16   2001-05  TO  Etanol Hidratado   m3    1.068  2022-09-10
17   2001-06  TO  Etanol Hidratado   m3    1.038  2022-09-10
18   2001-07  TO  Etanol Hidratado   m3    1.189  2022-09-10
19   2001-08  TO  Etanol Hidratado   m3    1.127  2022-09-10
20   2001-09  TO  Etanol Hidratado   m3  944.000  2022-09-10
21   2001-10  TO  Etanol Hidratado   m3  983.000  2022-09-10
22   2001-11  TO  Etanol Hidratado   m3  884.000  2022-09-10
23   2001-12  TO  Etanol Hidratado   m3    1.017  2022-09-10
24   2002-01  TO  Etanol Hidratado   m3  937.000  2022-09-10
25   2002-02  TO  Etanol Hidratado   m3  734.000  2022-09-10
26   2002-03  TO  Etanol Hidratado   m3  902.000  2022-09-10
27   2002-04  TO  Etanol Hidratado   m3    1.013  2022-09-10
28   2002-05  TO  Etanol Hidratado   m3    1.028  2022-09-10
29   2002-06  TO  Etanol Hidratado   m3  992.000  2022-09-10
30   2002-07  TO  Etanol Hidratado   m3    1.338  2022-09-10
31   2002-08  TO  Etanol Hidratado   m3    1.187  2022-09-10
32   2002-09  TO  Etanol Hidratado   m3    1.176  2022-09-10
33   2002-10  TO  Etanol Hidratado   m3    1.374  2022-09-10
34   2002-11  TO  Etanol Hidratado   m3    1.049  2022-09-10
35   2002-12  TO  Etanol Hidratado   m3    1.315  2022-09-10
36   2003-01  TO  Etanol Hidratado   m3    1.167  2022-09-10
37   2003-02  TO  Etanol Hidratado   m3    1.027  2022-09-10
38   2003-03  TO  Etanol Hidratado   m3  935.000  2022-09-10
39   2003-04  TO  Etanol Hidratado   m3  759.000  2022-09-10
40   2003-05  TO  Etanol Hidratado   m3  904.000  2022-09-10
41   2003-06  TO  Etanol Hidratado   m3  875.000  2022-09-10
42   2003-07  TO  Etanol Hidratado   m3    1.172  2022-09-10
43   2003-08  TO  Etanol Hidratado   m3  992.000  2022-09-10
44   2003-09  TO  Etanol Hidratado   m3    1.032  2022-09-10
45   2003-10  TO  Etanol Hidratado   m3    1.050  2022-09-10
46   2003-11  TO  Etanol Hidratado   m3    1.015  2022-09-10
47   2003-12  TO  Etanol Hidratado   m3    1.243  2022-09-10
48   2004-01  TO  Etanol Hidratado   m3    1.084  2022-09-10
49   2004-02  TO  Etanol Hidratado   m3    1.134  2022-09-10
50   2004-03  TO  Etanol Hidratado   m3    1.135  2022-09-10
51   2004-04  TO  Etanol Hidratado   m3    1.041  2022-09-10
52   2004-05  TO  Etanol Hidratado   m3  994.000  2022-09-10
53   2004-06  TO  Etanol Hidratado   m3    1.110  2022-09-10
54   2004-07  TO  Etanol Hidratado   m3    1.221  2022-09-10
55   2004-08  TO  Etanol Hidratado   m3    1.045  2022-09-10
56   2004-09  TO  Etanol Hidratado   m3    1.000  2022-09-10
57   2004-10  TO  Etanol Hidratado   m3    1.047  2022-09-10
58   2004-11  TO  Etanol Hidratado   m3    1.078  2022-09-10
59   2004-12  TO  Etanol Hidratado   m3    1.203  2022-09-10
60   2005-01  TO  Etanol Hidratado   m3    1.032  2022-09-10
61   2005-02  TO  Etanol Hidratado   m3  817.000  2022-09-10
62   2005-03  TO  Etanol Hidratado   m3  941.000  2022-09-10
63   2005-04  TO  Etanol Hidratado   m3    1.035  2022-09-10
64   2005-05  TO  Etanol Hidratado   m3 

In [1196]:
# Verificando os tipos

dfto.dtypes

ano_mês       object
uf            object
produto       object
unid          object
venda        float64
criado_em     object
dtype: object

In [1197]:
# Validação

schema = pa.DataFrameSchema(
    columns = {
        'ano_mês': pa.Column(pa.String, nullable=True),
        'uf': pa.Column(pa.String, nullable = True),
        'produto': pa.Column(pa.String, nullable = True),
        'unid': pa.Column(pa.String, nullable = True),
        'venda': pa.Column(pa.Float, nullable = True),
        'criado_em': pa.Column(pa.String, nullable = True),
                
    }
)
schema.validate(dfto)

ano_mês  uf           produto unid    venda   criado_em
0    2000-01  TO  Etanol Hidratado   m3    1.375  2022-09-10
1    2000-02  TO  Etanol Hidratado   m3    1.200  2022-09-10
2    2000-03  TO  Etanol Hidratado   m3    1.278  2022-09-10
3    2000-04  TO  Etanol Hidratado   m3    1.323  2022-09-10
4    2000-05  TO  Etanol Hidratado   m3    1.377  2022-09-10
5    2000-06  TO  Etanol Hidratado   m3    1.234  2022-09-10
6    2000-07  TO  Etanol Hidratado   m3    1.582  2022-09-10
7    2000-08  TO  Etanol Hidratado   m3    1.543  2022-09-10
8    2000-09  TO  Etanol Hidratado   m3    1.428  2022-09-10
9    2000-10  TO  Etanol Hidratado   m3    1.025  2022-09-10
10   2000-11  TO  Etanol Hidratado   m3  973.000  2022-09-10
11   2000-12  TO  Etanol Hidratado   m3    1.144  2022-09-10
12   2001-01  TO  Etanol Hidratado   m3    1.194  2022-09-10
13   2001-02  TO  Etanol Hidratado   m3    1.026  2022-09-10
14   2001-03  TO  Etanol Hidratado   m3    1.038  2022-09-10
15   2001-04  TO  Etanol Hidratado   m3    1.044  2022-09-10
16   2001-05  TO  Etanol Hidratado   m3    1.068  2022-09-10
17   2001-06  TO  Etanol Hidratado   m3    1.038  2022-09-10
18   2001-07  TO  Etanol Hidratado   m3    1.189  2022-09-10
19   2001-08  TO  Etanol Hidratado   m3    1.127  2022-09-10
20   2001-09  TO  Etanol Hidratado   m3  944.000  2022-09-10
21   2001-10  TO  Etanol Hidratado   m3  983.000  2022-09-10
22   2001-11  TO  Etanol Hidratado   m3  884.000  2022-09-10
23   2001-12  TO  Etanol Hidratado   m3    1.017  2022-09-10
24   2002-01  TO  Etanol Hidratado   m3  937.000  2022-09-10
25   2002-02  TO  Etanol Hidratado   m3  734.000  2022-09-10
26   2002-03  TO  Etanol Hidratado   m3  902.000  2022-09-10
27   2002-04  TO  Etanol Hidratado   m3    1.013  2022-09-10
28   2002-05  TO  Etanol Hidratado   m3    1.028  2022-09-10
29   2002-06  TO  Etanol Hidratado   m3  992.000  2022-09-10
30   2002-07  TO  Etanol Hidratado   m3    1.338  2022-09-10
31   2002-08  TO  Etanol Hidratado   m3    1.187  2022-09-10
32   2002-09  TO  Etanol Hidratado   m3    1.176  2022-09-10
33   2002-10  TO  Etanol Hidratado   m3    1.374  2022-09-10
34   2002-11  TO  Etanol Hidratado   m3    1.049  2022-09-10
35   2002-12  TO  Etanol Hidratado   m3    1.315  2022-09-10
36   2003-01  TO  Etanol Hidratado   m3    1.167  2022-09-10
37   2003-02  TO  Etanol Hidratado   m3    1.027  2022-09-10
38   2003-03  TO  Etanol Hidratado   m3  935.000  2022-09-10
39   2003-04  TO  Etanol Hidratado   m3  759.000  2022-09-10
40   2003-05  TO  Etanol Hidratado   m3  904.000  2022-09-10
41   2003-06  TO  Etanol Hidratado   m3  875.000  2022-09-10
42   2003-07  TO  Etanol Hidratado   m3    1.172  2022-09-10
43   2003-08  TO  Etanol Hidratado   m3  992.000  2022-09-10
44   2003-09  TO  Etanol Hidratado   m3    1.032  2022-09-10
45   2003-10  TO  Etanol Hidratado   m3    1.050  2022-09-10
46   2003-11  TO  Etanol Hidratado   m3    1.015  2022-09-10
47   2003-12  TO  Etanol Hidratado   m3    1.243  2022-09-10
48   2004-01  TO  Etanol Hidratado   m3    1.084  2022-09-10
49   2004-02  TO  Etanol Hidratado   m3    1.134  2022-09-10
50   2004-03  TO  Etanol Hidratado   m3    1.135  2022-09-10
51   2004-04  TO  Etanol Hidratado   m3    1.041  2022-09-10
52   2004-05  TO  Etanol Hidratado   m3  994.000  2022-09-10
53   2004-06  TO  Etanol Hidratado   m3    1.110  2022-09-10
54   2004-07  TO  Etanol Hidratado   m3    1.221  2022-09-10
55   2004-08  TO  Etanol Hidratado   m3    1.045  2022-09-10
56   2004-09  TO  Etanol Hidratado   m3    1.000  2022-09-10
57   2004-10  TO  Etanol Hidratado   m3    1.047  2022-09-10
58   2004-11  TO  Etanol Hidratado   m3    1.078  2022-09-10
59   2004-12  TO  Etanol Hidratado   m3    1.203  2022-09-10
60   2005-01  TO  Etanol Hidratado   m3    1.032  2022-09-10
61   2005-02  TO  Etanol Hidratado   m3  817.000  2022-09-10
62   2005-03  TO  Etanol Hidratado   m3  941.000  2022-09-10
63   2005-04  TO  Etanol Hidratado   m3    1.035  2022-09-10
64   2005-05  TO  Etanol Hidratado   m3 

In [1198]:
dfto_pandas = dfto.copy()

# CONCATENAÇÃO DE DATASETS


In [1199]:
teste = 0

In [1200]:
teste = pd.merge(dfac_pandas, dfal_pandas, how = 'outer')


In [1201]:
teste = pd.merge(teste, dfap_pandas, how = 'outer')

In [1202]:
teste = pd.merge(teste, dfba_pandas, how = 'outer')

In [1203]:
teste = pd.merge(teste, dfce_pandas, how = 'outer')

In [1204]:
teste = pd.merge(teste, dfdf_pandas, how = 'outer')

In [1205]:
teste = pd.merge(teste, dfes_pandas, how = 'outer')

In [1206]:
teste = pd.merge(teste, dfgo_pandas, how = 'outer')

In [1207]:
teste = pd.merge(teste, dfma_pandas, how = 'outer')


In [1208]:
teste = pd.merge(teste, dfmg_pandas, how = 'outer')

In [1209]:
teste = pd.merge(teste, dfms_pandas, how = 'outer')

In [1210]:
teste = pd.merge(teste, dfmt_pandas, how = 'outer')

In [1211]:
teste = pd.merge(teste, dfpa_pandas, how = 'outer')

In [1212]:
teste = pd.merge(teste, dfpb_pandas, how = 'outer')

In [1213]:
teste = pd.merge(teste, dfpe_pandas, how = 'outer')

In [1214]:
teste = pd.merge(teste, dfpi_pandas, how = 'outer')

In [1215]:
teste = pd.merge(teste, dfpr_pandas, how = 'outer')

In [1216]:
teste = pd.merge(teste, dfrj_pandas, how = 'outer')

In [1217]:
teste = pd.merge(teste, dfrn_pandas, how = 'outer')

In [1218]:
teste = pd.merge(teste, dfro_pandas, how = 'outer')

In [1219]:
teste = pd.merge(teste, dfrr_pandas, how = 'outer')

In [1220]:
teste = pd.merge(teste, dfrs_pandas, how = 'outer')

In [1221]:
teste = pd.merge(teste, dfsc_pandas, how = 'outer')

In [1222]:
teste = pd.merge(teste, dfse_pandas, how = 'outer')

In [1223]:
teste = pd.merge(teste, dfsp_pandas, how = 'outer')

In [1224]:
teste = pd.merge(teste, dfto_pandas, how = 'outer')

In [1225]:
teste = pd.merge(teste, dfam_pandas, how = 'outer')

In [1226]:
# Arquivo foi salvo em formato csv sem o index

teste.to_csv('dataset_etanol_hidratado.csv', index=False)